# Default Code

In [1]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData1"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return ['AGW']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 20,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('ma_5')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AGW
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-06 09:17:00
2017-01-06 09:18:00
2017-01-06 09:19:00
2017-01-06 09:20:00
2017-01-06 09:21:00
2017-01-06 09:22:00
2017-01-06 09:23:00
2017-01-06 09:24:00
2017-01-06 09:25:00
2017-01-06 09:26:00
2017-01-06 09:27:00
2017-01-06 09:28:00
2017-01-06 09:29:00
2017-01-06 09:30:00
2017-01-06 09:31:00
2017-01-06 09:32:00
2017-01-06 09:33:00
2017-01-06 09:34:00
2017-01-06 09:35:00
2017-01-06 09:36:00
2017-01-06 09:37:00
2017-01-06 09:38:00
2017-01-06 09:39:00
2017-01-06 09:40:00
2017-01-06 09:41:00
2017-01-06 09:42:00
2017-01-06 09:43:00
2017-01-06 09:44:00
2017-01-06 09:45:00
2017-01-06 09:46:00
2017-01-06 09:47:00
2017-01-06 09:48:00
2017-01-06 09:49:00
2017-01-06 09:50:00
2017-01-06 09:51:00
2017-01-06 09:52:00
2017-01-06 09:53:00
2017-01-06 09:54:00
2017-01-06 09:55:00
2017-01-06 09:56:00
2017-01-06 09:57:00
2017-01-06 09:58:00

2017-01-09 09:47:00
2017-01-09 09:48:00
2017-01-09 09:49:00
2017-01-09 09:50:00
2017-01-09 09:51:00
2017-01-09 09:52:00
2017-01-09 09:53:00
2017-01-09 09:54:00
2017-01-09 09:55:00
2017-01-09 09:56:00
2017-01-09 09:57:00
2017-01-09 09:58:00
2017-01-09 09:59:00
2017-01-09 10:00:00
2017-01-09 10:01:00
2017-01-09 10:02:00
2017-01-09 10:03:00
2017-01-09 10:04:00
2017-01-09 10:05:00
2017-01-09 10:06:00
2017-01-09 10:07:00
2017-01-09 10:08:00
2017-01-09 10:09:00
2017-01-09 10:10:00
2017-01-09 10:11:00
2017-01-09 10:12:00
2017-01-09 10:13:00
2017-01-09 10:14:00
2017-01-09 10:15:00
2017-01-09 10:16:00
2017-01-09 10:17:00
2017-01-09 10:18:00
2017-01-09 10:19:00
2017-01-09 10:20:00
2017-01-09 10:21:00
2017-01-09 10:22:00
2017-01-09 10:23:00
2017-01-09 10:24:00
2017-01-09 10:25:00
2017-01-09 10:26:00
2017-01-09 10:27:00
2017-01-09 10:28:00
2017-01-09 10:29:00
2017-01-09 10:30:00
2017-01-09 10:31:00
2017-01-09 10:32:00
2017-01-09 10:33:00
2017-01-09 10:34:00
2017-01-09 10:35:00
2017-01-09 10:36:00


2017-01-10 10:29:00
2017-01-10 10:30:00
2017-01-10 10:31:00
2017-01-10 10:32:00
2017-01-10 10:33:00
2017-01-10 10:34:00
2017-01-10 10:35:00
2017-01-10 10:36:00
2017-01-10 10:37:00
2017-01-10 10:38:00
2017-01-10 10:39:00
2017-01-10 10:40:00
2017-01-10 10:41:00
2017-01-10 10:42:00
2017-01-10 10:43:00
2017-01-10 10:44:00
2017-01-10 10:45:00
2017-01-10 10:46:00
2017-01-10 10:47:00
2017-01-10 10:48:00
2017-01-10 10:49:00
2017-01-10 10:50:00
2017-01-10 10:51:00
2017-01-10 10:52:00
2017-01-10 10:53:00
2017-01-10 10:54:00
2017-01-10 10:55:00
2017-01-10 10:56:00
2017-01-10 10:57:00
2017-01-10 10:58:00
2017-01-10 10:59:00
2017-01-10 11:00:00
2017-01-10 11:01:00
2017-01-10 11:02:00
2017-01-10 11:03:00
2017-01-10 11:04:00
2017-01-10 11:05:00
2017-01-10 11:06:00
2017-01-10 11:07:00
2017-01-10 11:08:00
2017-01-10 11:09:00
2017-01-10 11:10:00
2017-01-10 11:11:00
2017-01-10 11:12:00
2017-01-10 11:13:00
2017-01-10 11:14:00
2017-01-10 11:15:00
2017-01-10 11:16:00
2017-01-10 11:17:00
2017-01-10 11:18:00


2017-01-11 11:07:00
2017-01-11 11:08:00
2017-01-11 11:09:00
2017-01-11 11:10:00
2017-01-11 11:11:00
2017-01-11 11:12:00
2017-01-11 11:13:00
2017-01-11 11:14:00
2017-01-11 11:15:00
2017-01-11 11:16:00
2017-01-11 11:17:00
2017-01-11 11:18:00
2017-01-11 11:19:00
2017-01-11 11:20:00
2017-01-11 11:21:00
2017-01-11 11:22:00
2017-01-11 11:23:00
2017-01-11 11:24:00
2017-01-11 11:25:00
2017-01-11 11:26:00
2017-01-11 11:27:00
2017-01-11 11:28:00
2017-01-11 11:29:00
2017-01-11 11:30:00
2017-01-11 11:31:00
2017-01-11 11:32:00
2017-01-11 11:33:00
2017-01-11 11:34:00
2017-01-11 11:35:00
2017-01-11 11:36:00
2017-01-11 11:37:00
2017-01-11 11:38:00
2017-01-11 11:39:00
2017-01-11 11:40:00
2017-01-11 11:41:00
2017-01-11 11:42:00
2017-01-11 11:43:00
2017-01-11 11:44:00
2017-01-11 11:45:00
2017-01-11 11:46:00
2017-01-11 11:47:00
2017-01-11 11:48:00
2017-01-11 11:49:00
2017-01-11 11:50:00
2017-01-11 11:51:00
2017-01-11 11:52:00
2017-01-11 11:53:00
2017-01-11 11:54:00
2017-01-11 11:55:00
2017-01-11 11:56:00


2017-01-12 11:44:00
2017-01-12 11:45:00
2017-01-12 11:46:00
2017-01-12 11:47:00
2017-01-12 11:48:00
2017-01-12 11:49:00
2017-01-12 11:50:00
2017-01-12 11:51:00
2017-01-12 11:52:00
2017-01-12 11:53:00
2017-01-12 11:54:00
2017-01-12 11:55:00
2017-01-12 11:56:00
2017-01-12 11:57:00
2017-01-12 11:58:00
2017-01-12 11:59:00
2017-01-12 12:00:00
2017-01-12 12:01:00
2017-01-12 12:02:00
2017-01-12 12:03:00
2017-01-12 12:04:00
2017-01-12 12:05:00
2017-01-12 12:06:00
2017-01-12 12:07:00
2017-01-12 12:08:00
2017-01-12 12:09:00
2017-01-12 12:10:00
2017-01-12 12:11:00
2017-01-12 12:12:00
2017-01-12 12:13:00
2017-01-12 12:14:00
2017-01-12 12:15:00
2017-01-12 12:16:00
2017-01-12 12:17:00
2017-01-12 12:18:00
2017-01-12 12:19:00
2017-01-12 12:20:00
2017-01-12 12:21:00
2017-01-12 12:22:00
2017-01-12 12:23:00
2017-01-12 12:24:00
2017-01-12 12:25:00
2017-01-12 12:26:00
2017-01-12 12:27:00
2017-01-12 12:28:00
2017-01-12 12:29:00
2017-01-12 12:30:00
2017-01-12 12:31:00
2017-01-12 12:32:00
2017-01-12 12:33:00


...

2017-01-27 12:04:00
2017-01-27 12:05:00
2017-01-27 12:06:00
2017-01-27 12:07:00
2017-01-27 12:08:00
2017-01-27 12:09:00
2017-01-27 12:10:00
2017-01-27 12:11:00
2017-01-27 12:12:00
2017-01-27 12:13:00
2017-01-27 12:14:00
2017-01-27 12:15:00
2017-01-27 12:16:00
2017-01-27 12:17:00
2017-01-27 12:18:00
2017-01-27 12:19:00
2017-01-27 12:20:00
2017-01-27 12:21:00
2017-01-27 12:22:00
2017-01-27 12:23:00
2017-01-27 12:24:00
2017-01-27 12:25:00
2017-01-27 12:26:00
2017-01-27 12:27:00
2017-01-27 12:28:00
2017-01-27 12:29:00
2017-01-27 12:30:00
2017-01-27 12:31:00
2017-01-27 12:32:00
2017-01-27 12:33:00
2017-01-27 12:34:00
2017-01-27 12:35:00
2017-01-27 12:36:00
2017-01-27 12:37:00
2017-01-27 12:38:00
2017-01-27 12:39:00
2017-01-27 12:40:00
2017-01-27 12:41:00
2017-01-27 12:42:00
2017-01-27 12:43:00
2017-01-27 12:44:00
2017-01-27 12:45:00
2017-01-27 12:46:00
2017-01-27 12:47:00
2017-01-27 12:48:00
2017-01-27 12:49:00
2017-01-27 12:50:00
2017-01-27 12:51:00
2017-01-27 12:52:00
2017-01-27 12:53:00


2017-01-30 12:44:00
2017-01-30 12:45:00
2017-01-30 12:46:00
2017-01-30 12:47:00
2017-01-30 12:48:00
2017-01-30 12:49:00
2017-01-30 12:50:00
2017-01-30 12:51:00
2017-01-30 12:52:00
2017-01-30 12:53:00
2017-01-30 12:54:00
2017-01-30 12:55:00
2017-01-30 12:56:00
2017-01-30 12:57:00
2017-01-30 12:58:00
2017-01-30 12:59:00
2017-01-30 13:00:00
2017-01-30 13:01:00
2017-01-30 13:02:00
2017-01-30 13:03:00
2017-01-30 13:04:00
2017-01-30 13:05:00
2017-01-30 13:06:00
2017-01-30 13:07:00
2017-01-30 13:08:00
2017-01-30 13:09:00
2017-01-30 13:10:00
2017-01-30 13:11:00
2017-01-30 13:12:00
2017-01-30 13:13:00
2017-01-30 13:14:00
2017-01-30 13:15:00
2017-01-30 13:16:00
2017-01-30 13:17:00
2017-01-30 13:18:00
2017-01-30 13:19:00
2017-01-30 13:20:00
2017-01-30 13:21:00
2017-01-30 13:22:00
2017-01-30 13:23:00
2017-01-30 13:24:00
2017-01-30 13:25:00
2017-01-30 13:26:00
2017-01-30 13:27:00
2017-01-30 13:28:00
2017-01-30 13:29:00
2017-01-30 13:30:00
2017-01-30 13:31:00
2017-01-30 13:32:00
2017-01-30 13:33:00


2017-01-31 13:22:00
2017-01-31 13:23:00
2017-01-31 13:24:00
2017-01-31 13:25:00
2017-01-31 13:26:00
2017-01-31 13:27:00
2017-01-31 13:28:00
2017-01-31 13:29:00
2017-01-31 13:30:00
2017-01-31 13:31:00
2017-01-31 13:32:00
2017-01-31 13:33:00
2017-01-31 13:34:00
2017-01-31 13:35:00
2017-01-31 13:36:00
2017-01-31 13:37:00
2017-01-31 13:38:00
2017-01-31 13:39:00
2017-01-31 13:40:00
2017-01-31 13:41:00
2017-01-31 13:42:00
2017-01-31 13:43:00
2017-01-31 13:44:00
2017-01-31 13:45:00
2017-01-31 13:46:00
2017-01-31 13:47:00
2017-01-31 13:48:00
2017-01-31 13:49:00
2017-01-31 13:50:00
2017-01-31 13:51:00
2017-01-31 13:52:00
2017-01-31 13:53:00
2017-01-31 13:54:00
2017-01-31 13:55:00
2017-01-31 13:56:00
2017-01-31 13:57:00
2017-01-31 13:58:00
2017-01-31 13:59:00
2017-01-31 14:00:00
2017-01-31 14:01:00
2017-01-31 14:02:00
2017-01-31 14:03:00
2017-01-31 14:04:00
2017-01-31 14:05:00
2017-01-31 14:06:00
2017-01-31 14:07:00
2017-01-31 14:08:00
2017-01-31 14:09:00
2017-01-31 14:10:00
2017-01-31 14:11:00


2017-02-01 13:59:00
2017-02-01 14:00:00
2017-02-01 14:01:00
2017-02-01 14:02:00
2017-02-01 14:03:00
2017-02-01 14:04:00
2017-02-01 14:05:00
2017-02-01 14:06:00
2017-02-01 14:07:00
2017-02-01 14:08:00
2017-02-01 14:09:00
2017-02-01 14:10:00
2017-02-01 14:11:00
2017-02-01 14:12:00
2017-02-01 14:13:00
2017-02-01 14:14:00
2017-02-01 14:15:00
2017-02-01 14:16:00
2017-02-01 14:17:00
2017-02-01 14:18:00
2017-02-01 14:19:00
2017-02-01 14:20:00
2017-02-01 14:21:00
2017-02-01 14:22:00
2017-02-01 14:23:00
2017-02-01 14:24:00
2017-02-01 14:25:00
2017-02-01 14:26:00
2017-02-01 14:27:00
2017-02-01 14:28:00
2017-02-01 14:29:00
2017-02-01 14:30:00
2017-02-01 14:31:00
2017-02-01 14:32:00
2017-02-01 14:33:00
2017-02-01 14:34:00
2017-02-01 14:35:00
2017-02-01 14:36:00
2017-02-01 14:37:00
2017-02-01 14:38:00
2017-02-01 14:39:00
2017-02-01 14:40:00
2017-02-01 14:41:00
2017-02-01 14:42:00
2017-02-01 14:43:00
2017-02-01 14:44:00
2017-02-01 14:45:00
2017-02-01 14:46:00
2017-02-01 14:47:00
2017-02-01 14:48:00


KeyboardInterrupt: 

# Changing the periods of the features

In [ ]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData1"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return ['AGW']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 10, # Change the period
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 10, # Changed the period
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 10,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('ma_5')
        expma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]
        expma5 = expma5Data.iloc[-1]

        return ma5


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


# Testing the sdev_5 feature for training dataset 1 and stock 'AGW'

In [ ]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData1"

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return ['AGW']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 10,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 10,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 10,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('sdev_5') # Changed the feature

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


# Testing the sdev_5 feature for training dataset 1 and stock 'AGW'

In [ ]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData3" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return ['AGW']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 20,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('sdev_5')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


# Data Set 1
# testing the sdev_5 feature for the whole training dataset 1

In [ ]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData2" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return ['AGW',
 'AIO',
 'AUZ',
 'BSN',
 'BWU',
 'CBT',
 'CHV',
 'CSR',
 'CUN',
 'CYD',
 'DCO',
 'DFZ',
 'DVV',
 'DYE',
 'EGV',
 'FCY',
 'FFA',
 'FFS',
 'FKI',
 'FRE',
 'FUR',
 'GFQ',
 'GGK',
 'GYJ',
 'GYV',
 'HHK',
 'IES',
 'IFL',
 'ILW',
 'IMC',
 'IUE',
 'IUQ',
 'IYU',
 'JSG',
 'JYW',
 'KAA',
 'KFW',
 'KKG',
 'KMV',
 'KRZ',
 'LDU',
 'LKB',
 'LPQ',
 'MAS',
 'MQK',
 'MUF',
 'NDG',
 'NSL',
 'NYO',
 'OED',
 'OGU',
 'OMP',
 'PFK',
 'PLX',
 'PMS',
 'PQS',
 'PUO',
 'QRK',
 'SCN',
 'SVG',
 'TGI',
 'TWK',
 'UBF',
 'UWC',
 'UWD',
 'VKE',
 'VML',
 'VND',
 'VSL',
 'VTN',
 'WAG',
 'WTJ',
 'XAD',
 'XCS',
 'XFD',
 'XIT',
 'XPV',
 'XYR',
 'XZR',
 'YGC',
 'YHW',
 'YUZ',
 'ZEW',
 'ZLX']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 20,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('sdev_5')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


# Data Set 2
# Testing the whole dataset 2 for sdev_5 feature

In [ ]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData2" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return []

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 20,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('sdev_5')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


# Data  Set 3

In [ ]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData3" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return []

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 20,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('sdev_5')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


In [2]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData3" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return []

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 20,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('sdev_5')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5+0.1


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AGW
Processing data for stock: AIO
Processing data for stock: AUZ
Processing data for stock: BSN
Processing data for stock: BWU
Processing data for stock: CBT
Processing data for stock: CHV
Processing data for stock: CSR
Processing data for stock: CUN
Processing data for stock: CYD
Processing data for stock: DCO
Processing data for stock: DFZ
Processing data for stock: DVV
Processing data for stock: DYE
Processing data for stock: EGV
Processing data for stock: FCY
Processing data for stock: FFA
Processing data for stock: FFS
Processing data for stock: FKI
Processing data for stock: FRE
Processing data for stock: FUR
Processing data for stock: GFQ
Processing data for stock: GGK
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: HHK
Processing data for stock: IES
Processing data for stock: IFL
Processing data for stock: ILW
Processing data for stock: IMC
Processing data for stock: IUE
Processing data for stock: IUQ
Processi

C:\Users\hp\Anaconda2\lib\site-packages\backtester\executionSystem\QQ_execution_system.py:32: RuntimeWarning:

invalid value encountered in sign



2017-01-06 09:19:00
2017-01-06 09:20:00
2017-01-06 09:21:00
2017-01-06 09:22:00
2017-01-06 09:23:00
2017-01-06 09:24:00
2017-01-06 09:25:00
2017-01-06 09:26:00
2017-01-06 09:27:00
2017-01-06 09:28:00
2017-01-06 09:29:00
2017-01-06 09:30:00
2017-01-06 09:31:00
2017-01-06 09:32:00
2017-01-06 09:33:00
2017-01-06 09:34:00
2017-01-06 09:35:00
2017-01-06 09:36:00
2017-01-06 09:37:00
2017-01-06 09:38:00
2017-01-06 09:39:00
2017-01-06 09:40:00
2017-01-06 09:41:00
2017-01-06 09:42:00
2017-01-06 09:43:00
2017-01-06 09:44:00
2017-01-06 09:45:00
2017-01-06 09:46:00
2017-01-06 09:47:00
2017-01-06 09:48:00
2017-01-06 09:49:00
2017-01-06 09:50:00
2017-01-06 09:51:00
2017-01-06 09:52:00
2017-01-06 09:53:00
2017-01-06 09:54:00
2017-01-06 09:55:00
2017-01-06 09:56:00
2017-01-06 09:57:00
2017-01-06 09:58:00
2017-01-06 09:59:00
2017-01-06 10:00:00
2017-01-06 10:01:00
2017-01-06 10:02:00
2017-01-06 10:03:00
2017-01-06 10:04:00
2017-01-06 10:05:00
2017-01-06 10:06:00
2017-01-06 10:07:00
2017-01-06 10:08:00


2017-01-10 09:56:00
2017-01-10 09:57:00
2017-01-10 09:58:00
2017-01-10 09:59:00
2017-01-10 10:00:00
2017-01-10 10:01:00
2017-01-10 10:02:00
2017-01-10 10:03:00
2017-01-10 10:04:00
2017-01-10 10:05:00
2017-01-10 10:06:00
2017-01-10 10:07:00
2017-01-10 10:08:00
2017-01-10 10:09:00
2017-01-10 10:10:00
2017-01-10 10:11:00
2017-01-10 10:12:00
2017-01-10 10:13:00
2017-01-10 10:14:00
2017-01-10 10:15:00
2017-01-10 10:16:00
2017-01-10 10:17:00
2017-01-10 10:18:00
2017-01-10 10:19:00
2017-01-10 10:20:00
2017-01-10 10:21:00
2017-01-10 10:22:00
2017-01-10 10:23:00
2017-01-10 10:24:00
2017-01-10 10:25:00
2017-01-10 10:26:00
2017-01-10 10:27:00
2017-01-10 10:28:00
2017-01-10 10:29:00
2017-01-10 10:30:00
2017-01-10 10:31:00
2017-01-10 10:32:00
2017-01-10 10:33:00
2017-01-10 10:34:00
2017-01-10 10:35:00
2017-01-10 10:36:00
2017-01-10 10:37:00
2017-01-10 10:38:00
2017-01-10 10:39:00
2017-01-10 10:40:00
2017-01-10 10:41:00
2017-01-10 10:42:00
2017-01-10 10:43:00
2017-01-10 10:44:00
2017-01-10 10:45:00


2017-01-11 10:33:00
2017-01-11 10:34:00
2017-01-11 10:35:00
2017-01-11 10:36:00
2017-01-11 10:37:00
2017-01-11 10:38:00
2017-01-11 10:39:00
2017-01-11 10:40:00
2017-01-11 10:41:00
2017-01-11 10:42:00
2017-01-11 10:43:00
2017-01-11 10:44:00
2017-01-11 10:45:00
2017-01-11 10:46:00
2017-01-11 10:47:00
2017-01-11 10:48:00
2017-01-11 10:49:00
2017-01-11 10:50:00
2017-01-11 10:51:00
2017-01-11 10:52:00
2017-01-11 10:53:00
2017-01-11 10:54:00
2017-01-11 10:55:00
2017-01-11 10:56:00
2017-01-11 10:57:00
2017-01-11 10:58:00
2017-01-11 10:59:00
2017-01-11 11:00:00
2017-01-11 11:01:00
2017-01-11 11:02:00
2017-01-11 11:03:00
2017-01-11 11:04:00
2017-01-11 11:05:00
2017-01-11 11:06:00
2017-01-11 11:07:00
2017-01-11 11:08:00
2017-01-11 11:09:00
2017-01-11 11:10:00
2017-01-11 11:11:00
2017-01-11 11:12:00
2017-01-11 11:13:00
2017-01-11 11:14:00
2017-01-11 11:15:00
2017-01-11 11:16:00
2017-01-11 11:17:00
2017-01-11 11:18:00
2017-01-11 11:19:00
2017-01-11 11:20:00
2017-01-11 11:21:00
2017-01-11 11:22:00


...

2017-01-27 10:04:00
2017-01-27 10:05:00
2017-01-27 10:06:00
2017-01-27 10:07:00
2017-01-27 10:08:00
2017-01-27 10:09:00
2017-01-27 10:10:00
2017-01-27 10:11:00
2017-01-27 10:12:00
2017-01-27 10:13:00
2017-01-27 10:14:00
2017-01-27 10:15:00
2017-01-27 10:16:00
2017-01-27 10:17:00
2017-01-27 10:18:00
2017-01-27 10:19:00
2017-01-27 10:20:00
2017-01-27 10:21:00
2017-01-27 10:22:00
2017-01-27 10:23:00
2017-01-27 10:24:00
2017-01-27 10:25:00
2017-01-27 10:26:00
2017-01-27 10:27:00
2017-01-27 10:28:00
2017-01-27 10:29:00
2017-01-27 10:30:00
2017-01-27 10:31:00
2017-01-27 10:32:00
2017-01-27 10:33:00
2017-01-27 10:34:00
2017-01-27 10:35:00
2017-01-27 10:36:00
2017-01-27 10:37:00
2017-01-27 10:38:00
2017-01-27 10:39:00
2017-01-27 10:40:00
2017-01-27 10:41:00
2017-01-27 10:42:00
2017-01-27 10:43:00
2017-01-27 10:44:00
2017-01-27 10:45:00
2017-01-27 10:46:00
2017-01-27 10:47:00
2017-01-27 10:48:00
2017-01-27 10:49:00
2017-01-27 10:50:00
2017-01-27 10:51:00
2017-01-27 10:52:00
2017-01-27 10:53:00


2017-01-30 10:43:00
2017-01-30 10:44:00
2017-01-30 10:45:00
2017-01-30 10:46:00
2017-01-30 10:47:00
2017-01-30 10:48:00
2017-01-30 10:49:00
2017-01-30 10:50:00
2017-01-30 10:51:00
2017-01-30 10:52:00
2017-01-30 10:53:00
2017-01-30 10:54:00
2017-01-30 10:55:00
2017-01-30 10:56:00
2017-01-30 10:57:00
2017-01-30 10:58:00
2017-01-30 10:59:00
2017-01-30 11:00:00
2017-01-30 11:01:00
2017-01-30 11:02:00
2017-01-30 11:03:00
2017-01-30 11:04:00
2017-01-30 11:05:00
2017-01-30 11:06:00
2017-01-30 11:07:00
2017-01-30 11:08:00
2017-01-30 11:09:00
2017-01-30 11:10:00
2017-01-30 11:11:00
2017-01-30 11:12:00
2017-01-30 11:13:00
2017-01-30 11:14:00
2017-01-30 11:15:00
2017-01-30 11:16:00
2017-01-30 11:17:00
2017-01-30 11:18:00
2017-01-30 11:19:00
2017-01-30 11:20:00
2017-01-30 11:21:00
2017-01-30 11:22:00
2017-01-30 11:23:00
2017-01-30 11:24:00
2017-01-30 11:25:00
2017-01-30 11:26:00
2017-01-30 11:27:00
2017-01-30 11:28:00
2017-01-30 11:29:00
2017-01-30 11:30:00
2017-01-30 11:31:00
2017-01-30 11:32:00


2017-01-31 11:21:00
2017-01-31 11:22:00
2017-01-31 11:23:00
2017-01-31 11:24:00
2017-01-31 11:25:00
2017-01-31 11:26:00
2017-01-31 11:27:00
2017-01-31 11:28:00
2017-01-31 11:29:00
2017-01-31 11:30:00
2017-01-31 11:31:00
2017-01-31 11:32:00
2017-01-31 11:33:00
2017-01-31 11:34:00
2017-01-31 11:35:00
2017-01-31 11:36:00
2017-01-31 11:37:00
2017-01-31 11:38:00
2017-01-31 11:39:00
2017-01-31 11:40:00
2017-01-31 11:41:00
2017-01-31 11:42:00
2017-01-31 11:43:00
2017-01-31 11:44:00
2017-01-31 11:45:00
2017-01-31 11:46:00
2017-01-31 11:47:00
2017-01-31 11:48:00
2017-01-31 11:49:00
2017-01-31 11:50:00
2017-01-31 11:51:00
2017-01-31 11:52:00
2017-01-31 11:53:00
2017-01-31 11:54:00
2017-01-31 11:55:00
2017-01-31 11:56:00
2017-01-31 11:57:00
2017-01-31 11:58:00
2017-01-31 11:59:00
2017-01-31 12:00:00
2017-01-31 12:01:00
2017-01-31 12:02:00
2017-01-31 12:03:00
2017-01-31 12:04:00
2017-01-31 12:05:00
2017-01-31 12:06:00
2017-01-31 12:07:00
2017-01-31 12:08:00
2017-01-31 12:09:00
2017-01-31 12:10:00


2017-02-01 11:58:00
2017-02-01 11:59:00
2017-02-01 12:00:00
2017-02-01 12:01:00
2017-02-01 12:02:00
2017-02-01 12:03:00
2017-02-01 12:04:00
2017-02-01 12:05:00
2017-02-01 12:06:00
2017-02-01 12:07:00
2017-02-01 12:08:00
2017-02-01 12:09:00
2017-02-01 12:10:00
2017-02-01 12:11:00
2017-02-01 12:12:00
2017-02-01 12:13:00
2017-02-01 12:14:00
2017-02-01 12:15:00
2017-02-01 12:16:00
2017-02-01 12:17:00
2017-02-01 12:18:00
2017-02-01 12:19:00
2017-02-01 12:20:00
2017-02-01 12:21:00
2017-02-01 12:22:00
2017-02-01 12:23:00
2017-02-01 12:24:00
2017-02-01 12:25:00
2017-02-01 12:26:00
2017-02-01 12:27:00
2017-02-01 12:28:00
2017-02-01 12:29:00
2017-02-01 12:30:00
2017-02-01 12:31:00
2017-02-01 12:32:00
2017-02-01 12:33:00
2017-02-01 12:34:00
2017-02-01 12:35:00
2017-02-01 12:36:00
2017-02-01 12:37:00
2017-02-01 12:38:00
2017-02-01 12:39:00
2017-02-01 12:40:00
2017-02-01 12:41:00
2017-02-01 12:42:00
2017-02-01 12:43:00
2017-02-01 12:44:00
2017-02-01 12:45:00
2017-02-01 12:46:00
2017-02-01 12:47:00


Info: DYE:  Total Pnl: 3.19%  Profit/Loss Ratio: 1.02  Accuracy: 0.50  Score: nan  Normalized Score: nan 
Info: WTJ:  Total Pnl: 0.95%  Profit/Loss Ratio: 1.01  Accuracy: 0.49  Score: nan  Normalized Score: nan 
Info: TGI:  Total Pnl: 25.37%  Profit/Loss Ratio: 1.04  Accuracy: 0.50  Score: nan  Normalized Score: nan 
Info: VND:  Total Pnl: 5.14%  Profit/Loss Ratio: 1.01  Accuracy: 0.49  Score: nan  Normalized Score: nan 
Info: GGK:  Total Pnl: 4.69%  Profit/Loss Ratio: 1.03  Accuracy: 0.49  Score: nan  Normalized Score: nan 
Info: KRZ:  Total Pnl: 1.89%  Profit/Loss Ratio: 1.01  Accuracy: 0.49  Score: nan  Normalized Score: nan 
Info: FKI:  Total Pnl: 16.64%  Profit/Loss Ratio: 1.04  Accuracy: 0.49  Score: nan  Normalized Score: nan 
Info: IMC:  Total Pnl: 4.18%  Profit/Loss Ratio: 1.05  Accuracy: 0.46  Score: nan  Normalized Score: nan 
Info: FRE:  Total Pnl: 3.62%  Profit/Loss Ratio: 1.02  Accuracy: 0.49  Score: nan  Normalized Score: nan 
Info: DFZ:  Total Pnl: 15.77%  Profit/Loss R

In [4]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData3" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return ['AGW']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 20,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5+0.1


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AGW
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-06 09:17:00
2017-01-06 09:18:00
2017-01-06 09:19:00
2017-01-06 09:20:00
2017-01-06 09:21:00
2017-01-06 09:22:00
2017-01-06 09:23:00
2017-01-06 09:24:00
2017-01-06 09:25:00
2017-01-06 09:26:00
2017-01-06 09:27:00
2017-01-06 09:28:00
2017-01-06 09:29:00
2017-01-06 09:30:00
2017-01-06 09:31:00
2017-01-06 09:32:00
2017-01-06 09:33:00
2017-01-06 09:34:00
2017-01-06 09:35:00
2017-01-06 09:36:00
2017-01-06 09:37:00
2017-01-06 09:38:00
2017-01-06 09:39:00
2017-01-06 09:40:00
2017-01-06 09:41:00
2017-01-06 09:42:00
2017-01-06 09:43:00
2017-01-06 09:44:00
2017-01-06 09:45:00
2017-01-06 09:46:00
2017-01-06 09:47:00
2017-01-06 09:48:00
2017-01-06 09:49:00
2017-01-06 09:50:00
2017-01-06 09:51:00
2017-01-06 09:52:00
2017-01-06 09:53:00
2017-01-06 09:54:00
2017-01-06 09:55:00
2017-01-06 09:56:00
2017-01-06 09:57:00
2017-01-06 09:58:00

2017-01-10 09:57:00
2017-01-10 09:58:00
2017-01-10 09:59:00
2017-01-10 10:00:00
2017-01-10 10:01:00
2017-01-10 10:02:00
2017-01-10 10:03:00
2017-01-10 10:04:00
2017-01-10 10:05:00
2017-01-10 10:06:00
2017-01-10 10:07:00
2017-01-10 10:08:00
2017-01-10 10:09:00
2017-01-10 10:10:00
2017-01-10 10:11:00
2017-01-10 10:12:00
2017-01-10 10:13:00
2017-01-10 10:14:00
2017-01-10 10:15:00
2017-01-10 10:16:00
2017-01-10 10:17:00
2017-01-10 10:18:00
2017-01-10 10:19:00
2017-01-10 10:20:00
2017-01-10 10:21:00
2017-01-10 10:22:00
2017-01-10 10:23:00
2017-01-10 10:24:00
2017-01-10 10:25:00
2017-01-10 10:26:00
2017-01-10 10:27:00
2017-01-10 10:28:00
2017-01-10 10:29:00
2017-01-10 10:30:00
2017-01-10 10:31:00
2017-01-10 10:32:00
2017-01-10 10:33:00
2017-01-10 10:34:00
2017-01-10 10:35:00
2017-01-10 10:36:00
2017-01-10 10:37:00
2017-01-10 10:38:00
2017-01-10 10:39:00
2017-01-10 10:40:00
2017-01-10 10:41:00
2017-01-10 10:42:00
2017-01-10 10:43:00
2017-01-10 10:44:00
2017-01-10 10:45:00
2017-01-10 10:46:00


2017-01-11 10:38:00
2017-01-11 10:39:00
2017-01-11 10:40:00
2017-01-11 10:41:00
2017-01-11 10:42:00
2017-01-11 10:43:00
2017-01-11 10:44:00
2017-01-11 10:45:00
2017-01-11 10:46:00
2017-01-11 10:47:00
2017-01-11 10:48:00
2017-01-11 10:49:00
2017-01-11 10:50:00
2017-01-11 10:51:00
2017-01-11 10:52:00
2017-01-11 10:53:00
2017-01-11 10:54:00
2017-01-11 10:55:00
2017-01-11 10:56:00
2017-01-11 10:57:00
2017-01-11 10:58:00
2017-01-11 10:59:00
2017-01-11 11:00:00
2017-01-11 11:01:00
2017-01-11 11:02:00
2017-01-11 11:03:00
2017-01-11 11:04:00
2017-01-11 11:05:00
2017-01-11 11:06:00
2017-01-11 11:07:00
2017-01-11 11:08:00
2017-01-11 11:09:00
2017-01-11 11:10:00
2017-01-11 11:11:00
2017-01-11 11:12:00
2017-01-11 11:13:00
2017-01-11 11:14:00
2017-01-11 11:15:00
2017-01-11 11:16:00
2017-01-11 11:17:00
2017-01-11 11:18:00
2017-01-11 11:19:00
2017-01-11 11:20:00
2017-01-11 11:21:00
2017-01-11 11:22:00
2017-01-11 11:23:00
2017-01-11 11:24:00
2017-01-11 11:25:00
2017-01-11 11:26:00
2017-01-11 11:27:00


2017-01-12 11:18:00
2017-01-12 11:19:00
2017-01-12 11:20:00
2017-01-12 11:21:00
2017-01-12 11:22:00
2017-01-12 11:23:00
2017-01-12 11:24:00
2017-01-12 11:25:00
2017-01-12 11:26:00
2017-01-12 11:27:00
2017-01-12 11:28:00
2017-01-12 11:29:00
2017-01-12 11:30:00
2017-01-12 11:31:00
2017-01-12 11:32:00
2017-01-12 11:33:00
2017-01-12 11:34:00
2017-01-12 11:35:00
2017-01-12 11:36:00
2017-01-12 11:37:00
2017-01-12 11:38:00
2017-01-12 11:39:00
2017-01-12 11:40:00
2017-01-12 11:41:00
2017-01-12 11:42:00
2017-01-12 11:43:00
2017-01-12 11:44:00
2017-01-12 11:45:00
2017-01-12 11:46:00
2017-01-12 11:47:00
2017-01-12 11:48:00
2017-01-12 11:49:00
2017-01-12 11:50:00
2017-01-12 11:51:00
2017-01-12 11:52:00
2017-01-12 11:53:00
2017-01-12 11:54:00
2017-01-12 11:55:00
2017-01-12 11:56:00
2017-01-12 11:57:00
2017-01-12 11:58:00
2017-01-12 11:59:00
2017-01-12 12:00:00
2017-01-12 12:01:00
2017-01-12 12:02:00
2017-01-12 12:03:00
2017-01-12 12:04:00
2017-01-12 12:05:00
2017-01-12 12:06:00
2017-01-12 12:07:00


2017-01-13 11:58:00
2017-01-13 11:59:00
2017-01-13 12:00:00
2017-01-13 12:01:00
2017-01-13 12:02:00
2017-01-13 12:03:00
2017-01-13 12:04:00
2017-01-13 12:05:00
2017-01-13 12:06:00
2017-01-13 12:07:00
2017-01-13 12:08:00
2017-01-13 12:09:00
2017-01-13 12:10:00
2017-01-13 12:11:00
2017-01-13 12:12:00
2017-01-13 12:13:00
2017-01-13 12:14:00
2017-01-13 12:15:00
2017-01-13 12:16:00
2017-01-13 12:17:00
2017-01-13 12:18:00
2017-01-13 12:19:00
2017-01-13 12:20:00
2017-01-13 12:21:00
2017-01-13 12:22:00
2017-01-13 12:23:00
2017-01-13 12:24:00
2017-01-13 12:25:00
2017-01-13 12:26:00
2017-01-13 12:27:00
2017-01-13 12:28:00
2017-01-13 12:29:00
2017-01-13 12:30:00
2017-01-13 12:31:00
2017-01-13 12:32:00
2017-01-13 12:33:00
2017-01-13 12:34:00
2017-01-13 12:35:00
2017-01-13 12:36:00
2017-01-13 12:37:00
2017-01-13 12:38:00
2017-01-13 12:39:00
2017-01-13 12:40:00
2017-01-13 12:41:00
2017-01-13 12:42:00
2017-01-13 12:43:00
2017-01-13 12:44:00
2017-01-13 12:45:00
2017-01-13 12:46:00
2017-01-13 12:47:00


...

2017-01-26 09:38:00
2017-01-26 09:39:00
2017-01-26 09:40:00
2017-01-26 09:41:00
2017-01-26 09:42:00
2017-01-26 09:43:00
2017-01-26 09:44:00
2017-01-26 09:45:00
2017-01-26 09:46:00
2017-01-26 09:47:00
2017-01-26 09:48:00
2017-01-26 09:49:00
2017-01-26 09:50:00
2017-01-26 09:51:00
2017-01-26 09:52:00
2017-01-26 09:53:00
2017-01-26 09:54:00
2017-01-26 09:55:00
2017-01-26 09:56:00
2017-01-26 09:57:00
2017-01-26 09:58:00
2017-01-26 09:59:00
2017-01-26 10:00:00
2017-01-26 10:01:00
2017-01-26 10:02:00
2017-01-26 10:03:00
2017-01-26 10:04:00
2017-01-26 10:05:00
2017-01-26 10:06:00
2017-01-26 10:07:00
2017-01-26 10:08:00
2017-01-26 10:09:00
2017-01-26 10:10:00
2017-01-26 10:11:00
2017-01-26 10:12:00
2017-01-26 10:13:00
2017-01-26 10:14:00
2017-01-26 10:15:00
2017-01-26 10:16:00
2017-01-26 10:17:00
2017-01-26 10:18:00
2017-01-26 10:19:00
2017-01-26 10:20:00
2017-01-26 10:21:00
2017-01-26 10:22:00
2017-01-26 10:23:00
2017-01-26 10:24:00
2017-01-26 10:25:00
2017-01-26 10:26:00
2017-01-26 10:27:00


2017-01-27 10:18:00
2017-01-27 10:19:00
2017-01-27 10:20:00
2017-01-27 10:21:00
2017-01-27 10:22:00
2017-01-27 10:23:00
2017-01-27 10:24:00
2017-01-27 10:25:00
2017-01-27 10:26:00
2017-01-27 10:27:00
2017-01-27 10:28:00
2017-01-27 10:29:00
2017-01-27 10:30:00
2017-01-27 10:31:00
2017-01-27 10:32:00
2017-01-27 10:33:00
2017-01-27 10:34:00
2017-01-27 10:35:00
2017-01-27 10:36:00
2017-01-27 10:37:00
2017-01-27 10:38:00
2017-01-27 10:39:00
2017-01-27 10:40:00
2017-01-27 10:41:00
2017-01-27 10:42:00
2017-01-27 10:43:00
2017-01-27 10:44:00
2017-01-27 10:45:00
2017-01-27 10:46:00
2017-01-27 10:47:00
2017-01-27 10:48:00
2017-01-27 10:49:00
2017-01-27 10:50:00
2017-01-27 10:51:00
2017-01-27 10:52:00
2017-01-27 10:53:00
2017-01-27 10:54:00
2017-01-27 10:55:00
2017-01-27 10:56:00
2017-01-27 10:57:00
2017-01-27 10:58:00
2017-01-27 10:59:00
2017-01-27 11:00:00
2017-01-27 11:01:00
2017-01-27 11:02:00
2017-01-27 11:03:00
2017-01-27 11:04:00
2017-01-27 11:05:00
2017-01-27 11:06:00
2017-01-27 11:07:00


2017-01-30 10:55:00
2017-01-30 10:56:00
2017-01-30 10:57:00
2017-01-30 10:58:00
2017-01-30 10:59:00
2017-01-30 11:00:00
2017-01-30 11:01:00
2017-01-30 11:02:00
2017-01-30 11:03:00
2017-01-30 11:04:00
2017-01-30 11:05:00
2017-01-30 11:06:00
2017-01-30 11:07:00
2017-01-30 11:08:00
2017-01-30 11:09:00
2017-01-30 11:10:00
2017-01-30 11:11:00
2017-01-30 11:12:00
2017-01-30 11:13:00
2017-01-30 11:14:00
2017-01-30 11:15:00
2017-01-30 11:16:00
2017-01-30 11:17:00
2017-01-30 11:18:00
2017-01-30 11:19:00
2017-01-30 11:20:00
2017-01-30 11:21:00
2017-01-30 11:22:00
2017-01-30 11:23:00
2017-01-30 11:24:00
2017-01-30 11:25:00
2017-01-30 11:26:00
2017-01-30 11:27:00
2017-01-30 11:28:00
2017-01-30 11:29:00
2017-01-30 11:30:00
2017-01-30 11:31:00
2017-01-30 11:32:00
2017-01-30 11:33:00
2017-01-30 11:34:00
2017-01-30 11:35:00
2017-01-30 11:36:00
2017-01-30 11:37:00
2017-01-30 11:38:00
2017-01-30 11:39:00
2017-01-30 11:40:00
2017-01-30 11:41:00
2017-01-30 11:42:00
2017-01-30 11:43:00
2017-01-30 11:44:00


2017-01-31 11:32:00
2017-01-31 11:33:00
2017-01-31 11:34:00
2017-01-31 11:35:00
2017-01-31 11:36:00
2017-01-31 11:37:00
2017-01-31 11:38:00
2017-01-31 11:39:00
2017-01-31 11:40:00
2017-01-31 11:41:00
2017-01-31 11:42:00
2017-01-31 11:43:00
2017-01-31 11:44:00
2017-01-31 11:45:00
2017-01-31 11:46:00
2017-01-31 11:47:00
2017-01-31 11:48:00
2017-01-31 11:49:00
2017-01-31 11:50:00
2017-01-31 11:51:00
2017-01-31 11:52:00
2017-01-31 11:53:00
2017-01-31 11:54:00
2017-01-31 11:55:00
2017-01-31 11:56:00
2017-01-31 11:57:00
2017-01-31 11:58:00
2017-01-31 11:59:00
2017-01-31 12:00:00
2017-01-31 12:01:00
2017-01-31 12:02:00
2017-01-31 12:03:00
2017-01-31 12:04:00
2017-01-31 12:05:00
2017-01-31 12:06:00
2017-01-31 12:07:00
2017-01-31 12:08:00
2017-01-31 12:09:00
2017-01-31 12:10:00
2017-01-31 12:11:00
2017-01-31 12:12:00
2017-01-31 12:13:00
2017-01-31 12:14:00
2017-01-31 12:15:00
2017-01-31 12:16:00
2017-01-31 12:17:00
2017-01-31 12:18:00
2017-01-31 12:19:00
2017-01-31 12:20:00
2017-01-31 12:21:00


2017-02-01 12:12:00
2017-02-01 12:13:00
2017-02-01 12:14:00
2017-02-01 12:15:00
2017-02-01 12:16:00
2017-02-01 12:17:00
2017-02-01 12:18:00
2017-02-01 12:19:00
2017-02-01 12:20:00
2017-02-01 12:21:00
2017-02-01 12:22:00
2017-02-01 12:23:00
2017-02-01 12:24:00
2017-02-01 12:25:00
2017-02-01 12:26:00
2017-02-01 12:27:00
2017-02-01 12:28:00
2017-02-01 12:29:00
2017-02-01 12:30:00
2017-02-01 12:31:00
2017-02-01 12:32:00
2017-02-01 12:33:00
2017-02-01 12:34:00
2017-02-01 12:35:00
2017-02-01 12:36:00
2017-02-01 12:37:00
2017-02-01 12:38:00
2017-02-01 12:39:00
2017-02-01 12:40:00
2017-02-01 12:41:00
2017-02-01 12:42:00
2017-02-01 12:43:00
2017-02-01 12:44:00
2017-02-01 12:45:00
2017-02-01 12:46:00
2017-02-01 12:47:00
2017-02-01 12:48:00
2017-02-01 12:49:00
2017-02-01 12:50:00
2017-02-01 12:51:00
2017-02-01 12:52:00
2017-02-01 12:53:00
2017-02-01 12:54:00
2017-02-01 12:55:00
2017-02-01 12:56:00
2017-02-01 12:57:00
2017-02-01 12:58:00
2017-02-01 12:59:00
2017-02-01 13:00:00
2017-02-01 13:01:00


In [7]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData3" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return ['AGW']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 20,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AGW
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-06 09:17:00
2017-01-06 09:18:00
2017-01-06 09:19:00
2017-01-06 09:20:00
2017-01-06 09:21:00
2017-01-06 09:22:00
2017-01-06 09:23:00
2017-01-06 09:24:00
2017-01-06 09:25:00
2017-01-06 09:26:00
2017-01-06 09:27:00
2017-01-06 09:28:00
2017-01-06 09:29:00
2017-01-06 09:30:00
2017-01-06 09:31:00
2017-01-06 09:32:00
2017-01-06 09:33:00
2017-01-06 09:34:00
2017-01-06 09:35:00
2017-01-06 09:36:00
2017-01-06 09:37:00
2017-01-06 09:38:00
2017-01-06 09:39:00
2017-01-06 09:40:00
2017-01-06 09:41:00
2017-01-06 09:42:00
2017-01-06 09:43:00
2017-01-06 09:44:00
2017-01-06 09:45:00
2017-01-06 09:46:00
2017-01-06 09:47:00
2017-01-06 09:48:00
2017-01-06 09:49:00
2017-01-06 09:50:00
2017-01-06 09:51:00
2017-01-06 09:52:00
2017-01-06 09:53:00
2017-01-06 09:54:00
2017-01-06 09:55:00
2017-01-06 09:56:00
2017-01-06 09:57:00
2017-01-06 09:58:00

2017-01-10 09:56:00
2017-01-10 09:57:00
2017-01-10 09:58:00
2017-01-10 09:59:00
2017-01-10 10:00:00
2017-01-10 10:01:00
2017-01-10 10:02:00
2017-01-10 10:03:00
2017-01-10 10:04:00
2017-01-10 10:05:00
2017-01-10 10:06:00
2017-01-10 10:07:00
2017-01-10 10:08:00
2017-01-10 10:09:00
2017-01-10 10:10:00
2017-01-10 10:11:00
2017-01-10 10:12:00
2017-01-10 10:13:00
2017-01-10 10:14:00
2017-01-10 10:15:00
2017-01-10 10:16:00
2017-01-10 10:17:00
2017-01-10 10:18:00
2017-01-10 10:19:00
2017-01-10 10:20:00
2017-01-10 10:21:00
2017-01-10 10:22:00
2017-01-10 10:23:00
2017-01-10 10:24:00
2017-01-10 10:25:00
2017-01-10 10:26:00
2017-01-10 10:27:00
2017-01-10 10:28:00
2017-01-10 10:29:00
2017-01-10 10:30:00
2017-01-10 10:31:00
2017-01-10 10:32:00
2017-01-10 10:33:00
2017-01-10 10:34:00
2017-01-10 10:35:00
2017-01-10 10:36:00
2017-01-10 10:37:00
2017-01-10 10:38:00
2017-01-10 10:39:00
2017-01-10 10:40:00
2017-01-10 10:41:00
2017-01-10 10:42:00
2017-01-10 10:43:00
2017-01-10 10:44:00
2017-01-10 10:45:00


2017-01-11 10:33:00
2017-01-11 10:34:00
2017-01-11 10:35:00
2017-01-11 10:36:00
2017-01-11 10:37:00
2017-01-11 10:38:00
2017-01-11 10:39:00
2017-01-11 10:40:00
2017-01-11 10:41:00
2017-01-11 10:42:00
2017-01-11 10:43:00
2017-01-11 10:44:00
2017-01-11 10:45:00
2017-01-11 10:46:00
2017-01-11 10:47:00
2017-01-11 10:48:00
2017-01-11 10:49:00
2017-01-11 10:50:00
2017-01-11 10:51:00
2017-01-11 10:52:00
2017-01-11 10:53:00
2017-01-11 10:54:00
2017-01-11 10:55:00
2017-01-11 10:56:00
2017-01-11 10:57:00
2017-01-11 10:58:00
2017-01-11 10:59:00
2017-01-11 11:00:00
2017-01-11 11:01:00
2017-01-11 11:02:00
2017-01-11 11:03:00
2017-01-11 11:04:00
2017-01-11 11:05:00
2017-01-11 11:06:00
2017-01-11 11:07:00
2017-01-11 11:08:00
2017-01-11 11:09:00
2017-01-11 11:10:00
2017-01-11 11:11:00
2017-01-11 11:12:00
2017-01-11 11:13:00
2017-01-11 11:14:00
2017-01-11 11:15:00
2017-01-11 11:16:00
2017-01-11 11:17:00
2017-01-11 11:18:00
2017-01-11 11:19:00
2017-01-11 11:20:00
2017-01-11 11:21:00
2017-01-11 11:22:00


2017-01-12 11:12:00
2017-01-12 11:13:00
2017-01-12 11:14:00
2017-01-12 11:15:00
2017-01-12 11:16:00
2017-01-12 11:17:00
2017-01-12 11:18:00
2017-01-12 11:19:00
2017-01-12 11:20:00
2017-01-12 11:21:00
2017-01-12 11:22:00
2017-01-12 11:23:00
2017-01-12 11:24:00
2017-01-12 11:25:00
2017-01-12 11:26:00
2017-01-12 11:27:00
2017-01-12 11:28:00
2017-01-12 11:29:00
2017-01-12 11:30:00
2017-01-12 11:31:00
2017-01-12 11:32:00
2017-01-12 11:33:00
2017-01-12 11:34:00
2017-01-12 11:35:00
2017-01-12 11:36:00
2017-01-12 11:37:00
2017-01-12 11:38:00
2017-01-12 11:39:00
2017-01-12 11:40:00
2017-01-12 11:41:00
2017-01-12 11:42:00
2017-01-12 11:43:00
2017-01-12 11:44:00
2017-01-12 11:45:00
2017-01-12 11:46:00
2017-01-12 11:47:00
2017-01-12 11:48:00
2017-01-12 11:49:00
2017-01-12 11:50:00
2017-01-12 11:51:00
2017-01-12 11:52:00
2017-01-12 11:53:00
2017-01-12 11:54:00
2017-01-12 11:55:00
2017-01-12 11:56:00
2017-01-12 11:57:00
2017-01-12 11:58:00
2017-01-12 11:59:00
2017-01-12 12:00:00
2017-01-12 12:01:00


2017-01-13 11:53:00
2017-01-13 11:54:00
2017-01-13 11:55:00
2017-01-13 11:56:00
2017-01-13 11:57:00
2017-01-13 11:58:00
2017-01-13 11:59:00
2017-01-13 12:00:00
2017-01-13 12:01:00
2017-01-13 12:02:00
2017-01-13 12:03:00
2017-01-13 12:04:00
2017-01-13 12:05:00
2017-01-13 12:06:00
2017-01-13 12:07:00
2017-01-13 12:08:00
2017-01-13 12:09:00
2017-01-13 12:10:00
2017-01-13 12:11:00
2017-01-13 12:12:00
2017-01-13 12:13:00
2017-01-13 12:14:00
2017-01-13 12:15:00
2017-01-13 12:16:00
2017-01-13 12:17:00
2017-01-13 12:18:00
2017-01-13 12:19:00
2017-01-13 12:20:00
2017-01-13 12:21:00
2017-01-13 12:22:00
2017-01-13 12:23:00
2017-01-13 12:24:00
2017-01-13 12:25:00
2017-01-13 12:26:00
2017-01-13 12:27:00
2017-01-13 12:28:00
2017-01-13 12:29:00
2017-01-13 12:30:00
2017-01-13 12:31:00
2017-01-13 12:32:00
2017-01-13 12:33:00
2017-01-13 12:34:00
2017-01-13 12:35:00
2017-01-13 12:36:00
2017-01-13 12:37:00
2017-01-13 12:38:00
2017-01-13 12:39:00
2017-01-13 12:40:00
2017-01-13 12:41:00
2017-01-13 12:42:00


...

2017-01-26 09:27:00
2017-01-26 09:28:00
2017-01-26 09:29:00
2017-01-26 09:30:00
2017-01-26 09:31:00
2017-01-26 09:32:00
2017-01-26 09:33:00
2017-01-26 09:34:00
2017-01-26 09:35:00
2017-01-26 09:36:00
2017-01-26 09:37:00
2017-01-26 09:38:00
2017-01-26 09:39:00
2017-01-26 09:40:00
2017-01-26 09:41:00
2017-01-26 09:42:00
2017-01-26 09:43:00
2017-01-26 09:44:00
2017-01-26 09:45:00
2017-01-26 09:46:00
2017-01-26 09:47:00
2017-01-26 09:48:00
2017-01-26 09:49:00
2017-01-26 09:50:00
2017-01-26 09:51:00
2017-01-26 09:52:00
2017-01-26 09:53:00
2017-01-26 09:54:00
2017-01-26 09:55:00
2017-01-26 09:56:00
2017-01-26 09:57:00
2017-01-26 09:58:00
2017-01-26 09:59:00
2017-01-26 10:00:00
2017-01-26 10:01:00
2017-01-26 10:02:00
2017-01-26 10:03:00
2017-01-26 10:04:00
2017-01-26 10:05:00
2017-01-26 10:06:00
2017-01-26 10:07:00
2017-01-26 10:08:00
2017-01-26 10:09:00
2017-01-26 10:10:00
2017-01-26 10:11:00
2017-01-26 10:12:00
2017-01-26 10:13:00
2017-01-26 10:14:00
2017-01-26 10:15:00
2017-01-26 10:16:00


2017-01-27 10:05:00
2017-01-27 10:06:00
2017-01-27 10:07:00
2017-01-27 10:08:00
2017-01-27 10:09:00
2017-01-27 10:10:00
2017-01-27 10:11:00
2017-01-27 10:12:00
2017-01-27 10:13:00
2017-01-27 10:14:00
2017-01-27 10:15:00
2017-01-27 10:16:00
2017-01-27 10:17:00
2017-01-27 10:18:00
2017-01-27 10:19:00
2017-01-27 10:20:00
2017-01-27 10:21:00
2017-01-27 10:22:00
2017-01-27 10:23:00
2017-01-27 10:24:00
2017-01-27 10:25:00
2017-01-27 10:26:00
2017-01-27 10:27:00
2017-01-27 10:28:00
2017-01-27 10:29:00
2017-01-27 10:30:00
2017-01-27 10:31:00
2017-01-27 10:32:00
2017-01-27 10:33:00
2017-01-27 10:34:00
2017-01-27 10:35:00
2017-01-27 10:36:00
2017-01-27 10:37:00
2017-01-27 10:38:00
2017-01-27 10:39:00
2017-01-27 10:40:00
2017-01-27 10:41:00
2017-01-27 10:42:00
2017-01-27 10:43:00
2017-01-27 10:44:00
2017-01-27 10:45:00
2017-01-27 10:46:00
2017-01-27 10:47:00
2017-01-27 10:48:00
2017-01-27 10:49:00
2017-01-27 10:50:00
2017-01-27 10:51:00
2017-01-27 10:52:00
2017-01-27 10:53:00
2017-01-27 10:54:00


2017-01-30 10:46:00
2017-01-30 10:47:00
2017-01-30 10:48:00
2017-01-30 10:49:00
2017-01-30 10:50:00
2017-01-30 10:51:00
2017-01-30 10:52:00
2017-01-30 10:53:00
2017-01-30 10:54:00
2017-01-30 10:55:00
2017-01-30 10:56:00
2017-01-30 10:57:00
2017-01-30 10:58:00
2017-01-30 10:59:00
2017-01-30 11:00:00
2017-01-30 11:01:00
2017-01-30 11:02:00
2017-01-30 11:03:00
2017-01-30 11:04:00
2017-01-30 11:05:00
2017-01-30 11:06:00
2017-01-30 11:07:00
2017-01-30 11:08:00
2017-01-30 11:09:00
2017-01-30 11:10:00
2017-01-30 11:11:00
2017-01-30 11:12:00
2017-01-30 11:13:00
2017-01-30 11:14:00
2017-01-30 11:15:00
2017-01-30 11:16:00
2017-01-30 11:17:00
2017-01-30 11:18:00
2017-01-30 11:19:00
2017-01-30 11:20:00
2017-01-30 11:21:00
2017-01-30 11:22:00
2017-01-30 11:23:00
2017-01-30 11:24:00
2017-01-30 11:25:00
2017-01-30 11:26:00
2017-01-30 11:27:00
2017-01-30 11:28:00
2017-01-30 11:29:00
2017-01-30 11:30:00
2017-01-30 11:31:00
2017-01-30 11:32:00
2017-01-30 11:33:00
2017-01-30 11:34:00
2017-01-30 11:35:00


2017-01-31 11:23:00
2017-01-31 11:24:00
2017-01-31 11:25:00
2017-01-31 11:26:00
2017-01-31 11:27:00
2017-01-31 11:28:00
2017-01-31 11:29:00
2017-01-31 11:30:00
2017-01-31 11:31:00
2017-01-31 11:32:00
2017-01-31 11:33:00
2017-01-31 11:34:00
2017-01-31 11:35:00
2017-01-31 11:36:00
2017-01-31 11:37:00
2017-01-31 11:38:00
2017-01-31 11:39:00
2017-01-31 11:40:00
2017-01-31 11:41:00
2017-01-31 11:42:00
2017-01-31 11:43:00
2017-01-31 11:44:00
2017-01-31 11:45:00
2017-01-31 11:46:00
2017-01-31 11:47:00
2017-01-31 11:48:00
2017-01-31 11:49:00
2017-01-31 11:50:00
2017-01-31 11:51:00
2017-01-31 11:52:00
2017-01-31 11:53:00
2017-01-31 11:54:00
2017-01-31 11:55:00
2017-01-31 11:56:00
2017-01-31 11:57:00
2017-01-31 11:58:00
2017-01-31 11:59:00
2017-01-31 12:00:00
2017-01-31 12:01:00
2017-01-31 12:02:00
2017-01-31 12:03:00
2017-01-31 12:04:00
2017-01-31 12:05:00
2017-01-31 12:06:00
2017-01-31 12:07:00
2017-01-31 12:08:00
2017-01-31 12:09:00
2017-01-31 12:10:00
2017-01-31 12:11:00
2017-01-31 12:12:00


2017-02-01 12:03:00
2017-02-01 12:04:00
2017-02-01 12:05:00
2017-02-01 12:06:00
2017-02-01 12:07:00
2017-02-01 12:08:00
2017-02-01 12:09:00
2017-02-01 12:10:00
2017-02-01 12:11:00
2017-02-01 12:12:00
2017-02-01 12:13:00
2017-02-01 12:14:00
2017-02-01 12:15:00
2017-02-01 12:16:00
2017-02-01 12:17:00
2017-02-01 12:18:00
2017-02-01 12:19:00
2017-02-01 12:20:00
2017-02-01 12:21:00
2017-02-01 12:22:00
2017-02-01 12:23:00
2017-02-01 12:24:00
2017-02-01 12:25:00
2017-02-01 12:26:00
2017-02-01 12:27:00
2017-02-01 12:28:00
2017-02-01 12:29:00
2017-02-01 12:30:00
2017-02-01 12:31:00
2017-02-01 12:32:00
2017-02-01 12:33:00
2017-02-01 12:34:00
2017-02-01 12:35:00
2017-02-01 12:36:00
2017-02-01 12:37:00
2017-02-01 12:38:00
2017-02-01 12:39:00
2017-02-01 12:40:00
2017-02-01 12:41:00
2017-02-01 12:42:00
2017-02-01 12:43:00
2017-02-01 12:44:00
2017-02-01 12:45:00
2017-02-01 12:46:00
2017-02-01 12:47:00
2017-02-01 12:48:00
2017-02-01 12:49:00
2017-02-01 12:50:00
2017-02-01 12:51:00
2017-02-01 12:52:00


In [9]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData3" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return ['AGW']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 20,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5 - 0.1


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AGW
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-06 09:17:00
2017-01-06 09:18:00
2017-01-06 09:19:00
2017-01-06 09:20:00
2017-01-06 09:21:00
2017-01-06 09:22:00
2017-01-06 09:23:00
2017-01-06 09:24:00
2017-01-06 09:25:00
2017-01-06 09:26:00
2017-01-06 09:27:00
2017-01-06 09:28:00
2017-01-06 09:29:00
2017-01-06 09:30:00
2017-01-06 09:31:00
2017-01-06 09:32:00
2017-01-06 09:33:00
2017-01-06 09:34:00
2017-01-06 09:35:00
2017-01-06 09:36:00
2017-01-06 09:37:00
2017-01-06 09:38:00
2017-01-06 09:39:00
2017-01-06 09:40:00
2017-01-06 09:41:00
2017-01-06 09:42:00
2017-01-06 09:43:00
2017-01-06 09:44:00
2017-01-06 09:45:00
2017-01-06 09:46:00
2017-01-06 09:47:00
2017-01-06 09:48:00
2017-01-06 09:49:00
2017-01-06 09:50:00
2017-01-06 09:51:00
2017-01-06 09:52:00
2017-01-06 09:53:00
2017-01-06 09:54:00
2017-01-06 09:55:00
2017-01-06 09:56:00
2017-01-06 09:57:00
2017-01-06 09:58:00

2017-01-10 09:54:00
2017-01-10 09:55:00
2017-01-10 09:56:00
2017-01-10 09:57:00
2017-01-10 09:58:00
2017-01-10 09:59:00
2017-01-10 10:00:00
2017-01-10 10:01:00
2017-01-10 10:02:00
2017-01-10 10:03:00
2017-01-10 10:04:00
2017-01-10 10:05:00
2017-01-10 10:06:00
2017-01-10 10:07:00
2017-01-10 10:08:00
2017-01-10 10:09:00
2017-01-10 10:10:00
2017-01-10 10:11:00
2017-01-10 10:12:00
2017-01-10 10:13:00
2017-01-10 10:14:00
2017-01-10 10:15:00
2017-01-10 10:16:00
2017-01-10 10:17:00
2017-01-10 10:18:00
2017-01-10 10:19:00
2017-01-10 10:20:00
2017-01-10 10:21:00
2017-01-10 10:22:00
2017-01-10 10:23:00
2017-01-10 10:24:00
2017-01-10 10:25:00
2017-01-10 10:26:00
2017-01-10 10:27:00
2017-01-10 10:28:00
2017-01-10 10:29:00
2017-01-10 10:30:00
2017-01-10 10:31:00
2017-01-10 10:32:00
2017-01-10 10:33:00
2017-01-10 10:34:00
2017-01-10 10:35:00
2017-01-10 10:36:00
2017-01-10 10:37:00
2017-01-10 10:38:00
2017-01-10 10:39:00
2017-01-10 10:40:00
2017-01-10 10:41:00
2017-01-10 10:42:00
2017-01-10 10:43:00


2017-01-11 10:31:00
2017-01-11 10:32:00
2017-01-11 10:33:00
2017-01-11 10:34:00
2017-01-11 10:35:00
2017-01-11 10:36:00
2017-01-11 10:37:00
2017-01-11 10:38:00
2017-01-11 10:39:00
2017-01-11 10:40:00
2017-01-11 10:41:00
2017-01-11 10:42:00
2017-01-11 10:43:00
2017-01-11 10:44:00
2017-01-11 10:45:00
2017-01-11 10:46:00
2017-01-11 10:47:00
2017-01-11 10:48:00
2017-01-11 10:49:00
2017-01-11 10:50:00
2017-01-11 10:51:00
2017-01-11 10:52:00
2017-01-11 10:53:00
2017-01-11 10:54:00
2017-01-11 10:55:00
2017-01-11 10:56:00
2017-01-11 10:57:00
2017-01-11 10:58:00
2017-01-11 10:59:00
2017-01-11 11:00:00
2017-01-11 11:01:00
2017-01-11 11:02:00
2017-01-11 11:03:00
2017-01-11 11:04:00
2017-01-11 11:05:00
2017-01-11 11:06:00
2017-01-11 11:07:00
2017-01-11 11:08:00
2017-01-11 11:09:00
2017-01-11 11:10:00
2017-01-11 11:11:00
2017-01-11 11:12:00
2017-01-11 11:13:00
2017-01-11 11:14:00
2017-01-11 11:15:00
2017-01-11 11:16:00
2017-01-11 11:17:00
2017-01-11 11:18:00
2017-01-11 11:19:00
2017-01-11 11:20:00


2017-01-12 11:09:00
2017-01-12 11:10:00
2017-01-12 11:11:00
2017-01-12 11:12:00
2017-01-12 11:13:00
2017-01-12 11:14:00
2017-01-12 11:15:00
2017-01-12 11:16:00
2017-01-12 11:17:00
2017-01-12 11:18:00
2017-01-12 11:19:00
2017-01-12 11:20:00
2017-01-12 11:21:00
2017-01-12 11:22:00
2017-01-12 11:23:00
2017-01-12 11:24:00
2017-01-12 11:25:00
2017-01-12 11:26:00
2017-01-12 11:27:00
2017-01-12 11:28:00
2017-01-12 11:29:00
2017-01-12 11:30:00
2017-01-12 11:31:00
2017-01-12 11:32:00
2017-01-12 11:33:00
2017-01-12 11:34:00
2017-01-12 11:35:00
2017-01-12 11:36:00
2017-01-12 11:37:00
2017-01-12 11:38:00
2017-01-12 11:39:00
2017-01-12 11:40:00
2017-01-12 11:41:00
2017-01-12 11:42:00
2017-01-12 11:43:00
2017-01-12 11:44:00
2017-01-12 11:45:00
2017-01-12 11:46:00
2017-01-12 11:47:00
2017-01-12 11:48:00
2017-01-12 11:49:00
2017-01-12 11:50:00
2017-01-12 11:51:00
2017-01-12 11:52:00
2017-01-12 11:53:00
2017-01-12 11:54:00
2017-01-12 11:55:00
2017-01-12 11:56:00
2017-01-12 11:57:00
2017-01-12 11:58:00


2017-01-13 11:49:00
2017-01-13 11:50:00
2017-01-13 11:51:00
2017-01-13 11:52:00
2017-01-13 11:53:00
2017-01-13 11:54:00
2017-01-13 11:55:00
2017-01-13 11:56:00
2017-01-13 11:57:00
2017-01-13 11:58:00
2017-01-13 11:59:00
2017-01-13 12:00:00
2017-01-13 12:01:00
2017-01-13 12:02:00
2017-01-13 12:03:00
2017-01-13 12:04:00
2017-01-13 12:05:00
2017-01-13 12:06:00
2017-01-13 12:07:00
2017-01-13 12:08:00
2017-01-13 12:09:00
2017-01-13 12:10:00
2017-01-13 12:11:00
2017-01-13 12:12:00
2017-01-13 12:13:00
2017-01-13 12:14:00
2017-01-13 12:15:00
2017-01-13 12:16:00
2017-01-13 12:17:00
2017-01-13 12:18:00
2017-01-13 12:19:00
2017-01-13 12:20:00
2017-01-13 12:21:00
2017-01-13 12:22:00
2017-01-13 12:23:00
2017-01-13 12:24:00
2017-01-13 12:25:00
2017-01-13 12:26:00
2017-01-13 12:27:00
2017-01-13 12:28:00
2017-01-13 12:29:00
2017-01-13 12:30:00
2017-01-13 12:31:00
2017-01-13 12:32:00
2017-01-13 12:33:00
2017-01-13 12:34:00
2017-01-13 12:35:00
2017-01-13 12:36:00
2017-01-13 12:37:00
2017-01-13 12:38:00


...

2017-01-23 15:04:00
2017-01-23 15:05:00
2017-01-23 15:06:00
2017-01-23 15:07:00
2017-01-23 15:08:00
2017-01-23 15:09:00
2017-01-23 15:10:00
2017-01-23 15:11:00
2017-01-23 15:12:00
2017-01-23 15:13:00
2017-01-23 15:14:00
2017-01-23 15:15:00
2017-01-23 15:16:00
2017-01-23 15:17:00
2017-01-23 15:18:00
2017-01-23 15:19:00
2017-01-23 15:20:00
2017-01-23 15:21:00
2017-01-23 15:22:00
2017-01-23 15:23:00
2017-01-23 15:24:00
2017-01-23 15:25:00
2017-01-23 15:26:00
2017-01-23 15:27:00
2017-01-23 15:28:00
2017-01-23 15:29:00
2017-01-25 09:17:00
2017-01-25 09:18:00
2017-01-25 09:19:00
2017-01-25 09:20:00
2017-01-25 09:21:00
2017-01-25 09:22:00
2017-01-25 09:23:00
2017-01-25 09:24:00
2017-01-25 09:25:00
2017-01-25 09:26:00
2017-01-25 09:27:00
2017-01-25 09:28:00
2017-01-25 09:29:00
2017-01-25 09:30:00
2017-01-25 09:31:00
2017-01-25 09:32:00
2017-01-25 09:33:00
2017-01-25 09:34:00
2017-01-25 09:35:00
2017-01-25 09:36:00
2017-01-25 09:37:00
2017-01-25 09:38:00
2017-01-25 09:39:00
2017-01-25 09:40:00


2017-01-26 09:30:00
2017-01-26 09:31:00
2017-01-26 09:32:00
2017-01-26 09:33:00
2017-01-26 09:34:00
2017-01-26 09:35:00
2017-01-26 09:36:00
2017-01-26 09:37:00
2017-01-26 09:38:00
2017-01-26 09:39:00
2017-01-26 09:40:00
2017-01-26 09:41:00
2017-01-26 09:42:00
2017-01-26 09:43:00
2017-01-26 09:44:00
2017-01-26 09:45:00
2017-01-26 09:46:00
2017-01-26 09:47:00
2017-01-26 09:48:00
2017-01-26 09:49:00
2017-01-26 09:50:00
2017-01-26 09:51:00
2017-01-26 09:52:00
2017-01-26 09:53:00
2017-01-26 09:54:00
2017-01-26 09:55:00
2017-01-26 09:56:00
2017-01-26 09:57:00
2017-01-26 09:58:00
2017-01-26 09:59:00
2017-01-26 10:00:00
2017-01-26 10:01:00
2017-01-26 10:02:00
2017-01-26 10:03:00
2017-01-26 10:04:00
2017-01-26 10:05:00
2017-01-26 10:06:00
2017-01-26 10:07:00
2017-01-26 10:08:00
2017-01-26 10:09:00
2017-01-26 10:10:00
2017-01-26 10:11:00
2017-01-26 10:12:00
2017-01-26 10:13:00
2017-01-26 10:14:00
2017-01-26 10:15:00
2017-01-26 10:16:00
2017-01-26 10:17:00
2017-01-26 10:18:00
2017-01-26 10:19:00


2017-01-27 10:09:00
2017-01-27 10:10:00
2017-01-27 10:11:00
2017-01-27 10:12:00
2017-01-27 10:13:00
2017-01-27 10:14:00
2017-01-27 10:15:00
2017-01-27 10:16:00
2017-01-27 10:17:00
2017-01-27 10:18:00
2017-01-27 10:19:00
2017-01-27 10:20:00
2017-01-27 10:21:00
2017-01-27 10:22:00
2017-01-27 10:23:00
2017-01-27 10:24:00
2017-01-27 10:25:00
2017-01-27 10:26:00
2017-01-27 10:27:00
2017-01-27 10:28:00
2017-01-27 10:29:00
2017-01-27 10:30:00
2017-01-27 10:31:00
2017-01-27 10:32:00
2017-01-27 10:33:00
2017-01-27 10:34:00
2017-01-27 10:35:00
2017-01-27 10:36:00
2017-01-27 10:37:00
2017-01-27 10:38:00
2017-01-27 10:39:00
2017-01-27 10:40:00
2017-01-27 10:41:00
2017-01-27 10:42:00
2017-01-27 10:43:00
2017-01-27 10:44:00
2017-01-27 10:45:00
2017-01-27 10:46:00
2017-01-27 10:47:00
2017-01-27 10:48:00
2017-01-27 10:49:00
2017-01-27 10:50:00
2017-01-27 10:51:00
2017-01-27 10:52:00
2017-01-27 10:53:00
2017-01-27 10:54:00
2017-01-27 10:55:00
2017-01-27 10:56:00
2017-01-27 10:57:00
2017-01-27 10:58:00


2017-01-30 10:46:00
2017-01-30 10:47:00
2017-01-30 10:48:00
2017-01-30 10:49:00
2017-01-30 10:50:00
2017-01-30 10:51:00
2017-01-30 10:52:00
2017-01-30 10:53:00
2017-01-30 10:54:00
2017-01-30 10:55:00
2017-01-30 10:56:00
2017-01-30 10:57:00
2017-01-30 10:58:00
2017-01-30 10:59:00
2017-01-30 11:00:00
2017-01-30 11:01:00
2017-01-30 11:02:00
2017-01-30 11:03:00
2017-01-30 11:04:00
2017-01-30 11:05:00
2017-01-30 11:06:00
2017-01-30 11:07:00
2017-01-30 11:08:00
2017-01-30 11:09:00
2017-01-30 11:10:00
2017-01-30 11:11:00
2017-01-30 11:12:00
2017-01-30 11:13:00
2017-01-30 11:14:00
2017-01-30 11:15:00
2017-01-30 11:16:00
2017-01-30 11:17:00
2017-01-30 11:18:00
2017-01-30 11:19:00
2017-01-30 11:20:00
2017-01-30 11:21:00
2017-01-30 11:22:00
2017-01-30 11:23:00
2017-01-30 11:24:00
2017-01-30 11:25:00
2017-01-30 11:26:00
2017-01-30 11:27:00
2017-01-30 11:28:00
2017-01-30 11:29:00
2017-01-30 11:30:00
2017-01-30 11:31:00
2017-01-30 11:32:00
2017-01-30 11:33:00
2017-01-30 11:34:00
2017-01-30 11:35:00


2017-02-01 11:59:00
2017-02-01 12:00:00
2017-02-01 12:01:00
2017-02-01 12:02:00
2017-02-01 12:03:00
2017-02-01 12:04:00
2017-02-01 12:05:00
2017-02-01 12:06:00
2017-02-01 12:07:00
2017-02-01 12:08:00
2017-02-01 12:09:00
2017-02-01 12:10:00
2017-02-01 12:11:00
2017-02-01 12:12:00
2017-02-01 12:13:00
2017-02-01 12:14:00
2017-02-01 12:15:00
2017-02-01 12:16:00
2017-02-01 12:17:00
2017-02-01 12:18:00
2017-02-01 12:19:00
2017-02-01 12:20:00
2017-02-01 12:21:00
2017-02-01 12:22:00
2017-02-01 12:23:00
2017-02-01 12:24:00
2017-02-01 12:25:00
2017-02-01 12:26:00
2017-02-01 12:27:00
2017-02-01 12:28:00
2017-02-01 12:29:00
2017-02-01 12:30:00
2017-02-01 12:31:00
2017-02-01 12:32:00
2017-02-01 12:33:00
2017-02-01 12:34:00
2017-02-01 12:35:00
2017-02-01 12:36:00
2017-02-01 12:37:00
2017-02-01 12:38:00
2017-02-01 12:39:00
2017-02-01 12:40:00
2017-02-01 12:41:00
2017-02-01 12:42:00
2017-02-01 12:43:00
2017-02-01 12:44:00
2017-02-01 12:45:00
2017-02-01 12:46:00
2017-02-01 12:47:00
2017-02-01 12:48:00


In [10]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData3" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return []

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 20,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5+0.1


'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AGW
Processing data for stock: AIO
Processing data for stock: AUZ
Processing data for stock: BSN
Processing data for stock: BWU
Processing data for stock: CBT
Processing data for stock: CHV
Processing data for stock: CSR
Processing data for stock: CUN
Processing data for stock: CYD
Processing data for stock: DCO
Processing data for stock: DFZ
Processing data for stock: DVV
Processing data for stock: DYE
Processing data for stock: EGV
Processing data for stock: FCY
Processing data for stock: FFA
Processing data for stock: FFS
Processing data for stock: FKI
Processing data for stock: FRE
Processing data for stock: FUR
Processing data for stock: GFQ
Processing data for stock: GGK
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: HHK
Processing data for stock: IES
Processing data for stock: IFL
Processing data for stock: ILW
Processing data for stock: IMC
Processing data for stock: IUE
Processing data for stock: IUQ
Processi

2017-01-06 13:48:00
2017-01-06 13:49:00
2017-01-06 13:50:00
2017-01-06 13:51:00
2017-01-06 13:52:00
2017-01-06 13:53:00
2017-01-06 13:54:00
2017-01-06 13:55:00
2017-01-06 13:56:00
2017-01-06 13:57:00
2017-01-06 13:58:00
2017-01-06 13:59:00
2017-01-06 14:00:00
2017-01-06 14:01:00
2017-01-06 14:02:00
2017-01-06 14:03:00
2017-01-06 14:04:00
2017-01-06 14:05:00
2017-01-06 14:06:00
2017-01-06 14:07:00
2017-01-06 14:08:00
2017-01-06 14:09:00
2017-01-06 14:10:00
2017-01-06 14:11:00
2017-01-06 14:12:00
2017-01-06 14:13:00
2017-01-06 14:14:00
2017-01-06 14:15:00
2017-01-06 14:16:00
2017-01-06 14:17:00
2017-01-06 14:18:00
2017-01-06 14:19:00
2017-01-06 14:20:00
2017-01-06 14:21:00
2017-01-06 14:22:00
2017-01-06 14:23:00
2017-01-06 14:24:00
2017-01-06 14:25:00
2017-01-06 14:26:00
2017-01-06 14:27:00
2017-01-06 14:28:00
2017-01-06 14:29:00
2017-01-06 14:30:00
2017-01-06 14:31:00
2017-01-06 14:32:00
2017-01-06 14:33:00
2017-01-06 14:34:00
2017-01-06 14:35:00
2017-01-06 14:36:00
2017-01-06 14:37:00


2017-01-10 14:26:00
2017-01-10 14:27:00
2017-01-10 14:28:00
2017-01-10 14:29:00
2017-01-10 14:30:00
2017-01-10 14:31:00
2017-01-10 14:32:00
2017-01-10 14:33:00
2017-01-10 14:34:00
2017-01-10 14:35:00
2017-01-10 14:36:00
2017-01-10 14:37:00
2017-01-10 14:38:00
2017-01-10 14:39:00
2017-01-10 14:40:00
2017-01-10 14:41:00
2017-01-10 14:42:00
2017-01-10 14:43:00
2017-01-10 14:44:00
2017-01-10 14:45:00
2017-01-10 14:46:00
2017-01-10 14:47:00
2017-01-10 14:48:00
2017-01-10 14:49:00
2017-01-10 14:50:00
2017-01-10 14:51:00
2017-01-10 14:52:00
2017-01-10 14:53:00
2017-01-10 14:54:00
2017-01-10 14:55:00
2017-01-10 14:56:00
2017-01-10 14:57:00
2017-01-10 14:58:00
2017-01-10 14:59:00
2017-01-10 15:00:00
2017-01-10 15:01:00
2017-01-10 15:02:00
2017-01-10 15:03:00
2017-01-10 15:04:00
2017-01-10 15:05:00
2017-01-10 15:06:00
2017-01-10 15:07:00
2017-01-10 15:08:00
2017-01-10 15:09:00
2017-01-10 15:10:00
2017-01-10 15:11:00
2017-01-10 15:12:00
2017-01-10 15:13:00
2017-01-10 15:14:00
2017-01-10 15:15:00


2017-01-11 15:04:00
2017-01-11 15:05:00
2017-01-11 15:06:00
2017-01-11 15:07:00
2017-01-11 15:08:00
2017-01-11 15:09:00
2017-01-11 15:10:00
2017-01-11 15:11:00
2017-01-11 15:12:00
2017-01-11 15:13:00
2017-01-11 15:14:00
2017-01-11 15:15:00
2017-01-11 15:16:00
2017-01-11 15:17:00
2017-01-11 15:18:00
2017-01-11 15:19:00
2017-01-11 15:20:00
2017-01-11 15:21:00
2017-01-11 15:22:00
2017-01-11 15:23:00
2017-01-11 15:24:00
2017-01-11 15:25:00
2017-01-11 15:26:00
2017-01-11 15:27:00
2017-01-11 15:28:00
2017-01-11 15:29:00
2017-01-12 09:17:00
2017-01-12 09:18:00
2017-01-12 09:19:00
2017-01-12 09:20:00
2017-01-12 09:21:00
2017-01-12 09:22:00
2017-01-12 09:23:00
2017-01-12 09:24:00
2017-01-12 09:25:00
2017-01-12 09:26:00
2017-01-12 09:27:00
2017-01-12 09:28:00
2017-01-12 09:29:00
2017-01-12 09:30:00
2017-01-12 09:31:00
2017-01-12 09:32:00
2017-01-12 09:33:00
2017-01-12 09:34:00
2017-01-12 09:35:00
2017-01-12 09:36:00
2017-01-12 09:37:00
2017-01-12 09:38:00
2017-01-12 09:39:00
2017-01-12 09:40:00


2017-01-13 09:28:00
2017-01-13 09:29:00
2017-01-13 09:30:00
2017-01-13 09:31:00
2017-01-13 09:32:00
2017-01-13 09:33:00
2017-01-13 09:34:00
2017-01-13 09:35:00
2017-01-13 09:36:00
2017-01-13 09:37:00
2017-01-13 09:38:00
2017-01-13 09:39:00
2017-01-13 09:40:00
2017-01-13 09:41:00
2017-01-13 09:42:00
2017-01-13 09:43:00
2017-01-13 09:44:00
2017-01-13 09:45:00
2017-01-13 09:46:00
2017-01-13 09:47:00
2017-01-13 09:48:00
2017-01-13 09:49:00
2017-01-13 09:50:00
2017-01-13 09:51:00
2017-01-13 09:52:00
2017-01-13 09:53:00
2017-01-13 09:54:00
2017-01-13 09:55:00
2017-01-13 09:56:00
2017-01-13 09:57:00
2017-01-13 09:58:00
2017-01-13 09:59:00
2017-01-13 10:00:00
2017-01-13 10:01:00
2017-01-13 10:02:00
2017-01-13 10:03:00
2017-01-13 10:04:00
2017-01-13 10:05:00
2017-01-13 10:06:00
2017-01-13 10:07:00
2017-01-13 10:08:00
2017-01-13 10:09:00
2017-01-13 10:10:00
2017-01-13 10:11:00
2017-01-13 10:12:00
2017-01-13 10:13:00
2017-01-13 10:14:00
2017-01-13 10:15:00
2017-01-13 10:16:00
2017-01-13 10:17:00


...

2017-01-27 14:31:00
2017-01-27 14:32:00
2017-01-27 14:33:00
2017-01-27 14:34:00
2017-01-27 14:35:00
2017-01-27 14:36:00
2017-01-27 14:37:00
2017-01-27 14:38:00
2017-01-27 14:39:00
2017-01-27 14:40:00
2017-01-27 14:41:00
2017-01-27 14:42:00
2017-01-27 14:43:00
2017-01-27 14:44:00
2017-01-27 14:45:00
2017-01-27 14:46:00
2017-01-27 14:47:00
2017-01-27 14:48:00
2017-01-27 14:49:00
2017-01-27 14:50:00
2017-01-27 14:51:00
2017-01-27 14:52:00
2017-01-27 14:53:00
2017-01-27 14:54:00
2017-01-27 14:55:00
2017-01-27 14:56:00
2017-01-27 14:57:00
2017-01-27 14:58:00
2017-01-27 14:59:00
2017-01-27 15:00:00
2017-01-27 15:01:00
2017-01-27 15:02:00
2017-01-27 15:03:00
2017-01-27 15:04:00
2017-01-27 15:05:00
2017-01-27 15:06:00
2017-01-27 15:07:00
2017-01-27 15:08:00
2017-01-27 15:09:00
2017-01-27 15:10:00
2017-01-27 15:11:00
2017-01-27 15:12:00
2017-01-27 15:13:00
2017-01-27 15:14:00
2017-01-27 15:15:00
2017-01-27 15:16:00
2017-01-27 15:17:00
2017-01-27 15:18:00
2017-01-27 15:19:00
2017-01-27 15:20:00


2017-01-30 15:08:00
2017-01-30 15:09:00
2017-01-30 15:10:00
2017-01-30 15:11:00
2017-01-30 15:12:00
2017-01-30 15:13:00
2017-01-30 15:14:00
2017-01-30 15:15:00
2017-01-30 15:16:00
2017-01-30 15:17:00
2017-01-30 15:18:00
2017-01-30 15:19:00
2017-01-30 15:20:00
2017-01-30 15:21:00
2017-01-30 15:22:00
2017-01-30 15:23:00
2017-01-30 15:24:00
2017-01-30 15:25:00
2017-01-30 15:26:00
2017-01-30 15:27:00
2017-01-30 15:28:00
2017-01-30 15:29:00
2017-01-31 09:17:00
2017-01-31 09:18:00
2017-01-31 09:19:00
2017-01-31 09:20:00
2017-01-31 09:21:00
2017-01-31 09:22:00
2017-01-31 09:23:00
2017-01-31 09:24:00
2017-01-31 09:25:00
2017-01-31 09:26:00
2017-01-31 09:27:00
2017-01-31 09:28:00
2017-01-31 09:29:00
2017-01-31 09:30:00
2017-01-31 09:31:00
2017-01-31 09:32:00
2017-01-31 09:33:00
2017-01-31 09:34:00
2017-01-31 09:35:00
2017-01-31 09:36:00
2017-01-31 09:37:00
2017-01-31 09:38:00
2017-01-31 09:39:00
2017-01-31 09:40:00
2017-01-31 09:41:00
2017-01-31 09:42:00
2017-01-31 09:43:00
2017-01-31 09:44:00


2017-02-01 09:33:00
2017-02-01 09:34:00
2017-02-01 09:35:00
2017-02-01 09:36:00
2017-02-01 09:37:00
2017-02-01 09:38:00
2017-02-01 09:39:00
2017-02-01 09:40:00
2017-02-01 09:41:00
2017-02-01 09:42:00
2017-02-01 09:43:00
2017-02-01 09:44:00
2017-02-01 09:45:00
2017-02-01 09:46:00
2017-02-01 09:47:00
2017-02-01 09:48:00
2017-02-01 09:49:00
2017-02-01 09:50:00
2017-02-01 09:51:00
2017-02-01 09:52:00
2017-02-01 09:53:00
2017-02-01 09:54:00
2017-02-01 09:55:00
2017-02-01 09:56:00
2017-02-01 09:57:00
2017-02-01 09:58:00
2017-02-01 09:59:00
2017-02-01 10:00:00
2017-02-01 10:01:00
2017-02-01 10:02:00
2017-02-01 10:03:00
2017-02-01 10:04:00
2017-02-01 10:05:00
2017-02-01 10:06:00
2017-02-01 10:07:00
2017-02-01 10:08:00
2017-02-01 10:09:00
2017-02-01 10:10:00
2017-02-01 10:11:00
2017-02-01 10:12:00
2017-02-01 10:13:00
2017-02-01 10:14:00
2017-02-01 10:15:00
2017-02-01 10:16:00
2017-02-01 10:17:00
2017-02-01 10:18:00
2017-02-01 10:19:00
2017-02-01 10:20:00
2017-02-01 10:21:00
2017-02-01 10:22:00


2017-02-02 10:11:00
2017-02-02 10:12:00
2017-02-02 10:13:00
2017-02-02 10:14:00
2017-02-02 10:15:00
2017-02-02 10:16:00
2017-02-02 10:17:00
2017-02-02 10:18:00
2017-02-02 10:19:00
2017-02-02 10:20:00
2017-02-02 10:21:00
2017-02-02 10:22:00
2017-02-02 10:23:00
2017-02-02 10:24:00
2017-02-02 10:25:00
2017-02-02 10:26:00
2017-02-02 10:27:00
2017-02-02 10:28:00
2017-02-02 10:29:00
2017-02-02 10:30:00
2017-02-02 10:31:00
2017-02-02 10:32:00
2017-02-02 10:33:00
2017-02-02 10:34:00
2017-02-02 10:35:00
2017-02-02 10:36:00
2017-02-02 10:37:00
2017-02-02 10:38:00
2017-02-02 10:39:00
2017-02-02 10:40:00
2017-02-02 10:41:00
2017-02-02 10:42:00
2017-02-02 10:43:00
2017-02-02 10:44:00
2017-02-02 10:45:00
2017-02-02 10:46:00
2017-02-02 10:47:00
2017-02-02 10:48:00
2017-02-02 10:49:00
2017-02-02 10:50:00
2017-02-02 10:51:00
2017-02-02 10:52:00
2017-02-02 10:53:00
2017-02-02 10:54:00
2017-02-02 10:55:00
2017-02-02 10:56:00
2017-02-02 10:57:00
2017-02-02 10:58:00
2017-02-02 10:59:00
2017-02-02 11:00:00


Info: KKG:  Total Pnl: 0.70%  Profit/Loss Ratio: 1.02  Accuracy: 0.43  Score: 0.11  Normalized Score: 2.96 
Info: UWD:  Total Pnl: 7.63%  Profit/Loss Ratio: 1.26  Accuracy: 0.48  Score: 0.29  Normalized Score: 1.43 
Info: VSL:  Total Pnl: 2.05%  Profit/Loss Ratio: 1.11  Accuracy: 0.45  Score: 0.19  Normalized Score: 2.12 
Info: FFA:  Total Pnl: 1.01%  Profit/Loss Ratio: 1.04  Accuracy: 0.44  Score: 0.16  Normalized Score: 2.50 
Info: OED:  Total Pnl: 7.79%  Profit/Loss Ratio: 1.29  Accuracy: 0.47  Score: 0.30  Normalized Score: 1.54 
Info:  Total Pnl: 452.90%  Score: 1.99  Max Drawdown: 6.87%  RoC: 7559.60%  P/L Ratio: 1.95  Accuracy: 0.59  Score: 1.99 


In [8]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData3" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return []

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 20,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AGW
Processing data for stock: AIO
Processing data for stock: AUZ
Processing data for stock: BSN
Processing data for stock: BWU
Processing data for stock: CBT
Processing data for stock: CHV
Processing data for stock: CSR
Processing data for stock: CUN
Processing data for stock: CYD
Processing data for stock: DCO
Processing data for stock: DFZ
Processing data for stock: DVV
Processing data for stock: DYE
Processing data for stock: EGV
Processing data for stock: FCY
Processing data for stock: FFA
Processing data for stock: FFS
Processing data for stock: FKI
Processing data for stock: FRE
Processing data for stock: FUR
Processing data for stock: GFQ
Processing data for stock: GGK
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: HHK
Processing data for stock: IES
Processing data for stock: IFL
Processing data for stock: ILW
Processing data for stock: IMC
Processing data for stock: IUE
Processing data for stock: IUQ
Processi

2017-01-06 13:47:00
2017-01-06 13:48:00
2017-01-06 13:49:00
2017-01-06 13:50:00
2017-01-06 13:51:00
2017-01-06 13:52:00
2017-01-06 13:53:00
2017-01-06 13:54:00
2017-01-06 13:55:00
2017-01-06 13:56:00
2017-01-06 13:57:00
2017-01-06 13:58:00
2017-01-06 13:59:00
2017-01-06 14:00:00
2017-01-06 14:01:00
2017-01-06 14:02:00
2017-01-06 14:03:00
2017-01-06 14:04:00
2017-01-06 14:05:00
2017-01-06 14:06:00
2017-01-06 14:07:00
2017-01-06 14:08:00
2017-01-06 14:09:00
2017-01-06 14:10:00
2017-01-06 14:11:00
2017-01-06 14:12:00
2017-01-06 14:13:00
2017-01-06 14:14:00
2017-01-06 14:15:00
2017-01-06 14:16:00
2017-01-06 14:17:00
2017-01-06 14:18:00
2017-01-06 14:19:00
2017-01-06 14:20:00
2017-01-06 14:21:00
2017-01-06 14:22:00
2017-01-06 14:23:00
2017-01-06 14:24:00
2017-01-06 14:25:00
2017-01-06 14:26:00
2017-01-06 14:27:00
2017-01-06 14:28:00
2017-01-06 14:29:00
2017-01-06 14:30:00
2017-01-06 14:31:00
2017-01-06 14:32:00
2017-01-06 14:33:00
2017-01-06 14:34:00
2017-01-06 14:35:00
2017-01-06 14:36:00


2017-01-10 14:24:00
2017-01-10 14:25:00
2017-01-10 14:26:00
2017-01-10 14:27:00
2017-01-10 14:28:00
2017-01-10 14:29:00
2017-01-10 14:30:00
2017-01-10 14:31:00
2017-01-10 14:32:00
2017-01-10 14:33:00
2017-01-10 14:34:00
2017-01-10 14:35:00
2017-01-10 14:36:00
2017-01-10 14:37:00
2017-01-10 14:38:00
2017-01-10 14:39:00
2017-01-10 14:40:00
2017-01-10 14:41:00
2017-01-10 14:42:00
2017-01-10 14:43:00
2017-01-10 14:44:00
2017-01-10 14:45:00
2017-01-10 14:46:00
2017-01-10 14:47:00
2017-01-10 14:48:00
2017-01-10 14:49:00
2017-01-10 14:50:00
2017-01-10 14:51:00
2017-01-10 14:52:00
2017-01-10 14:53:00
2017-01-10 14:54:00
2017-01-10 14:55:00
2017-01-10 14:56:00
2017-01-10 14:57:00
2017-01-10 14:58:00
2017-01-10 14:59:00
2017-01-10 15:00:00
2017-01-10 15:01:00
2017-01-10 15:02:00
2017-01-10 15:03:00
2017-01-10 15:04:00
2017-01-10 15:05:00
2017-01-10 15:06:00
2017-01-10 15:07:00
2017-01-10 15:08:00
2017-01-10 15:09:00
2017-01-10 15:10:00
2017-01-10 15:11:00
2017-01-10 15:12:00
2017-01-10 15:13:00


2017-01-11 15:03:00
2017-01-11 15:04:00
2017-01-11 15:05:00
2017-01-11 15:06:00
2017-01-11 15:07:00
2017-01-11 15:08:00
2017-01-11 15:09:00
2017-01-11 15:10:00
2017-01-11 15:11:00
2017-01-11 15:12:00
2017-01-11 15:13:00
2017-01-11 15:14:00
2017-01-11 15:15:00
2017-01-11 15:16:00
2017-01-11 15:17:00
2017-01-11 15:18:00
2017-01-11 15:19:00
2017-01-11 15:20:00
2017-01-11 15:21:00
2017-01-11 15:22:00
2017-01-11 15:23:00
2017-01-11 15:24:00
2017-01-11 15:25:00
2017-01-11 15:26:00
2017-01-11 15:27:00
2017-01-11 15:28:00
2017-01-11 15:29:00
2017-01-12 09:17:00
2017-01-12 09:18:00
2017-01-12 09:19:00
2017-01-12 09:20:00
2017-01-12 09:21:00
2017-01-12 09:22:00
2017-01-12 09:23:00
2017-01-12 09:24:00
2017-01-12 09:25:00
2017-01-12 09:26:00
2017-01-12 09:27:00
2017-01-12 09:28:00
2017-01-12 09:29:00
2017-01-12 09:30:00
2017-01-12 09:31:00
2017-01-12 09:32:00
2017-01-12 09:33:00
2017-01-12 09:34:00
2017-01-12 09:35:00
2017-01-12 09:36:00
2017-01-12 09:37:00
2017-01-12 09:38:00
2017-01-12 09:39:00


2017-01-13 09:28:00
2017-01-13 09:29:00
2017-01-13 09:30:00
2017-01-13 09:31:00
2017-01-13 09:32:00
2017-01-13 09:33:00
2017-01-13 09:34:00
2017-01-13 09:35:00
2017-01-13 09:36:00
2017-01-13 09:37:00
2017-01-13 09:38:00
2017-01-13 09:39:00
2017-01-13 09:40:00
2017-01-13 09:41:00
2017-01-13 09:42:00
2017-01-13 09:43:00
2017-01-13 09:44:00
2017-01-13 09:45:00
2017-01-13 09:46:00
2017-01-13 09:47:00
2017-01-13 09:48:00
2017-01-13 09:49:00
2017-01-13 09:50:00
2017-01-13 09:51:00
2017-01-13 09:52:00
2017-01-13 09:53:00
2017-01-13 09:54:00
2017-01-13 09:55:00
2017-01-13 09:56:00
2017-01-13 09:57:00
2017-01-13 09:58:00
2017-01-13 09:59:00
2017-01-13 10:00:00
2017-01-13 10:01:00
2017-01-13 10:02:00
2017-01-13 10:03:00
2017-01-13 10:04:00
2017-01-13 10:05:00
2017-01-13 10:06:00
2017-01-13 10:07:00
2017-01-13 10:08:00
2017-01-13 10:09:00
2017-01-13 10:10:00
2017-01-13 10:11:00
2017-01-13 10:12:00
2017-01-13 10:13:00
2017-01-13 10:14:00
2017-01-13 10:15:00
2017-01-13 10:16:00
2017-01-13 10:17:00


...

2017-01-26 13:55:00
2017-01-26 13:56:00
2017-01-26 13:57:00
2017-01-26 13:58:00
2017-01-26 13:59:00
2017-01-26 14:00:00
2017-01-26 14:01:00
2017-01-26 14:02:00
2017-01-26 14:03:00
2017-01-26 14:04:00
2017-01-26 14:05:00
2017-01-26 14:06:00
2017-01-26 14:07:00
2017-01-26 14:08:00
2017-01-26 14:09:00
2017-01-26 14:10:00
2017-01-26 14:11:00
2017-01-26 14:12:00
2017-01-26 14:13:00
2017-01-26 14:14:00
2017-01-26 14:15:00
2017-01-26 14:16:00
2017-01-26 14:17:00
2017-01-26 14:18:00
2017-01-26 14:19:00
2017-01-26 14:20:00
2017-01-26 14:21:00
2017-01-26 14:22:00
2017-01-26 14:23:00
2017-01-26 14:24:00
2017-01-26 14:25:00
2017-01-26 14:26:00
2017-01-26 14:27:00
2017-01-26 14:28:00
2017-01-26 14:29:00
2017-01-26 14:30:00
2017-01-26 14:31:00
2017-01-26 14:32:00
2017-01-26 14:33:00
2017-01-26 14:34:00
2017-01-26 14:35:00
2017-01-26 14:36:00
2017-01-26 14:37:00
2017-01-26 14:38:00
2017-01-26 14:39:00
2017-01-26 14:40:00
2017-01-26 14:41:00
2017-01-26 14:42:00
2017-01-26 14:43:00
2017-01-26 14:44:00


2017-01-27 14:33:00
2017-01-27 14:34:00
2017-01-27 14:35:00
2017-01-27 14:36:00
2017-01-27 14:37:00
2017-01-27 14:38:00
2017-01-27 14:39:00
2017-01-27 14:40:00
2017-01-27 14:41:00
2017-01-27 14:42:00
2017-01-27 14:43:00
2017-01-27 14:44:00
2017-01-27 14:45:00
2017-01-27 14:46:00
2017-01-27 14:47:00
2017-01-27 14:48:00
2017-01-27 14:49:00
2017-01-27 14:50:00
2017-01-27 14:51:00
2017-01-27 14:52:00
2017-01-27 14:53:00
2017-01-27 14:54:00
2017-01-27 14:55:00
2017-01-27 14:56:00
2017-01-27 14:57:00
2017-01-27 14:58:00
2017-01-27 14:59:00
2017-01-27 15:00:00
2017-01-27 15:01:00
2017-01-27 15:02:00
2017-01-27 15:03:00
2017-01-27 15:04:00
2017-01-27 15:05:00
2017-01-27 15:06:00
2017-01-27 15:07:00
2017-01-27 15:08:00
2017-01-27 15:09:00
2017-01-27 15:10:00
2017-01-27 15:11:00
2017-01-27 15:12:00
2017-01-27 15:13:00
2017-01-27 15:14:00
2017-01-27 15:15:00
2017-01-27 15:16:00
2017-01-27 15:17:00
2017-01-27 15:18:00
2017-01-27 15:19:00
2017-01-27 15:20:00
2017-01-27 15:21:00
2017-01-27 15:22:00


2017-01-30 15:12:00
2017-01-30 15:13:00
2017-01-30 15:14:00
2017-01-30 15:15:00
2017-01-30 15:16:00
2017-01-30 15:17:00
2017-01-30 15:18:00
2017-01-30 15:19:00
2017-01-30 15:20:00
2017-01-30 15:21:00
2017-01-30 15:22:00
2017-01-30 15:23:00
2017-01-30 15:24:00
2017-01-30 15:25:00
2017-01-30 15:26:00
2017-01-30 15:27:00
2017-01-30 15:28:00
2017-01-30 15:29:00
2017-01-31 09:17:00
2017-01-31 09:18:00
2017-01-31 09:19:00
2017-01-31 09:20:00
2017-01-31 09:21:00
2017-01-31 09:22:00
2017-01-31 09:23:00
2017-01-31 09:24:00
2017-01-31 09:25:00
2017-01-31 09:26:00
2017-01-31 09:27:00
2017-01-31 09:28:00
2017-01-31 09:29:00
2017-01-31 09:30:00
2017-01-31 09:31:00
2017-01-31 09:32:00
2017-01-31 09:33:00
2017-01-31 09:34:00
2017-01-31 09:35:00
2017-01-31 09:36:00
2017-01-31 09:37:00
2017-01-31 09:38:00
2017-01-31 09:39:00
2017-01-31 09:40:00
2017-01-31 09:41:00
2017-01-31 09:42:00
2017-01-31 09:43:00
2017-01-31 09:44:00
2017-01-31 09:45:00
2017-01-31 09:46:00
2017-01-31 09:47:00
2017-01-31 09:48:00


2017-02-01 09:36:00
2017-02-01 09:37:00
2017-02-01 09:38:00
2017-02-01 09:39:00
2017-02-01 09:40:00
2017-02-01 09:41:00
2017-02-01 09:42:00
2017-02-01 09:43:00
2017-02-01 09:44:00
2017-02-01 09:45:00
2017-02-01 09:46:00
2017-02-01 09:47:00
2017-02-01 09:48:00
2017-02-01 09:49:00
2017-02-01 09:50:00
2017-02-01 09:51:00
2017-02-01 09:52:00
2017-02-01 09:53:00
2017-02-01 09:54:00
2017-02-01 09:55:00
2017-02-01 09:56:00
2017-02-01 09:57:00
2017-02-01 09:58:00
2017-02-01 09:59:00
2017-02-01 10:00:00
2017-02-01 10:01:00
2017-02-01 10:02:00
2017-02-01 10:03:00
2017-02-01 10:04:00
2017-02-01 10:05:00
2017-02-01 10:06:00
2017-02-01 10:07:00
2017-02-01 10:08:00
2017-02-01 10:09:00
2017-02-01 10:10:00
2017-02-01 10:11:00
2017-02-01 10:12:00
2017-02-01 10:13:00
2017-02-01 10:14:00
2017-02-01 10:15:00
2017-02-01 10:16:00
2017-02-01 10:17:00
2017-02-01 10:18:00
2017-02-01 10:19:00
2017-02-01 10:20:00
2017-02-01 10:21:00
2017-02-01 10:22:00
2017-02-01 10:23:00
2017-02-01 10:24:00
2017-02-01 10:25:00


2017-02-02 10:13:00
2017-02-02 10:14:00
2017-02-02 10:15:00
2017-02-02 10:16:00
2017-02-02 10:17:00
2017-02-02 10:18:00
2017-02-02 10:19:00
2017-02-02 10:20:00
2017-02-02 10:21:00
2017-02-02 10:22:00
2017-02-02 10:23:00
2017-02-02 10:24:00
2017-02-02 10:25:00
2017-02-02 10:26:00
2017-02-02 10:27:00
2017-02-02 10:28:00
2017-02-02 10:29:00
2017-02-02 10:30:00
2017-02-02 10:31:00
2017-02-02 10:32:00
2017-02-02 10:33:00
2017-02-02 10:34:00
2017-02-02 10:35:00
2017-02-02 10:36:00
2017-02-02 10:37:00
2017-02-02 10:38:00
2017-02-02 10:39:00
2017-02-02 10:40:00
2017-02-02 10:41:00
2017-02-02 10:42:00
2017-02-02 10:43:00
2017-02-02 10:44:00
2017-02-02 10:45:00
2017-02-02 10:46:00
2017-02-02 10:47:00
2017-02-02 10:48:00
2017-02-02 10:49:00
2017-02-02 10:50:00
2017-02-02 10:51:00
2017-02-02 10:52:00
2017-02-02 10:53:00
2017-02-02 10:54:00
2017-02-02 10:55:00
2017-02-02 10:56:00
2017-02-02 10:57:00
2017-02-02 10:58:00
2017-02-02 10:59:00
2017-02-02 11:00:00
2017-02-02 11:01:00
2017-02-02 11:02:00


In [11]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData2" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return []

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 20,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AGW
Processing data for stock: AIO
Processing data for stock: AUZ
Processing data for stock: BSN
Processing data for stock: BWU
Processing data for stock: CBT
Processing data for stock: CHV
Processing data for stock: CSR
Processing data for stock: CUN
Processing data for stock: CYD
Processing data for stock: DCO
Processing data for stock: DFZ
Processing data for stock: DVV
Processing data for stock: DYE
Processing data for stock: EGV
Processing data for stock: FCY
Processing data for stock: FFA
Processing data for stock: FFS
Processing data for stock: FKI
Processing data for stock: FRE
Processing data for stock: FUR
Processing data for stock: GFQ
Processing data for stock: GGK
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: HHK
Processing data for stock: IES
Processing data for stock: IFL
Processing data for stock: ILW
Processing data for stock: IMC
Processing data for stock: IUE
Processing data for stock: IUQ
Processi

2017-01-13 13:48:00
2017-01-13 13:49:00
2017-01-13 13:50:00
2017-01-13 13:51:00
2017-01-13 13:52:00
2017-01-13 13:53:00
2017-01-13 13:54:00
2017-01-13 13:55:00
2017-01-13 13:56:00
2017-01-13 13:57:00
2017-01-13 13:58:00
2017-01-13 13:59:00
2017-01-13 14:00:00
2017-01-13 14:01:00
2017-01-13 14:02:00
2017-01-13 14:03:00
2017-01-13 14:04:00
2017-01-13 14:05:00
2017-01-13 14:06:00
2017-01-13 14:07:00
2017-01-13 14:08:00
2017-01-13 14:09:00
2017-01-13 14:10:00
2017-01-13 14:11:00
2017-01-13 14:12:00
2017-01-13 14:13:00
2017-01-13 14:14:00
2017-01-13 14:15:00
2017-01-13 14:16:00
2017-01-13 14:17:00
2017-01-13 14:18:00
2017-01-13 14:19:00
2017-01-13 14:20:00
2017-01-13 14:21:00
2017-01-13 14:22:00
2017-01-13 14:23:00
2017-01-13 14:24:00
2017-01-13 14:25:00
2017-01-13 14:26:00
2017-01-13 14:27:00
2017-01-13 14:28:00
2017-01-13 14:29:00
2017-01-13 14:30:00
2017-01-13 14:31:00
2017-01-13 14:32:00
2017-01-13 14:33:00
2017-01-13 14:34:00
2017-01-13 14:35:00
2017-01-13 14:36:00
2017-01-13 14:37:00


2017-01-16 14:26:00
2017-01-16 14:27:00
2017-01-16 14:28:00
2017-01-16 14:29:00
2017-01-16 14:30:00
2017-01-16 14:31:00
2017-01-16 14:32:00
2017-01-16 14:33:00
2017-01-16 14:34:00
2017-01-16 14:35:00
2017-01-16 14:36:00
2017-01-16 14:37:00
2017-01-16 14:38:00
2017-01-16 14:39:00
2017-01-16 14:40:00
2017-01-16 14:41:00
2017-01-16 14:42:00
2017-01-16 14:43:00
2017-01-16 14:44:00
2017-01-16 14:45:00
2017-01-16 14:46:00
2017-01-16 14:47:00
2017-01-16 14:48:00
2017-01-16 14:49:00
2017-01-16 14:50:00
2017-01-16 14:51:00
2017-01-16 14:52:00
2017-01-16 14:53:00
2017-01-16 14:54:00
2017-01-16 14:55:00
2017-01-16 14:56:00
2017-01-16 14:57:00
2017-01-16 14:58:00
2017-01-16 14:59:00
2017-01-16 15:00:00
2017-01-16 15:01:00
2017-01-16 15:02:00
2017-01-16 15:03:00
2017-01-16 15:04:00
2017-01-16 15:05:00
2017-01-16 15:06:00
2017-01-16 15:07:00
2017-01-16 15:08:00
2017-01-16 15:09:00
2017-01-16 15:10:00
2017-01-16 15:11:00
2017-01-16 15:12:00
2017-01-16 15:13:00
2017-01-16 15:14:00
2017-01-16 15:15:00


2017-01-18 15:03:00
2017-01-18 15:04:00
2017-01-18 15:05:00
2017-01-18 15:06:00
2017-01-18 15:07:00
2017-01-18 15:08:00
2017-01-18 15:09:00
2017-01-18 15:10:00
2017-01-18 15:11:00
2017-01-18 15:12:00
2017-01-18 15:13:00
2017-01-18 15:14:00
2017-01-18 15:15:00
2017-01-18 15:16:00
2017-01-18 15:17:00
2017-01-18 15:18:00
2017-01-18 15:19:00
2017-01-18 15:20:00
2017-01-18 15:21:00
2017-01-18 15:22:00
2017-01-18 15:23:00
2017-01-18 15:24:00
2017-01-18 15:25:00
2017-01-18 15:26:00
2017-01-18 15:27:00
2017-01-18 15:28:00
2017-01-18 15:29:00
2017-01-19 09:17:00
2017-01-19 09:18:00
2017-01-19 09:19:00
2017-01-19 09:20:00
2017-01-19 09:21:00
2017-01-19 09:22:00
2017-01-19 09:23:00
2017-01-19 09:24:00
2017-01-19 09:25:00
2017-01-19 09:26:00
2017-01-19 09:27:00
2017-01-19 09:28:00
2017-01-19 09:29:00
2017-01-19 09:30:00
2017-01-19 09:31:00
2017-01-19 09:32:00
2017-01-19 09:33:00
2017-01-19 09:34:00
2017-01-19 09:35:00
2017-01-19 09:36:00
2017-01-19 09:37:00
2017-01-19 09:38:00
2017-01-19 09:39:00


2017-01-20 09:29:00
2017-01-20 09:30:00
2017-01-20 09:31:00
2017-01-20 09:32:00
2017-01-20 09:33:00
2017-01-20 09:34:00
2017-01-20 09:35:00
2017-01-20 09:36:00
2017-01-20 09:37:00
2017-01-20 09:38:00
2017-01-20 09:39:00
2017-01-20 09:40:00
2017-01-20 09:41:00
2017-01-20 09:42:00
2017-01-20 09:43:00
2017-01-20 09:44:00
2017-01-20 09:45:00
2017-01-20 09:46:00
2017-01-20 09:47:00
2017-01-20 09:48:00
2017-01-20 09:49:00
2017-01-20 09:50:00
2017-01-20 09:51:00
2017-01-20 09:52:00
2017-01-20 09:53:00
2017-01-20 09:54:00
2017-01-20 09:55:00
2017-01-20 09:56:00
2017-01-20 09:57:00
2017-01-20 09:58:00
2017-01-20 09:59:00
2017-01-20 10:00:00
2017-01-20 10:01:00
2017-01-20 10:02:00
2017-01-20 10:03:00
2017-01-20 10:04:00
2017-01-20 10:05:00
2017-01-20 10:06:00
2017-01-20 10:07:00
2017-01-20 10:08:00
2017-01-20 10:09:00
2017-01-20 10:10:00
2017-01-20 10:11:00
2017-01-20 10:12:00
2017-01-20 10:13:00
2017-01-20 10:14:00
2017-01-20 10:15:00
2017-01-20 10:16:00
2017-01-20 10:17:00
2017-01-20 10:18:00


...

2017-02-02 14:32:00
2017-02-02 14:33:00
2017-02-02 14:34:00
2017-02-02 14:35:00
2017-02-02 14:36:00
2017-02-02 14:37:00
2017-02-02 14:38:00
2017-02-02 14:39:00
2017-02-02 14:40:00
2017-02-02 14:41:00
2017-02-02 14:42:00
2017-02-02 14:43:00
2017-02-02 14:44:00
2017-02-02 14:45:00
2017-02-02 14:46:00
2017-02-02 14:47:00
2017-02-02 14:48:00
2017-02-02 14:49:00
2017-02-02 14:50:00
2017-02-02 14:51:00
2017-02-02 14:52:00
2017-02-02 14:53:00
2017-02-02 14:54:00
2017-02-02 14:55:00
2017-02-02 14:56:00
2017-02-02 14:57:00
2017-02-02 14:58:00
2017-02-02 14:59:00
2017-02-02 15:00:00
2017-02-02 15:01:00
2017-02-02 15:02:00
2017-02-02 15:03:00
2017-02-02 15:04:00
2017-02-02 15:05:00
2017-02-02 15:06:00
2017-02-02 15:07:00
2017-02-02 15:08:00
2017-02-02 15:09:00
2017-02-02 15:10:00
2017-02-02 15:11:00
2017-02-02 15:12:00
2017-02-02 15:13:00
2017-02-02 15:14:00
2017-02-02 15:15:00
2017-02-02 15:16:00
2017-02-02 15:17:00
2017-02-02 15:18:00
2017-02-02 15:19:00
2017-02-02 15:20:00
2017-02-02 15:21:00


2017-02-03 15:10:00
2017-02-03 15:11:00
2017-02-03 15:12:00
2017-02-03 15:13:00
2017-02-03 15:14:00
2017-02-03 15:15:00
2017-02-03 15:16:00
2017-02-03 15:17:00
2017-02-03 15:18:00
2017-02-03 15:19:00
2017-02-03 15:20:00
2017-02-03 15:21:00
2017-02-03 15:22:00
2017-02-03 15:23:00
2017-02-03 15:24:00
2017-02-03 15:25:00
2017-02-03 15:26:00
2017-02-03 15:27:00
2017-02-03 15:28:00
2017-02-03 15:29:00
2017-02-06 09:17:00
2017-02-06 09:18:00
2017-02-06 09:19:00
2017-02-06 09:20:00
2017-02-06 09:21:00
2017-02-06 09:22:00
2017-02-06 09:23:00
2017-02-06 09:24:00
2017-02-06 09:25:00
2017-02-06 09:26:00
2017-02-06 09:27:00
2017-02-06 09:28:00
2017-02-06 09:29:00
2017-02-06 09:30:00
2017-02-06 09:31:00
2017-02-06 09:32:00
2017-02-06 09:33:00
2017-02-06 09:34:00
2017-02-06 09:35:00
2017-02-06 09:36:00
2017-02-06 09:37:00
2017-02-06 09:38:00
2017-02-06 09:39:00
2017-02-06 09:40:00
2017-02-06 09:41:00
2017-02-06 09:42:00
2017-02-06 09:43:00
2017-02-06 09:44:00
2017-02-06 09:45:00
2017-02-06 09:46:00


2017-02-07 09:35:00
2017-02-07 09:36:00
2017-02-07 09:37:00
2017-02-07 09:38:00
2017-02-07 09:39:00
2017-02-07 09:40:00
2017-02-07 09:41:00
2017-02-07 09:42:00
2017-02-07 09:43:00
2017-02-07 09:44:00
2017-02-07 09:45:00
2017-02-07 09:46:00
2017-02-07 09:47:00
2017-02-07 09:48:00
2017-02-07 09:49:00
2017-02-07 09:50:00
2017-02-07 09:51:00
2017-02-07 09:52:00
2017-02-07 09:53:00
2017-02-07 09:54:00
2017-02-07 09:55:00
2017-02-07 09:56:00
2017-02-07 09:57:00
2017-02-07 09:58:00
2017-02-07 09:59:00
2017-02-07 10:00:00
2017-02-07 10:01:00
2017-02-07 10:02:00
2017-02-07 10:03:00
2017-02-07 10:04:00
2017-02-07 10:05:00
2017-02-07 10:06:00
2017-02-07 10:07:00
2017-02-07 10:08:00
2017-02-07 10:09:00
2017-02-07 10:10:00
2017-02-07 10:11:00
2017-02-07 10:12:00
2017-02-07 10:13:00
2017-02-07 10:14:00
2017-02-07 10:15:00
2017-02-07 10:16:00
2017-02-07 10:17:00
2017-02-07 10:18:00
2017-02-07 10:19:00
2017-02-07 10:20:00
2017-02-07 10:21:00
2017-02-07 10:22:00
2017-02-07 10:23:00
2017-02-07 10:24:00


2017-02-08 10:14:00
2017-02-08 10:15:00
2017-02-08 10:16:00
2017-02-08 10:17:00
2017-02-08 10:18:00
2017-02-08 10:19:00
2017-02-08 10:20:00
2017-02-08 10:21:00
2017-02-08 10:22:00
2017-02-08 10:23:00
2017-02-08 10:24:00
2017-02-08 10:25:00
2017-02-08 10:26:00
2017-02-08 10:27:00
2017-02-08 10:28:00
2017-02-08 10:29:00
2017-02-08 10:30:00
2017-02-08 10:31:00
2017-02-08 10:32:00
2017-02-08 10:33:00
2017-02-08 10:34:00
2017-02-08 10:35:00
2017-02-08 10:36:00
2017-02-08 10:37:00
2017-02-08 10:38:00
2017-02-08 10:39:00
2017-02-08 10:40:00
2017-02-08 10:41:00
2017-02-08 10:42:00
2017-02-08 10:43:00
2017-02-08 10:44:00
2017-02-08 10:45:00
2017-02-08 10:46:00
2017-02-08 10:47:00
2017-02-08 10:48:00
2017-02-08 10:49:00
2017-02-08 10:50:00
2017-02-08 10:51:00
2017-02-08 10:52:00
2017-02-08 10:53:00
2017-02-08 10:54:00
2017-02-08 10:55:00
2017-02-08 10:56:00
2017-02-08 10:57:00
2017-02-08 10:58:00
2017-02-08 10:59:00
2017-02-08 11:00:00
2017-02-08 11:01:00
2017-02-08 11:02:00
2017-02-08 11:03:00


2017-02-09 10:53:00
2017-02-09 10:54:00
2017-02-09 10:55:00
2017-02-09 10:56:00
2017-02-09 10:57:00
2017-02-09 10:58:00
2017-02-09 10:59:00
2017-02-09 11:00:00
2017-02-09 11:01:00
2017-02-09 11:02:00
2017-02-09 11:03:00
2017-02-09 11:04:00
2017-02-09 11:05:00
2017-02-09 11:06:00
2017-02-09 11:07:00
2017-02-09 11:08:00
2017-02-09 11:09:00
2017-02-09 11:10:00
2017-02-09 11:11:00
2017-02-09 11:12:00
2017-02-09 11:13:00
2017-02-09 11:14:00
2017-02-09 11:15:00
2017-02-09 11:16:00
2017-02-09 11:17:00
2017-02-09 11:18:00
2017-02-09 11:19:00
2017-02-09 11:20:00
2017-02-09 11:21:00
2017-02-09 11:22:00
2017-02-09 11:23:00
2017-02-09 11:24:00
2017-02-09 11:25:00
2017-02-09 11:26:00
2017-02-09 11:27:00
2017-02-09 11:28:00
2017-02-09 11:29:00
2017-02-09 11:30:00
2017-02-09 11:31:00
2017-02-09 11:32:00
2017-02-09 11:33:00
2017-02-09 11:34:00
2017-02-09 11:35:00
2017-02-09 11:36:00
2017-02-09 11:37:00
2017-02-09 11:38:00
2017-02-09 11:39:00
2017-02-09 11:40:00
2017-02-09 11:41:00
2017-02-09 11:42:00


In [12]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData1" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return []

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 20,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AGW
Processing data for stock: AIO
Processing data for stock: AUZ
Processing data for stock: BSN
Processing data for stock: BWU
Processing data for stock: CBT
Processing data for stock: CHV
Processing data for stock: CSR
Processing data for stock: CUN
Processing data for stock: CYD
Processing data for stock: DCO
Processing data for stock: DFZ
Processing data for stock: DVV
Processing data for stock: DYE
Processing data for stock: EGV
Processing data for stock: FCY
Processing data for stock: FFA
Processing data for stock: FFS
Processing data for stock: FKI
Processing data for stock: FRE
Processing data for stock: FUR
Processing data for stock: GFQ
Processing data for stock: GGK
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: HHK
Processing data for stock: IES
Processing data for stock: IFL
Processing data for stock: ILW
Processing data for stock: IMC
Processing data for stock: IUE
Processing data for stock: IUQ
Processi

2017-01-06 13:47:00
2017-01-06 13:48:00
2017-01-06 13:49:00
2017-01-06 13:50:00
2017-01-06 13:51:00
2017-01-06 13:52:00
2017-01-06 13:53:00
2017-01-06 13:54:00
2017-01-06 13:55:00
2017-01-06 13:56:00
2017-01-06 13:57:00
2017-01-06 13:58:00
2017-01-06 13:59:00
2017-01-06 14:00:00
2017-01-06 14:01:00
2017-01-06 14:02:00
2017-01-06 14:03:00
2017-01-06 14:04:00
2017-01-06 14:05:00
2017-01-06 14:06:00
2017-01-06 14:07:00
2017-01-06 14:08:00
2017-01-06 14:09:00
2017-01-06 14:10:00
2017-01-06 14:11:00
2017-01-06 14:12:00
2017-01-06 14:13:00
2017-01-06 14:14:00
2017-01-06 14:15:00
2017-01-06 14:16:00
2017-01-06 14:17:00
2017-01-06 14:18:00
2017-01-06 14:19:00
2017-01-06 14:20:00
2017-01-06 14:21:00
2017-01-06 14:22:00
2017-01-06 14:23:00
2017-01-06 14:24:00
2017-01-06 14:25:00
2017-01-06 14:26:00
2017-01-06 14:27:00
2017-01-06 14:28:00
2017-01-06 14:29:00
2017-01-06 14:30:00
2017-01-06 14:31:00
2017-01-06 14:32:00
2017-01-06 14:33:00
2017-01-06 14:34:00
2017-01-06 14:35:00
2017-01-06 14:36:00


2017-01-09 14:25:00
2017-01-09 14:26:00
2017-01-09 14:27:00
2017-01-09 14:28:00
2017-01-09 14:29:00
2017-01-09 14:30:00
2017-01-09 14:31:00
2017-01-09 14:32:00
2017-01-09 14:33:00
2017-01-09 14:34:00
2017-01-09 14:35:00
2017-01-09 14:36:00
2017-01-09 14:37:00
2017-01-09 14:38:00
2017-01-09 14:39:00
2017-01-09 14:40:00
2017-01-09 14:41:00
2017-01-09 14:42:00
2017-01-09 14:43:00
2017-01-09 14:44:00
2017-01-09 14:45:00
2017-01-09 14:46:00
2017-01-09 14:47:00
2017-01-09 14:48:00
2017-01-09 14:49:00
2017-01-09 14:50:00
2017-01-09 14:51:00
2017-01-09 14:52:00
2017-01-09 14:53:00
2017-01-09 14:54:00
2017-01-09 14:55:00
2017-01-09 14:56:00
2017-01-09 14:57:00
2017-01-09 14:58:00
2017-01-09 14:59:00
2017-01-09 15:00:00
2017-01-09 15:01:00
2017-01-09 15:02:00
2017-01-09 15:03:00
2017-01-09 15:04:00
2017-01-09 15:05:00
2017-01-09 15:06:00
2017-01-09 15:07:00
2017-01-09 15:08:00
2017-01-09 15:09:00
2017-01-09 15:10:00
2017-01-09 15:11:00
2017-01-09 15:12:00
2017-01-09 15:13:00
2017-01-09 15:14:00


2017-01-10 15:02:00
2017-01-10 15:03:00
2017-01-10 15:04:00
2017-01-10 15:05:00
2017-01-10 15:06:00
2017-01-10 15:07:00
2017-01-10 15:08:00
2017-01-10 15:09:00
2017-01-10 15:10:00
2017-01-10 15:11:00
2017-01-10 15:12:00
2017-01-10 15:13:00
2017-01-10 15:14:00
2017-01-10 15:15:00
2017-01-10 15:16:00
2017-01-10 15:17:00
2017-01-10 15:18:00
2017-01-10 15:19:00
2017-01-10 15:20:00
2017-01-10 15:21:00
2017-01-10 15:22:00
2017-01-10 15:23:00
2017-01-10 15:24:00
2017-01-10 15:25:00
2017-01-10 15:26:00
2017-01-10 15:27:00
2017-01-10 15:28:00
2017-01-10 15:29:00
2017-01-11 09:17:00
2017-01-11 09:18:00
2017-01-11 09:19:00
2017-01-11 09:20:00
2017-01-11 09:21:00
2017-01-11 09:22:00
2017-01-11 09:23:00
2017-01-11 09:24:00
2017-01-11 09:25:00
2017-01-11 09:26:00
2017-01-11 09:27:00
2017-01-11 09:28:00
2017-01-11 09:29:00
2017-01-11 09:30:00
2017-01-11 09:31:00
2017-01-11 09:32:00
2017-01-11 09:33:00
2017-01-11 09:34:00
2017-01-11 09:35:00
2017-01-11 09:36:00
2017-01-11 09:37:00
2017-01-11 09:38:00


2017-01-12 09:26:00
2017-01-12 09:27:00
2017-01-12 09:28:00
2017-01-12 09:29:00
2017-01-12 09:30:00
2017-01-12 09:31:00
2017-01-12 09:32:00
2017-01-12 09:33:00
2017-01-12 09:34:00
2017-01-12 09:35:00
2017-01-12 09:36:00
2017-01-12 09:37:00
2017-01-12 09:38:00
2017-01-12 09:39:00
2017-01-12 09:40:00
2017-01-12 09:41:00
2017-01-12 09:42:00
2017-01-12 09:43:00
2017-01-12 09:44:00
2017-01-12 09:45:00
2017-01-12 09:46:00
2017-01-12 09:47:00
2017-01-12 09:48:00
2017-01-12 09:49:00
2017-01-12 09:50:00
2017-01-12 09:51:00
2017-01-12 09:52:00
2017-01-12 09:53:00
2017-01-12 09:54:00
2017-01-12 09:55:00
2017-01-12 09:56:00
2017-01-12 09:57:00
2017-01-12 09:58:00
2017-01-12 09:59:00
2017-01-12 10:00:00
2017-01-12 10:01:00
2017-01-12 10:02:00
2017-01-12 10:03:00
2017-01-12 10:04:00
2017-01-12 10:05:00
2017-01-12 10:06:00
2017-01-12 10:07:00
2017-01-12 10:08:00
2017-01-12 10:09:00
2017-01-12 10:10:00
2017-01-12 10:11:00
2017-01-12 10:12:00
2017-01-12 10:13:00
2017-01-12 10:14:00
2017-01-12 10:15:00


...

2017-02-01 11:23:00
2017-02-01 11:24:00
2017-02-01 11:25:00
2017-02-01 11:26:00
2017-02-01 11:27:00
2017-02-01 11:28:00
2017-02-01 11:29:00
2017-02-01 11:30:00
2017-02-01 11:31:00
2017-02-01 11:32:00
2017-02-01 11:33:00
2017-02-01 11:34:00
2017-02-01 11:35:00
2017-02-01 11:36:00
2017-02-01 11:37:00
2017-02-01 11:38:00
2017-02-01 11:39:00
2017-02-01 11:40:00
2017-02-01 11:41:00
2017-02-01 11:42:00
2017-02-01 11:43:00
2017-02-01 11:44:00
2017-02-01 11:45:00
2017-02-01 11:46:00
2017-02-01 11:47:00
2017-02-01 11:48:00
2017-02-01 11:49:00
2017-02-01 11:50:00
2017-02-01 11:51:00
2017-02-01 11:52:00
2017-02-01 11:53:00
2017-02-01 11:54:00
2017-02-01 11:55:00
2017-02-01 11:56:00
2017-02-01 11:57:00
2017-02-01 11:58:00
2017-02-01 11:59:00
2017-02-01 12:00:00
2017-02-01 12:01:00
2017-02-01 12:02:00
2017-02-01 12:03:00
2017-02-01 12:04:00
2017-02-01 12:05:00
2017-02-01 12:06:00
2017-02-01 12:07:00
2017-02-01 12:08:00
2017-02-01 12:09:00
2017-02-01 12:10:00
2017-02-01 12:11:00
2017-02-01 12:12:00


2017-02-02 12:01:00
2017-02-02 12:02:00
2017-02-02 12:03:00
2017-02-02 12:04:00
2017-02-02 12:05:00
2017-02-02 12:06:00
2017-02-02 12:07:00
2017-02-02 12:08:00
2017-02-02 12:09:00
2017-02-02 12:10:00
2017-02-02 12:11:00
2017-02-02 12:12:00
2017-02-02 12:13:00
2017-02-02 12:14:00
2017-02-02 12:15:00
2017-02-02 12:16:00
2017-02-02 12:17:00
2017-02-02 12:18:00
2017-02-02 12:19:00
2017-02-02 12:20:00
2017-02-02 12:21:00
2017-02-02 12:22:00
2017-02-02 12:23:00
2017-02-02 12:24:00
2017-02-02 12:25:00
2017-02-02 12:26:00
2017-02-02 12:27:00
2017-02-02 12:28:00
2017-02-02 12:29:00
2017-02-02 12:30:00
2017-02-02 12:31:00
2017-02-02 12:32:00
2017-02-02 12:33:00
2017-02-02 12:34:00
2017-02-02 12:35:00
2017-02-02 12:36:00
2017-02-02 12:37:00
2017-02-02 12:38:00
2017-02-02 12:39:00
2017-02-02 12:40:00
2017-02-02 12:41:00
2017-02-02 12:42:00
2017-02-02 12:43:00
2017-02-02 12:44:00
2017-02-02 12:45:00
2017-02-02 12:46:00
2017-02-02 12:47:00
2017-02-02 12:48:00
2017-02-02 12:49:00
2017-02-02 12:50:00


2017-02-03 12:39:00
2017-02-03 12:40:00
2017-02-03 12:41:00
2017-02-03 12:42:00
2017-02-03 12:43:00
2017-02-03 12:44:00
2017-02-03 12:45:00
2017-02-03 12:46:00
2017-02-03 12:47:00
2017-02-03 12:48:00
2017-02-03 12:49:00
2017-02-03 12:50:00
2017-02-03 12:51:00
2017-02-03 12:52:00
2017-02-03 12:53:00
2017-02-03 12:54:00
2017-02-03 12:55:00
2017-02-03 12:56:00
2017-02-03 12:57:00
2017-02-03 12:58:00
2017-02-03 12:59:00
2017-02-03 13:00:00
2017-02-03 13:01:00
2017-02-03 13:02:00
2017-02-03 13:03:00
2017-02-03 13:04:00
2017-02-03 13:05:00
2017-02-03 13:06:00
2017-02-03 13:07:00
2017-02-03 13:08:00
2017-02-03 13:09:00
2017-02-03 13:10:00
2017-02-03 13:11:00
2017-02-03 13:12:00
2017-02-03 13:13:00
2017-02-03 13:14:00
2017-02-03 13:15:00
2017-02-03 13:16:00
2017-02-03 13:17:00
2017-02-03 13:18:00
2017-02-03 13:19:00
2017-02-03 13:20:00
2017-02-03 13:21:00
2017-02-03 13:22:00
2017-02-03 13:23:00
2017-02-03 13:24:00
2017-02-03 13:25:00
2017-02-03 13:26:00
2017-02-03 13:27:00
2017-02-03 13:28:00


2017-02-07 13:18:00
2017-02-07 13:19:00
2017-02-07 13:20:00
2017-02-07 13:21:00
2017-02-07 13:22:00
2017-02-07 13:23:00
2017-02-07 13:24:00
2017-02-07 13:25:00
2017-02-07 13:26:00
2017-02-07 13:27:00
2017-02-07 13:28:00
2017-02-07 13:29:00
2017-02-07 13:30:00
2017-02-07 13:31:00
2017-02-07 13:32:00
2017-02-07 13:33:00
2017-02-07 13:34:00
2017-02-07 13:35:00
2017-02-07 13:36:00
2017-02-07 13:37:00
2017-02-07 13:38:00
2017-02-07 13:39:00
2017-02-07 13:40:00
2017-02-07 13:41:00
2017-02-07 13:42:00
2017-02-07 13:43:00
2017-02-07 13:44:00
2017-02-07 13:45:00
2017-02-07 13:46:00
2017-02-07 13:47:00
2017-02-07 13:48:00
2017-02-07 13:49:00
2017-02-07 13:50:00
2017-02-07 13:51:00
2017-02-07 13:52:00
2017-02-07 13:53:00
2017-02-07 13:54:00
2017-02-07 13:55:00
2017-02-07 13:56:00
2017-02-07 13:57:00
2017-02-07 13:58:00
2017-02-07 13:59:00
2017-02-07 14:00:00
2017-02-07 14:01:00
2017-02-07 14:02:00
2017-02-07 14:03:00
2017-02-07 14:04:00
2017-02-07 14:05:00
2017-02-07 14:06:00
2017-02-07 14:07:00


2017-02-08 13:56:00
2017-02-08 13:57:00
2017-02-08 13:58:00
2017-02-08 13:59:00
2017-02-08 14:00:00
2017-02-08 14:01:00
2017-02-08 14:02:00
2017-02-08 14:03:00
2017-02-08 14:04:00
2017-02-08 14:05:00
2017-02-08 14:06:00
2017-02-08 14:07:00
2017-02-08 14:08:00
2017-02-08 14:09:00
2017-02-08 14:10:00
2017-02-08 14:11:00
2017-02-08 14:12:00
2017-02-08 14:13:00
2017-02-08 14:14:00
2017-02-08 14:15:00
2017-02-08 14:16:00
2017-02-08 14:17:00
2017-02-08 14:18:00
2017-02-08 14:19:00
2017-02-08 14:20:00
2017-02-08 14:21:00
2017-02-08 14:22:00
2017-02-08 14:23:00
2017-02-08 14:24:00
2017-02-08 14:25:00
2017-02-08 14:26:00
2017-02-08 14:27:00
2017-02-08 14:28:00
2017-02-08 14:29:00
2017-02-08 14:30:00
2017-02-08 14:31:00
2017-02-08 14:32:00
2017-02-08 14:33:00
2017-02-08 14:34:00
2017-02-08 14:35:00
2017-02-08 14:36:00
2017-02-08 14:37:00
2017-02-08 14:38:00
2017-02-08 14:39:00
2017-02-08 14:40:00
2017-02-08 14:41:00
2017-02-08 14:42:00
2017-02-08 14:43:00
2017-02-08 14:44:00
2017-02-08 14:45:00


In [13]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData1" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return []

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 10,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AGW
Processing data for stock: AIO
Processing data for stock: AUZ
Processing data for stock: BSN
Processing data for stock: BWU
Processing data for stock: CBT
Processing data for stock: CHV
Processing data for stock: CSR
Processing data for stock: CUN
Processing data for stock: CYD
Processing data for stock: DCO
Processing data for stock: DFZ
Processing data for stock: DVV
Processing data for stock: DYE
Processing data for stock: EGV
Processing data for stock: FCY
Processing data for stock: FFA
Processing data for stock: FFS
Processing data for stock: FKI
Processing data for stock: FRE
Processing data for stock: FUR
Processing data for stock: GFQ
Processing data for stock: GGK
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: HHK
Processing data for stock: IES
Processing data for stock: IFL
Processing data for stock: ILW
Processing data for stock: IMC
Processing data for stock: IUE
Processing data for stock: IUQ
Processi

2017-01-06 13:47:00
2017-01-06 13:48:00
2017-01-06 13:49:00
2017-01-06 13:50:00
2017-01-06 13:51:00
2017-01-06 13:52:00
2017-01-06 13:53:00
2017-01-06 13:54:00
2017-01-06 13:55:00
2017-01-06 13:56:00
2017-01-06 13:57:00
2017-01-06 13:58:00
2017-01-06 13:59:00
2017-01-06 14:00:00
2017-01-06 14:01:00
2017-01-06 14:02:00
2017-01-06 14:03:00
2017-01-06 14:04:00
2017-01-06 14:05:00
2017-01-06 14:06:00
2017-01-06 14:07:00
2017-01-06 14:08:00
2017-01-06 14:09:00
2017-01-06 14:10:00
2017-01-06 14:11:00
2017-01-06 14:12:00
2017-01-06 14:13:00
2017-01-06 14:14:00
2017-01-06 14:15:00
2017-01-06 14:16:00
2017-01-06 14:17:00
2017-01-06 14:18:00
2017-01-06 14:19:00
2017-01-06 14:20:00
2017-01-06 14:21:00
2017-01-06 14:22:00
2017-01-06 14:23:00
2017-01-06 14:24:00
2017-01-06 14:25:00
2017-01-06 14:26:00
2017-01-06 14:27:00
2017-01-06 14:28:00
2017-01-06 14:29:00
2017-01-06 14:30:00
2017-01-06 14:31:00
2017-01-06 14:32:00
2017-01-06 14:33:00
2017-01-06 14:34:00
2017-01-06 14:35:00
2017-01-06 14:36:00


2017-01-09 14:26:00
2017-01-09 14:27:00
2017-01-09 14:28:00
2017-01-09 14:29:00
2017-01-09 14:30:00
2017-01-09 14:31:00
2017-01-09 14:32:00
2017-01-09 14:33:00
2017-01-09 14:34:00
2017-01-09 14:35:00
2017-01-09 14:36:00
2017-01-09 14:37:00
2017-01-09 14:38:00
2017-01-09 14:39:00
2017-01-09 14:40:00
2017-01-09 14:41:00
2017-01-09 14:42:00
2017-01-09 14:43:00
2017-01-09 14:44:00
2017-01-09 14:45:00
2017-01-09 14:46:00
2017-01-09 14:47:00
2017-01-09 14:48:00
2017-01-09 14:49:00
2017-01-09 14:50:00
2017-01-09 14:51:00
2017-01-09 14:52:00
2017-01-09 14:53:00
2017-01-09 14:54:00
2017-01-09 14:55:00
2017-01-09 14:56:00
2017-01-09 14:57:00
2017-01-09 14:58:00
2017-01-09 14:59:00
2017-01-09 15:00:00
2017-01-09 15:01:00
2017-01-09 15:02:00
2017-01-09 15:03:00
2017-01-09 15:04:00
2017-01-09 15:05:00
2017-01-09 15:06:00
2017-01-09 15:07:00
2017-01-09 15:08:00
2017-01-09 15:09:00
2017-01-09 15:10:00
2017-01-09 15:11:00
2017-01-09 15:12:00
2017-01-09 15:13:00
2017-01-09 15:14:00
2017-01-09 15:15:00


2017-01-10 15:04:00
2017-01-10 15:05:00
2017-01-10 15:06:00
2017-01-10 15:07:00
2017-01-10 15:08:00
2017-01-10 15:09:00
2017-01-10 15:10:00
2017-01-10 15:11:00
2017-01-10 15:12:00
2017-01-10 15:13:00
2017-01-10 15:14:00
2017-01-10 15:15:00
2017-01-10 15:16:00
2017-01-10 15:17:00
2017-01-10 15:18:00
2017-01-10 15:19:00
2017-01-10 15:20:00
2017-01-10 15:21:00
2017-01-10 15:22:00
2017-01-10 15:23:00
2017-01-10 15:24:00
2017-01-10 15:25:00
2017-01-10 15:26:00
2017-01-10 15:27:00
2017-01-10 15:28:00
2017-01-10 15:29:00
2017-01-11 09:17:00
2017-01-11 09:18:00
2017-01-11 09:19:00
2017-01-11 09:20:00
2017-01-11 09:21:00
2017-01-11 09:22:00
2017-01-11 09:23:00
2017-01-11 09:24:00
2017-01-11 09:25:00
2017-01-11 09:26:00
2017-01-11 09:27:00
2017-01-11 09:28:00
2017-01-11 09:29:00
2017-01-11 09:30:00
2017-01-11 09:31:00
2017-01-11 09:32:00
2017-01-11 09:33:00
2017-01-11 09:34:00
2017-01-11 09:35:00
2017-01-11 09:36:00
2017-01-11 09:37:00
2017-01-11 09:38:00
2017-01-11 09:39:00
2017-01-11 09:40:00


2017-01-12 09:29:00
2017-01-12 09:30:00
2017-01-12 09:31:00
2017-01-12 09:32:00
2017-01-12 09:33:00
2017-01-12 09:34:00
2017-01-12 09:35:00
2017-01-12 09:36:00
2017-01-12 09:37:00
2017-01-12 09:38:00
2017-01-12 09:39:00
2017-01-12 09:40:00
2017-01-12 09:41:00
2017-01-12 09:42:00
2017-01-12 09:43:00
2017-01-12 09:44:00
2017-01-12 09:45:00
2017-01-12 09:46:00
2017-01-12 09:47:00
2017-01-12 09:48:00
2017-01-12 09:49:00
2017-01-12 09:50:00
2017-01-12 09:51:00
2017-01-12 09:52:00
2017-01-12 09:53:00
2017-01-12 09:54:00
2017-01-12 09:55:00
2017-01-12 09:56:00
2017-01-12 09:57:00
2017-01-12 09:58:00
2017-01-12 09:59:00
2017-01-12 10:00:00
2017-01-12 10:01:00
2017-01-12 10:02:00
2017-01-12 10:03:00
2017-01-12 10:04:00
2017-01-12 10:05:00
2017-01-12 10:06:00
2017-01-12 10:07:00
2017-01-12 10:08:00
2017-01-12 10:09:00
2017-01-12 10:10:00
2017-01-12 10:11:00
2017-01-12 10:12:00
2017-01-12 10:13:00
2017-01-12 10:14:00
2017-01-12 10:15:00
2017-01-12 10:16:00
2017-01-12 10:17:00
2017-01-12 10:18:00


...

2017-02-02 12:12:00
2017-02-02 12:13:00
2017-02-02 12:14:00
2017-02-02 12:15:00
2017-02-02 12:16:00
2017-02-02 12:17:00
2017-02-02 12:18:00
2017-02-02 12:19:00
2017-02-02 12:20:00
2017-02-02 12:21:00
2017-02-02 12:22:00
2017-02-02 12:23:00
2017-02-02 12:24:00
2017-02-02 12:25:00
2017-02-02 12:26:00
2017-02-02 12:27:00
2017-02-02 12:28:00
2017-02-02 12:29:00
2017-02-02 12:30:00
2017-02-02 12:31:00
2017-02-02 12:32:00
2017-02-02 12:33:00
2017-02-02 12:34:00
2017-02-02 12:35:00
2017-02-02 12:36:00
2017-02-02 12:37:00
2017-02-02 12:38:00
2017-02-02 12:39:00
2017-02-02 12:40:00
2017-02-02 12:41:00
2017-02-02 12:42:00
2017-02-02 12:43:00
2017-02-02 12:44:00
2017-02-02 12:45:00
2017-02-02 12:46:00
2017-02-02 12:47:00
2017-02-02 12:48:00
2017-02-02 12:49:00
2017-02-02 12:50:00
2017-02-02 12:51:00
2017-02-02 12:52:00
2017-02-02 12:53:00
2017-02-02 12:54:00
2017-02-02 12:55:00
2017-02-02 12:56:00
2017-02-02 12:57:00
2017-02-02 12:58:00
2017-02-02 12:59:00
2017-02-02 13:00:00
2017-02-02 13:01:00


2017-02-03 12:50:00
2017-02-03 12:51:00
2017-02-03 12:52:00
2017-02-03 12:53:00
2017-02-03 12:54:00
2017-02-03 12:55:00
2017-02-03 12:56:00
2017-02-03 12:57:00
2017-02-03 12:58:00
2017-02-03 12:59:00
2017-02-03 13:00:00
2017-02-03 13:01:00
2017-02-03 13:02:00
2017-02-03 13:03:00
2017-02-03 13:04:00
2017-02-03 13:05:00
2017-02-03 13:06:00
2017-02-03 13:07:00
2017-02-03 13:08:00
2017-02-03 13:09:00
2017-02-03 13:10:00
2017-02-03 13:11:00
2017-02-03 13:12:00
2017-02-03 13:13:00
2017-02-03 13:14:00
2017-02-03 13:15:00
2017-02-03 13:16:00
2017-02-03 13:17:00
2017-02-03 13:18:00
2017-02-03 13:19:00
2017-02-03 13:20:00
2017-02-03 13:21:00
2017-02-03 13:22:00
2017-02-03 13:23:00
2017-02-03 13:24:00
2017-02-03 13:25:00
2017-02-03 13:26:00
2017-02-03 13:27:00
2017-02-03 13:28:00
2017-02-03 13:29:00
2017-02-03 13:30:00
2017-02-03 13:31:00
2017-02-03 13:32:00
2017-02-03 13:33:00
2017-02-03 13:34:00
2017-02-03 13:35:00
2017-02-03 13:36:00
2017-02-03 13:37:00
2017-02-03 13:38:00
2017-02-03 13:39:00


2017-02-07 13:29:00
2017-02-07 13:30:00
2017-02-07 13:31:00
2017-02-07 13:32:00
2017-02-07 13:33:00
2017-02-07 13:34:00
2017-02-07 13:35:00
2017-02-07 13:36:00
2017-02-07 13:37:00
2017-02-07 13:38:00
2017-02-07 13:39:00
2017-02-07 13:40:00
2017-02-07 13:41:00
2017-02-07 13:42:00
2017-02-07 13:43:00
2017-02-07 13:44:00
2017-02-07 13:45:00
2017-02-07 13:46:00
2017-02-07 13:47:00
2017-02-07 13:48:00
2017-02-07 13:49:00
2017-02-07 13:50:00
2017-02-07 13:51:00
2017-02-07 13:52:00
2017-02-07 13:53:00
2017-02-07 13:54:00
2017-02-07 13:55:00
2017-02-07 13:56:00
2017-02-07 13:57:00
2017-02-07 13:58:00
2017-02-07 13:59:00
2017-02-07 14:00:00
2017-02-07 14:01:00
2017-02-07 14:02:00
2017-02-07 14:03:00
2017-02-07 14:04:00
2017-02-07 14:05:00
2017-02-07 14:06:00
2017-02-07 14:07:00
2017-02-07 14:08:00
2017-02-07 14:09:00
2017-02-07 14:10:00
2017-02-07 14:11:00
2017-02-07 14:12:00
2017-02-07 14:13:00
2017-02-07 14:14:00
2017-02-07 14:15:00
2017-02-07 14:16:00
2017-02-07 14:17:00
2017-02-07 14:18:00


2017-02-08 14:09:00
2017-02-08 14:10:00
2017-02-08 14:11:00
2017-02-08 14:12:00
2017-02-08 14:13:00
2017-02-08 14:14:00
2017-02-08 14:15:00
2017-02-08 14:16:00
2017-02-08 14:17:00
2017-02-08 14:18:00
2017-02-08 14:19:00
2017-02-08 14:20:00
2017-02-08 14:21:00
2017-02-08 14:22:00
2017-02-08 14:23:00
2017-02-08 14:24:00
2017-02-08 14:25:00
2017-02-08 14:26:00
2017-02-08 14:27:00
2017-02-08 14:28:00
2017-02-08 14:29:00
2017-02-08 14:30:00
2017-02-08 14:31:00
2017-02-08 14:32:00
2017-02-08 14:33:00
2017-02-08 14:34:00
2017-02-08 14:35:00
2017-02-08 14:36:00
2017-02-08 14:37:00
2017-02-08 14:38:00
2017-02-08 14:39:00
2017-02-08 14:40:00
2017-02-08 14:41:00
2017-02-08 14:42:00
2017-02-08 14:43:00
2017-02-08 14:44:00
2017-02-08 14:45:00
2017-02-08 14:46:00
2017-02-08 14:47:00
2017-02-08 14:48:00
2017-02-08 14:49:00
2017-02-08 14:50:00
2017-02-08 14:51:00
2017-02-08 14:52:00
2017-02-08 14:53:00
2017-02-08 14:54:00
2017-02-08 14:55:00
2017-02-08 14:56:00
2017-02-08 14:57:00
2017-02-08 14:58:00


Info: CSR:  Total Pnl: 0.53%  Profit/Loss Ratio: 1.19  Accuracy: 0.46  Score: 0.09  Normalized Score: 1.29 
Info: KAA:  Total Pnl: 0.02%  Profit/Loss Ratio: 1.04  Accuracy: 0.48  Score: 0.06  Normalized Score: 1.26 
Info: PUO:  Total Pnl: 0.56%  Profit/Loss Ratio: 1.24  Accuracy: 0.47  Score: 0.09  Normalized Score: 1.17 
Info: YGC:  Total Pnl: 2.45%  Profit/Loss Ratio: 1.17  Accuracy: 0.47  Score: 0.20  Normalized Score: 1.43 
Info: ILW:  Total Pnl: 0.14%  Profit/Loss Ratio: 1.08  Accuracy: 0.46  Score: 0.07  Normalized Score: 1.33 
Info: OGU:  Total Pnl: 0.45%  Profit/Loss Ratio: 1.11  Accuracy: 0.47  Score: 0.10  Normalized Score: 1.36 
Info: PFK:  Total Pnl: 0.04%  Profit/Loss Ratio: 1.02  Accuracy: 0.47  Score: 0.07  Normalized Score: 1.38 
Info: GFQ:  Total Pnl: 0.71%  Profit/Loss Ratio: 1.12  Accuracy: 0.47  Score: 0.12  Normalized Score: 1.30 
Info: FFS:  Total Pnl: -0.12%  Profit/Loss Ratio: 0.98  Accuracy: 0.44  Score: 0.12  Normalized Score: 1.44 
Info: PLX:  Total Pnl: 1.90

In [14]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData2" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return []

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 10,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AGW
Processing data for stock: AIO
Processing data for stock: AUZ
Processing data for stock: BSN
Processing data for stock: BWU
Processing data for stock: CBT
Processing data for stock: CHV
Processing data for stock: CSR
Processing data for stock: CUN
Processing data for stock: CYD
Processing data for stock: DCO
Processing data for stock: DFZ
Processing data for stock: DVV
Processing data for stock: DYE
Processing data for stock: EGV
Processing data for stock: FCY
Processing data for stock: FFA
Processing data for stock: FFS
Processing data for stock: FKI
Processing data for stock: FRE
Processing data for stock: FUR
Processing data for stock: GFQ
Processing data for stock: GGK
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: HHK
Processing data for stock: IES
Processing data for stock: IFL
Processing data for stock: ILW
Processing data for stock: IMC
Processing data for stock: IUE
Processing data for stock: IUQ
Processi

2017-01-16 14:23:00
2017-01-16 14:24:00
2017-01-16 14:25:00
2017-01-16 14:26:00
2017-01-16 14:27:00
2017-01-16 14:28:00
2017-01-16 14:29:00
2017-01-16 14:30:00
2017-01-16 14:31:00
2017-01-16 14:32:00
2017-01-16 14:33:00
2017-01-16 14:34:00
2017-01-16 14:35:00
2017-01-16 14:36:00
2017-01-16 14:37:00
2017-01-16 14:38:00
2017-01-16 14:39:00
2017-01-16 14:40:00
2017-01-16 14:41:00
2017-01-16 14:42:00
2017-01-16 14:43:00
2017-01-16 14:44:00
2017-01-16 14:45:00
2017-01-16 14:46:00
2017-01-16 14:47:00
2017-01-16 14:48:00
2017-01-16 14:49:00
2017-01-16 14:50:00
2017-01-16 14:51:00
2017-01-16 14:52:00
2017-01-16 14:53:00
2017-01-16 14:54:00
2017-01-16 14:55:00
2017-01-16 14:56:00
2017-01-16 14:57:00
2017-01-16 14:58:00
2017-01-16 14:59:00
2017-01-16 15:00:00
2017-01-16 15:01:00
2017-01-16 15:02:00
2017-01-16 15:03:00
2017-01-16 15:04:00
2017-01-16 15:05:00
2017-01-16 15:06:00
2017-01-16 15:07:00
2017-01-16 15:08:00
2017-01-16 15:09:00
2017-01-16 15:10:00
2017-01-16 15:11:00
2017-01-16 15:12:00


2017-01-18 15:01:00
2017-01-18 15:02:00
2017-01-18 15:03:00
2017-01-18 15:04:00
2017-01-18 15:05:00
2017-01-18 15:06:00
2017-01-18 15:07:00
2017-01-18 15:08:00
2017-01-18 15:09:00
2017-01-18 15:10:00
2017-01-18 15:11:00
2017-01-18 15:12:00
2017-01-18 15:13:00
2017-01-18 15:14:00
2017-01-18 15:15:00
2017-01-18 15:16:00
2017-01-18 15:17:00
2017-01-18 15:18:00
2017-01-18 15:19:00
2017-01-18 15:20:00
2017-01-18 15:21:00
2017-01-18 15:22:00
2017-01-18 15:23:00
2017-01-18 15:24:00
2017-01-18 15:25:00
2017-01-18 15:26:00
2017-01-18 15:27:00
2017-01-18 15:28:00
2017-01-18 15:29:00
2017-01-19 09:17:00
2017-01-19 09:18:00
2017-01-19 09:19:00
2017-01-19 09:20:00
2017-01-19 09:21:00
2017-01-19 09:22:00
2017-01-19 09:23:00
2017-01-19 09:24:00
2017-01-19 09:25:00
2017-01-19 09:26:00
2017-01-19 09:27:00
2017-01-19 09:28:00
2017-01-19 09:29:00
2017-01-19 09:30:00
2017-01-19 09:31:00
2017-01-19 09:32:00
2017-01-19 09:33:00
2017-01-19 09:34:00
2017-01-19 09:35:00
2017-01-19 09:36:00
2017-01-19 09:37:00


2017-01-20 09:27:00
2017-01-20 09:28:00
2017-01-20 09:29:00
2017-01-20 09:30:00
2017-01-20 09:31:00
2017-01-20 09:32:00
2017-01-20 09:33:00
2017-01-20 09:34:00
2017-01-20 09:35:00
2017-01-20 09:36:00
2017-01-20 09:37:00
2017-01-20 09:38:00
2017-01-20 09:39:00
2017-01-20 09:40:00
2017-01-20 09:41:00
2017-01-20 09:42:00
2017-01-20 09:43:00
2017-01-20 09:44:00
2017-01-20 09:45:00
2017-01-20 09:46:00
2017-01-20 09:47:00
2017-01-20 09:48:00
2017-01-20 09:49:00
2017-01-20 09:50:00
2017-01-20 09:51:00
2017-01-20 09:52:00
2017-01-20 09:53:00
2017-01-20 09:54:00
2017-01-20 09:55:00
2017-01-20 09:56:00
2017-01-20 09:57:00
2017-01-20 09:58:00
2017-01-20 09:59:00
2017-01-20 10:00:00
2017-01-20 10:01:00
2017-01-20 10:02:00
2017-01-20 10:03:00
2017-01-20 10:04:00
2017-01-20 10:05:00
2017-01-20 10:06:00
2017-01-20 10:07:00
2017-01-20 10:08:00
2017-01-20 10:09:00
2017-01-20 10:10:00
2017-01-20 10:11:00
2017-01-20 10:12:00
2017-01-20 10:13:00
2017-01-20 10:14:00
2017-01-20 10:15:00
2017-01-20 10:16:00


2017-01-23 10:05:00
2017-01-23 10:06:00
2017-01-23 10:07:00
2017-01-23 10:08:00
2017-01-23 10:09:00
2017-01-23 10:10:00
2017-01-23 10:11:00
2017-01-23 10:12:00
2017-01-23 10:13:00
2017-01-23 10:14:00
2017-01-23 10:15:00
2017-01-23 10:16:00
2017-01-23 10:17:00
2017-01-23 10:18:00
2017-01-23 10:19:00
2017-01-23 10:20:00
2017-01-23 10:21:00
2017-01-23 10:22:00
2017-01-23 10:23:00
2017-01-23 10:24:00
2017-01-23 10:25:00
2017-01-23 10:26:00
2017-01-23 10:27:00
2017-01-23 10:28:00
2017-01-23 10:29:00
2017-01-23 10:30:00
2017-01-23 10:31:00
2017-01-23 10:32:00
2017-01-23 10:33:00
2017-01-23 10:34:00
2017-01-23 10:35:00
2017-01-23 10:36:00
2017-01-23 10:37:00
2017-01-23 10:38:00
2017-01-23 10:39:00
2017-01-23 10:40:00
2017-01-23 10:41:00
2017-01-23 10:42:00
2017-01-23 10:43:00
2017-01-23 10:44:00
2017-01-23 10:45:00
2017-01-23 10:46:00
2017-01-23 10:47:00
2017-01-23 10:48:00
2017-01-23 10:49:00
2017-01-23 10:50:00
2017-01-23 10:51:00
2017-01-23 10:52:00
2017-01-23 10:53:00
2017-01-23 10:54:00


...

2017-02-02 14:31:00
2017-02-02 14:32:00
2017-02-02 14:33:00
2017-02-02 14:34:00
2017-02-02 14:35:00
2017-02-02 14:36:00
2017-02-02 14:37:00
2017-02-02 14:38:00
2017-02-02 14:39:00
2017-02-02 14:40:00
2017-02-02 14:41:00
2017-02-02 14:42:00
2017-02-02 14:43:00
2017-02-02 14:44:00
2017-02-02 14:45:00
2017-02-02 14:46:00
2017-02-02 14:47:00
2017-02-02 14:48:00
2017-02-02 14:49:00
2017-02-02 14:50:00
2017-02-02 14:51:00
2017-02-02 14:52:00
2017-02-02 14:53:00
2017-02-02 14:54:00
2017-02-02 14:55:00
2017-02-02 14:56:00
2017-02-02 14:57:00
2017-02-02 14:58:00
2017-02-02 14:59:00
2017-02-02 15:00:00
2017-02-02 15:01:00
2017-02-02 15:02:00
2017-02-02 15:03:00
2017-02-02 15:04:00
2017-02-02 15:05:00
2017-02-02 15:06:00
2017-02-02 15:07:00
2017-02-02 15:08:00
2017-02-02 15:09:00
2017-02-02 15:10:00
2017-02-02 15:11:00
2017-02-02 15:12:00
2017-02-02 15:13:00
2017-02-02 15:14:00
2017-02-02 15:15:00
2017-02-02 15:16:00
2017-02-02 15:17:00
2017-02-02 15:18:00
2017-02-02 15:19:00
2017-02-02 15:20:00


2017-02-07 09:32:00
2017-02-07 09:33:00
2017-02-07 09:34:00
2017-02-07 09:35:00
2017-02-07 09:36:00
2017-02-07 09:37:00
2017-02-07 09:38:00
2017-02-07 09:39:00
2017-02-07 09:40:00
2017-02-07 09:41:00
2017-02-07 09:42:00
2017-02-07 09:43:00
2017-02-07 09:44:00
2017-02-07 09:45:00
2017-02-07 09:46:00
2017-02-07 09:47:00
2017-02-07 09:48:00
2017-02-07 09:49:00
2017-02-07 09:50:00
2017-02-07 09:51:00
2017-02-07 09:52:00
2017-02-07 09:53:00
2017-02-07 09:54:00
2017-02-07 09:55:00
2017-02-07 09:56:00
2017-02-07 09:57:00
2017-02-07 09:58:00
2017-02-07 09:59:00
2017-02-07 10:00:00
2017-02-07 10:01:00
2017-02-07 10:02:00
2017-02-07 10:03:00
2017-02-07 10:04:00
2017-02-07 10:05:00
2017-02-07 10:06:00
2017-02-07 10:07:00
2017-02-07 10:08:00
2017-02-07 10:09:00
2017-02-07 10:10:00
2017-02-07 10:11:00
2017-02-07 10:12:00
2017-02-07 10:13:00
2017-02-07 10:14:00
2017-02-07 10:15:00
2017-02-07 10:16:00
2017-02-07 10:17:00
2017-02-07 10:18:00
2017-02-07 10:19:00
2017-02-07 10:20:00
2017-02-07 10:21:00


2017-02-08 10:10:00
2017-02-08 10:11:00
2017-02-08 10:12:00
2017-02-08 10:13:00
2017-02-08 10:14:00
2017-02-08 10:15:00
2017-02-08 10:16:00
2017-02-08 10:17:00
2017-02-08 10:18:00
2017-02-08 10:19:00
2017-02-08 10:20:00
2017-02-08 10:21:00
2017-02-08 10:22:00
2017-02-08 10:23:00
2017-02-08 10:24:00
2017-02-08 10:25:00
2017-02-08 10:26:00
2017-02-08 10:27:00
2017-02-08 10:28:00
2017-02-08 10:29:00
2017-02-08 10:30:00
2017-02-08 10:31:00
2017-02-08 10:32:00
2017-02-08 10:33:00
2017-02-08 10:34:00
2017-02-08 10:35:00
2017-02-08 10:36:00
2017-02-08 10:37:00
2017-02-08 10:38:00
2017-02-08 10:39:00
2017-02-08 10:40:00
2017-02-08 10:41:00
2017-02-08 10:42:00
2017-02-08 10:43:00
2017-02-08 10:44:00
2017-02-08 10:45:00
2017-02-08 10:46:00
2017-02-08 10:47:00
2017-02-08 10:48:00
2017-02-08 10:49:00
2017-02-08 10:50:00
2017-02-08 10:51:00
2017-02-08 10:52:00
2017-02-08 10:53:00
2017-02-08 10:54:00
2017-02-08 10:55:00
2017-02-08 10:56:00
2017-02-08 10:57:00
2017-02-08 10:58:00
2017-02-08 10:59:00


2017-02-09 10:48:00
2017-02-09 10:49:00
2017-02-09 10:50:00
2017-02-09 10:51:00
2017-02-09 10:52:00
2017-02-09 10:53:00
2017-02-09 10:54:00
2017-02-09 10:55:00
2017-02-09 10:56:00
2017-02-09 10:57:00
2017-02-09 10:58:00
2017-02-09 10:59:00
2017-02-09 11:00:00
2017-02-09 11:01:00
2017-02-09 11:02:00
2017-02-09 11:03:00
2017-02-09 11:04:00
2017-02-09 11:05:00
2017-02-09 11:06:00
2017-02-09 11:07:00
2017-02-09 11:08:00
2017-02-09 11:09:00
2017-02-09 11:10:00
2017-02-09 11:11:00
2017-02-09 11:12:00
2017-02-09 11:13:00
2017-02-09 11:14:00
2017-02-09 11:15:00
2017-02-09 11:16:00
2017-02-09 11:17:00
2017-02-09 11:18:00
2017-02-09 11:19:00
2017-02-09 11:20:00
2017-02-09 11:21:00
2017-02-09 11:22:00
2017-02-09 11:23:00
2017-02-09 11:24:00
2017-02-09 11:25:00
2017-02-09 11:26:00
2017-02-09 11:27:00
2017-02-09 11:28:00
2017-02-09 11:29:00
2017-02-09 11:30:00
2017-02-09 11:31:00
2017-02-09 11:32:00
2017-02-09 11:33:00
2017-02-09 11:34:00
2017-02-09 11:35:00
2017-02-09 11:36:00
2017-02-09 11:37:00


Info: GFQ:  Total Pnl: 0.94%  Profit/Loss Ratio: 1.22  Accuracy: 0.48  Score: 0.12  Normalized Score: 1.27 
Info: FFS:  Total Pnl: -0.14%  Profit/Loss Ratio: 0.97  Accuracy: 0.44  Score: 0.12  Normalized Score: 1.56 
Info: PLX:  Total Pnl: 1.58%  Profit/Loss Ratio: 1.26  Accuracy: 0.48  Score: 0.14  Normalized Score: 1.35 
Info: XCS:  Total Pnl: 0.65%  Profit/Loss Ratio: 1.32  Accuracy: 0.50  Score: 0.09  Normalized Score: 1.21 
Info: UBF:  Total Pnl: 0.66%  Profit/Loss Ratio: 1.12  Accuracy: 0.48  Score: 0.14  Normalized Score: 1.40 
Info: OMP:  Total Pnl: 0.01%  Profit/Loss Ratio: 1.24  Accuracy: 0.50  Score: 0.04  Normalized Score: 1.14 
Info: ZEW:  Total Pnl: 2.94%  Profit/Loss Ratio: 1.30  Accuracy: 0.48  Score: 0.19  Normalized Score: 1.23 
Info: CBT:  Total Pnl: 0.57%  Profit/Loss Ratio: 1.04  Accuracy: 0.46  Score: 0.20  Normalized Score: 1.54 
Info: HHK:  Total Pnl: 5.93%  Profit/Loss Ratio: 1.38  Accuracy: 0.49  Score: 0.29  Normalized Score: 1.35 
Info: KKG:  Total Pnl: -0.0

In [15]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData3" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return []

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 10,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AGW
Processing data for stock: AIO
Processing data for stock: AUZ
Processing data for stock: BSN
Processing data for stock: BWU
Processing data for stock: CBT
Processing data for stock: CHV
Processing data for stock: CSR
Processing data for stock: CUN
Processing data for stock: CYD
Processing data for stock: DCO
Processing data for stock: DFZ
Processing data for stock: DVV
Processing data for stock: DYE
Processing data for stock: EGV
Processing data for stock: FCY
Processing data for stock: FFA
Processing data for stock: FFS
Processing data for stock: FKI
Processing data for stock: FRE
Processing data for stock: FUR
Processing data for stock: GFQ
Processing data for stock: GGK
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: HHK
Processing data for stock: IES
Processing data for stock: IFL
Processing data for stock: ILW
Processing data for stock: IMC
Processing data for stock: IUE
Processing data for stock: IUQ
Processi

2017-01-06 13:48:00
2017-01-06 13:49:00
2017-01-06 13:50:00
2017-01-06 13:51:00
2017-01-06 13:52:00
2017-01-06 13:53:00
2017-01-06 13:54:00
2017-01-06 13:55:00
2017-01-06 13:56:00
2017-01-06 13:57:00
2017-01-06 13:58:00
2017-01-06 13:59:00
2017-01-06 14:00:00
2017-01-06 14:01:00
2017-01-06 14:02:00
2017-01-06 14:03:00
2017-01-06 14:04:00
2017-01-06 14:05:00
2017-01-06 14:06:00
2017-01-06 14:07:00
2017-01-06 14:08:00
2017-01-06 14:09:00
2017-01-06 14:10:00
2017-01-06 14:11:00
2017-01-06 14:12:00
2017-01-06 14:13:00
2017-01-06 14:14:00
2017-01-06 14:15:00
2017-01-06 14:16:00
2017-01-06 14:17:00
2017-01-06 14:18:00
2017-01-06 14:19:00
2017-01-06 14:20:00
2017-01-06 14:21:00
2017-01-06 14:22:00
2017-01-06 14:23:00
2017-01-06 14:24:00
2017-01-06 14:25:00
2017-01-06 14:26:00
2017-01-06 14:27:00
2017-01-06 14:28:00
2017-01-06 14:29:00
2017-01-06 14:30:00
2017-01-06 14:31:00
2017-01-06 14:32:00
2017-01-06 14:33:00
2017-01-06 14:34:00
2017-01-06 14:35:00
2017-01-06 14:36:00
2017-01-06 14:37:00


2017-01-10 14:27:00
2017-01-10 14:28:00
2017-01-10 14:29:00
2017-01-10 14:30:00
2017-01-10 14:31:00
2017-01-10 14:32:00
2017-01-10 14:33:00
2017-01-10 14:34:00
2017-01-10 14:35:00
2017-01-10 14:36:00
2017-01-10 14:37:00
2017-01-10 14:38:00
2017-01-10 14:39:00
2017-01-10 14:40:00
2017-01-10 14:41:00
2017-01-10 14:42:00
2017-01-10 14:43:00
2017-01-10 14:44:00
2017-01-10 14:45:00
2017-01-10 14:46:00
2017-01-10 14:47:00
2017-01-10 14:48:00
2017-01-10 14:49:00
2017-01-10 14:50:00
2017-01-10 14:51:00
2017-01-10 14:52:00
2017-01-10 14:53:00
2017-01-10 14:54:00
2017-01-10 14:55:00
2017-01-10 14:56:00
2017-01-10 14:57:00
2017-01-10 14:58:00
2017-01-10 14:59:00
2017-01-10 15:00:00
2017-01-10 15:01:00
2017-01-10 15:02:00
2017-01-10 15:03:00
2017-01-10 15:04:00
2017-01-10 15:05:00
2017-01-10 15:06:00
2017-01-10 15:07:00
2017-01-10 15:08:00
2017-01-10 15:09:00
2017-01-10 15:10:00
2017-01-10 15:11:00
2017-01-10 15:12:00
2017-01-10 15:13:00
2017-01-10 15:14:00
2017-01-10 15:15:00
2017-01-10 15:16:00


2017-01-11 15:05:00
2017-01-11 15:06:00
2017-01-11 15:07:00
2017-01-11 15:08:00
2017-01-11 15:09:00
2017-01-11 15:10:00
2017-01-11 15:11:00
2017-01-11 15:12:00
2017-01-11 15:13:00
2017-01-11 15:14:00
2017-01-11 15:15:00
2017-01-11 15:16:00
2017-01-11 15:17:00
2017-01-11 15:18:00
2017-01-11 15:19:00
2017-01-11 15:20:00
2017-01-11 15:21:00
2017-01-11 15:22:00
2017-01-11 15:23:00
2017-01-11 15:24:00
2017-01-11 15:25:00
2017-01-11 15:26:00
2017-01-11 15:27:00
2017-01-11 15:28:00
2017-01-11 15:29:00
2017-01-12 09:17:00
2017-01-12 09:18:00
2017-01-12 09:19:00
2017-01-12 09:20:00
2017-01-12 09:21:00
2017-01-12 09:22:00
2017-01-12 09:23:00
2017-01-12 09:24:00
2017-01-12 09:25:00
2017-01-12 09:26:00
2017-01-12 09:27:00
2017-01-12 09:28:00
2017-01-12 09:29:00
2017-01-12 09:30:00
2017-01-12 09:31:00
2017-01-12 09:32:00
2017-01-12 09:33:00
2017-01-12 09:34:00
2017-01-12 09:35:00
2017-01-12 09:36:00
2017-01-12 09:37:00
2017-01-12 09:38:00
2017-01-12 09:39:00
2017-01-12 09:40:00
2017-01-12 09:41:00


2017-01-13 09:30:00
2017-01-13 09:31:00
2017-01-13 09:32:00
2017-01-13 09:33:00
2017-01-13 09:34:00
2017-01-13 09:35:00
2017-01-13 09:36:00
2017-01-13 09:37:00
2017-01-13 09:38:00
2017-01-13 09:39:00
2017-01-13 09:40:00
2017-01-13 09:41:00
2017-01-13 09:42:00
2017-01-13 09:43:00
2017-01-13 09:44:00
2017-01-13 09:45:00
2017-01-13 09:46:00
2017-01-13 09:47:00
2017-01-13 09:48:00
2017-01-13 09:49:00
2017-01-13 09:50:00
2017-01-13 09:51:00
2017-01-13 09:52:00
2017-01-13 09:53:00
2017-01-13 09:54:00
2017-01-13 09:55:00
2017-01-13 09:56:00
2017-01-13 09:57:00
2017-01-13 09:58:00
2017-01-13 09:59:00
2017-01-13 10:00:00
2017-01-13 10:01:00
2017-01-13 10:02:00
2017-01-13 10:03:00
2017-01-13 10:04:00
2017-01-13 10:05:00
2017-01-13 10:06:00
2017-01-13 10:07:00
2017-01-13 10:08:00
2017-01-13 10:09:00
2017-01-13 10:10:00
2017-01-13 10:11:00
2017-01-13 10:12:00
2017-01-13 10:13:00
2017-01-13 10:14:00
2017-01-13 10:15:00
2017-01-13 10:16:00
2017-01-13 10:17:00
2017-01-13 10:18:00
2017-01-13 10:19:00


...

2017-01-26 13:57:00
2017-01-26 13:58:00
2017-01-26 13:59:00
2017-01-26 14:00:00
2017-01-26 14:01:00
2017-01-26 14:02:00
2017-01-26 14:03:00
2017-01-26 14:04:00
2017-01-26 14:05:00
2017-01-26 14:06:00
2017-01-26 14:07:00
2017-01-26 14:08:00
2017-01-26 14:09:00
2017-01-26 14:10:00
2017-01-26 14:11:00
2017-01-26 14:12:00
2017-01-26 14:13:00
2017-01-26 14:14:00
2017-01-26 14:15:00
2017-01-26 14:16:00
2017-01-26 14:17:00
2017-01-26 14:18:00
2017-01-26 14:19:00
2017-01-26 14:20:00
2017-01-26 14:21:00
2017-01-26 14:22:00
2017-01-26 14:23:00
2017-01-26 14:24:00
2017-01-26 14:25:00
2017-01-26 14:26:00
2017-01-26 14:27:00
2017-01-26 14:28:00
2017-01-26 14:29:00
2017-01-26 14:30:00
2017-01-26 14:31:00
2017-01-26 14:32:00
2017-01-26 14:33:00
2017-01-26 14:34:00
2017-01-26 14:35:00
2017-01-26 14:36:00
2017-01-26 14:37:00
2017-01-26 14:38:00
2017-01-26 14:39:00
2017-01-26 14:40:00
2017-01-26 14:41:00
2017-01-26 14:42:00
2017-01-26 14:43:00
2017-01-26 14:44:00
2017-01-26 14:45:00
2017-01-26 14:46:00


2017-01-27 14:37:00
2017-01-27 14:38:00
2017-01-27 14:39:00
2017-01-27 14:40:00
2017-01-27 14:41:00
2017-01-27 14:42:00
2017-01-27 14:43:00
2017-01-27 14:44:00
2017-01-27 14:45:00
2017-01-27 14:46:00
2017-01-27 14:47:00
2017-01-27 14:48:00
2017-01-27 14:49:00
2017-01-27 14:50:00
2017-01-27 14:51:00
2017-01-27 14:52:00
2017-01-27 14:53:00
2017-01-27 14:54:00
2017-01-27 14:55:00
2017-01-27 14:56:00
2017-01-27 14:57:00
2017-01-27 14:58:00
2017-01-27 14:59:00
2017-01-27 15:00:00
2017-01-27 15:01:00
2017-01-27 15:02:00
2017-01-27 15:03:00
2017-01-27 15:04:00
2017-01-27 15:05:00
2017-01-27 15:06:00
2017-01-27 15:07:00
2017-01-27 15:08:00
2017-01-27 15:09:00
2017-01-27 15:10:00
2017-01-27 15:11:00
2017-01-27 15:12:00
2017-01-27 15:13:00
2017-01-27 15:14:00
2017-01-27 15:15:00
2017-01-27 15:16:00
2017-01-27 15:17:00
2017-01-27 15:18:00
2017-01-27 15:19:00
2017-01-27 15:20:00
2017-01-27 15:21:00
2017-01-27 15:22:00
2017-01-27 15:23:00
2017-01-27 15:24:00
2017-01-27 15:25:00
2017-01-27 15:26:00


2017-01-30 15:15:00
2017-01-30 15:16:00
2017-01-30 15:17:00
2017-01-30 15:18:00
2017-01-30 15:19:00
2017-01-30 15:20:00
2017-01-30 15:21:00
2017-01-30 15:22:00
2017-01-30 15:23:00
2017-01-30 15:24:00
2017-01-30 15:25:00
2017-01-30 15:26:00
2017-01-30 15:27:00
2017-01-30 15:28:00
2017-01-30 15:29:00
2017-01-31 09:17:00
2017-01-31 09:18:00
2017-01-31 09:19:00
2017-01-31 09:20:00
2017-01-31 09:21:00
2017-01-31 09:22:00
2017-01-31 09:23:00
2017-01-31 09:24:00
2017-01-31 09:25:00
2017-01-31 09:26:00
2017-01-31 09:27:00
2017-01-31 09:28:00
2017-01-31 09:29:00
2017-01-31 09:30:00
2017-01-31 09:31:00
2017-01-31 09:32:00
2017-01-31 09:33:00
2017-01-31 09:34:00
2017-01-31 09:35:00
2017-01-31 09:36:00
2017-01-31 09:37:00
2017-01-31 09:38:00
2017-01-31 09:39:00
2017-01-31 09:40:00
2017-01-31 09:41:00
2017-01-31 09:42:00
2017-01-31 09:43:00
2017-01-31 09:44:00
2017-01-31 09:45:00
2017-01-31 09:46:00
2017-01-31 09:47:00
2017-01-31 09:48:00
2017-01-31 09:49:00
2017-01-31 09:50:00
2017-01-31 09:51:00


2017-02-01 09:41:00
2017-02-01 09:42:00
2017-02-01 09:43:00
2017-02-01 09:44:00
2017-02-01 09:45:00
2017-02-01 09:46:00
2017-02-01 09:47:00
2017-02-01 09:48:00
2017-02-01 09:49:00
2017-02-01 09:50:00
2017-02-01 09:51:00
2017-02-01 09:52:00
2017-02-01 09:53:00
2017-02-01 09:54:00
2017-02-01 09:55:00
2017-02-01 09:56:00
2017-02-01 09:57:00
2017-02-01 09:58:00
2017-02-01 09:59:00
2017-02-01 10:00:00
2017-02-01 10:01:00
2017-02-01 10:02:00
2017-02-01 10:03:00
2017-02-01 10:04:00
2017-02-01 10:05:00
2017-02-01 10:06:00
2017-02-01 10:07:00
2017-02-01 10:08:00
2017-02-01 10:09:00
2017-02-01 10:10:00
2017-02-01 10:11:00
2017-02-01 10:12:00
2017-02-01 10:13:00
2017-02-01 10:14:00
2017-02-01 10:15:00
2017-02-01 10:16:00
2017-02-01 10:17:00
2017-02-01 10:18:00
2017-02-01 10:19:00
2017-02-01 10:20:00
2017-02-01 10:21:00
2017-02-01 10:22:00
2017-02-01 10:23:00
2017-02-01 10:24:00
2017-02-01 10:25:00
2017-02-01 10:26:00
2017-02-01 10:27:00
2017-02-01 10:28:00
2017-02-01 10:29:00
2017-02-01 10:30:00


2017-02-02 10:18:00
2017-02-02 10:19:00
2017-02-02 10:20:00
2017-02-02 10:21:00
2017-02-02 10:22:00
2017-02-02 10:23:00
2017-02-02 10:24:00
2017-02-02 10:25:00
2017-02-02 10:26:00
2017-02-02 10:27:00
2017-02-02 10:28:00
2017-02-02 10:29:00
2017-02-02 10:30:00
2017-02-02 10:31:00
2017-02-02 10:32:00
2017-02-02 10:33:00
2017-02-02 10:34:00
2017-02-02 10:35:00
2017-02-02 10:36:00
2017-02-02 10:37:00
2017-02-02 10:38:00
2017-02-02 10:39:00
2017-02-02 10:40:00
2017-02-02 10:41:00
2017-02-02 10:42:00
2017-02-02 10:43:00
2017-02-02 10:44:00
2017-02-02 10:45:00
2017-02-02 10:46:00
2017-02-02 10:47:00
2017-02-02 10:48:00
2017-02-02 10:49:00
2017-02-02 10:50:00
2017-02-02 10:51:00
2017-02-02 10:52:00
2017-02-02 10:53:00
2017-02-02 10:54:00
2017-02-02 10:55:00
2017-02-02 10:56:00
2017-02-02 10:57:00
2017-02-02 10:58:00
2017-02-02 10:59:00
2017-02-02 11:00:00
2017-02-02 11:01:00
2017-02-02 11:02:00
2017-02-02 11:03:00
2017-02-02 11:04:00
2017-02-02 11:05:00
2017-02-02 11:06:00
2017-02-02 11:07:00


In [16]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData1" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return []

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 5,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AGW
Processing data for stock: AIO
Processing data for stock: AUZ
Processing data for stock: BSN
Processing data for stock: BWU
Processing data for stock: CBT
Processing data for stock: CHV
Processing data for stock: CSR
Processing data for stock: CUN
Processing data for stock: CYD
Processing data for stock: DCO
Processing data for stock: DFZ
Processing data for stock: DVV
Processing data for stock: DYE
Processing data for stock: EGV
Processing data for stock: FCY
Processing data for stock: FFA
Processing data for stock: FFS
Processing data for stock: FKI
Processing data for stock: FRE
Processing data for stock: FUR
Processing data for stock: GFQ
Processing data for stock: GGK
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: HHK
Processing data for stock: IES
Processing data for stock: IFL
Processing data for stock: ILW
Processing data for stock: IMC
Processing data for stock: IUE
Processing data for stock: IUQ
Processi

2017-01-06 13:49:00
2017-01-06 13:50:00
2017-01-06 13:51:00
2017-01-06 13:52:00
2017-01-06 13:53:00
2017-01-06 13:54:00
2017-01-06 13:55:00
2017-01-06 13:56:00
2017-01-06 13:57:00
2017-01-06 13:58:00
2017-01-06 13:59:00
2017-01-06 14:00:00
2017-01-06 14:01:00
2017-01-06 14:02:00
2017-01-06 14:03:00
2017-01-06 14:04:00
2017-01-06 14:05:00
2017-01-06 14:06:00
2017-01-06 14:07:00
2017-01-06 14:08:00
2017-01-06 14:09:00
2017-01-06 14:10:00
2017-01-06 14:11:00
2017-01-06 14:12:00
2017-01-06 14:13:00
2017-01-06 14:14:00
2017-01-06 14:15:00
2017-01-06 14:16:00
2017-01-06 14:17:00
2017-01-06 14:18:00
2017-01-06 14:19:00
2017-01-06 14:20:00
2017-01-06 14:21:00
2017-01-06 14:22:00
2017-01-06 14:23:00
2017-01-06 14:24:00
2017-01-06 14:25:00
2017-01-06 14:26:00
2017-01-06 14:27:00
2017-01-06 14:28:00
2017-01-06 14:29:00
2017-01-06 14:30:00
2017-01-06 14:31:00
2017-01-06 14:32:00
2017-01-06 14:33:00
2017-01-06 14:34:00
2017-01-06 14:35:00
2017-01-06 14:36:00
2017-01-06 14:37:00
2017-01-06 14:38:00


2017-01-09 14:28:00
2017-01-09 14:29:00
2017-01-09 14:30:00
2017-01-09 14:31:00
2017-01-09 14:32:00
2017-01-09 14:33:00
2017-01-09 14:34:00
2017-01-09 14:35:00
2017-01-09 14:36:00
2017-01-09 14:37:00
2017-01-09 14:38:00
2017-01-09 14:39:00
2017-01-09 14:40:00
2017-01-09 14:41:00
2017-01-09 14:42:00
2017-01-09 14:43:00
2017-01-09 14:44:00
2017-01-09 14:45:00
2017-01-09 14:46:00
2017-01-09 14:47:00
2017-01-09 14:48:00
2017-01-09 14:49:00
2017-01-09 14:50:00
2017-01-09 14:51:00
2017-01-09 14:52:00
2017-01-09 14:53:00
2017-01-09 14:54:00
2017-01-09 14:55:00
2017-01-09 14:56:00
2017-01-09 14:57:00
2017-01-09 14:58:00
2017-01-09 14:59:00
2017-01-09 15:00:00
2017-01-09 15:01:00
2017-01-09 15:02:00
2017-01-09 15:03:00
2017-01-09 15:04:00
2017-01-09 15:05:00
2017-01-09 15:06:00
2017-01-09 15:07:00
2017-01-09 15:08:00
2017-01-09 15:09:00
2017-01-09 15:10:00
2017-01-09 15:11:00
2017-01-09 15:12:00
2017-01-09 15:13:00
2017-01-09 15:14:00
2017-01-09 15:15:00
2017-01-09 15:16:00
2017-01-09 15:17:00


2017-01-10 15:06:00
2017-01-10 15:07:00
2017-01-10 15:08:00
2017-01-10 15:09:00
2017-01-10 15:10:00
2017-01-10 15:11:00
2017-01-10 15:12:00
2017-01-10 15:13:00
2017-01-10 15:14:00
2017-01-10 15:15:00
2017-01-10 15:16:00
2017-01-10 15:17:00
2017-01-10 15:18:00
2017-01-10 15:19:00
2017-01-10 15:20:00
2017-01-10 15:21:00
2017-01-10 15:22:00
2017-01-10 15:23:00
2017-01-10 15:24:00
2017-01-10 15:25:00
2017-01-10 15:26:00
2017-01-10 15:27:00
2017-01-10 15:28:00
2017-01-10 15:29:00
2017-01-11 09:17:00
2017-01-11 09:18:00
2017-01-11 09:19:00
2017-01-11 09:20:00
2017-01-11 09:21:00
2017-01-11 09:22:00
2017-01-11 09:23:00
2017-01-11 09:24:00
2017-01-11 09:25:00
2017-01-11 09:26:00
2017-01-11 09:27:00
2017-01-11 09:28:00
2017-01-11 09:29:00
2017-01-11 09:30:00
2017-01-11 09:31:00
2017-01-11 09:32:00
2017-01-11 09:33:00
2017-01-11 09:34:00
2017-01-11 09:35:00
2017-01-11 09:36:00
2017-01-11 09:37:00
2017-01-11 09:38:00
2017-01-11 09:39:00
2017-01-11 09:40:00
2017-01-11 09:41:00
2017-01-11 09:42:00


2017-01-12 09:32:00
2017-01-12 09:33:00
2017-01-12 09:34:00
2017-01-12 09:35:00
2017-01-12 09:36:00
2017-01-12 09:37:00
2017-01-12 09:38:00
2017-01-12 09:39:00
2017-01-12 09:40:00
2017-01-12 09:41:00
2017-01-12 09:42:00
2017-01-12 09:43:00
2017-01-12 09:44:00
2017-01-12 09:45:00
2017-01-12 09:46:00
2017-01-12 09:47:00
2017-01-12 09:48:00
2017-01-12 09:49:00
2017-01-12 09:50:00
2017-01-12 09:51:00
2017-01-12 09:52:00
2017-01-12 09:53:00
2017-01-12 09:54:00
2017-01-12 09:55:00
2017-01-12 09:56:00
2017-01-12 09:57:00
2017-01-12 09:58:00
2017-01-12 09:59:00
2017-01-12 10:00:00
2017-01-12 10:01:00
2017-01-12 10:02:00
2017-01-12 10:03:00
2017-01-12 10:04:00
2017-01-12 10:05:00
2017-01-12 10:06:00
2017-01-12 10:07:00
2017-01-12 10:08:00
2017-01-12 10:09:00
2017-01-12 10:10:00
2017-01-12 10:11:00
2017-01-12 10:12:00
2017-01-12 10:13:00
2017-01-12 10:14:00
2017-01-12 10:15:00
2017-01-12 10:16:00
2017-01-12 10:17:00
2017-01-12 10:18:00
2017-01-12 10:19:00
2017-01-12 10:20:00
2017-01-12 10:21:00


...

2017-02-02 12:00:00
2017-02-02 12:01:00
2017-02-02 12:02:00
2017-02-02 12:03:00
2017-02-02 12:04:00
2017-02-02 12:05:00
2017-02-02 12:06:00
2017-02-02 12:07:00
2017-02-02 12:08:00
2017-02-02 12:09:00
2017-02-02 12:10:00
2017-02-02 12:11:00
2017-02-02 12:12:00
2017-02-02 12:13:00
2017-02-02 12:14:00
2017-02-02 12:15:00
2017-02-02 12:16:00
2017-02-02 12:17:00
2017-02-02 12:18:00
2017-02-02 12:19:00
2017-02-02 12:20:00
2017-02-02 12:21:00
2017-02-02 12:22:00
2017-02-02 12:23:00
2017-02-02 12:24:00
2017-02-02 12:25:00
2017-02-02 12:26:00
2017-02-02 12:27:00
2017-02-02 12:28:00
2017-02-02 12:29:00
2017-02-02 12:30:00
2017-02-02 12:31:00
2017-02-02 12:32:00
2017-02-02 12:33:00
2017-02-02 12:34:00
2017-02-02 12:35:00
2017-02-02 12:36:00
2017-02-02 12:37:00
2017-02-02 12:38:00
2017-02-02 12:39:00
2017-02-02 12:40:00
2017-02-02 12:41:00
2017-02-02 12:42:00
2017-02-02 12:43:00
2017-02-02 12:44:00
2017-02-02 12:45:00
2017-02-02 12:46:00
2017-02-02 12:47:00
2017-02-02 12:48:00
2017-02-02 12:49:00


2017-02-03 12:37:00
2017-02-03 12:38:00
2017-02-03 12:39:00
2017-02-03 12:40:00
2017-02-03 12:41:00
2017-02-03 12:42:00
2017-02-03 12:43:00
2017-02-03 12:44:00
2017-02-03 12:45:00
2017-02-03 12:46:00
2017-02-03 12:47:00
2017-02-03 12:48:00
2017-02-03 12:49:00
2017-02-03 12:50:00
2017-02-03 12:51:00
2017-02-03 12:52:00
2017-02-03 12:53:00
2017-02-03 12:54:00
2017-02-03 12:55:00
2017-02-03 12:56:00
2017-02-03 12:57:00
2017-02-03 12:58:00
2017-02-03 12:59:00
2017-02-03 13:00:00
2017-02-03 13:01:00
2017-02-03 13:02:00
2017-02-03 13:03:00
2017-02-03 13:04:00
2017-02-03 13:05:00
2017-02-03 13:06:00
2017-02-03 13:07:00
2017-02-03 13:08:00
2017-02-03 13:09:00
2017-02-03 13:10:00
2017-02-03 13:11:00
2017-02-03 13:12:00
2017-02-03 13:13:00
2017-02-03 13:14:00
2017-02-03 13:15:00
2017-02-03 13:16:00
2017-02-03 13:17:00
2017-02-03 13:18:00
2017-02-03 13:19:00
2017-02-03 13:20:00
2017-02-03 13:21:00
2017-02-03 13:22:00
2017-02-03 13:23:00
2017-02-03 13:24:00
2017-02-03 13:25:00
2017-02-03 13:26:00


2017-02-07 13:15:00
2017-02-07 13:16:00
2017-02-07 13:17:00
2017-02-07 13:18:00
2017-02-07 13:19:00
2017-02-07 13:20:00
2017-02-07 13:21:00
2017-02-07 13:22:00
2017-02-07 13:23:00
2017-02-07 13:24:00
2017-02-07 13:25:00
2017-02-07 13:26:00
2017-02-07 13:27:00
2017-02-07 13:28:00
2017-02-07 13:29:00
2017-02-07 13:30:00
2017-02-07 13:31:00
2017-02-07 13:32:00
2017-02-07 13:33:00
2017-02-07 13:34:00
2017-02-07 13:35:00
2017-02-07 13:36:00
2017-02-07 13:37:00
2017-02-07 13:38:00
2017-02-07 13:39:00
2017-02-07 13:40:00
2017-02-07 13:41:00
2017-02-07 13:42:00
2017-02-07 13:43:00
2017-02-07 13:44:00
2017-02-07 13:45:00
2017-02-07 13:46:00
2017-02-07 13:47:00
2017-02-07 13:48:00
2017-02-07 13:49:00
2017-02-07 13:50:00
2017-02-07 13:51:00
2017-02-07 13:52:00
2017-02-07 13:53:00
2017-02-07 13:54:00
2017-02-07 13:55:00
2017-02-07 13:56:00
2017-02-07 13:57:00
2017-02-07 13:58:00
2017-02-07 13:59:00
2017-02-07 14:00:00
2017-02-07 14:01:00
2017-02-07 14:02:00
2017-02-07 14:03:00
2017-02-07 14:04:00


2017-02-08 13:55:00
2017-02-08 13:56:00
2017-02-08 13:57:00
2017-02-08 13:58:00
2017-02-08 13:59:00
2017-02-08 14:00:00
2017-02-08 14:01:00
2017-02-08 14:02:00
2017-02-08 14:03:00
2017-02-08 14:04:00
2017-02-08 14:05:00
2017-02-08 14:06:00
2017-02-08 14:07:00
2017-02-08 14:08:00
2017-02-08 14:09:00
2017-02-08 14:10:00
2017-02-08 14:11:00
2017-02-08 14:12:00
2017-02-08 14:13:00
2017-02-08 14:14:00
2017-02-08 14:15:00
2017-02-08 14:16:00
2017-02-08 14:17:00
2017-02-08 14:18:00
2017-02-08 14:19:00
2017-02-08 14:20:00
2017-02-08 14:21:00
2017-02-08 14:22:00
2017-02-08 14:23:00
2017-02-08 14:24:00
2017-02-08 14:25:00
2017-02-08 14:26:00
2017-02-08 14:27:00
2017-02-08 14:28:00
2017-02-08 14:29:00
2017-02-08 14:30:00
2017-02-08 14:31:00
2017-02-08 14:32:00
2017-02-08 14:33:00
2017-02-08 14:34:00
2017-02-08 14:35:00
2017-02-08 14:36:00
2017-02-08 14:37:00
2017-02-08 14:38:00
2017-02-08 14:39:00
2017-02-08 14:40:00
2017-02-08 14:41:00
2017-02-08 14:42:00
2017-02-08 14:43:00
2017-02-08 14:44:00


Info: HHK:  Total Pnl: 3.98%  Profit/Loss Ratio: 1.31  Accuracy: 0.49  Score: 0.33  Normalized Score: 1.25 
Info: KKG:  Total Pnl: 0.00%  Profit/Loss Ratio: 1.11  Accuracy: 0.52  Score: 0.03  Normalized Score: 1.10 
Info: UWD:  Total Pnl: 2.81%  Profit/Loss Ratio: 1.58  Accuracy: 0.49  Score: 0.16  Normalized Score: 1.06 
Info: VSL:  Total Pnl: 0.26%  Profit/Loss Ratio: 1.11  Accuracy: 0.47  Score: 0.10  Normalized Score: 1.21 
Info: FFA:  Total Pnl: 0.06%  Profit/Loss Ratio: 1.13  Accuracy: 0.47  Score: 0.06  Normalized Score: 1.15 
Info: OED:  Total Pnl: 3.48%  Profit/Loss Ratio: 1.35  Accuracy: 0.48  Score: 0.22  Normalized Score: 1.13 
Info:  Total Pnl: 193.37%  Score: 1.14  Max Drawdown: 3.24%  RoC: 5225.08%  P/L Ratio: 2.77  Accuracy: 0.65  Score: 1.14 


In [17]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData2" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return []

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 5,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AGW
Processing data for stock: AIO
Processing data for stock: AUZ
Processing data for stock: BSN
Processing data for stock: BWU
Processing data for stock: CBT
Processing data for stock: CHV
Processing data for stock: CSR
Processing data for stock: CUN
Processing data for stock: CYD
Processing data for stock: DCO
Processing data for stock: DFZ
Processing data for stock: DVV
Processing data for stock: DYE
Processing data for stock: EGV
Processing data for stock: FCY
Processing data for stock: FFA
Processing data for stock: FFS
Processing data for stock: FKI
Processing data for stock: FRE
Processing data for stock: FUR
Processing data for stock: GFQ
Processing data for stock: GGK
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: HHK
Processing data for stock: IES
Processing data for stock: IFL
Processing data for stock: ILW
Processing data for stock: IMC
Processing data for stock: IUE
Processing data for stock: IUQ
Processi

2017-01-13 13:50:00
2017-01-13 13:51:00
2017-01-13 13:52:00
2017-01-13 13:53:00
2017-01-13 13:54:00
2017-01-13 13:55:00
2017-01-13 13:56:00
2017-01-13 13:57:00
2017-01-13 13:58:00
2017-01-13 13:59:00
2017-01-13 14:00:00
2017-01-13 14:01:00
2017-01-13 14:02:00
2017-01-13 14:03:00
2017-01-13 14:04:00
2017-01-13 14:05:00
2017-01-13 14:06:00
2017-01-13 14:07:00
2017-01-13 14:08:00
2017-01-13 14:09:00
2017-01-13 14:10:00
2017-01-13 14:11:00
2017-01-13 14:12:00
2017-01-13 14:13:00
2017-01-13 14:14:00
2017-01-13 14:15:00
2017-01-13 14:16:00
2017-01-13 14:17:00
2017-01-13 14:18:00
2017-01-13 14:19:00
2017-01-13 14:20:00
2017-01-13 14:21:00
2017-01-13 14:22:00
2017-01-13 14:23:00
2017-01-13 14:24:00
2017-01-13 14:25:00
2017-01-13 14:26:00
2017-01-13 14:27:00
2017-01-13 14:28:00
2017-01-13 14:29:00
2017-01-13 14:30:00
2017-01-13 14:31:00
2017-01-13 14:32:00
2017-01-13 14:33:00
2017-01-13 14:34:00
2017-01-13 14:35:00
2017-01-13 14:36:00
2017-01-13 14:37:00
2017-01-13 14:38:00
2017-01-13 14:39:00


2017-01-16 14:27:00
2017-01-16 14:28:00
2017-01-16 14:29:00
2017-01-16 14:30:00
2017-01-16 14:31:00
2017-01-16 14:32:00
2017-01-16 14:33:00
2017-01-16 14:34:00
2017-01-16 14:35:00
2017-01-16 14:36:00
2017-01-16 14:37:00
2017-01-16 14:38:00
2017-01-16 14:39:00
2017-01-16 14:40:00
2017-01-16 14:41:00
2017-01-16 14:42:00
2017-01-16 14:43:00
2017-01-16 14:44:00
2017-01-16 14:45:00
2017-01-16 14:46:00
2017-01-16 14:47:00
2017-01-16 14:48:00
2017-01-16 14:49:00
2017-01-16 14:50:00
2017-01-16 14:51:00
2017-01-16 14:52:00
2017-01-16 14:53:00
2017-01-16 14:54:00
2017-01-16 14:55:00
2017-01-16 14:56:00
2017-01-16 14:57:00
2017-01-16 14:58:00
2017-01-16 14:59:00
2017-01-16 15:00:00
2017-01-16 15:01:00
2017-01-16 15:02:00
2017-01-16 15:03:00
2017-01-16 15:04:00
2017-01-16 15:05:00
2017-01-16 15:06:00
2017-01-16 15:07:00
2017-01-16 15:08:00
2017-01-16 15:09:00
2017-01-16 15:10:00
2017-01-16 15:11:00
2017-01-16 15:12:00
2017-01-16 15:13:00
2017-01-16 15:14:00
2017-01-16 15:15:00
2017-01-16 15:16:00


2017-01-18 15:04:00
2017-01-18 15:05:00
2017-01-18 15:06:00
2017-01-18 15:07:00
2017-01-18 15:08:00
2017-01-18 15:09:00
2017-01-18 15:10:00
2017-01-18 15:11:00
2017-01-18 15:12:00
2017-01-18 15:13:00
2017-01-18 15:14:00
2017-01-18 15:15:00
2017-01-18 15:16:00
2017-01-18 15:17:00
2017-01-18 15:18:00
2017-01-18 15:19:00
2017-01-18 15:20:00
2017-01-18 15:21:00
2017-01-18 15:22:00
2017-01-18 15:23:00
2017-01-18 15:24:00
2017-01-18 15:25:00
2017-01-18 15:26:00
2017-01-18 15:27:00
2017-01-18 15:28:00
2017-01-18 15:29:00
2017-01-19 09:17:00
2017-01-19 09:18:00
2017-01-19 09:19:00
2017-01-19 09:20:00
2017-01-19 09:21:00
2017-01-19 09:22:00
2017-01-19 09:23:00
2017-01-19 09:24:00
2017-01-19 09:25:00
2017-01-19 09:26:00
2017-01-19 09:27:00
2017-01-19 09:28:00
2017-01-19 09:29:00
2017-01-19 09:30:00
2017-01-19 09:31:00
2017-01-19 09:32:00
2017-01-19 09:33:00
2017-01-19 09:34:00
2017-01-19 09:35:00
2017-01-19 09:36:00
2017-01-19 09:37:00
2017-01-19 09:38:00
2017-01-19 09:39:00
2017-01-19 09:40:00


2017-01-20 09:30:00
2017-01-20 09:31:00
2017-01-20 09:32:00
2017-01-20 09:33:00
2017-01-20 09:34:00
2017-01-20 09:35:00
2017-01-20 09:36:00
2017-01-20 09:37:00
2017-01-20 09:38:00
2017-01-20 09:39:00
2017-01-20 09:40:00
2017-01-20 09:41:00
2017-01-20 09:42:00
2017-01-20 09:43:00
2017-01-20 09:44:00
2017-01-20 09:45:00
2017-01-20 09:46:00
2017-01-20 09:47:00
2017-01-20 09:48:00
2017-01-20 09:49:00
2017-01-20 09:50:00
2017-01-20 09:51:00
2017-01-20 09:52:00
2017-01-20 09:53:00
2017-01-20 09:54:00
2017-01-20 09:55:00
2017-01-20 09:56:00
2017-01-20 09:57:00
2017-01-20 09:58:00
2017-01-20 09:59:00
2017-01-20 10:00:00
2017-01-20 10:01:00
2017-01-20 10:02:00
2017-01-20 10:03:00
2017-01-20 10:04:00
2017-01-20 10:05:00
2017-01-20 10:06:00
2017-01-20 10:07:00
2017-01-20 10:08:00
2017-01-20 10:09:00
2017-01-20 10:10:00
2017-01-20 10:11:00
2017-01-20 10:12:00
2017-01-20 10:13:00
2017-01-20 10:14:00
2017-01-20 10:15:00
2017-01-20 10:16:00
2017-01-20 10:17:00
2017-01-20 10:18:00
2017-01-20 10:19:00


...

2017-02-02 14:38:00
2017-02-02 14:39:00
2017-02-02 14:40:00
2017-02-02 14:41:00
2017-02-02 14:42:00
2017-02-02 14:43:00
2017-02-02 14:44:00
2017-02-02 14:45:00
2017-02-02 14:46:00
2017-02-02 14:47:00
2017-02-02 14:48:00
2017-02-02 14:49:00
2017-02-02 14:50:00
2017-02-02 14:51:00
2017-02-02 14:52:00
2017-02-02 14:53:00
2017-02-02 14:54:00
2017-02-02 14:55:00
2017-02-02 14:56:00
2017-02-02 14:57:00
2017-02-02 14:58:00
2017-02-02 14:59:00
2017-02-02 15:00:00
2017-02-02 15:01:00
2017-02-02 15:02:00
2017-02-02 15:03:00
2017-02-02 15:04:00
2017-02-02 15:05:00
2017-02-02 15:06:00
2017-02-02 15:07:00
2017-02-02 15:08:00
2017-02-02 15:09:00
2017-02-02 15:10:00
2017-02-02 15:11:00
2017-02-02 15:12:00
2017-02-02 15:13:00
2017-02-02 15:14:00
2017-02-02 15:15:00
2017-02-02 15:16:00
2017-02-02 15:17:00
2017-02-02 15:18:00
2017-02-02 15:19:00
2017-02-02 15:20:00
2017-02-02 15:21:00
2017-02-02 15:22:00
2017-02-02 15:23:00
2017-02-02 15:24:00
2017-02-02 15:25:00
2017-02-02 15:26:00
2017-02-02 15:27:00


2017-02-03 15:17:00
2017-02-03 15:18:00
2017-02-03 15:19:00
2017-02-03 15:20:00
2017-02-03 15:21:00
2017-02-03 15:22:00
2017-02-03 15:23:00
2017-02-03 15:24:00
2017-02-03 15:25:00
2017-02-03 15:26:00
2017-02-03 15:27:00
2017-02-03 15:28:00
2017-02-03 15:29:00
2017-02-06 09:17:00
2017-02-06 09:18:00
2017-02-06 09:19:00
2017-02-06 09:20:00
2017-02-06 09:21:00
2017-02-06 09:22:00
2017-02-06 09:23:00
2017-02-06 09:24:00
2017-02-06 09:25:00
2017-02-06 09:26:00
2017-02-06 09:27:00
2017-02-06 09:28:00
2017-02-06 09:29:00
2017-02-06 09:30:00
2017-02-06 09:31:00
2017-02-06 09:32:00
2017-02-06 09:33:00
2017-02-06 09:34:00
2017-02-06 09:35:00
2017-02-06 09:36:00
2017-02-06 09:37:00
2017-02-06 09:38:00
2017-02-06 09:39:00
2017-02-06 09:40:00
2017-02-06 09:41:00
2017-02-06 09:42:00
2017-02-06 09:43:00
2017-02-06 09:44:00
2017-02-06 09:45:00
2017-02-06 09:46:00
2017-02-06 09:47:00
2017-02-06 09:48:00
2017-02-06 09:49:00
2017-02-06 09:50:00
2017-02-06 09:51:00
2017-02-06 09:52:00
2017-02-06 09:53:00


2017-02-07 09:43:00
2017-02-07 09:44:00
2017-02-07 09:45:00
2017-02-07 09:46:00
2017-02-07 09:47:00
2017-02-07 09:48:00
2017-02-07 09:49:00
2017-02-07 09:50:00
2017-02-07 09:51:00
2017-02-07 09:52:00
2017-02-07 09:53:00
2017-02-07 09:54:00
2017-02-07 09:55:00
2017-02-07 09:56:00
2017-02-07 09:57:00
2017-02-07 09:58:00
2017-02-07 09:59:00
2017-02-07 10:00:00
2017-02-07 10:01:00
2017-02-07 10:02:00
2017-02-07 10:03:00
2017-02-07 10:04:00
2017-02-07 10:05:00
2017-02-07 10:06:00
2017-02-07 10:07:00
2017-02-07 10:08:00
2017-02-07 10:09:00
2017-02-07 10:10:00
2017-02-07 10:11:00
2017-02-07 10:12:00
2017-02-07 10:13:00
2017-02-07 10:14:00
2017-02-07 10:15:00
2017-02-07 10:16:00
2017-02-07 10:17:00
2017-02-07 10:18:00
2017-02-07 10:19:00
2017-02-07 10:20:00
2017-02-07 10:21:00
2017-02-07 10:22:00
2017-02-07 10:23:00
2017-02-07 10:24:00
2017-02-07 10:25:00
2017-02-07 10:26:00
2017-02-07 10:27:00
2017-02-07 10:28:00
2017-02-07 10:29:00
2017-02-07 10:30:00
2017-02-07 10:31:00
2017-02-07 10:32:00


2017-02-08 10:22:00
2017-02-08 10:23:00
2017-02-08 10:24:00
2017-02-08 10:25:00
2017-02-08 10:26:00
2017-02-08 10:27:00
2017-02-08 10:28:00
2017-02-08 10:29:00
2017-02-08 10:30:00
2017-02-08 10:31:00
2017-02-08 10:32:00
2017-02-08 10:33:00
2017-02-08 10:34:00
2017-02-08 10:35:00
2017-02-08 10:36:00
2017-02-08 10:37:00
2017-02-08 10:38:00
2017-02-08 10:39:00
2017-02-08 10:40:00
2017-02-08 10:41:00
2017-02-08 10:42:00
2017-02-08 10:43:00
2017-02-08 10:44:00
2017-02-08 10:45:00
2017-02-08 10:46:00
2017-02-08 10:47:00
2017-02-08 10:48:00
2017-02-08 10:49:00
2017-02-08 10:50:00
2017-02-08 10:51:00
2017-02-08 10:52:00
2017-02-08 10:53:00
2017-02-08 10:54:00
2017-02-08 10:55:00
2017-02-08 10:56:00
2017-02-08 10:57:00
2017-02-08 10:58:00
2017-02-08 10:59:00
2017-02-08 11:00:00
2017-02-08 11:01:00
2017-02-08 11:02:00
2017-02-08 11:03:00
2017-02-08 11:04:00
2017-02-08 11:05:00
2017-02-08 11:06:00
2017-02-08 11:07:00
2017-02-08 11:08:00
2017-02-08 11:09:00
2017-02-08 11:10:00
2017-02-08 11:11:00


2017-02-09 11:00:00
2017-02-09 11:01:00
2017-02-09 11:02:00
2017-02-09 11:03:00
2017-02-09 11:04:00
2017-02-09 11:05:00
2017-02-09 11:06:00
2017-02-09 11:07:00
2017-02-09 11:08:00
2017-02-09 11:09:00
2017-02-09 11:10:00
2017-02-09 11:11:00
2017-02-09 11:12:00
2017-02-09 11:13:00
2017-02-09 11:14:00
2017-02-09 11:15:00
2017-02-09 11:16:00
2017-02-09 11:17:00
2017-02-09 11:18:00
2017-02-09 11:19:00
2017-02-09 11:20:00
2017-02-09 11:21:00
2017-02-09 11:22:00
2017-02-09 11:23:00
2017-02-09 11:24:00
2017-02-09 11:25:00
2017-02-09 11:26:00
2017-02-09 11:27:00
2017-02-09 11:28:00
2017-02-09 11:29:00
2017-02-09 11:30:00
2017-02-09 11:31:00
2017-02-09 11:32:00
2017-02-09 11:33:00
2017-02-09 11:34:00
2017-02-09 11:35:00
2017-02-09 11:36:00
2017-02-09 11:37:00
2017-02-09 11:38:00
2017-02-09 11:39:00
2017-02-09 11:40:00
2017-02-09 11:41:00
2017-02-09 11:42:00
2017-02-09 11:43:00
2017-02-09 11:44:00
2017-02-09 11:45:00
2017-02-09 11:46:00
2017-02-09 11:47:00
2017-02-09 11:48:00
2017-02-09 11:49:00


In [18]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData3" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return []

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 5,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AGW
Processing data for stock: AIO
Processing data for stock: AUZ
Processing data for stock: BSN
Processing data for stock: BWU
Processing data for stock: CBT
Processing data for stock: CHV
Processing data for stock: CSR
Processing data for stock: CUN
Processing data for stock: CYD
Processing data for stock: DCO
Processing data for stock: DFZ
Processing data for stock: DVV
Processing data for stock: DYE
Processing data for stock: EGV
Processing data for stock: FCY
Processing data for stock: FFA
Processing data for stock: FFS
Processing data for stock: FKI
Processing data for stock: FRE
Processing data for stock: FUR
Processing data for stock: GFQ
Processing data for stock: GGK
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: HHK
Processing data for stock: IES
Processing data for stock: IFL
Processing data for stock: ILW
Processing data for stock: IMC
Processing data for stock: IUE
Processing data for stock: IUQ
Processi

2017-01-06 13:49:00
2017-01-06 13:50:00
2017-01-06 13:51:00
2017-01-06 13:52:00
2017-01-06 13:53:00
2017-01-06 13:54:00
2017-01-06 13:55:00
2017-01-06 13:56:00
2017-01-06 13:57:00
2017-01-06 13:58:00
2017-01-06 13:59:00
2017-01-06 14:00:00
2017-01-06 14:01:00
2017-01-06 14:02:00
2017-01-06 14:03:00
2017-01-06 14:04:00
2017-01-06 14:05:00
2017-01-06 14:06:00
2017-01-06 14:07:00
2017-01-06 14:08:00
2017-01-06 14:09:00
2017-01-06 14:10:00
2017-01-06 14:11:00
2017-01-06 14:12:00
2017-01-06 14:13:00
2017-01-06 14:14:00
2017-01-06 14:15:00
2017-01-06 14:16:00
2017-01-06 14:17:00
2017-01-06 14:18:00
2017-01-06 14:19:00
2017-01-06 14:20:00
2017-01-06 14:21:00
2017-01-06 14:22:00
2017-01-06 14:23:00
2017-01-06 14:24:00
2017-01-06 14:25:00
2017-01-06 14:26:00
2017-01-06 14:27:00
2017-01-06 14:28:00
2017-01-06 14:29:00
2017-01-06 14:30:00
2017-01-06 14:31:00
2017-01-06 14:32:00
2017-01-06 14:33:00
2017-01-06 14:34:00
2017-01-06 14:35:00
2017-01-06 14:36:00
2017-01-06 14:37:00
2017-01-06 14:38:00


2017-01-10 14:27:00
2017-01-10 14:28:00
2017-01-10 14:29:00
2017-01-10 14:30:00
2017-01-10 14:31:00
2017-01-10 14:32:00
2017-01-10 14:33:00
2017-01-10 14:34:00
2017-01-10 14:35:00
2017-01-10 14:36:00
2017-01-10 14:37:00
2017-01-10 14:38:00
2017-01-10 14:39:00
2017-01-10 14:40:00
2017-01-10 14:41:00
2017-01-10 14:42:00
2017-01-10 14:43:00
2017-01-10 14:44:00
2017-01-10 14:45:00
2017-01-10 14:46:00
2017-01-10 14:47:00
2017-01-10 14:48:00
2017-01-10 14:49:00
2017-01-10 14:50:00
2017-01-10 14:51:00
2017-01-10 14:52:00
2017-01-10 14:53:00
2017-01-10 14:54:00
2017-01-10 14:55:00
2017-01-10 14:56:00
2017-01-10 14:57:00
2017-01-10 14:58:00
2017-01-10 14:59:00
2017-01-10 15:00:00
2017-01-10 15:01:00
2017-01-10 15:02:00
2017-01-10 15:03:00
2017-01-10 15:04:00
2017-01-10 15:05:00
2017-01-10 15:06:00
2017-01-10 15:07:00
2017-01-10 15:08:00
2017-01-10 15:09:00
2017-01-10 15:10:00
2017-01-10 15:11:00
2017-01-10 15:12:00
2017-01-10 15:13:00
2017-01-10 15:14:00
2017-01-10 15:15:00
2017-01-10 15:16:00


2017-01-11 15:06:00
2017-01-11 15:07:00
2017-01-11 15:08:00
2017-01-11 15:09:00
2017-01-11 15:10:00
2017-01-11 15:11:00
2017-01-11 15:12:00
2017-01-11 15:13:00
2017-01-11 15:14:00
2017-01-11 15:15:00
2017-01-11 15:16:00
2017-01-11 15:17:00
2017-01-11 15:18:00
2017-01-11 15:19:00
2017-01-11 15:20:00
2017-01-11 15:21:00
2017-01-11 15:22:00
2017-01-11 15:23:00
2017-01-11 15:24:00
2017-01-11 15:25:00
2017-01-11 15:26:00
2017-01-11 15:27:00
2017-01-11 15:28:00
2017-01-11 15:29:00
2017-01-12 09:17:00
2017-01-12 09:18:00
2017-01-12 09:19:00
2017-01-12 09:20:00
2017-01-12 09:21:00
2017-01-12 09:22:00
2017-01-12 09:23:00
2017-01-12 09:24:00
2017-01-12 09:25:00
2017-01-12 09:26:00
2017-01-12 09:27:00
2017-01-12 09:28:00
2017-01-12 09:29:00
2017-01-12 09:30:00
2017-01-12 09:31:00
2017-01-12 09:32:00
2017-01-12 09:33:00
2017-01-12 09:34:00
2017-01-12 09:35:00
2017-01-12 09:36:00
2017-01-12 09:37:00
2017-01-12 09:38:00
2017-01-12 09:39:00
2017-01-12 09:40:00
2017-01-12 09:41:00
2017-01-12 09:42:00


2017-01-13 09:31:00
2017-01-13 09:32:00
2017-01-13 09:33:00
2017-01-13 09:34:00
2017-01-13 09:35:00
2017-01-13 09:36:00
2017-01-13 09:37:00
2017-01-13 09:38:00
2017-01-13 09:39:00
2017-01-13 09:40:00
2017-01-13 09:41:00
2017-01-13 09:42:00
2017-01-13 09:43:00
2017-01-13 09:44:00
2017-01-13 09:45:00
2017-01-13 09:46:00
2017-01-13 09:47:00
2017-01-13 09:48:00
2017-01-13 09:49:00
2017-01-13 09:50:00
2017-01-13 09:51:00
2017-01-13 09:52:00
2017-01-13 09:53:00
2017-01-13 09:54:00
2017-01-13 09:55:00
2017-01-13 09:56:00
2017-01-13 09:57:00
2017-01-13 09:58:00
2017-01-13 09:59:00
2017-01-13 10:00:00
2017-01-13 10:01:00
2017-01-13 10:02:00
2017-01-13 10:03:00
2017-01-13 10:04:00
2017-01-13 10:05:00
2017-01-13 10:06:00
2017-01-13 10:07:00
2017-01-13 10:08:00
2017-01-13 10:09:00
2017-01-13 10:10:00
2017-01-13 10:11:00
2017-01-13 10:12:00
2017-01-13 10:13:00
2017-01-13 10:14:00
2017-01-13 10:15:00
2017-01-13 10:16:00
2017-01-13 10:17:00
2017-01-13 10:18:00
2017-01-13 10:19:00
2017-01-13 10:20:00


...

2017-01-27 14:42:00
2017-01-27 14:43:00
2017-01-27 14:44:00
2017-01-27 14:45:00
2017-01-27 14:46:00
2017-01-27 14:47:00
2017-01-27 14:48:00
2017-01-27 14:49:00
2017-01-27 14:50:00
2017-01-27 14:51:00
2017-01-27 14:52:00
2017-01-27 14:53:00
2017-01-27 14:54:00
2017-01-27 14:55:00
2017-01-27 14:56:00
2017-01-27 14:57:00
2017-01-27 14:58:00
2017-01-27 14:59:00
2017-01-27 15:00:00
2017-01-27 15:01:00
2017-01-27 15:02:00
2017-01-27 15:03:00
2017-01-27 15:04:00
2017-01-27 15:05:00
2017-01-27 15:06:00
2017-01-27 15:07:00
2017-01-27 15:08:00
2017-01-27 15:09:00
2017-01-27 15:10:00
2017-01-27 15:11:00
2017-01-27 15:12:00
2017-01-27 15:13:00
2017-01-27 15:14:00
2017-01-27 15:15:00
2017-01-27 15:16:00
2017-01-27 15:17:00
2017-01-27 15:18:00
2017-01-27 15:19:00
2017-01-27 15:20:00
2017-01-27 15:21:00
2017-01-27 15:22:00
2017-01-27 15:23:00
2017-01-27 15:24:00
2017-01-27 15:25:00
2017-01-27 15:26:00
2017-01-27 15:27:00
2017-01-27 15:28:00
2017-01-27 15:29:00
2017-01-30 09:17:00
2017-01-30 09:18:00


2017-01-30 15:19:00
2017-01-30 15:20:00
2017-01-30 15:21:00
2017-01-30 15:22:00
2017-01-30 15:23:00
2017-01-30 15:24:00
2017-01-30 15:25:00
2017-01-30 15:26:00
2017-01-30 15:27:00
2017-01-30 15:28:00
2017-01-30 15:29:00
2017-01-31 09:17:00
2017-01-31 09:18:00
2017-01-31 09:19:00
2017-01-31 09:20:00
2017-01-31 09:21:00
2017-01-31 09:22:00
2017-01-31 09:23:00
2017-01-31 09:24:00
2017-01-31 09:25:00
2017-01-31 09:26:00
2017-01-31 09:27:00
2017-01-31 09:28:00
2017-01-31 09:29:00
2017-01-31 09:30:00
2017-01-31 09:31:00
2017-01-31 09:32:00
2017-01-31 09:33:00
2017-01-31 09:34:00
2017-01-31 09:35:00
2017-01-31 09:36:00
2017-01-31 09:37:00
2017-01-31 09:38:00
2017-01-31 09:39:00
2017-01-31 09:40:00
2017-01-31 09:41:00
2017-01-31 09:42:00
2017-01-31 09:43:00
2017-01-31 09:44:00
2017-01-31 09:45:00
2017-01-31 09:46:00
2017-01-31 09:47:00
2017-01-31 09:48:00
2017-01-31 09:49:00
2017-01-31 09:50:00
2017-01-31 09:51:00
2017-01-31 09:52:00
2017-01-31 09:53:00
2017-01-31 09:54:00
2017-01-31 09:55:00


2017-02-01 09:45:00
2017-02-01 09:46:00
2017-02-01 09:47:00
2017-02-01 09:48:00
2017-02-01 09:49:00
2017-02-01 09:50:00
2017-02-01 09:51:00
2017-02-01 09:52:00
2017-02-01 09:53:00
2017-02-01 09:54:00
2017-02-01 09:55:00
2017-02-01 09:56:00
2017-02-01 09:57:00
2017-02-01 09:58:00
2017-02-01 09:59:00
2017-02-01 10:00:00
2017-02-01 10:01:00
2017-02-01 10:02:00
2017-02-01 10:03:00
2017-02-01 10:04:00
2017-02-01 10:05:00
2017-02-01 10:06:00
2017-02-01 10:07:00
2017-02-01 10:08:00
2017-02-01 10:09:00
2017-02-01 10:10:00
2017-02-01 10:11:00
2017-02-01 10:12:00
2017-02-01 10:13:00
2017-02-01 10:14:00
2017-02-01 10:15:00
2017-02-01 10:16:00
2017-02-01 10:17:00
2017-02-01 10:18:00
2017-02-01 10:19:00
2017-02-01 10:20:00
2017-02-01 10:21:00
2017-02-01 10:22:00
2017-02-01 10:23:00
2017-02-01 10:24:00
2017-02-01 10:25:00
2017-02-01 10:26:00
2017-02-01 10:27:00
2017-02-01 10:28:00
2017-02-01 10:29:00
2017-02-01 10:30:00
2017-02-01 10:31:00
2017-02-01 10:32:00
2017-02-01 10:33:00
2017-02-01 10:34:00


2017-02-02 10:23:00
2017-02-02 10:24:00
2017-02-02 10:25:00
2017-02-02 10:26:00
2017-02-02 10:27:00
2017-02-02 10:28:00
2017-02-02 10:29:00
2017-02-02 10:30:00
2017-02-02 10:31:00
2017-02-02 10:32:00
2017-02-02 10:33:00
2017-02-02 10:34:00
2017-02-02 10:35:00
2017-02-02 10:36:00
2017-02-02 10:37:00
2017-02-02 10:38:00
2017-02-02 10:39:00
2017-02-02 10:40:00
2017-02-02 10:41:00
2017-02-02 10:42:00
2017-02-02 10:43:00
2017-02-02 10:44:00
2017-02-02 10:45:00
2017-02-02 10:46:00
2017-02-02 10:47:00
2017-02-02 10:48:00
2017-02-02 10:49:00
2017-02-02 10:50:00
2017-02-02 10:51:00
2017-02-02 10:52:00
2017-02-02 10:53:00
2017-02-02 10:54:00
2017-02-02 10:55:00
2017-02-02 10:56:00
2017-02-02 10:57:00
2017-02-02 10:58:00
2017-02-02 10:59:00
2017-02-02 11:00:00
2017-02-02 11:01:00
2017-02-02 11:02:00
2017-02-02 11:03:00
2017-02-02 11:04:00
2017-02-02 11:05:00
2017-02-02 11:06:00
2017-02-02 11:07:00
2017-02-02 11:08:00
2017-02-02 11:09:00
2017-02-02 11:10:00
2017-02-02 11:11:00
2017-02-02 11:12:00


Info: CHV:  Total Pnl: 0.80%  Profit/Loss Ratio: 1.21  Accuracy: 0.47  Score: 0.14  Normalized Score: 1.10 
Info: CUN:  Total Pnl: 0.09%  Profit/Loss Ratio: 1.24  Accuracy: 0.48  Score: 0.06  Normalized Score: 1.05 
Info: AUZ:  Total Pnl: 2.33%  Profit/Loss Ratio: 1.47  Accuracy: 0.49  Score: 0.21  Normalized Score: 1.03 
Info: XAD:  Total Pnl: 0.31%  Profit/Loss Ratio: 1.11  Accuracy: 0.47  Score: 0.13  Normalized Score: 1.16 
Info: VKE:  Total Pnl: 12.91%  Profit/Loss Ratio: 1.71  Accuracy: 0.50  Score: 0.49  Normalized Score: 1.09 
Info: CSR:  Total Pnl: 0.16%  Profit/Loss Ratio: 1.19  Accuracy: 0.48  Score: 0.08  Normalized Score: 1.10 
Info: KAA:  Total Pnl: 0.05%  Profit/Loss Ratio: 1.13  Accuracy: 0.47  Score: 0.06  Normalized Score: 1.08 
Info: PUO:  Total Pnl: 0.08%  Profit/Loss Ratio: 1.11  Accuracy: 0.47  Score: 0.08  Normalized Score: 1.12 
Info: YGC:  Total Pnl: 1.20%  Profit/Loss Ratio: 1.21  Accuracy: 0.46  Score: 0.17  Normalized Score: 1.12 
Info: ILW:  Total Pnl: 0.25

In [20]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData1" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return []

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 1,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 2,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AGW
Processing data for stock: AIO
Processing data for stock: AUZ
Processing data for stock: BSN
Processing data for stock: BWU
Processing data for stock: CBT
Processing data for stock: CHV
Processing data for stock: CSR
Processing data for stock: CUN
Processing data for stock: CYD
Processing data for stock: DCO
Processing data for stock: DFZ
Processing data for stock: DVV
Processing data for stock: DYE
Processing data for stock: EGV
Processing data for stock: FCY
Processing data for stock: FFA
Processing data for stock: FFS
Processing data for stock: FKI
Processing data for stock: FRE
Processing data for stock: FUR
Processing data for stock: GFQ
Processing data for stock: GGK
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: HHK
Processing data for stock: IES
Processing data for stock: IFL
Processing data for stock: ILW
Processing data for stock: IMC
Processing data for stock: IUE
Processing data for stock: IUQ
Processi

2017-01-06 13:48:00
2017-01-06 13:49:00
2017-01-06 13:50:00
2017-01-06 13:51:00
2017-01-06 13:52:00
2017-01-06 13:53:00
2017-01-06 13:54:00
2017-01-06 13:55:00
2017-01-06 13:56:00
2017-01-06 13:57:00
2017-01-06 13:58:00
2017-01-06 13:59:00
2017-01-06 14:00:00
2017-01-06 14:01:00
2017-01-06 14:02:00
2017-01-06 14:03:00
2017-01-06 14:04:00
2017-01-06 14:05:00
2017-01-06 14:06:00
2017-01-06 14:07:00
2017-01-06 14:08:00
2017-01-06 14:09:00
2017-01-06 14:10:00
2017-01-06 14:11:00
2017-01-06 14:12:00
2017-01-06 14:13:00
2017-01-06 14:14:00
2017-01-06 14:15:00
2017-01-06 14:16:00
2017-01-06 14:17:00
2017-01-06 14:18:00
2017-01-06 14:19:00
2017-01-06 14:20:00
2017-01-06 14:21:00
2017-01-06 14:22:00
2017-01-06 14:23:00
2017-01-06 14:24:00
2017-01-06 14:25:00
2017-01-06 14:26:00
2017-01-06 14:27:00
2017-01-06 14:28:00
2017-01-06 14:29:00
2017-01-06 14:30:00
2017-01-06 14:31:00
2017-01-06 14:32:00
2017-01-06 14:33:00
2017-01-06 14:34:00
2017-01-06 14:35:00
2017-01-06 14:36:00
2017-01-06 14:37:00


2017-01-09 14:26:00
2017-01-09 14:27:00
2017-01-09 14:28:00
2017-01-09 14:29:00
2017-01-09 14:30:00
2017-01-09 14:31:00
2017-01-09 14:32:00
2017-01-09 14:33:00
2017-01-09 14:34:00
2017-01-09 14:35:00
2017-01-09 14:36:00
2017-01-09 14:37:00
2017-01-09 14:38:00
2017-01-09 14:39:00
2017-01-09 14:40:00
2017-01-09 14:41:00
2017-01-09 14:42:00
2017-01-09 14:43:00
2017-01-09 14:44:00
2017-01-09 14:45:00
2017-01-09 14:46:00
2017-01-09 14:47:00
2017-01-09 14:48:00
2017-01-09 14:49:00
2017-01-09 14:50:00
2017-01-09 14:51:00
2017-01-09 14:52:00
2017-01-09 14:53:00
2017-01-09 14:54:00
2017-01-09 14:55:00
2017-01-09 14:56:00
2017-01-09 14:57:00
2017-01-09 14:58:00
2017-01-09 14:59:00
2017-01-09 15:00:00
2017-01-09 15:01:00
2017-01-09 15:02:00
2017-01-09 15:03:00
2017-01-09 15:04:00
2017-01-09 15:05:00
2017-01-09 15:06:00
2017-01-09 15:07:00
2017-01-09 15:08:00
2017-01-09 15:09:00
2017-01-09 15:10:00
2017-01-09 15:11:00
2017-01-09 15:12:00
2017-01-09 15:13:00
2017-01-09 15:14:00
2017-01-09 15:15:00


2017-01-10 15:05:00
2017-01-10 15:06:00
2017-01-10 15:07:00
2017-01-10 15:08:00
2017-01-10 15:09:00
2017-01-10 15:10:00
2017-01-10 15:11:00
2017-01-10 15:12:00
2017-01-10 15:13:00
2017-01-10 15:14:00
2017-01-10 15:15:00
2017-01-10 15:16:00
2017-01-10 15:17:00
2017-01-10 15:18:00
2017-01-10 15:19:00
2017-01-10 15:20:00
2017-01-10 15:21:00
2017-01-10 15:22:00
2017-01-10 15:23:00
2017-01-10 15:24:00
2017-01-10 15:25:00
2017-01-10 15:26:00
2017-01-10 15:27:00
2017-01-10 15:28:00
2017-01-10 15:29:00
2017-01-11 09:17:00
2017-01-11 09:18:00
2017-01-11 09:19:00
2017-01-11 09:20:00
2017-01-11 09:21:00
2017-01-11 09:22:00
2017-01-11 09:23:00
2017-01-11 09:24:00
2017-01-11 09:25:00
2017-01-11 09:26:00
2017-01-11 09:27:00
2017-01-11 09:28:00
2017-01-11 09:29:00
2017-01-11 09:30:00
2017-01-11 09:31:00
2017-01-11 09:32:00
2017-01-11 09:33:00
2017-01-11 09:34:00
2017-01-11 09:35:00
2017-01-11 09:36:00
2017-01-11 09:37:00
2017-01-11 09:38:00
2017-01-11 09:39:00
2017-01-11 09:40:00
2017-01-11 09:41:00


2017-01-13 10:06:00
2017-01-13 10:07:00
2017-01-13 10:08:00
2017-01-13 10:09:00
2017-01-13 10:10:00
2017-01-13 10:11:00
2017-01-13 10:12:00
2017-01-13 10:13:00
2017-01-13 10:14:00
2017-01-13 10:15:00
2017-01-13 10:16:00
2017-01-13 10:17:00
2017-01-13 10:18:00
2017-01-13 10:19:00
2017-01-13 10:20:00
2017-01-13 10:21:00
2017-01-13 10:22:00
2017-01-13 10:23:00
2017-01-13 10:24:00
2017-01-13 10:25:00
2017-01-13 10:26:00
2017-01-13 10:27:00
2017-01-13 10:28:00
2017-01-13 10:29:00
2017-01-13 10:30:00
2017-01-13 10:31:00
2017-01-13 10:32:00
2017-01-13 10:33:00
2017-01-13 10:34:00
2017-01-13 10:35:00
2017-01-13 10:36:00
2017-01-13 10:37:00
2017-01-13 10:38:00
2017-01-13 10:39:00
2017-01-13 10:40:00
2017-01-13 10:41:00
2017-01-13 10:42:00
2017-01-13 10:43:00
2017-01-13 10:44:00
2017-01-13 10:45:00
2017-01-13 10:46:00
2017-01-13 10:47:00
2017-01-13 10:48:00
2017-01-13 10:49:00
2017-01-13 10:50:00
2017-01-13 10:51:00
2017-01-13 10:52:00
2017-01-13 10:53:00
2017-01-13 10:54:00
2017-01-13 10:55:00


...

2017-02-02 12:07:00
2017-02-02 12:08:00
2017-02-02 12:09:00
2017-02-02 12:10:00
2017-02-02 12:11:00
2017-02-02 12:12:00
2017-02-02 12:13:00
2017-02-02 12:14:00
2017-02-02 12:15:00
2017-02-02 12:16:00
2017-02-02 12:17:00
2017-02-02 12:18:00
2017-02-02 12:19:00
2017-02-02 12:20:00
2017-02-02 12:21:00
2017-02-02 12:22:00
2017-02-02 12:23:00
2017-02-02 12:24:00
2017-02-02 12:25:00
2017-02-02 12:26:00
2017-02-02 12:27:00
2017-02-02 12:28:00
2017-02-02 12:29:00
2017-02-02 12:30:00
2017-02-02 12:31:00
2017-02-02 12:32:00
2017-02-02 12:33:00
2017-02-02 12:34:00
2017-02-02 12:35:00
2017-02-02 12:36:00
2017-02-02 12:37:00
2017-02-02 12:38:00
2017-02-02 12:39:00
2017-02-02 12:40:00
2017-02-02 12:41:00
2017-02-02 12:42:00
2017-02-02 12:43:00
2017-02-02 12:44:00
2017-02-02 12:45:00
2017-02-02 12:46:00
2017-02-02 12:47:00
2017-02-02 12:48:00
2017-02-02 12:49:00
2017-02-02 12:50:00
2017-02-02 12:51:00
2017-02-02 12:52:00
2017-02-02 12:53:00
2017-02-02 12:54:00
2017-02-02 12:55:00
2017-02-02 12:56:00


2017-02-03 12:45:00
2017-02-03 12:46:00
2017-02-03 12:47:00
2017-02-03 12:48:00
2017-02-03 12:49:00
2017-02-03 12:50:00
2017-02-03 12:51:00
2017-02-03 12:52:00
2017-02-03 12:53:00
2017-02-03 12:54:00
2017-02-03 12:55:00
2017-02-03 12:56:00
2017-02-03 12:57:00
2017-02-03 12:58:00
2017-02-03 12:59:00
2017-02-03 13:00:00
2017-02-03 13:01:00
2017-02-03 13:02:00
2017-02-03 13:03:00
2017-02-03 13:04:00
2017-02-03 13:05:00
2017-02-03 13:06:00
2017-02-03 13:07:00
2017-02-03 13:08:00
2017-02-03 13:09:00
2017-02-03 13:10:00
2017-02-03 13:11:00
2017-02-03 13:12:00
2017-02-03 13:13:00
2017-02-03 13:14:00
2017-02-03 13:15:00
2017-02-03 13:16:00
2017-02-03 13:17:00
2017-02-03 13:18:00
2017-02-03 13:19:00
2017-02-03 13:20:00
2017-02-03 13:21:00
2017-02-03 13:22:00
2017-02-03 13:23:00
2017-02-03 13:24:00
2017-02-03 13:25:00
2017-02-03 13:26:00
2017-02-03 13:27:00
2017-02-03 13:28:00
2017-02-03 13:29:00
2017-02-03 13:30:00
2017-02-03 13:31:00
2017-02-03 13:32:00
2017-02-03 13:33:00
2017-02-03 13:34:00


2017-02-07 13:22:00
2017-02-07 13:23:00
2017-02-07 13:24:00
2017-02-07 13:25:00
2017-02-07 13:26:00
2017-02-07 13:27:00
2017-02-07 13:28:00
2017-02-07 13:29:00
2017-02-07 13:30:00
2017-02-07 13:31:00
2017-02-07 13:32:00
2017-02-07 13:33:00
2017-02-07 13:34:00
2017-02-07 13:35:00
2017-02-07 13:36:00
2017-02-07 13:37:00
2017-02-07 13:38:00
2017-02-07 13:39:00
2017-02-07 13:40:00
2017-02-07 13:41:00
2017-02-07 13:42:00
2017-02-07 13:43:00
2017-02-07 13:44:00
2017-02-07 13:45:00
2017-02-07 13:46:00
2017-02-07 13:47:00
2017-02-07 13:48:00
2017-02-07 13:49:00
2017-02-07 13:50:00
2017-02-07 13:51:00
2017-02-07 13:52:00
2017-02-07 13:53:00
2017-02-07 13:54:00
2017-02-07 13:55:00
2017-02-07 13:56:00
2017-02-07 13:57:00
2017-02-07 13:58:00
2017-02-07 13:59:00
2017-02-07 14:00:00
2017-02-07 14:01:00
2017-02-07 14:02:00
2017-02-07 14:03:00
2017-02-07 14:04:00
2017-02-07 14:05:00
2017-02-07 14:06:00
2017-02-07 14:07:00
2017-02-07 14:08:00
2017-02-07 14:09:00
2017-02-07 14:10:00
2017-02-07 14:11:00


2017-02-08 14:00:00
2017-02-08 14:01:00
2017-02-08 14:02:00
2017-02-08 14:03:00
2017-02-08 14:04:00
2017-02-08 14:05:00
2017-02-08 14:06:00
2017-02-08 14:07:00
2017-02-08 14:08:00
2017-02-08 14:09:00
2017-02-08 14:10:00
2017-02-08 14:11:00
2017-02-08 14:12:00
2017-02-08 14:13:00
2017-02-08 14:14:00
2017-02-08 14:15:00
2017-02-08 14:16:00
2017-02-08 14:17:00
2017-02-08 14:18:00
2017-02-08 14:19:00
2017-02-08 14:20:00
2017-02-08 14:21:00
2017-02-08 14:22:00
2017-02-08 14:23:00
2017-02-08 14:24:00
2017-02-08 14:25:00
2017-02-08 14:26:00
2017-02-08 14:27:00
2017-02-08 14:28:00
2017-02-08 14:29:00
2017-02-08 14:30:00
2017-02-08 14:31:00
2017-02-08 14:32:00
2017-02-08 14:33:00
2017-02-08 14:34:00
2017-02-08 14:35:00
2017-02-08 14:36:00
2017-02-08 14:37:00
2017-02-08 14:38:00
2017-02-08 14:39:00
2017-02-08 14:40:00
2017-02-08 14:41:00
2017-02-08 14:42:00
2017-02-08 14:43:00
2017-02-08 14:44:00
2017-02-08 14:45:00
2017-02-08 14:46:00
2017-02-08 14:47:00
2017-02-08 14:48:00
2017-02-08 14:49:00


Info: LKB:  Total Pnl: -0.25%  Profit/Loss Ratio: 0.91  Accuracy: 0.46  Score: 0.17  Normalized Score: 1.03 
Info: IES:  Total Pnl: 0.06%  Profit/Loss Ratio: 1.17  Accuracy: 0.45  Score: 0.09  Normalized Score: 1.02 
Info: SVG:  Total Pnl: 2.14%  Profit/Loss Ratio: 1.53  Accuracy: 0.46  Score: 0.23  Normalized Score: 0.97 
Info: MAS:  Total Pnl: 2.79%  Profit/Loss Ratio: 1.61  Accuracy: 0.47  Score: 0.25  Normalized Score: 0.97 
Info: LPQ:  Total Pnl: 0.00%  Profit/Loss Ratio: nan  Accuracy: 0.00  Score: 0.02  Normalized Score: 0.96 
Info: VTN:  Total Pnl: 5.14%  Profit/Loss Ratio: 1.99  Accuracy: 0.49  Score: 0.33  Normalized Score: 0.94 
Info: UWC:  Total Pnl: 0.80%  Profit/Loss Ratio: 1.35  Accuracy: 0.46  Score: 0.17  Normalized Score: 0.97 
Info: SCN:  Total Pnl: 0.00%  Profit/Loss Ratio: 1.32  Accuracy: 0.50  Score: 0.04  Normalized Score: 0.94 
Info: XIT:  Total Pnl: 0.27%  Profit/Loss Ratio: 1.15  Accuracy: 0.45  Score: 0.16  Normalized Score: 0.96 
Info: NDG:  Total Pnl: 0.39%

In [21]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData2" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return []

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 1,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 2,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AGW
Processing data for stock: AIO
Processing data for stock: AUZ
Processing data for stock: BSN
Processing data for stock: BWU
Processing data for stock: CBT
Processing data for stock: CHV
Processing data for stock: CSR
Processing data for stock: CUN
Processing data for stock: CYD
Processing data for stock: DCO
Processing data for stock: DFZ
Processing data for stock: DVV
Processing data for stock: DYE
Processing data for stock: EGV
Processing data for stock: FCY
Processing data for stock: FFA
Processing data for stock: FFS
Processing data for stock: FKI
Processing data for stock: FRE
Processing data for stock: FUR
Processing data for stock: GFQ
Processing data for stock: GGK
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: HHK
Processing data for stock: IES
Processing data for stock: IFL
Processing data for stock: ILW
Processing data for stock: IMC
Processing data for stock: IUE
Processing data for stock: IUQ
Processi

2017-01-13 13:48:00
2017-01-13 13:49:00
2017-01-13 13:50:00
2017-01-13 13:51:00
2017-01-13 13:52:00
2017-01-13 13:53:00
2017-01-13 13:54:00
2017-01-13 13:55:00
2017-01-13 13:56:00
2017-01-13 13:57:00
2017-01-13 13:58:00
2017-01-13 13:59:00
2017-01-13 14:00:00
2017-01-13 14:01:00
2017-01-13 14:02:00
2017-01-13 14:03:00
2017-01-13 14:04:00
2017-01-13 14:05:00
2017-01-13 14:06:00
2017-01-13 14:07:00
2017-01-13 14:08:00
2017-01-13 14:09:00
2017-01-13 14:10:00
2017-01-13 14:11:00
2017-01-13 14:12:00
2017-01-13 14:13:00
2017-01-13 14:14:00
2017-01-13 14:15:00
2017-01-13 14:16:00
2017-01-13 14:17:00
2017-01-13 14:18:00
2017-01-13 14:19:00
2017-01-13 14:20:00
2017-01-13 14:21:00
2017-01-13 14:22:00
2017-01-13 14:23:00
2017-01-13 14:24:00
2017-01-13 14:25:00
2017-01-13 14:26:00
2017-01-13 14:27:00
2017-01-13 14:28:00
2017-01-13 14:29:00
2017-01-13 14:30:00
2017-01-13 14:31:00
2017-01-13 14:32:00
2017-01-13 14:33:00
2017-01-13 14:34:00
2017-01-13 14:35:00
2017-01-13 14:36:00
2017-01-13 14:37:00


2017-01-16 14:26:00
2017-01-16 14:27:00
2017-01-16 14:28:00
2017-01-16 14:29:00
2017-01-16 14:30:00
2017-01-16 14:31:00
2017-01-16 14:32:00
2017-01-16 14:33:00
2017-01-16 14:34:00
2017-01-16 14:35:00
2017-01-16 14:36:00
2017-01-16 14:37:00
2017-01-16 14:38:00
2017-01-16 14:39:00
2017-01-16 14:40:00
2017-01-16 14:41:00
2017-01-16 14:42:00
2017-01-16 14:43:00
2017-01-16 14:44:00
2017-01-16 14:45:00
2017-01-16 14:46:00
2017-01-16 14:47:00
2017-01-16 14:48:00
2017-01-16 14:49:00
2017-01-16 14:50:00
2017-01-16 14:51:00
2017-01-16 14:52:00
2017-01-16 14:53:00
2017-01-16 14:54:00
2017-01-16 14:55:00
2017-01-16 14:56:00
2017-01-16 14:57:00
2017-01-16 14:58:00
2017-01-16 14:59:00
2017-01-16 15:00:00
2017-01-16 15:01:00
2017-01-16 15:02:00
2017-01-16 15:03:00
2017-01-16 15:04:00
2017-01-16 15:05:00
2017-01-16 15:06:00
2017-01-16 15:07:00
2017-01-16 15:08:00
2017-01-16 15:09:00
2017-01-16 15:10:00
2017-01-16 15:11:00
2017-01-16 15:12:00
2017-01-16 15:13:00
2017-01-16 15:14:00
2017-01-16 15:15:00


2017-01-18 15:03:00
2017-01-18 15:04:00
2017-01-18 15:05:00
2017-01-18 15:06:00
2017-01-18 15:07:00
2017-01-18 15:08:00
2017-01-18 15:09:00
2017-01-18 15:10:00
2017-01-18 15:11:00
2017-01-18 15:12:00
2017-01-18 15:13:00
2017-01-18 15:14:00
2017-01-18 15:15:00
2017-01-18 15:16:00
2017-01-18 15:17:00
2017-01-18 15:18:00
2017-01-18 15:19:00
2017-01-18 15:20:00
2017-01-18 15:21:00
2017-01-18 15:22:00
2017-01-18 15:23:00
2017-01-18 15:24:00
2017-01-18 15:25:00
2017-01-18 15:26:00
2017-01-18 15:27:00
2017-01-18 15:28:00
2017-01-18 15:29:00
2017-01-19 09:17:00
2017-01-19 09:18:00
2017-01-19 09:19:00
2017-01-19 09:20:00
2017-01-19 09:21:00
2017-01-19 09:22:00
2017-01-19 09:23:00
2017-01-19 09:24:00
2017-01-19 09:25:00
2017-01-19 09:26:00
2017-01-19 09:27:00
2017-01-19 09:28:00
2017-01-19 09:29:00
2017-01-19 09:30:00
2017-01-19 09:31:00
2017-01-19 09:32:00
2017-01-19 09:33:00
2017-01-19 09:34:00
2017-01-19 09:35:00
2017-01-19 09:36:00
2017-01-19 09:37:00
2017-01-19 09:38:00
2017-01-19 09:39:00


2017-01-20 09:28:00
2017-01-20 09:29:00
2017-01-20 09:30:00
2017-01-20 09:31:00
2017-01-20 09:32:00
2017-01-20 09:33:00
2017-01-20 09:34:00
2017-01-20 09:35:00
2017-01-20 09:36:00
2017-01-20 09:37:00
2017-01-20 09:38:00
2017-01-20 09:39:00
2017-01-20 09:40:00
2017-01-20 09:41:00
2017-01-20 09:42:00
2017-01-20 09:43:00
2017-01-20 09:44:00
2017-01-20 09:45:00
2017-01-20 09:46:00
2017-01-20 09:47:00
2017-01-20 09:48:00
2017-01-20 09:49:00
2017-01-20 09:50:00
2017-01-20 09:51:00
2017-01-20 09:52:00
2017-01-20 09:53:00
2017-01-20 09:54:00
2017-01-20 09:55:00
2017-01-20 09:56:00
2017-01-20 09:57:00
2017-01-20 09:58:00
2017-01-20 09:59:00
2017-01-20 10:00:00
2017-01-20 10:01:00
2017-01-20 10:02:00
2017-01-20 10:03:00
2017-01-20 10:04:00
2017-01-20 10:05:00
2017-01-20 10:06:00
2017-01-20 10:07:00
2017-01-20 10:08:00
2017-01-20 10:09:00
2017-01-20 10:10:00
2017-01-20 10:11:00
2017-01-20 10:12:00
2017-01-20 10:13:00
2017-01-20 10:14:00
2017-01-20 10:15:00
2017-01-20 10:16:00
2017-01-20 10:17:00


...

2017-02-01 13:58:00
2017-02-01 13:59:00
2017-02-01 14:00:00
2017-02-01 14:01:00
2017-02-01 14:02:00
2017-02-01 14:03:00
2017-02-01 14:04:00
2017-02-01 14:05:00
2017-02-01 14:06:00
2017-02-01 14:07:00
2017-02-01 14:08:00
2017-02-01 14:09:00
2017-02-01 14:10:00
2017-02-01 14:11:00
2017-02-01 14:12:00
2017-02-01 14:13:00
2017-02-01 14:14:00
2017-02-01 14:15:00
2017-02-01 14:16:00
2017-02-01 14:17:00
2017-02-01 14:18:00
2017-02-01 14:19:00
2017-02-01 14:20:00
2017-02-01 14:21:00
2017-02-01 14:22:00
2017-02-01 14:23:00
2017-02-01 14:24:00
2017-02-01 14:25:00
2017-02-01 14:26:00
2017-02-01 14:27:00
2017-02-01 14:28:00
2017-02-01 14:29:00
2017-02-01 14:30:00
2017-02-01 14:31:00
2017-02-01 14:32:00
2017-02-01 14:33:00
2017-02-01 14:34:00
2017-02-01 14:35:00
2017-02-01 14:36:00
2017-02-01 14:37:00
2017-02-01 14:38:00
2017-02-01 14:39:00
2017-02-01 14:40:00
2017-02-01 14:41:00
2017-02-01 14:42:00
2017-02-01 14:43:00
2017-02-01 14:44:00
2017-02-01 14:45:00
2017-02-01 14:46:00
2017-02-01 14:47:00


2017-02-02 14:36:00
2017-02-02 14:37:00
2017-02-02 14:38:00
2017-02-02 14:39:00
2017-02-02 14:40:00
2017-02-02 14:41:00
2017-02-02 14:42:00
2017-02-02 14:43:00
2017-02-02 14:44:00
2017-02-02 14:45:00
2017-02-02 14:46:00
2017-02-02 14:47:00
2017-02-02 14:48:00
2017-02-02 14:49:00
2017-02-02 14:50:00
2017-02-02 14:51:00
2017-02-02 14:52:00
2017-02-02 14:53:00
2017-02-02 14:54:00
2017-02-02 14:55:00
2017-02-02 14:56:00
2017-02-02 14:57:00
2017-02-02 14:58:00
2017-02-02 14:59:00
2017-02-02 15:00:00
2017-02-02 15:01:00
2017-02-02 15:02:00
2017-02-02 15:03:00
2017-02-02 15:04:00
2017-02-02 15:05:00
2017-02-02 15:06:00
2017-02-02 15:07:00
2017-02-02 15:08:00
2017-02-02 15:09:00
2017-02-02 15:10:00
2017-02-02 15:11:00
2017-02-02 15:12:00
2017-02-02 15:13:00
2017-02-02 15:14:00
2017-02-02 15:15:00
2017-02-02 15:16:00
2017-02-02 15:17:00
2017-02-02 15:18:00
2017-02-02 15:19:00
2017-02-02 15:20:00
2017-02-02 15:21:00
2017-02-02 15:22:00
2017-02-02 15:23:00
2017-02-02 15:24:00
2017-02-02 15:25:00


2017-02-03 15:16:00
2017-02-03 15:17:00
2017-02-03 15:18:00
2017-02-03 15:19:00
2017-02-03 15:20:00
2017-02-03 15:21:00
2017-02-03 15:22:00
2017-02-03 15:23:00
2017-02-03 15:24:00
2017-02-03 15:25:00
2017-02-03 15:26:00
2017-02-03 15:27:00
2017-02-03 15:28:00
2017-02-03 15:29:00
2017-02-06 09:17:00
2017-02-06 09:18:00
2017-02-06 09:19:00
2017-02-06 09:20:00
2017-02-06 09:21:00
2017-02-06 09:22:00
2017-02-06 09:23:00
2017-02-06 09:24:00
2017-02-06 09:25:00
2017-02-06 09:26:00
2017-02-06 09:27:00
2017-02-06 09:28:00
2017-02-06 09:29:00
2017-02-06 09:30:00
2017-02-06 09:31:00
2017-02-06 09:32:00
2017-02-06 09:33:00
2017-02-06 09:34:00
2017-02-06 09:35:00
2017-02-06 09:36:00
2017-02-06 09:37:00
2017-02-06 09:38:00
2017-02-06 09:39:00
2017-02-06 09:40:00
2017-02-06 09:41:00
2017-02-06 09:42:00
2017-02-06 09:43:00
2017-02-06 09:44:00
2017-02-06 09:45:00
2017-02-06 09:46:00
2017-02-06 09:47:00
2017-02-06 09:48:00
2017-02-06 09:49:00
2017-02-06 09:50:00
2017-02-06 09:51:00
2017-02-06 09:52:00


2017-02-07 09:42:00
2017-02-07 09:43:00
2017-02-07 09:44:00
2017-02-07 09:45:00
2017-02-07 09:46:00
2017-02-07 09:47:00
2017-02-07 09:48:00
2017-02-07 09:49:00
2017-02-07 09:50:00
2017-02-07 09:51:00
2017-02-07 09:52:00
2017-02-07 09:53:00
2017-02-07 09:54:00
2017-02-07 09:55:00
2017-02-07 09:56:00
2017-02-07 09:57:00
2017-02-07 09:58:00
2017-02-07 09:59:00
2017-02-07 10:00:00
2017-02-07 10:01:00
2017-02-07 10:02:00
2017-02-07 10:03:00
2017-02-07 10:04:00
2017-02-07 10:05:00
2017-02-07 10:06:00
2017-02-07 10:07:00
2017-02-07 10:08:00
2017-02-07 10:09:00
2017-02-07 10:10:00
2017-02-07 10:11:00
2017-02-07 10:12:00
2017-02-07 10:13:00
2017-02-07 10:14:00
2017-02-07 10:15:00
2017-02-07 10:16:00
2017-02-07 10:17:00
2017-02-07 10:18:00
2017-02-07 10:19:00
2017-02-07 10:20:00
2017-02-07 10:21:00
2017-02-07 10:22:00
2017-02-07 10:23:00
2017-02-07 10:24:00
2017-02-07 10:25:00
2017-02-07 10:26:00
2017-02-07 10:27:00
2017-02-07 10:28:00
2017-02-07 10:29:00
2017-02-07 10:30:00
2017-02-07 10:31:00


2017-02-09 10:56:00
2017-02-09 10:57:00
2017-02-09 10:58:00
2017-02-09 10:59:00
2017-02-09 11:00:00
2017-02-09 11:01:00
2017-02-09 11:02:00
2017-02-09 11:03:00
2017-02-09 11:04:00
2017-02-09 11:05:00
2017-02-09 11:06:00
2017-02-09 11:07:00
2017-02-09 11:08:00
2017-02-09 11:09:00
2017-02-09 11:10:00
2017-02-09 11:11:00
2017-02-09 11:12:00
2017-02-09 11:13:00
2017-02-09 11:14:00
2017-02-09 11:15:00
2017-02-09 11:16:00
2017-02-09 11:17:00
2017-02-09 11:18:00
2017-02-09 11:19:00
2017-02-09 11:20:00
2017-02-09 11:21:00
2017-02-09 11:22:00
2017-02-09 11:23:00
2017-02-09 11:24:00
2017-02-09 11:25:00
2017-02-09 11:26:00
2017-02-09 11:27:00
2017-02-09 11:28:00
2017-02-09 11:29:00
2017-02-09 11:30:00
2017-02-09 11:31:00
2017-02-09 11:32:00
2017-02-09 11:33:00
2017-02-09 11:34:00
2017-02-09 11:35:00
2017-02-09 11:36:00
2017-02-09 11:37:00
2017-02-09 11:38:00
2017-02-09 11:39:00
2017-02-09 11:40:00
2017-02-09 11:41:00
2017-02-09 11:42:00
2017-02-09 11:43:00
2017-02-09 11:44:00
2017-02-09 11:45:00


In [22]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData3" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return []

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 1,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 2,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AGW
Processing data for stock: AIO
Processing data for stock: AUZ
Processing data for stock: BSN
Processing data for stock: BWU
Processing data for stock: CBT
Processing data for stock: CHV
Processing data for stock: CSR
Processing data for stock: CUN
Processing data for stock: CYD
Processing data for stock: DCO
Processing data for stock: DFZ
Processing data for stock: DVV
Processing data for stock: DYE
Processing data for stock: EGV
Processing data for stock: FCY
Processing data for stock: FFA
Processing data for stock: FFS
Processing data for stock: FKI
Processing data for stock: FRE
Processing data for stock: FUR
Processing data for stock: GFQ
Processing data for stock: GGK
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: HHK
Processing data for stock: IES
Processing data for stock: IFL
Processing data for stock: ILW
Processing data for stock: IMC
Processing data for stock: IUE
Processing data for stock: IUQ
Processi

2017-01-06 13:48:00
2017-01-06 13:49:00
2017-01-06 13:50:00
2017-01-06 13:51:00
2017-01-06 13:52:00
2017-01-06 13:53:00
2017-01-06 13:54:00
2017-01-06 13:55:00
2017-01-06 13:56:00
2017-01-06 13:57:00
2017-01-06 13:58:00
2017-01-06 13:59:00
2017-01-06 14:00:00
2017-01-06 14:01:00
2017-01-06 14:02:00
2017-01-06 14:03:00
2017-01-06 14:04:00
2017-01-06 14:05:00
2017-01-06 14:06:00
2017-01-06 14:07:00
2017-01-06 14:08:00
2017-01-06 14:09:00
2017-01-06 14:10:00
2017-01-06 14:11:00
2017-01-06 14:12:00
2017-01-06 14:13:00
2017-01-06 14:14:00
2017-01-06 14:15:00
2017-01-06 14:16:00
2017-01-06 14:17:00
2017-01-06 14:18:00
2017-01-06 14:19:00
2017-01-06 14:20:00
2017-01-06 14:21:00
2017-01-06 14:22:00
2017-01-06 14:23:00
2017-01-06 14:24:00
2017-01-06 14:25:00
2017-01-06 14:26:00
2017-01-06 14:27:00
2017-01-06 14:28:00
2017-01-06 14:29:00
2017-01-06 14:30:00
2017-01-06 14:31:00
2017-01-06 14:32:00
2017-01-06 14:33:00
2017-01-06 14:34:00
2017-01-06 14:35:00
2017-01-06 14:36:00
2017-01-06 14:37:00


2017-01-10 14:27:00
2017-01-10 14:28:00
2017-01-10 14:29:00
2017-01-10 14:30:00
2017-01-10 14:31:00
2017-01-10 14:32:00
2017-01-10 14:33:00
2017-01-10 14:34:00
2017-01-10 14:35:00
2017-01-10 14:36:00
2017-01-10 14:37:00
2017-01-10 14:38:00
2017-01-10 14:39:00
2017-01-10 14:40:00
2017-01-10 14:41:00
2017-01-10 14:42:00
2017-01-10 14:43:00
2017-01-10 14:44:00
2017-01-10 14:45:00
2017-01-10 14:46:00
2017-01-10 14:47:00
2017-01-10 14:48:00
2017-01-10 14:49:00
2017-01-10 14:50:00
2017-01-10 14:51:00
2017-01-10 14:52:00
2017-01-10 14:53:00
2017-01-10 14:54:00
2017-01-10 14:55:00
2017-01-10 14:56:00
2017-01-10 14:57:00
2017-01-10 14:58:00
2017-01-10 14:59:00
2017-01-10 15:00:00
2017-01-10 15:01:00
2017-01-10 15:02:00
2017-01-10 15:03:00
2017-01-10 15:04:00
2017-01-10 15:05:00
2017-01-10 15:06:00
2017-01-10 15:07:00
2017-01-10 15:08:00
2017-01-10 15:09:00
2017-01-10 15:10:00
2017-01-10 15:11:00
2017-01-10 15:12:00
2017-01-10 15:13:00
2017-01-10 15:14:00
2017-01-10 15:15:00
2017-01-10 15:16:00


2017-01-11 15:04:00
2017-01-11 15:05:00
2017-01-11 15:06:00
2017-01-11 15:07:00
2017-01-11 15:08:00
2017-01-11 15:09:00
2017-01-11 15:10:00
2017-01-11 15:11:00
2017-01-11 15:12:00
2017-01-11 15:13:00
2017-01-11 15:14:00
2017-01-11 15:15:00
2017-01-11 15:16:00
2017-01-11 15:17:00
2017-01-11 15:18:00
2017-01-11 15:19:00
2017-01-11 15:20:00
2017-01-11 15:21:00
2017-01-11 15:22:00
2017-01-11 15:23:00
2017-01-11 15:24:00
2017-01-11 15:25:00
2017-01-11 15:26:00
2017-01-11 15:27:00
2017-01-11 15:28:00
2017-01-11 15:29:00
2017-01-12 09:17:00
2017-01-12 09:18:00
2017-01-12 09:19:00
2017-01-12 09:20:00
2017-01-12 09:21:00
2017-01-12 09:22:00
2017-01-12 09:23:00
2017-01-12 09:24:00
2017-01-12 09:25:00
2017-01-12 09:26:00
2017-01-12 09:27:00
2017-01-12 09:28:00
2017-01-12 09:29:00
2017-01-12 09:30:00
2017-01-12 09:31:00
2017-01-12 09:32:00
2017-01-12 09:33:00
2017-01-12 09:34:00
2017-01-12 09:35:00
2017-01-12 09:36:00
2017-01-12 09:37:00
2017-01-12 09:38:00
2017-01-12 09:39:00
2017-01-12 09:40:00


2017-01-13 09:29:00
2017-01-13 09:30:00
2017-01-13 09:31:00
2017-01-13 09:32:00
2017-01-13 09:33:00
2017-01-13 09:34:00
2017-01-13 09:35:00
2017-01-13 09:36:00
2017-01-13 09:37:00
2017-01-13 09:38:00
2017-01-13 09:39:00
2017-01-13 09:40:00
2017-01-13 09:41:00
2017-01-13 09:42:00
2017-01-13 09:43:00
2017-01-13 09:44:00
2017-01-13 09:45:00
2017-01-13 09:46:00
2017-01-13 09:47:00
2017-01-13 09:48:00
2017-01-13 09:49:00
2017-01-13 09:50:00
2017-01-13 09:51:00
2017-01-13 09:52:00
2017-01-13 09:53:00
2017-01-13 09:54:00
2017-01-13 09:55:00
2017-01-13 09:56:00
2017-01-13 09:57:00
2017-01-13 09:58:00
2017-01-13 09:59:00
2017-01-13 10:00:00
2017-01-13 10:01:00
2017-01-13 10:02:00
2017-01-13 10:03:00
2017-01-13 10:04:00
2017-01-13 10:05:00
2017-01-13 10:06:00
2017-01-13 10:07:00
2017-01-13 10:08:00
2017-01-13 10:09:00
2017-01-13 10:10:00
2017-01-13 10:11:00
2017-01-13 10:12:00
2017-01-13 10:13:00
2017-01-13 10:14:00
2017-01-13 10:15:00
2017-01-13 10:16:00
2017-01-13 10:17:00
2017-01-13 10:18:00


...

2017-01-27 14:36:00
2017-01-27 14:37:00
2017-01-27 14:38:00
2017-01-27 14:39:00
2017-01-27 14:40:00
2017-01-27 14:41:00
2017-01-27 14:42:00
2017-01-27 14:43:00
2017-01-27 14:44:00
2017-01-27 14:45:00
2017-01-27 14:46:00
2017-01-27 14:47:00
2017-01-27 14:48:00
2017-01-27 14:49:00
2017-01-27 14:50:00
2017-01-27 14:51:00
2017-01-27 14:52:00
2017-01-27 14:53:00
2017-01-27 14:54:00
2017-01-27 14:55:00
2017-01-27 14:56:00
2017-01-27 14:57:00
2017-01-27 14:58:00
2017-01-27 14:59:00
2017-01-27 15:00:00
2017-01-27 15:01:00
2017-01-27 15:02:00
2017-01-27 15:03:00
2017-01-27 15:04:00
2017-01-27 15:05:00
2017-01-27 15:06:00
2017-01-27 15:07:00
2017-01-27 15:08:00
2017-01-27 15:09:00
2017-01-27 15:10:00
2017-01-27 15:11:00
2017-01-27 15:12:00
2017-01-27 15:13:00
2017-01-27 15:14:00
2017-01-27 15:15:00
2017-01-27 15:16:00
2017-01-27 15:17:00
2017-01-27 15:18:00
2017-01-27 15:19:00
2017-01-27 15:20:00
2017-01-27 15:21:00
2017-01-27 15:22:00
2017-01-27 15:23:00
2017-01-27 15:24:00
2017-01-27 15:25:00


2017-01-30 15:15:00
2017-01-30 15:16:00
2017-01-30 15:17:00
2017-01-30 15:18:00
2017-01-30 15:19:00
2017-01-30 15:20:00
2017-01-30 15:21:00
2017-01-30 15:22:00
2017-01-30 15:23:00
2017-01-30 15:24:00
2017-01-30 15:25:00
2017-01-30 15:26:00
2017-01-30 15:27:00
2017-01-30 15:28:00
2017-01-30 15:29:00
2017-01-31 09:17:00
2017-01-31 09:18:00
2017-01-31 09:19:00
2017-01-31 09:20:00
2017-01-31 09:21:00
2017-01-31 09:22:00
2017-01-31 09:23:00
2017-01-31 09:24:00
2017-01-31 09:25:00
2017-01-31 09:26:00
2017-01-31 09:27:00
2017-01-31 09:28:00
2017-01-31 09:29:00
2017-01-31 09:30:00
2017-01-31 09:31:00
2017-01-31 09:32:00
2017-01-31 09:33:00
2017-01-31 09:34:00
2017-01-31 09:35:00
2017-01-31 09:36:00
2017-01-31 09:37:00
2017-01-31 09:38:00
2017-01-31 09:39:00
2017-01-31 09:40:00
2017-01-31 09:41:00
2017-01-31 09:42:00
2017-01-31 09:43:00
2017-01-31 09:44:00
2017-01-31 09:45:00
2017-01-31 09:46:00
2017-01-31 09:47:00
2017-01-31 09:48:00
2017-01-31 09:49:00
2017-01-31 09:50:00
2017-01-31 09:51:00


2017-02-01 09:40:00
2017-02-01 09:41:00
2017-02-01 09:42:00
2017-02-01 09:43:00
2017-02-01 09:44:00
2017-02-01 09:45:00
2017-02-01 09:46:00
2017-02-01 09:47:00
2017-02-01 09:48:00
2017-02-01 09:49:00
2017-02-01 09:50:00
2017-02-01 09:51:00
2017-02-01 09:52:00
2017-02-01 09:53:00
2017-02-01 09:54:00
2017-02-01 09:55:00
2017-02-01 09:56:00
2017-02-01 09:57:00
2017-02-01 09:58:00
2017-02-01 09:59:00
2017-02-01 10:00:00
2017-02-01 10:01:00
2017-02-01 10:02:00
2017-02-01 10:03:00
2017-02-01 10:04:00
2017-02-01 10:05:00
2017-02-01 10:06:00
2017-02-01 10:07:00
2017-02-01 10:08:00
2017-02-01 10:09:00
2017-02-01 10:10:00
2017-02-01 10:11:00
2017-02-01 10:12:00
2017-02-01 10:13:00
2017-02-01 10:14:00
2017-02-01 10:15:00
2017-02-01 10:16:00
2017-02-01 10:17:00
2017-02-01 10:18:00
2017-02-01 10:19:00
2017-02-01 10:20:00
2017-02-01 10:21:00
2017-02-01 10:22:00
2017-02-01 10:23:00
2017-02-01 10:24:00
2017-02-01 10:25:00
2017-02-01 10:26:00
2017-02-01 10:27:00
2017-02-01 10:28:00
2017-02-01 10:29:00


2017-02-02 10:20:00
2017-02-02 10:21:00
2017-02-02 10:22:00
2017-02-02 10:23:00
2017-02-02 10:24:00
2017-02-02 10:25:00
2017-02-02 10:26:00
2017-02-02 10:27:00
2017-02-02 10:28:00
2017-02-02 10:29:00
2017-02-02 10:30:00
2017-02-02 10:31:00
2017-02-02 10:32:00
2017-02-02 10:33:00
2017-02-02 10:34:00
2017-02-02 10:35:00
2017-02-02 10:36:00
2017-02-02 10:37:00
2017-02-02 10:38:00
2017-02-02 10:39:00
2017-02-02 10:40:00
2017-02-02 10:41:00
2017-02-02 10:42:00
2017-02-02 10:43:00
2017-02-02 10:44:00
2017-02-02 10:45:00
2017-02-02 10:46:00
2017-02-02 10:47:00
2017-02-02 10:48:00
2017-02-02 10:49:00
2017-02-02 10:50:00
2017-02-02 10:51:00
2017-02-02 10:52:00
2017-02-02 10:53:00
2017-02-02 10:54:00
2017-02-02 10:55:00
2017-02-02 10:56:00
2017-02-02 10:57:00
2017-02-02 10:58:00
2017-02-02 10:59:00
2017-02-02 11:00:00
2017-02-02 11:01:00
2017-02-02 11:02:00
2017-02-02 11:03:00
2017-02-02 11:04:00
2017-02-02 11:05:00
2017-02-02 11:06:00
2017-02-02 11:07:00
2017-02-02 11:08:00
2017-02-02 11:09:00


Info: OED:  Total Pnl: 1.42%  Profit/Loss Ratio: 1.89  Accuracy: 0.46  Score: 0.19  Normalized Score: 0.97 
Info:  Total Pnl: 82.11%  Score: 0.96  Max Drawdown: 1.28%  RoC: 3335.68%  P/L Ratio: 3.87  Accuracy: 0.70  Score: 0.96 


In [23]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData1" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return []

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 1,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AGW
Processing data for stock: AIO
Processing data for stock: AUZ
Processing data for stock: BSN
Processing data for stock: BWU
Processing data for stock: CBT
Processing data for stock: CHV
Processing data for stock: CSR
Processing data for stock: CUN
Processing data for stock: CYD
Processing data for stock: DCO
Processing data for stock: DFZ
Processing data for stock: DVV
Processing data for stock: DYE
Processing data for stock: EGV
Processing data for stock: FCY
Processing data for stock: FFA
Processing data for stock: FFS
Processing data for stock: FKI
Processing data for stock: FRE
Processing data for stock: FUR
Processing data for stock: GFQ
Processing data for stock: GGK
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: HHK
Processing data for stock: IES
Processing data for stock: IFL
Processing data for stock: ILW
Processing data for stock: IMC
Processing data for stock: IUE
Processing data for stock: IUQ
Processi

2017-01-06 13:47:00
2017-01-06 13:48:00
2017-01-06 13:49:00
2017-01-06 13:50:00
2017-01-06 13:51:00
2017-01-06 13:52:00
2017-01-06 13:53:00
2017-01-06 13:54:00
2017-01-06 13:55:00
2017-01-06 13:56:00
2017-01-06 13:57:00
2017-01-06 13:58:00
2017-01-06 13:59:00
2017-01-06 14:00:00
2017-01-06 14:01:00
2017-01-06 14:02:00
2017-01-06 14:03:00
2017-01-06 14:04:00
2017-01-06 14:05:00
2017-01-06 14:06:00
2017-01-06 14:07:00
2017-01-06 14:08:00
2017-01-06 14:09:00
2017-01-06 14:10:00
2017-01-06 14:11:00
2017-01-06 14:12:00
2017-01-06 14:13:00
2017-01-06 14:14:00
2017-01-06 14:15:00
2017-01-06 14:16:00
2017-01-06 14:17:00
2017-01-06 14:18:00
2017-01-06 14:19:00
2017-01-06 14:20:00
2017-01-06 14:21:00
2017-01-06 14:22:00
2017-01-06 14:23:00
2017-01-06 14:24:00
2017-01-06 14:25:00
2017-01-06 14:26:00
2017-01-06 14:27:00
2017-01-06 14:28:00
2017-01-06 14:29:00
2017-01-06 14:30:00
2017-01-06 14:31:00
2017-01-06 14:32:00
2017-01-06 14:33:00
2017-01-06 14:34:00
2017-01-06 14:35:00
2017-01-06 14:36:00


2017-01-09 14:26:00
2017-01-09 14:27:00
2017-01-09 14:28:00
2017-01-09 14:29:00
2017-01-09 14:30:00
2017-01-09 14:31:00
2017-01-09 14:32:00
2017-01-09 14:33:00
2017-01-09 14:34:00
2017-01-09 14:35:00
2017-01-09 14:36:00
2017-01-09 14:37:00
2017-01-09 14:38:00
2017-01-09 14:39:00
2017-01-09 14:40:00
2017-01-09 14:41:00
2017-01-09 14:42:00
2017-01-09 14:43:00
2017-01-09 14:44:00
2017-01-09 14:45:00
2017-01-09 14:46:00
2017-01-09 14:47:00
2017-01-09 14:48:00
2017-01-09 14:49:00
2017-01-09 14:50:00
2017-01-09 14:51:00
2017-01-09 14:52:00
2017-01-09 14:53:00
2017-01-09 14:54:00
2017-01-09 14:55:00
2017-01-09 14:56:00
2017-01-09 14:57:00
2017-01-09 14:58:00
2017-01-09 14:59:00
2017-01-09 15:00:00
2017-01-09 15:01:00
2017-01-09 15:02:00
2017-01-09 15:03:00
2017-01-09 15:04:00
2017-01-09 15:05:00
2017-01-09 15:06:00
2017-01-09 15:07:00
2017-01-09 15:08:00
2017-01-09 15:09:00
2017-01-09 15:10:00
2017-01-09 15:11:00
2017-01-09 15:12:00
2017-01-09 15:13:00
2017-01-09 15:14:00
2017-01-09 15:15:00


2017-01-10 15:03:00
2017-01-10 15:04:00
2017-01-10 15:05:00
2017-01-10 15:06:00
2017-01-10 15:07:00
2017-01-10 15:08:00
2017-01-10 15:09:00
2017-01-10 15:10:00
2017-01-10 15:11:00
2017-01-10 15:12:00
2017-01-10 15:13:00
2017-01-10 15:14:00
2017-01-10 15:15:00
2017-01-10 15:16:00
2017-01-10 15:17:00
2017-01-10 15:18:00
2017-01-10 15:19:00
2017-01-10 15:20:00
2017-01-10 15:21:00
2017-01-10 15:22:00
2017-01-10 15:23:00
2017-01-10 15:24:00
2017-01-10 15:25:00
2017-01-10 15:26:00
2017-01-10 15:27:00
2017-01-10 15:28:00
2017-01-10 15:29:00
2017-01-11 09:17:00
2017-01-11 09:18:00
2017-01-11 09:19:00
2017-01-11 09:20:00
2017-01-11 09:21:00
2017-01-11 09:22:00
2017-01-11 09:23:00
2017-01-11 09:24:00
2017-01-11 09:25:00
2017-01-11 09:26:00
2017-01-11 09:27:00
2017-01-11 09:28:00
2017-01-11 09:29:00
2017-01-11 09:30:00
2017-01-11 09:31:00
2017-01-11 09:32:00
2017-01-11 09:33:00
2017-01-11 09:34:00
2017-01-11 09:35:00
2017-01-11 09:36:00
2017-01-11 09:37:00
2017-01-11 09:38:00
2017-01-11 09:39:00


2017-01-12 09:27:00
2017-01-12 09:28:00
2017-01-12 09:29:00
2017-01-12 09:30:00
2017-01-12 09:31:00
2017-01-12 09:32:00
2017-01-12 09:33:00
2017-01-12 09:34:00
2017-01-12 09:35:00
2017-01-12 09:36:00
2017-01-12 09:37:00
2017-01-12 09:38:00
2017-01-12 09:39:00
2017-01-12 09:40:00
2017-01-12 09:41:00
2017-01-12 09:42:00
2017-01-12 09:43:00
2017-01-12 09:44:00
2017-01-12 09:45:00
2017-01-12 09:46:00
2017-01-12 09:47:00
2017-01-12 09:48:00
2017-01-12 09:49:00
2017-01-12 09:50:00
2017-01-12 09:51:00
2017-01-12 09:52:00
2017-01-12 09:53:00
2017-01-12 09:54:00
2017-01-12 09:55:00
2017-01-12 09:56:00
2017-01-12 09:57:00
2017-01-12 09:58:00
2017-01-12 09:59:00
2017-01-12 10:00:00
2017-01-12 10:01:00
2017-01-12 10:02:00
2017-01-12 10:03:00
2017-01-12 10:04:00
2017-01-12 10:05:00
2017-01-12 10:06:00
2017-01-12 10:07:00
2017-01-12 10:08:00
2017-01-12 10:09:00
2017-01-12 10:10:00
2017-01-12 10:11:00
2017-01-12 10:12:00
2017-01-12 10:13:00
2017-01-12 10:14:00
2017-01-12 10:15:00
2017-01-12 10:16:00


...

2017-02-02 12:15:00
2017-02-02 12:16:00
2017-02-02 12:17:00
2017-02-02 12:18:00
2017-02-02 12:19:00
2017-02-02 12:20:00
2017-02-02 12:21:00
2017-02-02 12:22:00
2017-02-02 12:23:00
2017-02-02 12:24:00
2017-02-02 12:25:00
2017-02-02 12:26:00
2017-02-02 12:27:00
2017-02-02 12:28:00
2017-02-02 12:29:00
2017-02-02 12:30:00
2017-02-02 12:31:00
2017-02-02 12:32:00
2017-02-02 12:33:00
2017-02-02 12:34:00
2017-02-02 12:35:00
2017-02-02 12:36:00
2017-02-02 12:37:00
2017-02-02 12:38:00
2017-02-02 12:39:00
2017-02-02 12:40:00
2017-02-02 12:41:00
2017-02-02 12:42:00
2017-02-02 12:43:00
2017-02-02 12:44:00
2017-02-02 12:45:00
2017-02-02 12:46:00
2017-02-02 12:47:00
2017-02-02 12:48:00
2017-02-02 12:49:00
2017-02-02 12:50:00
2017-02-02 12:51:00
2017-02-02 12:52:00
2017-02-02 12:53:00
2017-02-02 12:54:00
2017-02-02 12:55:00
2017-02-02 12:56:00
2017-02-02 12:57:00
2017-02-02 12:58:00
2017-02-02 12:59:00
2017-02-02 13:00:00
2017-02-02 13:01:00
2017-02-02 13:02:00
2017-02-02 13:03:00
2017-02-02 13:04:00


2017-02-03 12:52:00
2017-02-03 12:53:00
2017-02-03 12:54:00
2017-02-03 12:55:00
2017-02-03 12:56:00
2017-02-03 12:57:00
2017-02-03 12:58:00
2017-02-03 12:59:00
2017-02-03 13:00:00
2017-02-03 13:01:00
2017-02-03 13:02:00
2017-02-03 13:03:00
2017-02-03 13:04:00
2017-02-03 13:05:00
2017-02-03 13:06:00
2017-02-03 13:07:00
2017-02-03 13:08:00
2017-02-03 13:09:00
2017-02-03 13:10:00
2017-02-03 13:11:00
2017-02-03 13:12:00
2017-02-03 13:13:00
2017-02-03 13:14:00
2017-02-03 13:15:00
2017-02-03 13:16:00
2017-02-03 13:17:00
2017-02-03 13:18:00
2017-02-03 13:19:00
2017-02-03 13:20:00
2017-02-03 13:21:00
2017-02-03 13:22:00
2017-02-03 13:23:00
2017-02-03 13:24:00
2017-02-03 13:25:00
2017-02-03 13:26:00
2017-02-03 13:27:00
2017-02-03 13:28:00
2017-02-03 13:29:00
2017-02-03 13:30:00
2017-02-03 13:31:00
2017-02-03 13:32:00
2017-02-03 13:33:00
2017-02-03 13:34:00
2017-02-03 13:35:00
2017-02-03 13:36:00
2017-02-03 13:37:00
2017-02-03 13:38:00
2017-02-03 13:39:00
2017-02-03 13:40:00
2017-02-03 13:41:00


2017-02-07 13:31:00
2017-02-07 13:32:00
2017-02-07 13:33:00
2017-02-07 13:34:00
2017-02-07 13:35:00
2017-02-07 13:36:00
2017-02-07 13:37:00
2017-02-07 13:38:00
2017-02-07 13:39:00
2017-02-07 13:40:00
2017-02-07 13:41:00
2017-02-07 13:42:00
2017-02-07 13:43:00
2017-02-07 13:44:00
2017-02-07 13:45:00
2017-02-07 13:46:00
2017-02-07 13:47:00
2017-02-07 13:48:00
2017-02-07 13:49:00
2017-02-07 13:50:00
2017-02-07 13:51:00
2017-02-07 13:52:00
2017-02-07 13:53:00
2017-02-07 13:54:00
2017-02-07 13:55:00
2017-02-07 13:56:00
2017-02-07 13:57:00
2017-02-07 13:58:00
2017-02-07 13:59:00
2017-02-07 14:00:00
2017-02-07 14:01:00
2017-02-07 14:02:00
2017-02-07 14:03:00
2017-02-07 14:04:00
2017-02-07 14:05:00
2017-02-07 14:06:00
2017-02-07 14:07:00
2017-02-07 14:08:00
2017-02-07 14:09:00
2017-02-07 14:10:00
2017-02-07 14:11:00
2017-02-07 14:12:00
2017-02-07 14:13:00
2017-02-07 14:14:00
2017-02-07 14:15:00
2017-02-07 14:16:00
2017-02-07 14:17:00
2017-02-07 14:18:00
2017-02-07 14:19:00
2017-02-07 14:20:00


2017-02-08 14:10:00
2017-02-08 14:11:00
2017-02-08 14:12:00
2017-02-08 14:13:00
2017-02-08 14:14:00
2017-02-08 14:15:00
2017-02-08 14:16:00
2017-02-08 14:17:00
2017-02-08 14:18:00
2017-02-08 14:19:00
2017-02-08 14:20:00
2017-02-08 14:21:00
2017-02-08 14:22:00
2017-02-08 14:23:00
2017-02-08 14:24:00
2017-02-08 14:25:00
2017-02-08 14:26:00
2017-02-08 14:27:00
2017-02-08 14:28:00
2017-02-08 14:29:00
2017-02-08 14:30:00
2017-02-08 14:31:00
2017-02-08 14:32:00
2017-02-08 14:33:00
2017-02-08 14:34:00
2017-02-08 14:35:00
2017-02-08 14:36:00
2017-02-08 14:37:00
2017-02-08 14:38:00
2017-02-08 14:39:00
2017-02-08 14:40:00
2017-02-08 14:41:00
2017-02-08 14:42:00
2017-02-08 14:43:00
2017-02-08 14:44:00
2017-02-08 14:45:00
2017-02-08 14:46:00
2017-02-08 14:47:00
2017-02-08 14:48:00
2017-02-08 14:49:00
2017-02-08 14:50:00
2017-02-08 14:51:00
2017-02-08 14:52:00
2017-02-08 14:53:00
2017-02-08 14:54:00
2017-02-08 14:55:00
2017-02-08 14:56:00
2017-02-08 14:57:00
2017-02-08 14:58:00
2017-02-08 14:59:00


Info: CUN:  Total Pnl: -0.00%  Profit/Loss Ratio: 0.90  Accuracy: 0.33  Score: 0.05  Normalized Score: 0.93 
Info: AUZ:  Total Pnl: 0.12%  Profit/Loss Ratio: 1.80  Accuracy: 0.45  Score: 0.13  Normalized Score: 0.94 
Info: XAD:  Total Pnl: 0.01%  Profit/Loss Ratio: 1.55  Accuracy: 0.50  Score: 0.08  Normalized Score: 0.94 
Info: VKE:  Total Pnl: 1.62%  Profit/Loss Ratio: 1.71  Accuracy: 0.44  Score: 0.34  Normalized Score: 0.91 
Info: CSR:  Total Pnl: 0.00%  Profit/Loss Ratio: 1.32  Accuracy: 0.46  Score: 0.06  Normalized Score: 0.93 
Info: KAA:  Total Pnl: 0.00%  Profit/Loss Ratio: nan  Accuracy: 0.00  Score: 0.04  Normalized Score: 0.93 
Info: PUO:  Total Pnl: 0.00%  Profit/Loss Ratio: 1.29  Accuracy: 0.38  Score: 0.07  Normalized Score: 0.92 
Info: YGC:  Total Pnl: 0.01%  Profit/Loss Ratio: 1.03  Accuracy: 0.43  Score: 0.13  Normalized Score: 0.91 
Info: ILW:  Total Pnl: 0.00%  Profit/Loss Ratio: 1.08  Accuracy: 0.42  Score: 0.05  Normalized Score: 0.93 
Info: OGU:  Total Pnl: 0.00%

In [24]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData2" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return []

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 1,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AGW
Processing data for stock: AIO
Processing data for stock: AUZ
Processing data for stock: BSN
Processing data for stock: BWU
Processing data for stock: CBT
Processing data for stock: CHV
Processing data for stock: CSR
Processing data for stock: CUN
Processing data for stock: CYD
Processing data for stock: DCO
Processing data for stock: DFZ
Processing data for stock: DVV
Processing data for stock: DYE
Processing data for stock: EGV
Processing data for stock: FCY
Processing data for stock: FFA
Processing data for stock: FFS
Processing data for stock: FKI
Processing data for stock: FRE
Processing data for stock: FUR
Processing data for stock: GFQ
Processing data for stock: GGK
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: HHK
Processing data for stock: IES
Processing data for stock: IFL
Processing data for stock: ILW
Processing data for stock: IMC
Processing data for stock: IUE
Processing data for stock: IUQ
Processi

2017-01-13 13:48:00
2017-01-13 13:49:00
2017-01-13 13:50:00
2017-01-13 13:51:00
2017-01-13 13:52:00
2017-01-13 13:53:00
2017-01-13 13:54:00
2017-01-13 13:55:00
2017-01-13 13:56:00
2017-01-13 13:57:00
2017-01-13 13:58:00
2017-01-13 13:59:00
2017-01-13 14:00:00
2017-01-13 14:01:00
2017-01-13 14:02:00
2017-01-13 14:03:00
2017-01-13 14:04:00
2017-01-13 14:05:00
2017-01-13 14:06:00
2017-01-13 14:07:00
2017-01-13 14:08:00
2017-01-13 14:09:00
2017-01-13 14:10:00
2017-01-13 14:11:00
2017-01-13 14:12:00
2017-01-13 14:13:00
2017-01-13 14:14:00
2017-01-13 14:15:00
2017-01-13 14:16:00
2017-01-13 14:17:00
2017-01-13 14:18:00
2017-01-13 14:19:00
2017-01-13 14:20:00
2017-01-13 14:21:00
2017-01-13 14:22:00
2017-01-13 14:23:00
2017-01-13 14:24:00
2017-01-13 14:25:00
2017-01-13 14:26:00
2017-01-13 14:27:00
2017-01-13 14:28:00
2017-01-13 14:29:00
2017-01-13 14:30:00
2017-01-13 14:31:00
2017-01-13 14:32:00
2017-01-13 14:33:00
2017-01-13 14:34:00
2017-01-13 14:35:00
2017-01-13 14:36:00
2017-01-13 14:37:00


2017-01-16 14:28:00
2017-01-16 14:29:00
2017-01-16 14:30:00
2017-01-16 14:31:00
2017-01-16 14:32:00
2017-01-16 14:33:00
2017-01-16 14:34:00
2017-01-16 14:35:00
2017-01-16 14:36:00
2017-01-16 14:37:00
2017-01-16 14:38:00
2017-01-16 14:39:00
2017-01-16 14:40:00
2017-01-16 14:41:00
2017-01-16 14:42:00
2017-01-16 14:43:00
2017-01-16 14:44:00
2017-01-16 14:45:00
2017-01-16 14:46:00
2017-01-16 14:47:00
2017-01-16 14:48:00
2017-01-16 14:49:00
2017-01-16 14:50:00
2017-01-16 14:51:00
2017-01-16 14:52:00
2017-01-16 14:53:00
2017-01-16 14:54:00
2017-01-16 14:55:00
2017-01-16 14:56:00
2017-01-16 14:57:00
2017-01-16 14:58:00
2017-01-16 14:59:00
2017-01-16 15:00:00
2017-01-16 15:01:00
2017-01-16 15:02:00
2017-01-16 15:03:00
2017-01-16 15:04:00
2017-01-16 15:05:00
2017-01-16 15:06:00
2017-01-16 15:07:00
2017-01-16 15:08:00
2017-01-16 15:09:00
2017-01-16 15:10:00
2017-01-16 15:11:00
2017-01-16 15:12:00
2017-01-16 15:13:00
2017-01-16 15:14:00
2017-01-16 15:15:00
2017-01-16 15:16:00
2017-01-16 15:17:00


2017-01-20 09:29:00
2017-01-20 09:30:00
2017-01-20 09:31:00
2017-01-20 09:32:00
2017-01-20 09:33:00
2017-01-20 09:34:00
2017-01-20 09:35:00
2017-01-20 09:36:00
2017-01-20 09:37:00
2017-01-20 09:38:00
2017-01-20 09:39:00
2017-01-20 09:40:00
2017-01-20 09:41:00
2017-01-20 09:42:00
2017-01-20 09:43:00
2017-01-20 09:44:00
2017-01-20 09:45:00
2017-01-20 09:46:00
2017-01-20 09:47:00
2017-01-20 09:48:00
2017-01-20 09:49:00
2017-01-20 09:50:00
2017-01-20 09:51:00
2017-01-20 09:52:00
2017-01-20 09:53:00
2017-01-20 09:54:00
2017-01-20 09:55:00
2017-01-20 09:56:00
2017-01-20 09:57:00
2017-01-20 09:58:00
2017-01-20 09:59:00
2017-01-20 10:00:00
2017-01-20 10:01:00
2017-01-20 10:02:00
2017-01-20 10:03:00
2017-01-20 10:04:00
2017-01-20 10:05:00
2017-01-20 10:06:00
2017-01-20 10:07:00
2017-01-20 10:08:00
2017-01-20 10:09:00
2017-01-20 10:10:00
2017-01-20 10:11:00
2017-01-20 10:12:00
2017-01-20 10:13:00
2017-01-20 10:14:00
2017-01-20 10:15:00
2017-01-20 10:16:00
2017-01-20 10:17:00
2017-01-20 10:18:00


2017-01-23 10:08:00
2017-01-23 10:09:00
2017-01-23 10:10:00
2017-01-23 10:11:00
2017-01-23 10:12:00
2017-01-23 10:13:00
2017-01-23 10:14:00
2017-01-23 10:15:00
2017-01-23 10:16:00
2017-01-23 10:17:00
2017-01-23 10:18:00
2017-01-23 10:19:00
2017-01-23 10:20:00
2017-01-23 10:21:00
2017-01-23 10:22:00
2017-01-23 10:23:00
2017-01-23 10:24:00
2017-01-23 10:25:00
2017-01-23 10:26:00
2017-01-23 10:27:00
2017-01-23 10:28:00
2017-01-23 10:29:00
2017-01-23 10:30:00
2017-01-23 10:31:00
2017-01-23 10:32:00
2017-01-23 10:33:00
2017-01-23 10:34:00
2017-01-23 10:35:00
2017-01-23 10:36:00
2017-01-23 10:37:00
2017-01-23 10:38:00
2017-01-23 10:39:00
2017-01-23 10:40:00
2017-01-23 10:41:00
2017-01-23 10:42:00
2017-01-23 10:43:00
2017-01-23 10:44:00
2017-01-23 10:45:00
2017-01-23 10:46:00
2017-01-23 10:47:00
2017-01-23 10:48:00
2017-01-23 10:49:00
2017-01-23 10:50:00
2017-01-23 10:51:00
2017-01-23 10:52:00
2017-01-23 10:53:00
2017-01-23 10:54:00
2017-01-23 10:55:00
2017-01-23 10:56:00
2017-01-23 10:57:00


...

2017-02-02 14:38:00
2017-02-02 14:39:00
2017-02-02 14:40:00
2017-02-02 14:41:00
2017-02-02 14:42:00
2017-02-02 14:43:00
2017-02-02 14:44:00
2017-02-02 14:45:00
2017-02-02 14:46:00
2017-02-02 14:47:00
2017-02-02 14:48:00
2017-02-02 14:49:00
2017-02-02 14:50:00
2017-02-02 14:51:00
2017-02-02 14:52:00
2017-02-02 14:53:00
2017-02-02 14:54:00
2017-02-02 14:55:00
2017-02-02 14:56:00
2017-02-02 14:57:00
2017-02-02 14:58:00
2017-02-02 14:59:00
2017-02-02 15:00:00
2017-02-02 15:01:00
2017-02-02 15:02:00
2017-02-02 15:03:00
2017-02-02 15:04:00
2017-02-02 15:05:00
2017-02-02 15:06:00
2017-02-02 15:07:00
2017-02-02 15:08:00
2017-02-02 15:09:00
2017-02-02 15:10:00
2017-02-02 15:11:00
2017-02-02 15:12:00
2017-02-02 15:13:00
2017-02-02 15:14:00
2017-02-02 15:15:00
2017-02-02 15:16:00
2017-02-02 15:17:00
2017-02-02 15:18:00
2017-02-02 15:19:00
2017-02-02 15:20:00
2017-02-02 15:21:00
2017-02-02 15:22:00
2017-02-02 15:23:00
2017-02-02 15:24:00
2017-02-02 15:25:00
2017-02-02 15:26:00
2017-02-02 15:27:00


2017-02-03 15:17:00
2017-02-03 15:18:00
2017-02-03 15:19:00
2017-02-03 15:20:00
2017-02-03 15:21:00
2017-02-03 15:22:00
2017-02-03 15:23:00
2017-02-03 15:24:00
2017-02-03 15:25:00
2017-02-03 15:26:00
2017-02-03 15:27:00
2017-02-03 15:28:00
2017-02-03 15:29:00
2017-02-06 09:17:00
2017-02-06 09:18:00
2017-02-06 09:19:00
2017-02-06 09:20:00
2017-02-06 09:21:00
2017-02-06 09:22:00
2017-02-06 09:23:00
2017-02-06 09:24:00
2017-02-06 09:25:00
2017-02-06 09:26:00
2017-02-06 09:27:00
2017-02-06 09:28:00
2017-02-06 09:29:00
2017-02-06 09:30:00
2017-02-06 09:31:00
2017-02-06 09:32:00
2017-02-06 09:33:00
2017-02-06 09:34:00
2017-02-06 09:35:00
2017-02-06 09:36:00
2017-02-06 09:37:00
2017-02-06 09:38:00
2017-02-06 09:39:00
2017-02-06 09:40:00
2017-02-06 09:41:00
2017-02-06 09:42:00
2017-02-06 09:43:00
2017-02-06 09:44:00
2017-02-06 09:45:00
2017-02-06 09:46:00
2017-02-06 09:47:00
2017-02-06 09:48:00
2017-02-06 09:49:00
2017-02-06 09:50:00
2017-02-06 09:51:00
2017-02-06 09:52:00
2017-02-06 09:53:00


2017-02-07 09:43:00
2017-02-07 09:44:00
2017-02-07 09:45:00
2017-02-07 09:46:00
2017-02-07 09:47:00
2017-02-07 09:48:00
2017-02-07 09:49:00
2017-02-07 09:50:00
2017-02-07 09:51:00
2017-02-07 09:52:00
2017-02-07 09:53:00
2017-02-07 09:54:00
2017-02-07 09:55:00
2017-02-07 09:56:00
2017-02-07 09:57:00
2017-02-07 09:58:00
2017-02-07 09:59:00
2017-02-07 10:00:00
2017-02-07 10:01:00
2017-02-07 10:02:00
2017-02-07 10:03:00
2017-02-07 10:04:00
2017-02-07 10:05:00
2017-02-07 10:06:00
2017-02-07 10:07:00
2017-02-07 10:08:00
2017-02-07 10:09:00
2017-02-07 10:10:00
2017-02-07 10:11:00
2017-02-07 10:12:00
2017-02-07 10:13:00
2017-02-07 10:14:00
2017-02-07 10:15:00
2017-02-07 10:16:00
2017-02-07 10:17:00
2017-02-07 10:18:00
2017-02-07 10:19:00
2017-02-07 10:20:00
2017-02-07 10:21:00
2017-02-07 10:22:00
2017-02-07 10:23:00
2017-02-07 10:24:00
2017-02-07 10:25:00
2017-02-07 10:26:00
2017-02-07 10:27:00
2017-02-07 10:28:00
2017-02-07 10:29:00
2017-02-07 10:30:00
2017-02-07 10:31:00
2017-02-07 10:32:00


2017-02-08 10:20:00
2017-02-08 10:21:00
2017-02-08 10:22:00
2017-02-08 10:23:00
2017-02-08 10:24:00
2017-02-08 10:25:00
2017-02-08 10:26:00
2017-02-08 10:27:00
2017-02-08 10:28:00
2017-02-08 10:29:00
2017-02-08 10:30:00
2017-02-08 10:31:00
2017-02-08 10:32:00
2017-02-08 10:33:00
2017-02-08 10:34:00
2017-02-08 10:35:00
2017-02-08 10:36:00
2017-02-08 10:37:00
2017-02-08 10:38:00
2017-02-08 10:39:00
2017-02-08 10:40:00
2017-02-08 10:41:00
2017-02-08 10:42:00
2017-02-08 10:43:00
2017-02-08 10:44:00
2017-02-08 10:45:00
2017-02-08 10:46:00
2017-02-08 10:47:00
2017-02-08 10:48:00
2017-02-08 10:49:00
2017-02-08 10:50:00
2017-02-08 10:51:00
2017-02-08 10:52:00
2017-02-08 10:53:00
2017-02-08 10:54:00
2017-02-08 10:55:00
2017-02-08 10:56:00
2017-02-08 10:57:00
2017-02-08 10:58:00
2017-02-08 10:59:00
2017-02-08 11:00:00
2017-02-08 11:01:00
2017-02-08 11:02:00
2017-02-08 11:03:00
2017-02-08 11:04:00
2017-02-08 11:05:00
2017-02-08 11:06:00
2017-02-08 11:07:00
2017-02-08 11:08:00
2017-02-08 11:09:00


2017-02-09 10:59:00
2017-02-09 11:00:00
2017-02-09 11:01:00
2017-02-09 11:02:00
2017-02-09 11:03:00
2017-02-09 11:04:00
2017-02-09 11:05:00
2017-02-09 11:06:00
2017-02-09 11:07:00
2017-02-09 11:08:00
2017-02-09 11:09:00
2017-02-09 11:10:00
2017-02-09 11:11:00
2017-02-09 11:12:00
2017-02-09 11:13:00
2017-02-09 11:14:00
2017-02-09 11:15:00
2017-02-09 11:16:00
2017-02-09 11:17:00
2017-02-09 11:18:00
2017-02-09 11:19:00
2017-02-09 11:20:00
2017-02-09 11:21:00
2017-02-09 11:22:00
2017-02-09 11:23:00
2017-02-09 11:24:00
2017-02-09 11:25:00
2017-02-09 11:26:00
2017-02-09 11:27:00
2017-02-09 11:28:00
2017-02-09 11:29:00
2017-02-09 11:30:00
2017-02-09 11:31:00
2017-02-09 11:32:00
2017-02-09 11:33:00
2017-02-09 11:34:00
2017-02-09 11:35:00
2017-02-09 11:36:00
2017-02-09 11:37:00
2017-02-09 11:38:00
2017-02-09 11:39:00
2017-02-09 11:40:00
2017-02-09 11:41:00
2017-02-09 11:42:00
2017-02-09 11:43:00
2017-02-09 11:44:00
2017-02-09 11:45:00
2017-02-09 11:46:00
2017-02-09 11:47:00
2017-02-09 11:48:00


In [25]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData3" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return []

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 1,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 5,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AGW
Processing data for stock: AIO
Processing data for stock: AUZ
Processing data for stock: BSN
Processing data for stock: BWU
Processing data for stock: CBT
Processing data for stock: CHV
Processing data for stock: CSR
Processing data for stock: CUN
Processing data for stock: CYD
Processing data for stock: DCO
Processing data for stock: DFZ
Processing data for stock: DVV
Processing data for stock: DYE
Processing data for stock: EGV
Processing data for stock: FCY
Processing data for stock: FFA
Processing data for stock: FFS
Processing data for stock: FKI
Processing data for stock: FRE
Processing data for stock: FUR
Processing data for stock: GFQ
Processing data for stock: GGK
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: HHK
Processing data for stock: IES
Processing data for stock: IFL
Processing data for stock: ILW
Processing data for stock: IMC
Processing data for stock: IUE
Processing data for stock: IUQ
Processi

2017-01-06 13:47:00
2017-01-06 13:48:00
2017-01-06 13:49:00
2017-01-06 13:50:00
2017-01-06 13:51:00
2017-01-06 13:52:00
2017-01-06 13:53:00
2017-01-06 13:54:00
2017-01-06 13:55:00
2017-01-06 13:56:00
2017-01-06 13:57:00
2017-01-06 13:58:00
2017-01-06 13:59:00
2017-01-06 14:00:00
2017-01-06 14:01:00
2017-01-06 14:02:00
2017-01-06 14:03:00
2017-01-06 14:04:00
2017-01-06 14:05:00
2017-01-06 14:06:00
2017-01-06 14:07:00
2017-01-06 14:08:00
2017-01-06 14:09:00
2017-01-06 14:10:00
2017-01-06 14:11:00
2017-01-06 14:12:00
2017-01-06 14:13:00
2017-01-06 14:14:00
2017-01-06 14:15:00
2017-01-06 14:16:00
2017-01-06 14:17:00
2017-01-06 14:18:00
2017-01-06 14:19:00
2017-01-06 14:20:00
2017-01-06 14:21:00
2017-01-06 14:22:00
2017-01-06 14:23:00
2017-01-06 14:24:00
2017-01-06 14:25:00
2017-01-06 14:26:00
2017-01-06 14:27:00
2017-01-06 14:28:00
2017-01-06 14:29:00
2017-01-06 14:30:00
2017-01-06 14:31:00
2017-01-06 14:32:00
2017-01-06 14:33:00
2017-01-06 14:34:00
2017-01-06 14:35:00
2017-01-06 14:36:00


2017-01-10 14:25:00
2017-01-10 14:26:00
2017-01-10 14:27:00
2017-01-10 14:28:00
2017-01-10 14:29:00
2017-01-10 14:30:00
2017-01-10 14:31:00
2017-01-10 14:32:00
2017-01-10 14:33:00
2017-01-10 14:34:00
2017-01-10 14:35:00
2017-01-10 14:36:00
2017-01-10 14:37:00
2017-01-10 14:38:00
2017-01-10 14:39:00
2017-01-10 14:40:00
2017-01-10 14:41:00
2017-01-10 14:42:00
2017-01-10 14:43:00
2017-01-10 14:44:00
2017-01-10 14:45:00
2017-01-10 14:46:00
2017-01-10 14:47:00
2017-01-10 14:48:00
2017-01-10 14:49:00
2017-01-10 14:50:00
2017-01-10 14:51:00
2017-01-10 14:52:00
2017-01-10 14:53:00
2017-01-10 14:54:00
2017-01-10 14:55:00
2017-01-10 14:56:00
2017-01-10 14:57:00
2017-01-10 14:58:00
2017-01-10 14:59:00
2017-01-10 15:00:00
2017-01-10 15:01:00
2017-01-10 15:02:00
2017-01-10 15:03:00
2017-01-10 15:04:00
2017-01-10 15:05:00
2017-01-10 15:06:00
2017-01-10 15:07:00
2017-01-10 15:08:00
2017-01-10 15:09:00
2017-01-10 15:10:00
2017-01-10 15:11:00
2017-01-10 15:12:00
2017-01-10 15:13:00
2017-01-10 15:14:00


2017-01-11 15:04:00
2017-01-11 15:05:00
2017-01-11 15:06:00
2017-01-11 15:07:00
2017-01-11 15:08:00
2017-01-11 15:09:00
2017-01-11 15:10:00
2017-01-11 15:11:00
2017-01-11 15:12:00
2017-01-11 15:13:00
2017-01-11 15:14:00
2017-01-11 15:15:00
2017-01-11 15:16:00
2017-01-11 15:17:00
2017-01-11 15:18:00
2017-01-11 15:19:00
2017-01-11 15:20:00
2017-01-11 15:21:00
2017-01-11 15:22:00
2017-01-11 15:23:00
2017-01-11 15:24:00
2017-01-11 15:25:00
2017-01-11 15:26:00
2017-01-11 15:27:00
2017-01-11 15:28:00
2017-01-11 15:29:00
2017-01-12 09:17:00
2017-01-12 09:18:00
2017-01-12 09:19:00
2017-01-12 09:20:00
2017-01-12 09:21:00
2017-01-12 09:22:00
2017-01-12 09:23:00
2017-01-12 09:24:00
2017-01-12 09:25:00
2017-01-12 09:26:00
2017-01-12 09:27:00
2017-01-12 09:28:00
2017-01-12 09:29:00
2017-01-12 09:30:00
2017-01-12 09:31:00
2017-01-12 09:32:00
2017-01-12 09:33:00
2017-01-12 09:34:00
2017-01-12 09:35:00
2017-01-12 09:36:00
2017-01-12 09:37:00
2017-01-12 09:38:00
2017-01-12 09:39:00
2017-01-12 09:40:00


2017-01-13 09:28:00
2017-01-13 09:29:00
2017-01-13 09:30:00
2017-01-13 09:31:00
2017-01-13 09:32:00
2017-01-13 09:33:00
2017-01-13 09:34:00
2017-01-13 09:35:00
2017-01-13 09:36:00
2017-01-13 09:37:00
2017-01-13 09:38:00
2017-01-13 09:39:00
2017-01-13 09:40:00
2017-01-13 09:41:00
2017-01-13 09:42:00
2017-01-13 09:43:00
2017-01-13 09:44:00
2017-01-13 09:45:00
2017-01-13 09:46:00
2017-01-13 09:47:00
2017-01-13 09:48:00
2017-01-13 09:49:00
2017-01-13 09:50:00
2017-01-13 09:51:00
2017-01-13 09:52:00
2017-01-13 09:53:00
2017-01-13 09:54:00
2017-01-13 09:55:00
2017-01-13 09:56:00
2017-01-13 09:57:00
2017-01-13 09:58:00
2017-01-13 09:59:00
2017-01-13 10:00:00
2017-01-13 10:01:00
2017-01-13 10:02:00
2017-01-13 10:03:00
2017-01-13 10:04:00
2017-01-13 10:05:00
2017-01-13 10:06:00
2017-01-13 10:07:00
2017-01-13 10:08:00
2017-01-13 10:09:00
2017-01-13 10:10:00
2017-01-13 10:11:00
2017-01-13 10:12:00
2017-01-13 10:13:00
2017-01-13 10:14:00
2017-01-13 10:15:00
2017-01-13 10:16:00
2017-01-13 10:17:00


...

2017-01-26 13:59:00
2017-01-26 14:00:00
2017-01-26 14:01:00
2017-01-26 14:02:00
2017-01-26 14:03:00
2017-01-26 14:04:00
2017-01-26 14:05:00
2017-01-26 14:06:00
2017-01-26 14:07:00
2017-01-26 14:08:00
2017-01-26 14:09:00
2017-01-26 14:10:00
2017-01-26 14:11:00
2017-01-26 14:12:00
2017-01-26 14:13:00
2017-01-26 14:14:00
2017-01-26 14:15:00
2017-01-26 14:16:00
2017-01-26 14:17:00
2017-01-26 14:18:00
2017-01-26 14:19:00
2017-01-26 14:20:00
2017-01-26 14:21:00
2017-01-26 14:22:00
2017-01-26 14:23:00
2017-01-26 14:24:00
2017-01-26 14:25:00
2017-01-26 14:26:00
2017-01-26 14:27:00
2017-01-26 14:28:00
2017-01-26 14:29:00
2017-01-26 14:30:00
2017-01-26 14:31:00
2017-01-26 14:32:00
2017-01-26 14:33:00
2017-01-26 14:34:00
2017-01-26 14:35:00
2017-01-26 14:36:00
2017-01-26 14:37:00
2017-01-26 14:38:00
2017-01-26 14:39:00
2017-01-26 14:40:00
2017-01-26 14:41:00
2017-01-26 14:42:00
2017-01-26 14:43:00
2017-01-26 14:44:00
2017-01-26 14:45:00
2017-01-26 14:46:00
2017-01-26 14:47:00
2017-01-26 14:48:00


2017-01-27 14:38:00
2017-01-27 14:39:00
2017-01-27 14:40:00
2017-01-27 14:41:00
2017-01-27 14:42:00
2017-01-27 14:43:00
2017-01-27 14:44:00
2017-01-27 14:45:00
2017-01-27 14:46:00
2017-01-27 14:47:00
2017-01-27 14:48:00
2017-01-27 14:49:00
2017-01-27 14:50:00
2017-01-27 14:51:00
2017-01-27 14:52:00
2017-01-27 14:53:00
2017-01-27 14:54:00
2017-01-27 14:55:00
2017-01-27 14:56:00
2017-01-27 14:57:00
2017-01-27 14:58:00
2017-01-27 14:59:00
2017-01-27 15:00:00
2017-01-27 15:01:00
2017-01-27 15:02:00
2017-01-27 15:03:00
2017-01-27 15:04:00
2017-01-27 15:05:00
2017-01-27 15:06:00
2017-01-27 15:07:00
2017-01-27 15:08:00
2017-01-27 15:09:00
2017-01-27 15:10:00
2017-01-27 15:11:00
2017-01-27 15:12:00
2017-01-27 15:13:00
2017-01-27 15:14:00
2017-01-27 15:15:00
2017-01-27 15:16:00
2017-01-27 15:17:00
2017-01-27 15:18:00
2017-01-27 15:19:00
2017-01-27 15:20:00
2017-01-27 15:21:00
2017-01-27 15:22:00
2017-01-27 15:23:00
2017-01-27 15:24:00
2017-01-27 15:25:00
2017-01-27 15:26:00
2017-01-27 15:27:00


2017-01-30 15:17:00
2017-01-30 15:18:00
2017-01-30 15:19:00
2017-01-30 15:20:00
2017-01-30 15:21:00
2017-01-30 15:22:00
2017-01-30 15:23:00
2017-01-30 15:24:00
2017-01-30 15:25:00
2017-01-30 15:26:00
2017-01-30 15:27:00
2017-01-30 15:28:00
2017-01-30 15:29:00
2017-01-31 09:17:00
2017-01-31 09:18:00
2017-01-31 09:19:00
2017-01-31 09:20:00
2017-01-31 09:21:00
2017-01-31 09:22:00
2017-01-31 09:23:00
2017-01-31 09:24:00
2017-01-31 09:25:00
2017-01-31 09:26:00
2017-01-31 09:27:00
2017-01-31 09:28:00
2017-01-31 09:29:00
2017-01-31 09:30:00
2017-01-31 09:31:00
2017-01-31 09:32:00
2017-01-31 09:33:00
2017-01-31 09:34:00
2017-01-31 09:35:00
2017-01-31 09:36:00
2017-01-31 09:37:00
2017-01-31 09:38:00
2017-01-31 09:39:00
2017-01-31 09:40:00
2017-01-31 09:41:00
2017-01-31 09:42:00
2017-01-31 09:43:00
2017-01-31 09:44:00
2017-01-31 09:45:00
2017-01-31 09:46:00
2017-01-31 09:47:00
2017-01-31 09:48:00
2017-01-31 09:49:00
2017-01-31 09:50:00
2017-01-31 09:51:00
2017-01-31 09:52:00
2017-01-31 09:53:00


2017-02-01 09:44:00
2017-02-01 09:45:00
2017-02-01 09:46:00
2017-02-01 09:47:00
2017-02-01 09:48:00
2017-02-01 09:49:00
2017-02-01 09:50:00
2017-02-01 09:51:00
2017-02-01 09:52:00
2017-02-01 09:53:00
2017-02-01 09:54:00
2017-02-01 09:55:00
2017-02-01 09:56:00
2017-02-01 09:57:00
2017-02-01 09:58:00
2017-02-01 09:59:00
2017-02-01 10:00:00
2017-02-01 10:01:00
2017-02-01 10:02:00
2017-02-01 10:03:00
2017-02-01 10:04:00
2017-02-01 10:05:00
2017-02-01 10:06:00
2017-02-01 10:07:00
2017-02-01 10:08:00
2017-02-01 10:09:00
2017-02-01 10:10:00
2017-02-01 10:11:00
2017-02-01 10:12:00
2017-02-01 10:13:00
2017-02-01 10:14:00
2017-02-01 10:15:00
2017-02-01 10:16:00
2017-02-01 10:17:00
2017-02-01 10:18:00
2017-02-01 10:19:00
2017-02-01 10:20:00
2017-02-01 10:21:00
2017-02-01 10:22:00
2017-02-01 10:23:00
2017-02-01 10:24:00
2017-02-01 10:25:00
2017-02-01 10:26:00
2017-02-01 10:27:00
2017-02-01 10:28:00
2017-02-01 10:29:00
2017-02-01 10:30:00
2017-02-01 10:31:00
2017-02-01 10:32:00
2017-02-01 10:33:00


2017-02-02 10:23:00
2017-02-02 10:24:00
2017-02-02 10:25:00
2017-02-02 10:26:00
2017-02-02 10:27:00
2017-02-02 10:28:00
2017-02-02 10:29:00
2017-02-02 10:30:00
2017-02-02 10:31:00
2017-02-02 10:32:00
2017-02-02 10:33:00
2017-02-02 10:34:00
2017-02-02 10:35:00
2017-02-02 10:36:00
2017-02-02 10:37:00
2017-02-02 10:38:00
2017-02-02 10:39:00
2017-02-02 10:40:00
2017-02-02 10:41:00
2017-02-02 10:42:00
2017-02-02 10:43:00
2017-02-02 10:44:00
2017-02-02 10:45:00
2017-02-02 10:46:00
2017-02-02 10:47:00
2017-02-02 10:48:00
2017-02-02 10:49:00
2017-02-02 10:50:00
2017-02-02 10:51:00
2017-02-02 10:52:00
2017-02-02 10:53:00
2017-02-02 10:54:00
2017-02-02 10:55:00
2017-02-02 10:56:00
2017-02-02 10:57:00
2017-02-02 10:58:00
2017-02-02 10:59:00
2017-02-02 11:00:00
2017-02-02 11:01:00
2017-02-02 11:02:00
2017-02-02 11:03:00
2017-02-02 11:04:00
2017-02-02 11:05:00
2017-02-02 11:06:00
2017-02-02 11:07:00
2017-02-02 11:08:00
2017-02-02 11:09:00
2017-02-02 11:10:00
2017-02-02 11:11:00
2017-02-02 11:12:00


In [2]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData1" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return ['AUZ',
 'DFZ',
 'DVV',
 'EGV',
 'FKI',
 'FUR',
 'GYJ',
 'GYV',
 'HHK',
 'IFL',
 'JSG',
 'KFW',
 'KMV',
 'MAS',
 'OED',
 'PMS',
 'SVG',
 'TGI',
 'UWC',
 'UWD',
 'VKE',
 'VND',
 'VTN',
 'ZEW']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 1,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 2,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AUZ
Processing data for stock: DFZ
Processing data for stock: DVV
Processing data for stock: EGV
Processing data for stock: FKI
Processing data for stock: FUR
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: HHK
Processing data for stock: IFL
Processing data for stock: JSG
Processing data for stock: KFW
Processing data for stock: KMV
Processing data for stock: MAS
Processing data for stock: OED
Processing data for stock: PMS
Processing data for stock: SVG
Processing data for stock: TGI
Processing data for stock: UWC
Processing data for stock: UWD
Processing data for stock: VKE
Processing data for stock: VND
Processing data for stock: VTN
Processing data for stock: ZEW
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-06 09:17:00
2017-01-06 09:18:00
2017-01-06 09:19:00
2017-01-06 09:20:00
2017-01-06 09:21:00
2017-01-06 09:22:00
2017-0

2017-01-06 15:24:00
2017-01-06 15:25:00
2017-01-06 15:26:00
2017-01-06 15:27:00
2017-01-06 15:28:00
2017-01-06 15:29:00
2017-01-09 09:17:00
2017-01-09 09:18:00
2017-01-09 09:19:00
2017-01-09 09:20:00
2017-01-09 09:21:00
2017-01-09 09:22:00
2017-01-09 09:23:00
2017-01-09 09:24:00
2017-01-09 09:25:00
2017-01-09 09:26:00
2017-01-09 09:27:00
2017-01-09 09:28:00
2017-01-09 09:29:00
2017-01-09 09:30:00
2017-01-09 09:31:00
2017-01-09 09:32:00
2017-01-09 09:33:00
2017-01-09 09:34:00
2017-01-09 09:35:00
2017-01-09 09:36:00
2017-01-09 09:37:00
2017-01-09 09:38:00
2017-01-09 09:39:00
2017-01-09 09:40:00
2017-01-09 09:41:00
2017-01-09 09:42:00
2017-01-09 09:43:00
2017-01-09 09:44:00
2017-01-09 09:45:00
2017-01-09 09:46:00
2017-01-09 09:47:00
2017-01-09 09:48:00
2017-01-09 09:49:00
2017-01-09 09:50:00
2017-01-09 09:51:00
2017-01-09 09:52:00
2017-01-09 09:53:00
2017-01-09 09:54:00
2017-01-09 09:55:00
2017-01-09 09:56:00
2017-01-09 09:57:00
2017-01-09 09:58:00
2017-01-09 09:59:00
2017-01-09 10:00:00


2017-01-10 09:50:00
2017-01-10 09:51:00
2017-01-10 09:52:00
2017-01-10 09:53:00
2017-01-10 09:54:00
2017-01-10 09:55:00
2017-01-10 09:56:00
2017-01-10 09:57:00
2017-01-10 09:58:00
2017-01-10 09:59:00
2017-01-10 10:00:00
2017-01-10 10:01:00
2017-01-10 10:02:00
2017-01-10 10:03:00
2017-01-10 10:04:00
2017-01-10 10:05:00
2017-01-10 10:06:00
2017-01-10 10:07:00
2017-01-10 10:08:00
2017-01-10 10:09:00
2017-01-10 10:10:00
2017-01-10 10:11:00
2017-01-10 10:12:00
2017-01-10 10:13:00
2017-01-10 10:14:00
2017-01-10 10:15:00
2017-01-10 10:16:00
2017-01-10 10:17:00
2017-01-10 10:18:00
2017-01-10 10:19:00
2017-01-10 10:20:00
2017-01-10 10:21:00
2017-01-10 10:22:00
2017-01-10 10:23:00
2017-01-10 10:24:00
2017-01-10 10:25:00
2017-01-10 10:26:00
2017-01-10 10:27:00
2017-01-10 10:28:00
2017-01-10 10:29:00
2017-01-10 10:30:00
2017-01-10 10:31:00
2017-01-10 10:32:00
2017-01-10 10:33:00
2017-01-10 10:34:00
2017-01-10 10:35:00
2017-01-10 10:36:00
2017-01-10 10:37:00
2017-01-10 10:38:00
2017-01-10 10:39:00


2017-01-11 10:28:00
2017-01-11 10:29:00
2017-01-11 10:30:00
2017-01-11 10:31:00
2017-01-11 10:32:00
2017-01-11 10:33:00
2017-01-11 10:34:00
2017-01-11 10:35:00
2017-01-11 10:36:00
2017-01-11 10:37:00
2017-01-11 10:38:00
2017-01-11 10:39:00
2017-01-11 10:40:00
2017-01-11 10:41:00
2017-01-11 10:42:00
2017-01-11 10:43:00
2017-01-11 10:44:00
2017-01-11 10:45:00
2017-01-11 10:46:00
2017-01-11 10:47:00
2017-01-11 10:48:00
2017-01-11 10:49:00
2017-01-11 10:50:00
2017-01-11 10:51:00
2017-01-11 10:52:00
2017-01-11 10:53:00
2017-01-11 10:54:00
2017-01-11 10:55:00
2017-01-11 10:56:00
2017-01-11 10:57:00
2017-01-11 10:58:00
2017-01-11 10:59:00
2017-01-11 11:00:00
2017-01-11 11:01:00
2017-01-11 11:02:00
2017-01-11 11:03:00
2017-01-11 11:04:00
2017-01-11 11:05:00
2017-01-11 11:06:00
2017-01-11 11:07:00
2017-01-11 11:08:00
2017-01-11 11:09:00
2017-01-11 11:10:00
2017-01-11 11:11:00
2017-01-11 11:12:00
2017-01-11 11:13:00
2017-01-11 11:14:00
2017-01-11 11:15:00
2017-01-11 11:16:00
2017-01-11 11:17:00


2017-01-12 11:05:00
2017-01-12 11:06:00
2017-01-12 11:07:00
2017-01-12 11:08:00
2017-01-12 11:09:00
2017-01-12 11:10:00
2017-01-12 11:11:00
2017-01-12 11:12:00
2017-01-12 11:13:00
2017-01-12 11:14:00
2017-01-12 11:15:00
2017-01-12 11:16:00
2017-01-12 11:17:00
2017-01-12 11:18:00
2017-01-12 11:19:00
2017-01-12 11:20:00
2017-01-12 11:21:00
2017-01-12 11:22:00
2017-01-12 11:23:00
2017-01-12 11:24:00
2017-01-12 11:25:00
2017-01-12 11:26:00
2017-01-12 11:27:00
2017-01-12 11:28:00
2017-01-12 11:29:00
2017-01-12 11:30:00
2017-01-12 11:31:00
2017-01-12 11:32:00
2017-01-12 11:33:00
2017-01-12 11:34:00
2017-01-12 11:35:00
2017-01-12 11:36:00
2017-01-12 11:37:00
2017-01-12 11:38:00
2017-01-12 11:39:00
2017-01-12 11:40:00
2017-01-12 11:41:00
2017-01-12 11:42:00
2017-01-12 11:43:00
2017-01-12 11:44:00
2017-01-12 11:45:00
2017-01-12 11:46:00
2017-01-12 11:47:00
2017-01-12 11:48:00
2017-01-12 11:49:00
2017-01-12 11:50:00
2017-01-12 11:51:00
2017-01-12 11:52:00
2017-01-12 11:53:00
2017-01-12 11:54:00


...

2017-02-01 13:03:00
2017-02-01 13:04:00
2017-02-01 13:05:00
2017-02-01 13:06:00
2017-02-01 13:07:00
2017-02-01 13:08:00
2017-02-01 13:09:00
2017-02-01 13:10:00
2017-02-01 13:11:00
2017-02-01 13:12:00
2017-02-01 13:13:00
2017-02-01 13:14:00
2017-02-01 13:15:00
2017-02-01 13:16:00
2017-02-01 13:17:00
2017-02-01 13:18:00
2017-02-01 13:19:00
2017-02-01 13:20:00
2017-02-01 13:21:00
2017-02-01 13:22:00
2017-02-01 13:23:00
2017-02-01 13:24:00
2017-02-01 13:25:00
2017-02-01 13:26:00
2017-02-01 13:27:00
2017-02-01 13:28:00
2017-02-01 13:29:00
2017-02-01 13:30:00
2017-02-01 13:31:00
2017-02-01 13:32:00
2017-02-01 13:33:00
2017-02-01 13:34:00
2017-02-01 13:35:00
2017-02-01 13:36:00
2017-02-01 13:37:00
2017-02-01 13:38:00
2017-02-01 13:39:00
2017-02-01 13:40:00
2017-02-01 13:41:00
2017-02-01 13:42:00
2017-02-01 13:43:00
2017-02-01 13:44:00
2017-02-01 13:45:00
2017-02-01 13:46:00
2017-02-01 13:47:00
2017-02-01 13:48:00
2017-02-01 13:49:00
2017-02-01 13:50:00
2017-02-01 13:51:00
2017-02-01 13:52:00


2017-02-02 13:43:00
2017-02-02 13:44:00
2017-02-02 13:45:00
2017-02-02 13:46:00
2017-02-02 13:47:00
2017-02-02 13:48:00
2017-02-02 13:49:00
2017-02-02 13:50:00
2017-02-02 13:51:00
2017-02-02 13:52:00
2017-02-02 13:53:00
2017-02-02 13:54:00
2017-02-02 13:55:00
2017-02-02 13:56:00
2017-02-02 13:57:00
2017-02-02 13:58:00
2017-02-02 13:59:00
2017-02-02 14:00:00
2017-02-02 14:01:00
2017-02-02 14:02:00
2017-02-02 14:03:00
2017-02-02 14:04:00
2017-02-02 14:05:00
2017-02-02 14:06:00
2017-02-02 14:07:00
2017-02-02 14:08:00
2017-02-02 14:09:00
2017-02-02 14:10:00
2017-02-02 14:11:00
2017-02-02 14:12:00
2017-02-02 14:13:00
2017-02-02 14:14:00
2017-02-02 14:15:00
2017-02-02 14:16:00
2017-02-02 14:17:00
2017-02-02 14:18:00
2017-02-02 14:19:00
2017-02-02 14:20:00
2017-02-02 14:21:00
2017-02-02 14:22:00
2017-02-02 14:23:00
2017-02-02 14:24:00
2017-02-02 14:25:00
2017-02-02 14:26:00
2017-02-02 14:27:00
2017-02-02 14:28:00
2017-02-02 14:29:00
2017-02-02 14:30:00
2017-02-02 14:31:00
2017-02-02 14:32:00


2017-02-03 14:23:00
2017-02-03 14:24:00
2017-02-03 14:25:00
2017-02-03 14:26:00
2017-02-03 14:27:00
2017-02-03 14:28:00
2017-02-03 14:29:00
2017-02-03 14:30:00
2017-02-03 14:31:00
2017-02-03 14:32:00
2017-02-03 14:33:00
2017-02-03 14:34:00
2017-02-03 14:35:00
2017-02-03 14:36:00
2017-02-03 14:37:00
2017-02-03 14:38:00
2017-02-03 14:39:00
2017-02-03 14:40:00
2017-02-03 14:41:00
2017-02-03 14:42:00
2017-02-03 14:43:00
2017-02-03 14:44:00
2017-02-03 14:45:00
2017-02-03 14:46:00
2017-02-03 14:47:00
2017-02-03 14:48:00
2017-02-03 14:49:00
2017-02-03 14:50:00
2017-02-03 14:51:00
2017-02-03 14:52:00
2017-02-03 14:53:00
2017-02-03 14:54:00
2017-02-03 14:55:00
2017-02-03 14:56:00
2017-02-03 14:57:00
2017-02-03 14:58:00
2017-02-03 14:59:00
2017-02-03 15:00:00
2017-02-03 15:01:00
2017-02-03 15:02:00
2017-02-03 15:03:00
2017-02-03 15:04:00
2017-02-03 15:05:00
2017-02-03 15:06:00
2017-02-03 15:07:00
2017-02-03 15:08:00
2017-02-03 15:09:00
2017-02-03 15:10:00
2017-02-03 15:11:00
2017-02-03 15:12:00


2017-02-07 15:02:00
2017-02-07 15:03:00
2017-02-07 15:04:00
2017-02-07 15:05:00
2017-02-07 15:06:00
2017-02-07 15:07:00
2017-02-07 15:08:00
2017-02-07 15:09:00
2017-02-07 15:10:00
2017-02-07 15:11:00
2017-02-07 15:12:00
2017-02-07 15:13:00
2017-02-07 15:14:00
2017-02-07 15:15:00
2017-02-07 15:16:00
2017-02-07 15:17:00
2017-02-07 15:18:00
2017-02-07 15:19:00
2017-02-07 15:20:00
2017-02-07 15:21:00
2017-02-07 15:22:00
2017-02-07 15:23:00
2017-02-07 15:24:00
2017-02-07 15:25:00
2017-02-07 15:26:00
2017-02-07 15:27:00
2017-02-07 15:28:00
2017-02-07 15:29:00
2017-02-08 09:17:00
2017-02-08 09:18:00
2017-02-08 09:19:00
2017-02-08 09:20:00
2017-02-08 09:21:00
2017-02-08 09:22:00
2017-02-08 09:23:00
2017-02-08 09:24:00
2017-02-08 09:25:00
2017-02-08 09:26:00
2017-02-08 09:27:00
2017-02-08 09:28:00
2017-02-08 09:29:00
2017-02-08 09:30:00
2017-02-08 09:31:00
2017-02-08 09:32:00
2017-02-08 09:33:00
2017-02-08 09:34:00
2017-02-08 09:35:00
2017-02-08 09:36:00
2017-02-08 09:37:00
2017-02-08 09:38:00


2017-02-09 09:28:00
2017-02-09 09:29:00
2017-02-09 09:30:00
2017-02-09 09:31:00
2017-02-09 09:32:00
2017-02-09 09:33:00
2017-02-09 09:34:00
2017-02-09 09:35:00
2017-02-09 09:36:00
2017-02-09 09:37:00
2017-02-09 09:38:00
2017-02-09 09:39:00
2017-02-09 09:40:00
2017-02-09 09:41:00
2017-02-09 09:42:00
2017-02-09 09:43:00
2017-02-09 09:44:00
2017-02-09 09:45:00
2017-02-09 09:46:00
2017-02-09 09:47:00
2017-02-09 09:48:00
2017-02-09 09:49:00
2017-02-09 09:50:00
2017-02-09 09:51:00
2017-02-09 09:52:00
2017-02-09 09:53:00
2017-02-09 09:54:00
2017-02-09 09:55:00
2017-02-09 09:56:00
2017-02-09 09:57:00
2017-02-09 09:58:00
2017-02-09 09:59:00
2017-02-09 10:00:00
2017-02-09 10:01:00
2017-02-09 10:02:00
2017-02-09 10:03:00
2017-02-09 10:04:00
2017-02-09 10:05:00
2017-02-09 10:06:00
2017-02-09 10:07:00
2017-02-09 10:08:00
2017-02-09 10:09:00
2017-02-09 10:10:00
2017-02-09 10:11:00
2017-02-09 10:12:00
2017-02-09 10:13:00
2017-02-09 10:14:00
2017-02-09 10:15:00
2017-02-09 10:16:00
2017-02-09 10:17:00


In [6]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData2" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return ['AUZ',
 'DFZ',
 'DVV',
 'EGV',
 'FKI',
 'FUR',
 'GYJ',
 'GYV',
 'HHK',
 'IFL',
 'JSG',
 'KFW',
 'KMV',
 'MAS',
 'OED',
 'PMS',
 'SVG',
 'TGI',
 'UWC',
 'UWD',
 'VKE',
 'VND',
 'VTN',
 'ZEW']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 1,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 2,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AUZ
Processing data for stock: DFZ
Processing data for stock: DVV
Processing data for stock: EGV
Processing data for stock: FKI
Processing data for stock: FUR
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: HHK
Processing data for stock: IFL
Processing data for stock: JSG
Processing data for stock: KFW
Processing data for stock: KMV
Processing data for stock: MAS
Processing data for stock: OED
Processing data for stock: PMS
Processing data for stock: SVG
Processing data for stock: TGI
Processing data for stock: UWC
Processing data for stock: UWD
Processing data for stock: VKE
Processing data for stock: VND
Processing data for stock: VTN
Processing data for stock: ZEW
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-13 09:17:00
2017-01-13 09:18:00
2017-01-13 09:19:00
2017-01-13 09:20:00
2017-01-13 09:21:00
2017-01-13 09:22:00
2017-0

2017-01-13 15:26:00
2017-01-13 15:27:00
2017-01-13 15:28:00
2017-01-13 15:29:00
2017-01-16 09:17:00
2017-01-16 09:18:00
2017-01-16 09:19:00
2017-01-16 09:20:00
2017-01-16 09:21:00
2017-01-16 09:22:00
2017-01-16 09:23:00
2017-01-16 09:24:00
2017-01-16 09:25:00
2017-01-16 09:26:00
2017-01-16 09:27:00
2017-01-16 09:28:00
2017-01-16 09:29:00
2017-01-16 09:30:00
2017-01-16 09:31:00
2017-01-16 09:32:00
2017-01-16 09:33:00
2017-01-16 09:34:00
2017-01-16 09:35:00
2017-01-16 09:36:00
2017-01-16 09:37:00
2017-01-16 09:38:00
2017-01-16 09:39:00
2017-01-16 09:40:00
2017-01-16 09:41:00
2017-01-16 09:42:00
2017-01-16 09:43:00
2017-01-16 09:44:00
2017-01-16 09:45:00
2017-01-16 09:46:00
2017-01-16 09:47:00
2017-01-16 09:48:00
2017-01-16 09:49:00
2017-01-16 09:50:00
2017-01-16 09:51:00
2017-01-16 09:52:00
2017-01-16 09:53:00
2017-01-16 09:54:00
2017-01-16 09:55:00
2017-01-16 09:56:00
2017-01-16 09:57:00
2017-01-16 09:58:00
2017-01-16 09:59:00
2017-01-16 10:00:00
2017-01-16 10:01:00
2017-01-16 10:02:00


2017-01-18 09:52:00
2017-01-18 09:53:00
2017-01-18 09:54:00
2017-01-18 09:55:00
2017-01-18 09:56:00
2017-01-18 09:57:00
2017-01-18 09:58:00
2017-01-18 09:59:00
2017-01-18 10:00:00
2017-01-18 10:01:00
2017-01-18 10:02:00
2017-01-18 10:03:00
2017-01-18 10:04:00
2017-01-18 10:05:00
2017-01-18 10:06:00
2017-01-18 10:07:00
2017-01-18 10:08:00
2017-01-18 10:09:00
2017-01-18 10:10:00
2017-01-18 10:11:00
2017-01-18 10:12:00
2017-01-18 10:13:00
2017-01-18 10:14:00
2017-01-18 10:15:00
2017-01-18 10:16:00
2017-01-18 10:17:00
2017-01-18 10:18:00
2017-01-18 10:19:00
2017-01-18 10:20:00
2017-01-18 10:21:00
2017-01-18 10:22:00
2017-01-18 10:23:00
2017-01-18 10:24:00
2017-01-18 10:25:00
2017-01-18 10:26:00
2017-01-18 10:27:00
2017-01-18 10:28:00
2017-01-18 10:29:00
2017-01-18 10:30:00
2017-01-18 10:31:00
2017-01-18 10:32:00
2017-01-18 10:33:00
2017-01-18 10:34:00
2017-01-18 10:35:00
2017-01-18 10:36:00
2017-01-18 10:37:00
2017-01-18 10:38:00
2017-01-18 10:39:00
2017-01-18 10:40:00
2017-01-18 10:41:00


2017-01-19 10:32:00
2017-01-19 10:33:00
2017-01-19 10:34:00
2017-01-19 10:35:00
2017-01-19 10:36:00
2017-01-19 10:37:00
2017-01-19 10:38:00
2017-01-19 10:39:00
2017-01-19 10:40:00
2017-01-19 10:41:00
2017-01-19 10:42:00
2017-01-19 10:43:00
2017-01-19 10:44:00
2017-01-19 10:45:00
2017-01-19 10:46:00
2017-01-19 10:47:00
2017-01-19 10:48:00
2017-01-19 10:49:00
2017-01-19 10:50:00
2017-01-19 10:51:00
2017-01-19 10:52:00
2017-01-19 10:53:00
2017-01-19 10:54:00
2017-01-19 10:55:00
2017-01-19 10:56:00
2017-01-19 10:57:00
2017-01-19 10:58:00
2017-01-19 10:59:00
2017-01-19 11:00:00
2017-01-19 11:01:00
2017-01-19 11:02:00
2017-01-19 11:03:00
2017-01-19 11:04:00
2017-01-19 11:05:00
2017-01-19 11:06:00
2017-01-19 11:07:00
2017-01-19 11:08:00
2017-01-19 11:09:00
2017-01-19 11:10:00
2017-01-19 11:11:00
2017-01-19 11:12:00
2017-01-19 11:13:00
2017-01-19 11:14:00
2017-01-19 11:15:00
2017-01-19 11:16:00
2017-01-19 11:17:00
2017-01-19 11:18:00
2017-01-19 11:19:00
2017-01-19 11:20:00
2017-01-19 11:21:00


2017-01-20 11:10:00
2017-01-20 11:11:00
2017-01-20 11:12:00
2017-01-20 11:13:00
2017-01-20 11:14:00
2017-01-20 11:15:00
2017-01-20 11:16:00
2017-01-20 11:17:00
2017-01-20 11:18:00
2017-01-20 11:19:00
2017-01-20 11:20:00
2017-01-20 11:21:00
2017-01-20 11:22:00
2017-01-20 11:23:00
2017-01-20 11:24:00
2017-01-20 11:25:00
2017-01-20 11:26:00
2017-01-20 11:27:00
2017-01-20 11:28:00
2017-01-20 11:29:00
2017-01-20 11:30:00
2017-01-20 11:31:00
2017-01-20 11:32:00
2017-01-20 11:33:00
2017-01-20 11:34:00
2017-01-20 11:35:00
2017-01-20 11:36:00
2017-01-20 11:37:00
2017-01-20 11:38:00
2017-01-20 11:39:00
2017-01-20 11:40:00
2017-01-20 11:41:00
2017-01-20 11:42:00
2017-01-20 11:43:00
2017-01-20 11:44:00
2017-01-20 11:45:00
2017-01-20 11:46:00
2017-01-20 11:47:00
2017-01-20 11:48:00
2017-01-20 11:49:00
2017-01-20 11:50:00
2017-01-20 11:51:00
2017-01-20 11:52:00
2017-01-20 11:53:00
2017-01-20 11:54:00
2017-01-20 11:55:00
2017-01-20 11:56:00
2017-01-20 11:57:00
2017-01-20 11:58:00
2017-01-20 11:59:00


...

2017-02-03 10:04:00
2017-02-03 10:05:00
2017-02-03 10:06:00
2017-02-03 10:07:00
2017-02-03 10:08:00
2017-02-03 10:09:00
2017-02-03 10:10:00
2017-02-03 10:11:00
2017-02-03 10:12:00
2017-02-03 10:13:00
2017-02-03 10:14:00
2017-02-03 10:15:00
2017-02-03 10:16:00
2017-02-03 10:17:00
2017-02-03 10:18:00
2017-02-03 10:19:00
2017-02-03 10:20:00
2017-02-03 10:21:00
2017-02-03 10:22:00
2017-02-03 10:23:00
2017-02-03 10:24:00
2017-02-03 10:25:00
2017-02-03 10:26:00
2017-02-03 10:27:00
2017-02-03 10:28:00
2017-02-03 10:29:00
2017-02-03 10:30:00
2017-02-03 10:31:00
2017-02-03 10:32:00
2017-02-03 10:33:00
2017-02-03 10:34:00
2017-02-03 10:35:00
2017-02-03 10:36:00
2017-02-03 10:37:00
2017-02-03 10:38:00
2017-02-03 10:39:00
2017-02-03 10:40:00
2017-02-03 10:41:00
2017-02-03 10:42:00
2017-02-03 10:43:00
2017-02-03 10:44:00
2017-02-03 10:45:00
2017-02-03 10:46:00
2017-02-03 10:47:00
2017-02-03 10:48:00
2017-02-03 10:49:00
2017-02-03 10:50:00
2017-02-03 10:51:00
2017-02-03 10:52:00
2017-02-03 10:53:00


2017-02-06 10:43:00
2017-02-06 10:44:00
2017-02-06 10:45:00
2017-02-06 10:46:00
2017-02-06 10:47:00
2017-02-06 10:48:00
2017-02-06 10:49:00
2017-02-06 10:50:00
2017-02-06 10:51:00
2017-02-06 10:52:00
2017-02-06 10:53:00
2017-02-06 10:54:00
2017-02-06 10:55:00
2017-02-06 10:56:00
2017-02-06 10:57:00
2017-02-06 10:58:00
2017-02-06 10:59:00
2017-02-06 11:00:00
2017-02-06 11:01:00
2017-02-06 11:02:00
2017-02-06 11:03:00
2017-02-06 11:04:00
2017-02-06 11:05:00
2017-02-06 11:06:00
2017-02-06 11:07:00
2017-02-06 11:08:00
2017-02-06 11:09:00
2017-02-06 11:10:00
2017-02-06 11:11:00
2017-02-06 11:12:00
2017-02-06 11:13:00
2017-02-06 11:14:00
2017-02-06 11:15:00
2017-02-06 11:16:00
2017-02-06 11:17:00
2017-02-06 11:18:00
2017-02-06 11:19:00
2017-02-06 11:20:00
2017-02-06 11:21:00
2017-02-06 11:22:00
2017-02-06 11:23:00
2017-02-06 11:24:00
2017-02-06 11:25:00
2017-02-06 11:26:00
2017-02-06 11:27:00
2017-02-06 11:28:00
2017-02-06 11:29:00
2017-02-06 11:30:00
2017-02-06 11:31:00
2017-02-06 11:32:00


2017-02-07 11:21:00
2017-02-07 11:22:00
2017-02-07 11:23:00
2017-02-07 11:24:00
2017-02-07 11:25:00
2017-02-07 11:26:00
2017-02-07 11:27:00
2017-02-07 11:28:00
2017-02-07 11:29:00
2017-02-07 11:30:00
2017-02-07 11:31:00
2017-02-07 11:32:00
2017-02-07 11:33:00
2017-02-07 11:34:00
2017-02-07 11:35:00
2017-02-07 11:36:00
2017-02-07 11:37:00
2017-02-07 11:38:00
2017-02-07 11:39:00
2017-02-07 11:40:00
2017-02-07 11:41:00
2017-02-07 11:42:00
2017-02-07 11:43:00
2017-02-07 11:44:00
2017-02-07 11:45:00
2017-02-07 11:46:00
2017-02-07 11:47:00
2017-02-07 11:48:00
2017-02-07 11:49:00
2017-02-07 11:50:00
2017-02-07 11:51:00
2017-02-07 11:52:00
2017-02-07 11:53:00
2017-02-07 11:54:00
2017-02-07 11:55:00
2017-02-07 11:56:00
2017-02-07 11:57:00
2017-02-07 11:58:00
2017-02-07 11:59:00
2017-02-07 12:00:00
2017-02-07 12:01:00
2017-02-07 12:02:00
2017-02-07 12:03:00
2017-02-07 12:04:00
2017-02-07 12:05:00
2017-02-07 12:06:00
2017-02-07 12:07:00
2017-02-07 12:08:00
2017-02-07 12:09:00
2017-02-07 12:10:00


2017-02-08 12:02:00
2017-02-08 12:03:00
2017-02-08 12:04:00
2017-02-08 12:05:00
2017-02-08 12:06:00
2017-02-08 12:07:00
2017-02-08 12:08:00
2017-02-08 12:09:00
2017-02-08 12:10:00
2017-02-08 12:11:00
2017-02-08 12:12:00
2017-02-08 12:13:00
2017-02-08 12:14:00
2017-02-08 12:15:00
2017-02-08 12:16:00
2017-02-08 12:17:00
2017-02-08 12:18:00
2017-02-08 12:19:00
2017-02-08 12:20:00
2017-02-08 12:21:00
2017-02-08 12:22:00
2017-02-08 12:23:00
2017-02-08 12:24:00
2017-02-08 12:25:00
2017-02-08 12:26:00
2017-02-08 12:27:00
2017-02-08 12:28:00
2017-02-08 12:29:00
2017-02-08 12:30:00
2017-02-08 12:31:00
2017-02-08 12:32:00
2017-02-08 12:33:00
2017-02-08 12:34:00
2017-02-08 12:35:00
2017-02-08 12:36:00
2017-02-08 12:37:00
2017-02-08 12:38:00
2017-02-08 12:39:00
2017-02-08 12:40:00
2017-02-08 12:41:00
2017-02-08 12:42:00
2017-02-08 12:43:00
2017-02-08 12:44:00
2017-02-08 12:45:00
2017-02-08 12:46:00
2017-02-08 12:47:00
2017-02-08 12:48:00
2017-02-08 12:49:00
2017-02-08 12:50:00
2017-02-08 12:51:00


Info: UWD:  Total Pnl: 1.04%  Profit/Loss Ratio: 1.32  Accuracy: 0.47  Score: 0.13  Normalized Score: 0.96 
Info:  Total Pnl: 258.59%  Score: 0.97  Max Drawdown: 3.06%  RoC: 916.28%  P/L Ratio: 3.31  Accuracy: 0.68  Score: 0.97 


In [4]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData3" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return ['AUZ',
 'DFZ',
 'DVV',
 'EGV',
 'FKI',
 'FUR',
 'GYJ',
 'GYV',
 'HHK',
 'IFL',
 'JSG',
 'KFW',
 'KMV',
 'MAS',
 'OED',
 'PMS',
 'SVG',
 'TGI',
 'UWC',
 'UWD',
 'VKE',
 'VND',
 'VTN',
 'ZEW']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 1,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 2,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AUZ
Processing data for stock: DFZ
Processing data for stock: DVV
Processing data for stock: EGV
Processing data for stock: FKI
Processing data for stock: FUR
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: HHK
Processing data for stock: IFL
Processing data for stock: JSG
Processing data for stock: KFW
Processing data for stock: KMV
Processing data for stock: MAS
Processing data for stock: OED
Processing data for stock: PMS
Processing data for stock: SVG
Processing data for stock: TGI
Processing data for stock: UWC
Processing data for stock: UWD
Processing data for stock: VKE
Processing data for stock: VND
Processing data for stock: VTN
Processing data for stock: ZEW
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-06 09:17:00
2017-01-06 09:18:00
2017-01-06 09:19:00
2017-01-06 09:20:00
2017-01-06 09:21:00
2017-01-06 09:22:00
2017-0

2017-01-06 15:25:00
2017-01-06 15:26:00
2017-01-06 15:27:00
2017-01-06 15:28:00
2017-01-06 15:29:00
2017-01-10 09:17:00
2017-01-10 09:18:00
2017-01-10 09:19:00
2017-01-10 09:20:00
2017-01-10 09:21:00
2017-01-10 09:22:00
2017-01-10 09:23:00
2017-01-10 09:24:00
2017-01-10 09:25:00
2017-01-10 09:26:00
2017-01-10 09:27:00
2017-01-10 09:28:00
2017-01-10 09:29:00
2017-01-10 09:30:00
2017-01-10 09:31:00
2017-01-10 09:32:00
2017-01-10 09:33:00
2017-01-10 09:34:00
2017-01-10 09:35:00
2017-01-10 09:36:00
2017-01-10 09:37:00
2017-01-10 09:38:00
2017-01-10 09:39:00
2017-01-10 09:40:00
2017-01-10 09:41:00
2017-01-10 09:42:00
2017-01-10 09:43:00
2017-01-10 09:44:00
2017-01-10 09:45:00
2017-01-10 09:46:00
2017-01-10 09:47:00
2017-01-10 09:48:00
2017-01-10 09:49:00
2017-01-10 09:50:00
2017-01-10 09:51:00
2017-01-10 09:52:00
2017-01-10 09:53:00
2017-01-10 09:54:00
2017-01-10 09:55:00
2017-01-10 09:56:00
2017-01-10 09:57:00
2017-01-10 09:58:00
2017-01-10 09:59:00
2017-01-10 10:00:00
2017-01-10 10:01:00


2017-01-12 10:26:00
2017-01-12 10:27:00
2017-01-12 10:28:00
2017-01-12 10:29:00
2017-01-12 10:30:00
2017-01-12 10:31:00
2017-01-12 10:32:00
2017-01-12 10:33:00
2017-01-12 10:34:00
2017-01-12 10:35:00
2017-01-12 10:36:00
2017-01-12 10:37:00
2017-01-12 10:38:00
2017-01-12 10:39:00
2017-01-12 10:40:00
2017-01-12 10:41:00
2017-01-12 10:42:00
2017-01-12 10:43:00
2017-01-12 10:44:00
2017-01-12 10:45:00
2017-01-12 10:46:00
2017-01-12 10:47:00
2017-01-12 10:48:00
2017-01-12 10:49:00
2017-01-12 10:50:00
2017-01-12 10:51:00
2017-01-12 10:52:00
2017-01-12 10:53:00
2017-01-12 10:54:00
2017-01-12 10:55:00
2017-01-12 10:56:00
2017-01-12 10:57:00
2017-01-12 10:58:00
2017-01-12 10:59:00
2017-01-12 11:00:00
2017-01-12 11:01:00
2017-01-12 11:02:00
2017-01-12 11:03:00
2017-01-12 11:04:00
2017-01-12 11:05:00
2017-01-12 11:06:00
2017-01-12 11:07:00
2017-01-12 11:08:00
2017-01-12 11:09:00
2017-01-12 11:10:00
2017-01-12 11:11:00
2017-01-12 11:12:00
2017-01-12 11:13:00
2017-01-12 11:14:00
2017-01-12 11:15:00


2017-01-13 11:06:00
2017-01-13 11:07:00
2017-01-13 11:08:00
2017-01-13 11:09:00
2017-01-13 11:10:00
2017-01-13 11:11:00
2017-01-13 11:12:00
2017-01-13 11:13:00
2017-01-13 11:14:00
2017-01-13 11:15:00
2017-01-13 11:16:00
2017-01-13 11:17:00
2017-01-13 11:18:00
2017-01-13 11:19:00
2017-01-13 11:20:00
2017-01-13 11:21:00
2017-01-13 11:22:00
2017-01-13 11:23:00
2017-01-13 11:24:00
2017-01-13 11:25:00
2017-01-13 11:26:00
2017-01-13 11:27:00
2017-01-13 11:28:00
2017-01-13 11:29:00
2017-01-13 11:30:00
2017-01-13 11:31:00
2017-01-13 11:32:00
2017-01-13 11:33:00
2017-01-13 11:34:00
2017-01-13 11:35:00
2017-01-13 11:36:00
2017-01-13 11:37:00
2017-01-13 11:38:00
2017-01-13 11:39:00
2017-01-13 11:40:00
2017-01-13 11:41:00
2017-01-13 11:42:00
2017-01-13 11:43:00
2017-01-13 11:44:00
2017-01-13 11:45:00
2017-01-13 11:46:00
2017-01-13 11:47:00
2017-01-13 11:48:00
2017-01-13 11:49:00
2017-01-13 11:50:00
2017-01-13 11:51:00
2017-01-13 11:52:00
2017-01-13 11:53:00
2017-01-13 11:54:00
2017-01-13 11:55:00


2017-01-17 11:43:00
2017-01-17 11:44:00
2017-01-17 11:45:00
2017-01-17 11:46:00
2017-01-17 11:47:00
2017-01-17 11:48:00
2017-01-17 11:49:00
2017-01-17 11:50:00
2017-01-17 11:51:00
2017-01-17 11:52:00
2017-01-17 11:53:00
2017-01-17 11:54:00
2017-01-17 11:55:00
2017-01-17 11:56:00
2017-01-17 11:57:00
2017-01-17 11:58:00
2017-01-17 11:59:00
2017-01-17 12:00:00
2017-01-17 12:01:00
2017-01-17 12:02:00
2017-01-17 12:03:00
2017-01-17 12:04:00
2017-01-17 12:05:00
2017-01-17 12:06:00
2017-01-17 12:07:00
2017-01-17 12:08:00
2017-01-17 12:09:00
2017-01-17 12:10:00
2017-01-17 12:11:00
2017-01-17 12:12:00
2017-01-17 12:13:00
2017-01-17 12:14:00
2017-01-17 12:15:00
2017-01-17 12:16:00
2017-01-17 12:17:00
2017-01-17 12:18:00
2017-01-17 12:19:00
2017-01-17 12:20:00
2017-01-17 12:21:00
2017-01-17 12:22:00
2017-01-17 12:23:00
2017-01-17 12:24:00
2017-01-17 12:25:00
2017-01-17 12:26:00
2017-01-17 12:27:00
2017-01-17 12:28:00
2017-01-17 12:29:00
2017-01-17 12:30:00
2017-01-17 12:31:00
2017-01-17 12:32:00


...

2017-01-27 09:24:00
2017-01-27 09:25:00
2017-01-27 09:26:00
2017-01-27 09:27:00
2017-01-27 09:28:00
2017-01-27 09:29:00
2017-01-27 09:30:00
2017-01-27 09:31:00
2017-01-27 09:32:00
2017-01-27 09:33:00
2017-01-27 09:34:00
2017-01-27 09:35:00
2017-01-27 09:36:00
2017-01-27 09:37:00
2017-01-27 09:38:00
2017-01-27 09:39:00
2017-01-27 09:40:00
2017-01-27 09:41:00
2017-01-27 09:42:00
2017-01-27 09:43:00
2017-01-27 09:44:00
2017-01-27 09:45:00
2017-01-27 09:46:00
2017-01-27 09:47:00
2017-01-27 09:48:00
2017-01-27 09:49:00
2017-01-27 09:50:00
2017-01-27 09:51:00
2017-01-27 09:52:00
2017-01-27 09:53:00
2017-01-27 09:54:00
2017-01-27 09:55:00
2017-01-27 09:56:00
2017-01-27 09:57:00
2017-01-27 09:58:00
2017-01-27 09:59:00
2017-01-27 10:00:00
2017-01-27 10:01:00
2017-01-27 10:02:00
2017-01-27 10:03:00
2017-01-27 10:04:00
2017-01-27 10:05:00
2017-01-27 10:06:00
2017-01-27 10:07:00
2017-01-27 10:08:00
2017-01-27 10:09:00
2017-01-27 10:10:00
2017-01-27 10:11:00
2017-01-27 10:12:00
2017-01-27 10:13:00


2017-01-30 10:01:00
2017-01-30 10:02:00
2017-01-30 10:03:00
2017-01-30 10:04:00
2017-01-30 10:05:00
2017-01-30 10:06:00
2017-01-30 10:07:00
2017-01-30 10:08:00
2017-01-30 10:09:00
2017-01-30 10:10:00
2017-01-30 10:11:00
2017-01-30 10:12:00
2017-01-30 10:13:00
2017-01-30 10:14:00
2017-01-30 10:15:00
2017-01-30 10:16:00
2017-01-30 10:17:00
2017-01-30 10:18:00
2017-01-30 10:19:00
2017-01-30 10:20:00
2017-01-30 10:21:00
2017-01-30 10:22:00
2017-01-30 10:23:00
2017-01-30 10:24:00
2017-01-30 10:25:00
2017-01-30 10:26:00
2017-01-30 10:27:00
2017-01-30 10:28:00
2017-01-30 10:29:00
2017-01-30 10:30:00
2017-01-30 10:31:00
2017-01-30 10:32:00
2017-01-30 10:33:00
2017-01-30 10:34:00
2017-01-30 10:35:00
2017-01-30 10:36:00
2017-01-30 10:37:00
2017-01-30 10:38:00
2017-01-30 10:39:00
2017-01-30 10:40:00
2017-01-30 10:41:00
2017-01-30 10:42:00
2017-01-30 10:43:00
2017-01-30 10:44:00
2017-01-30 10:45:00
2017-01-30 10:46:00
2017-01-30 10:47:00
2017-01-30 10:48:00
2017-01-30 10:49:00
2017-01-30 10:50:00


2017-01-31 10:39:00
2017-01-31 10:40:00
2017-01-31 10:41:00
2017-01-31 10:42:00
2017-01-31 10:43:00
2017-01-31 10:44:00
2017-01-31 10:45:00
2017-01-31 10:46:00
2017-01-31 10:47:00
2017-01-31 10:48:00
2017-01-31 10:49:00
2017-01-31 10:50:00
2017-01-31 10:51:00
2017-01-31 10:52:00
2017-01-31 10:53:00
2017-01-31 10:54:00
2017-01-31 10:55:00
2017-01-31 10:56:00
2017-01-31 10:57:00
2017-01-31 10:58:00
2017-01-31 10:59:00
2017-01-31 11:00:00
2017-01-31 11:01:00
2017-01-31 11:02:00
2017-01-31 11:03:00
2017-01-31 11:04:00
2017-01-31 11:05:00
2017-01-31 11:06:00
2017-01-31 11:07:00
2017-01-31 11:08:00
2017-01-31 11:09:00
2017-01-31 11:10:00
2017-01-31 11:11:00
2017-01-31 11:12:00
2017-01-31 11:13:00
2017-01-31 11:14:00
2017-01-31 11:15:00
2017-01-31 11:16:00
2017-01-31 11:17:00
2017-01-31 11:18:00
2017-01-31 11:19:00
2017-01-31 11:20:00
2017-01-31 11:21:00
2017-01-31 11:22:00
2017-01-31 11:23:00
2017-01-31 11:24:00
2017-01-31 11:25:00
2017-01-31 11:26:00
2017-01-31 11:27:00
2017-01-31 11:28:00


2017-02-01 11:19:00
2017-02-01 11:20:00
2017-02-01 11:21:00
2017-02-01 11:22:00
2017-02-01 11:23:00
2017-02-01 11:24:00
2017-02-01 11:25:00
2017-02-01 11:26:00
2017-02-01 11:27:00
2017-02-01 11:28:00
2017-02-01 11:29:00
2017-02-01 11:30:00
2017-02-01 11:31:00
2017-02-01 11:32:00
2017-02-01 11:33:00
2017-02-01 11:34:00
2017-02-01 11:35:00
2017-02-01 11:36:00
2017-02-01 11:37:00
2017-02-01 11:38:00
2017-02-01 11:39:00
2017-02-01 11:40:00
2017-02-01 11:41:00
2017-02-01 11:42:00
2017-02-01 11:43:00
2017-02-01 11:44:00
2017-02-01 11:45:00
2017-02-01 11:46:00
2017-02-01 11:47:00
2017-02-01 11:48:00
2017-02-01 11:49:00
2017-02-01 11:50:00
2017-02-01 11:51:00
2017-02-01 11:52:00
2017-02-01 11:53:00
2017-02-01 11:54:00
2017-02-01 11:55:00
2017-02-01 11:56:00
2017-02-01 11:57:00
2017-02-01 11:58:00
2017-02-01 11:59:00
2017-02-01 12:00:00
2017-02-01 12:01:00
2017-02-01 12:02:00
2017-02-01 12:03:00
2017-02-01 12:04:00
2017-02-01 12:05:00
2017-02-01 12:06:00
2017-02-01 12:07:00
2017-02-01 12:08:00


2017-02-02 11:59:00
Info: FUR:  Total Pnl: 38.34%  Profit/Loss Ratio: 2.00  Accuracy: 0.48  Score: 0.52  Normalized Score: 0.97 
Info: EGV:  Total Pnl: 9.63%  Profit/Loss Ratio: 1.63  Accuracy: 0.48  Score: 0.27  Normalized Score: 0.98 
Info: KMV:  Total Pnl: 2.40%  Profit/Loss Ratio: 2.12  Accuracy: 0.49  Score: 0.12  Normalized Score: 0.94 
Info: IFL:  Total Pnl: 25.12%  Profit/Loss Ratio: 1.45  Accuracy: 0.47  Score: 0.57  Normalized Score: 0.99 
Info: DVV:  Total Pnl: 4.10%  Profit/Loss Ratio: 1.63  Accuracy: 0.47  Score: 0.20  Normalized Score: 0.93 
Info: KFW:  Total Pnl: 36.90%  Profit/Loss Ratio: 2.23  Accuracy: 0.49  Score: 0.44  Normalized Score: 0.95 
Info: VND:  Total Pnl: 9.22%  Profit/Loss Ratio: 1.69  Accuracy: 0.47  Score: 0.26  Normalized Score: 0.98 
Info: PMS:  Total Pnl: 3.12%  Profit/Loss Ratio: 1.67  Accuracy: 0.49  Score: 0.15  Normalized Score: 0.98 
Info: GYJ:  Total Pnl: 22.50%  Profit/Loss Ratio: 1.76  Accuracy: 0.47  Score: 0.40  Normalized Score: 0.98 
Info

In [9]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData1" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return ['AUZ',
 'DFZ',
 'DVV',
 #'EGV',
 #'FKI',
 'FUR',
 'GYJ',
 'GYV',
 #'HHK',
 'IFL',
 'JSG',
 'KFW',
 'KMV',
 'MAS',
 'OED',
 'PMS',
 'SVG',
 'TGI',
 'UWC',
 'UWD',
 'VKE',
 'VND',
 'VTN',
 #'ZEW'
               ]

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 1,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 2,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AUZ
Processing data for stock: DFZ
Processing data for stock: DVV
Processing data for stock: FUR
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: IFL
Processing data for stock: JSG
Processing data for stock: KFW
Processing data for stock: KMV
Processing data for stock: MAS
Processing data for stock: OED
Processing data for stock: PMS
Processing data for stock: SVG
Processing data for stock: TGI
Processing data for stock: UWC
Processing data for stock: UWD
Processing data for stock: VKE
Processing data for stock: VND
Processing data for stock: VTN
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-06 09:17:00
2017-01-06 09:18:00
2017-01-06 09:19:00
2017-01-06 09:20:00
2017-01-06 09:21:00
2017-01-06 09:22:00
2017-01-06 09:23:00
2017-01-06 09:24:00
2017-01-06 09:25:00
2017-01-06 09:26:00
2017-01-06 09:27:00
2017-01-06 09:28:00
2017-01-06

2017-01-09 09:20:00
2017-01-09 09:21:00
2017-01-09 09:22:00
2017-01-09 09:23:00
2017-01-09 09:24:00
2017-01-09 09:25:00
2017-01-09 09:26:00
2017-01-09 09:27:00
2017-01-09 09:28:00
2017-01-09 09:29:00
2017-01-09 09:30:00
2017-01-09 09:31:00
2017-01-09 09:32:00
2017-01-09 09:33:00
2017-01-09 09:34:00
2017-01-09 09:35:00
2017-01-09 09:36:00
2017-01-09 09:37:00
2017-01-09 09:38:00
2017-01-09 09:39:00
2017-01-09 09:40:00
2017-01-09 09:41:00
2017-01-09 09:42:00
2017-01-09 09:43:00
2017-01-09 09:44:00
2017-01-09 09:45:00
2017-01-09 09:46:00
2017-01-09 09:47:00
2017-01-09 09:48:00
2017-01-09 09:49:00
2017-01-09 09:50:00
2017-01-09 09:51:00
2017-01-09 09:52:00
2017-01-09 09:53:00
2017-01-09 09:54:00
2017-01-09 09:55:00
2017-01-09 09:56:00
2017-01-09 09:57:00
2017-01-09 09:58:00
2017-01-09 09:59:00
2017-01-09 10:00:00
2017-01-09 10:01:00
2017-01-09 10:02:00
2017-01-09 10:03:00
2017-01-09 10:04:00
2017-01-09 10:05:00
2017-01-09 10:06:00
2017-01-09 10:07:00
2017-01-09 10:08:00
2017-01-09 10:09:00


2017-01-10 09:58:00
2017-01-10 09:59:00
2017-01-10 10:00:00
2017-01-10 10:01:00
2017-01-10 10:02:00
2017-01-10 10:03:00
2017-01-10 10:04:00
2017-01-10 10:05:00
2017-01-10 10:06:00
2017-01-10 10:07:00
2017-01-10 10:08:00
2017-01-10 10:09:00
2017-01-10 10:10:00
2017-01-10 10:11:00
2017-01-10 10:12:00
2017-01-10 10:13:00
2017-01-10 10:14:00
2017-01-10 10:15:00
2017-01-10 10:16:00
2017-01-10 10:17:00
2017-01-10 10:18:00
2017-01-10 10:19:00
2017-01-10 10:20:00
2017-01-10 10:21:00
2017-01-10 10:22:00
2017-01-10 10:23:00
2017-01-10 10:24:00
2017-01-10 10:25:00
2017-01-10 10:26:00
2017-01-10 10:27:00
2017-01-10 10:28:00
2017-01-10 10:29:00
2017-01-10 10:30:00
2017-01-10 10:31:00
2017-01-10 10:32:00
2017-01-10 10:33:00
2017-01-10 10:34:00
2017-01-10 10:35:00
2017-01-10 10:36:00
2017-01-10 10:37:00
2017-01-10 10:38:00
2017-01-10 10:39:00
2017-01-10 10:40:00
2017-01-10 10:41:00
2017-01-10 10:42:00
2017-01-10 10:43:00
2017-01-10 10:44:00
2017-01-10 10:45:00
2017-01-10 10:46:00
2017-01-10 10:47:00


2017-01-11 10:36:00
2017-01-11 10:37:00
2017-01-11 10:38:00
2017-01-11 10:39:00
2017-01-11 10:40:00
2017-01-11 10:41:00
2017-01-11 10:42:00
2017-01-11 10:43:00
2017-01-11 10:44:00
2017-01-11 10:45:00
2017-01-11 10:46:00
2017-01-11 10:47:00
2017-01-11 10:48:00
2017-01-11 10:49:00
2017-01-11 10:50:00
2017-01-11 10:51:00
2017-01-11 10:52:00
2017-01-11 10:53:00
2017-01-11 10:54:00
2017-01-11 10:55:00
2017-01-11 10:56:00
2017-01-11 10:57:00
2017-01-11 10:58:00
2017-01-11 10:59:00
2017-01-11 11:00:00
2017-01-11 11:01:00
2017-01-11 11:02:00
2017-01-11 11:03:00
2017-01-11 11:04:00
2017-01-11 11:05:00
2017-01-11 11:06:00
2017-01-11 11:07:00
2017-01-11 11:08:00
2017-01-11 11:09:00
2017-01-11 11:10:00
2017-01-11 11:11:00
2017-01-11 11:12:00
2017-01-11 11:13:00
2017-01-11 11:14:00
2017-01-11 11:15:00
2017-01-11 11:16:00
2017-01-11 11:17:00
2017-01-11 11:18:00
2017-01-11 11:19:00
2017-01-11 11:20:00
2017-01-11 11:21:00
2017-01-11 11:22:00
2017-01-11 11:23:00
2017-01-11 11:24:00
2017-01-11 11:25:00


2017-01-12 11:15:00
2017-01-12 11:16:00
2017-01-12 11:17:00
2017-01-12 11:18:00
2017-01-12 11:19:00
2017-01-12 11:20:00
2017-01-12 11:21:00
2017-01-12 11:22:00
2017-01-12 11:23:00
2017-01-12 11:24:00
2017-01-12 11:25:00
2017-01-12 11:26:00
2017-01-12 11:27:00
2017-01-12 11:28:00
2017-01-12 11:29:00
2017-01-12 11:30:00
2017-01-12 11:31:00
2017-01-12 11:32:00
2017-01-12 11:33:00
2017-01-12 11:34:00
2017-01-12 11:35:00
2017-01-12 11:36:00
2017-01-12 11:37:00
2017-01-12 11:38:00
2017-01-12 11:39:00
2017-01-12 11:40:00
2017-01-12 11:41:00
2017-01-12 11:42:00
2017-01-12 11:43:00
2017-01-12 11:44:00
2017-01-12 11:45:00
2017-01-12 11:46:00
2017-01-12 11:47:00
2017-01-12 11:48:00
2017-01-12 11:49:00
2017-01-12 11:50:00
2017-01-12 11:51:00
2017-01-12 11:52:00
2017-01-12 11:53:00
2017-01-12 11:54:00
2017-01-12 11:55:00
2017-01-12 11:56:00
2017-01-12 11:57:00
2017-01-12 11:58:00
2017-01-12 11:59:00
2017-01-12 12:00:00
2017-01-12 12:01:00
2017-01-12 12:02:00
2017-01-12 12:03:00
2017-01-12 12:04:00


...

2017-02-01 13:26:00
2017-02-01 13:27:00
2017-02-01 13:28:00
2017-02-01 13:29:00
2017-02-01 13:30:00
2017-02-01 13:31:00
2017-02-01 13:32:00
2017-02-01 13:33:00
2017-02-01 13:34:00
2017-02-01 13:35:00
2017-02-01 13:36:00
2017-02-01 13:37:00
2017-02-01 13:38:00
2017-02-01 13:39:00
2017-02-01 13:40:00
2017-02-01 13:41:00
2017-02-01 13:42:00
2017-02-01 13:43:00
2017-02-01 13:44:00
2017-02-01 13:45:00
2017-02-01 13:46:00
2017-02-01 13:47:00
2017-02-01 13:48:00
2017-02-01 13:49:00
2017-02-01 13:50:00
2017-02-01 13:51:00
2017-02-01 13:52:00
2017-02-01 13:53:00
2017-02-01 13:54:00
2017-02-01 13:55:00
2017-02-01 13:56:00
2017-02-01 13:57:00
2017-02-01 13:58:00
2017-02-01 13:59:00
2017-02-01 14:00:00
2017-02-01 14:01:00
2017-02-01 14:02:00
2017-02-01 14:03:00
2017-02-01 14:04:00
2017-02-01 14:05:00
2017-02-01 14:06:00
2017-02-01 14:07:00
2017-02-01 14:08:00
2017-02-01 14:09:00
2017-02-01 14:10:00
2017-02-01 14:11:00
2017-02-01 14:12:00
2017-02-01 14:13:00
2017-02-01 14:14:00
2017-02-01 14:15:00


2017-02-02 14:03:00
2017-02-02 14:04:00
2017-02-02 14:05:00
2017-02-02 14:06:00
2017-02-02 14:07:00
2017-02-02 14:08:00
2017-02-02 14:09:00
2017-02-02 14:10:00
2017-02-02 14:11:00
2017-02-02 14:12:00
2017-02-02 14:13:00
2017-02-02 14:14:00
2017-02-02 14:15:00
2017-02-02 14:16:00
2017-02-02 14:17:00
2017-02-02 14:18:00
2017-02-02 14:19:00
2017-02-02 14:20:00
2017-02-02 14:21:00
2017-02-02 14:22:00
2017-02-02 14:23:00
2017-02-02 14:24:00
2017-02-02 14:25:00
2017-02-02 14:26:00
2017-02-02 14:27:00
2017-02-02 14:28:00
2017-02-02 14:29:00
2017-02-02 14:30:00
2017-02-02 14:31:00
2017-02-02 14:32:00
2017-02-02 14:33:00
2017-02-02 14:34:00
2017-02-02 14:35:00
2017-02-02 14:36:00
2017-02-02 14:37:00
2017-02-02 14:38:00
2017-02-02 14:39:00
2017-02-02 14:40:00
2017-02-02 14:41:00
2017-02-02 14:42:00
2017-02-02 14:43:00
2017-02-02 14:44:00
2017-02-02 14:45:00
2017-02-02 14:46:00
2017-02-02 14:47:00
2017-02-02 14:48:00
2017-02-02 14:49:00
2017-02-02 14:50:00
2017-02-02 14:51:00
2017-02-02 14:52:00


2017-02-03 14:43:00
2017-02-03 14:44:00
2017-02-03 14:45:00
2017-02-03 14:46:00
2017-02-03 14:47:00
2017-02-03 14:48:00
2017-02-03 14:49:00
2017-02-03 14:50:00
2017-02-03 14:51:00
2017-02-03 14:52:00
2017-02-03 14:53:00
2017-02-03 14:54:00
2017-02-03 14:55:00
2017-02-03 14:56:00
2017-02-03 14:57:00
2017-02-03 14:58:00
2017-02-03 14:59:00
2017-02-03 15:00:00
2017-02-03 15:01:00
2017-02-03 15:02:00
2017-02-03 15:03:00
2017-02-03 15:04:00
2017-02-03 15:05:00
2017-02-03 15:06:00
2017-02-03 15:07:00
2017-02-03 15:08:00
2017-02-03 15:09:00
2017-02-03 15:10:00
2017-02-03 15:11:00
2017-02-03 15:12:00
2017-02-03 15:13:00
2017-02-03 15:14:00
2017-02-03 15:15:00
2017-02-03 15:16:00
2017-02-03 15:17:00
2017-02-03 15:18:00
2017-02-03 15:19:00
2017-02-03 15:20:00
2017-02-03 15:21:00
2017-02-03 15:22:00
2017-02-03 15:23:00
2017-02-03 15:24:00
2017-02-03 15:25:00
2017-02-03 15:26:00
2017-02-03 15:27:00
2017-02-03 15:28:00
2017-02-03 15:29:00
2017-02-07 09:17:00
2017-02-07 09:18:00
2017-02-07 09:19:00


2017-02-07 15:22:00
2017-02-07 15:23:00
2017-02-07 15:24:00
2017-02-07 15:25:00
2017-02-07 15:26:00
2017-02-07 15:27:00
2017-02-07 15:28:00
2017-02-07 15:29:00
2017-02-08 09:17:00
2017-02-08 09:18:00
2017-02-08 09:19:00
2017-02-08 09:20:00
2017-02-08 09:21:00
2017-02-08 09:22:00
2017-02-08 09:23:00
2017-02-08 09:24:00
2017-02-08 09:25:00
2017-02-08 09:26:00
2017-02-08 09:27:00
2017-02-08 09:28:00
2017-02-08 09:29:00
2017-02-08 09:30:00
2017-02-08 09:31:00
2017-02-08 09:32:00
2017-02-08 09:33:00
2017-02-08 09:34:00
2017-02-08 09:35:00
2017-02-08 09:36:00
2017-02-08 09:37:00
2017-02-08 09:38:00
2017-02-08 09:39:00
2017-02-08 09:40:00
2017-02-08 09:41:00
2017-02-08 09:42:00
2017-02-08 09:43:00
2017-02-08 09:44:00
2017-02-08 09:45:00
2017-02-08 09:46:00
2017-02-08 09:47:00
2017-02-08 09:48:00
2017-02-08 09:49:00
2017-02-08 09:50:00
2017-02-08 09:51:00
2017-02-08 09:52:00
2017-02-08 09:53:00
2017-02-08 09:54:00
2017-02-08 09:55:00
2017-02-08 09:56:00
2017-02-08 09:57:00
2017-02-08 09:58:00


2017-02-09 09:49:00
2017-02-09 09:50:00
2017-02-09 09:51:00
2017-02-09 09:52:00
2017-02-09 09:53:00
2017-02-09 09:54:00
2017-02-09 09:55:00
2017-02-09 09:56:00
2017-02-09 09:57:00
2017-02-09 09:58:00
2017-02-09 09:59:00
2017-02-09 10:00:00
2017-02-09 10:01:00
2017-02-09 10:02:00
2017-02-09 10:03:00
2017-02-09 10:04:00
2017-02-09 10:05:00
2017-02-09 10:06:00
2017-02-09 10:07:00
2017-02-09 10:08:00
2017-02-09 10:09:00
2017-02-09 10:10:00
2017-02-09 10:11:00
2017-02-09 10:12:00
2017-02-09 10:13:00
2017-02-09 10:14:00
2017-02-09 10:15:00
2017-02-09 10:16:00
2017-02-09 10:17:00
2017-02-09 10:18:00
2017-02-09 10:19:00
2017-02-09 10:20:00
2017-02-09 10:21:00
2017-02-09 10:22:00
2017-02-09 10:23:00
2017-02-09 10:24:00
2017-02-09 10:25:00
2017-02-09 10:26:00
2017-02-09 10:27:00
2017-02-09 10:28:00
2017-02-09 10:29:00
2017-02-09 10:30:00
2017-02-09 10:31:00
2017-02-09 10:32:00
2017-02-09 10:33:00
2017-02-09 10:34:00
2017-02-09 10:35:00
2017-02-09 10:36:00
2017-02-09 10:37:00
2017-02-09 10:38:00


In [10]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData2" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return ['AUZ',
 'DFZ',
 'DVV',
 #'EGV',
 #'FKI',
 'FUR',
 'GYJ',
 'GYV',
 #'HHK',
 'IFL',
 'JSG',
 'KFW',
 'KMV',
 'MAS',
 'OED',
 'PMS',
 'SVG',
 'TGI',
 'UWC',
 'UWD',
 'VKE',
 'VND',
 'VTN',
 #'ZEW'
               ]

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 1,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 2,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AUZ
Processing data for stock: DFZ
Processing data for stock: DVV
Processing data for stock: FUR
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: IFL
Processing data for stock: JSG
Processing data for stock: KFW
Processing data for stock: KMV
Processing data for stock: MAS
Processing data for stock: OED
Processing data for stock: PMS
Processing data for stock: SVG
Processing data for stock: TGI
Processing data for stock: UWC
Processing data for stock: UWD
Processing data for stock: VKE
Processing data for stock: VND
Processing data for stock: VTN
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-13 09:17:00
2017-01-13 09:18:00
2017-01-13 09:19:00
2017-01-13 09:20:00
2017-01-13 09:21:00
2017-01-13 09:22:00
2017-01-13 09:23:00
2017-01-13 09:24:00
2017-01-13 09:25:00
2017-01-13 09:26:00
2017-01-13 09:27:00
2017-01-13 09:28:00
2017-01-13

2017-01-16 09:18:00
2017-01-16 09:19:00
2017-01-16 09:20:00
2017-01-16 09:21:00
2017-01-16 09:22:00
2017-01-16 09:23:00
2017-01-16 09:24:00
2017-01-16 09:25:00
2017-01-16 09:26:00
2017-01-16 09:27:00
2017-01-16 09:28:00
2017-01-16 09:29:00
2017-01-16 09:30:00
2017-01-16 09:31:00
2017-01-16 09:32:00
2017-01-16 09:33:00
2017-01-16 09:34:00
2017-01-16 09:35:00
2017-01-16 09:36:00
2017-01-16 09:37:00
2017-01-16 09:38:00
2017-01-16 09:39:00
2017-01-16 09:40:00
2017-01-16 09:41:00
2017-01-16 09:42:00
2017-01-16 09:43:00
2017-01-16 09:44:00
2017-01-16 09:45:00
2017-01-16 09:46:00
2017-01-16 09:47:00
2017-01-16 09:48:00
2017-01-16 09:49:00
2017-01-16 09:50:00
2017-01-16 09:51:00
2017-01-16 09:52:00
2017-01-16 09:53:00
2017-01-16 09:54:00
2017-01-16 09:55:00
2017-01-16 09:56:00
2017-01-16 09:57:00
2017-01-16 09:58:00
2017-01-16 09:59:00
2017-01-16 10:00:00
2017-01-16 10:01:00
2017-01-16 10:02:00
2017-01-16 10:03:00
2017-01-16 10:04:00
2017-01-16 10:05:00
2017-01-16 10:06:00
2017-01-16 10:07:00


2017-01-18 09:57:00
2017-01-18 09:58:00
2017-01-18 09:59:00
2017-01-18 10:00:00
2017-01-18 10:01:00
2017-01-18 10:02:00
2017-01-18 10:03:00
2017-01-18 10:04:00
2017-01-18 10:05:00
2017-01-18 10:06:00
2017-01-18 10:07:00
2017-01-18 10:08:00
2017-01-18 10:09:00
2017-01-18 10:10:00
2017-01-18 10:11:00
2017-01-18 10:12:00
2017-01-18 10:13:00
2017-01-18 10:14:00
2017-01-18 10:15:00
2017-01-18 10:16:00
2017-01-18 10:17:00
2017-01-18 10:18:00
2017-01-18 10:19:00
2017-01-18 10:20:00
2017-01-18 10:21:00
2017-01-18 10:22:00
2017-01-18 10:23:00
2017-01-18 10:24:00
2017-01-18 10:25:00
2017-01-18 10:26:00
2017-01-18 10:27:00
2017-01-18 10:28:00
2017-01-18 10:29:00
2017-01-18 10:30:00
2017-01-18 10:31:00
2017-01-18 10:32:00
2017-01-18 10:33:00
2017-01-18 10:34:00
2017-01-18 10:35:00
2017-01-18 10:36:00
2017-01-18 10:37:00
2017-01-18 10:38:00
2017-01-18 10:39:00
2017-01-18 10:40:00
2017-01-18 10:41:00
2017-01-18 10:42:00
2017-01-18 10:43:00
2017-01-18 10:44:00
2017-01-18 10:45:00
2017-01-18 10:46:00


2017-01-19 10:38:00
2017-01-19 10:39:00
2017-01-19 10:40:00
2017-01-19 10:41:00
2017-01-19 10:42:00
2017-01-19 10:43:00
2017-01-19 10:44:00
2017-01-19 10:45:00
2017-01-19 10:46:00
2017-01-19 10:47:00
2017-01-19 10:48:00
2017-01-19 10:49:00
2017-01-19 10:50:00
2017-01-19 10:51:00
2017-01-19 10:52:00
2017-01-19 10:53:00
2017-01-19 10:54:00
2017-01-19 10:55:00
2017-01-19 10:56:00
2017-01-19 10:57:00
2017-01-19 10:58:00
2017-01-19 10:59:00
2017-01-19 11:00:00
2017-01-19 11:01:00
2017-01-19 11:02:00
2017-01-19 11:03:00
2017-01-19 11:04:00
2017-01-19 11:05:00
2017-01-19 11:06:00
2017-01-19 11:07:00
2017-01-19 11:08:00
2017-01-19 11:09:00
2017-01-19 11:10:00
2017-01-19 11:11:00
2017-01-19 11:12:00
2017-01-19 11:13:00
2017-01-19 11:14:00
2017-01-19 11:15:00
2017-01-19 11:16:00
2017-01-19 11:17:00
2017-01-19 11:18:00
2017-01-19 11:19:00
2017-01-19 11:20:00
2017-01-19 11:21:00
2017-01-19 11:22:00
2017-01-19 11:23:00
2017-01-19 11:24:00
2017-01-19 11:25:00
2017-01-19 11:26:00
2017-01-19 11:27:00


2017-01-20 11:16:00
2017-01-20 11:17:00
2017-01-20 11:18:00
2017-01-20 11:19:00
2017-01-20 11:20:00
2017-01-20 11:21:00
2017-01-20 11:22:00
2017-01-20 11:23:00
2017-01-20 11:24:00
2017-01-20 11:25:00
2017-01-20 11:26:00
2017-01-20 11:27:00
2017-01-20 11:28:00
2017-01-20 11:29:00
2017-01-20 11:30:00
2017-01-20 11:31:00
2017-01-20 11:32:00
2017-01-20 11:33:00
2017-01-20 11:34:00
2017-01-20 11:35:00
2017-01-20 11:36:00
2017-01-20 11:37:00
2017-01-20 11:38:00
2017-01-20 11:39:00
2017-01-20 11:40:00
2017-01-20 11:41:00
2017-01-20 11:42:00
2017-01-20 11:43:00
2017-01-20 11:44:00
2017-01-20 11:45:00
2017-01-20 11:46:00
2017-01-20 11:47:00
2017-01-20 11:48:00
2017-01-20 11:49:00
2017-01-20 11:50:00
2017-01-20 11:51:00
2017-01-20 11:52:00
2017-01-20 11:53:00
2017-01-20 11:54:00
2017-01-20 11:55:00
2017-01-20 11:56:00
2017-01-20 11:57:00
2017-01-20 11:58:00
2017-01-20 11:59:00
2017-01-20 12:00:00
2017-01-20 12:01:00
2017-01-20 12:02:00
2017-01-20 12:03:00
2017-01-20 12:04:00
2017-01-20 12:05:00


...

2017-02-02 09:32:00
2017-02-02 09:33:00
2017-02-02 09:34:00
2017-02-02 09:35:00
2017-02-02 09:36:00
2017-02-02 09:37:00
2017-02-02 09:38:00
2017-02-02 09:39:00
2017-02-02 09:40:00
2017-02-02 09:41:00
2017-02-02 09:42:00
2017-02-02 09:43:00
2017-02-02 09:44:00
2017-02-02 09:45:00
2017-02-02 09:46:00
2017-02-02 09:47:00
2017-02-02 09:48:00
2017-02-02 09:49:00
2017-02-02 09:50:00
2017-02-02 09:51:00
2017-02-02 09:52:00
2017-02-02 09:53:00
2017-02-02 09:54:00
2017-02-02 09:55:00
2017-02-02 09:56:00
2017-02-02 09:57:00
2017-02-02 09:58:00
2017-02-02 09:59:00
2017-02-02 10:00:00
2017-02-02 10:01:00
2017-02-02 10:02:00
2017-02-02 10:03:00
2017-02-02 10:04:00
2017-02-02 10:05:00
2017-02-02 10:06:00
2017-02-02 10:07:00
2017-02-02 10:08:00
2017-02-02 10:09:00
2017-02-02 10:10:00
2017-02-02 10:11:00
2017-02-02 10:12:00
2017-02-02 10:13:00
2017-02-02 10:14:00
2017-02-02 10:15:00
2017-02-02 10:16:00
2017-02-02 10:17:00
2017-02-02 10:18:00
2017-02-02 10:19:00
2017-02-02 10:20:00
2017-02-02 10:21:00


2017-02-03 10:10:00
2017-02-03 10:11:00
2017-02-03 10:12:00
2017-02-03 10:13:00
2017-02-03 10:14:00
2017-02-03 10:15:00
2017-02-03 10:16:00
2017-02-03 10:17:00
2017-02-03 10:18:00
2017-02-03 10:19:00
2017-02-03 10:20:00
2017-02-03 10:21:00
2017-02-03 10:22:00
2017-02-03 10:23:00
2017-02-03 10:24:00
2017-02-03 10:25:00
2017-02-03 10:26:00
2017-02-03 10:27:00
2017-02-03 10:28:00
2017-02-03 10:29:00
2017-02-03 10:30:00
2017-02-03 10:31:00
2017-02-03 10:32:00
2017-02-03 10:33:00
2017-02-03 10:34:00
2017-02-03 10:35:00
2017-02-03 10:36:00
2017-02-03 10:37:00
2017-02-03 10:38:00
2017-02-03 10:39:00
2017-02-03 10:40:00
2017-02-03 10:41:00
2017-02-03 10:42:00
2017-02-03 10:43:00
2017-02-03 10:44:00
2017-02-03 10:45:00
2017-02-03 10:46:00
2017-02-03 10:47:00
2017-02-03 10:48:00
2017-02-03 10:49:00
2017-02-03 10:50:00
2017-02-03 10:51:00
2017-02-03 10:52:00
2017-02-03 10:53:00
2017-02-03 10:54:00
2017-02-03 10:55:00
2017-02-03 10:56:00
2017-02-03 10:57:00
2017-02-03 10:58:00
2017-02-03 10:59:00


2017-02-06 10:48:00
2017-02-06 10:49:00
2017-02-06 10:50:00
2017-02-06 10:51:00
2017-02-06 10:52:00
2017-02-06 10:53:00
2017-02-06 10:54:00
2017-02-06 10:55:00
2017-02-06 10:56:00
2017-02-06 10:57:00
2017-02-06 10:58:00
2017-02-06 10:59:00
2017-02-06 11:00:00
2017-02-06 11:01:00
2017-02-06 11:02:00
2017-02-06 11:03:00
2017-02-06 11:04:00
2017-02-06 11:05:00
2017-02-06 11:06:00
2017-02-06 11:07:00
2017-02-06 11:08:00
2017-02-06 11:09:00
2017-02-06 11:10:00
2017-02-06 11:11:00
2017-02-06 11:12:00
2017-02-06 11:13:00
2017-02-06 11:14:00
2017-02-06 11:15:00
2017-02-06 11:16:00
2017-02-06 11:17:00
2017-02-06 11:18:00
2017-02-06 11:19:00
2017-02-06 11:20:00
2017-02-06 11:21:00
2017-02-06 11:22:00
2017-02-06 11:23:00
2017-02-06 11:24:00
2017-02-06 11:25:00
2017-02-06 11:26:00
2017-02-06 11:27:00
2017-02-06 11:28:00
2017-02-06 11:29:00
2017-02-06 11:30:00
2017-02-06 11:31:00
2017-02-06 11:32:00
2017-02-06 11:33:00
2017-02-06 11:34:00
2017-02-06 11:35:00
2017-02-06 11:36:00
2017-02-06 11:37:00


2017-02-07 11:27:00
2017-02-07 11:28:00
2017-02-07 11:29:00
2017-02-07 11:30:00
2017-02-07 11:31:00
2017-02-07 11:32:00
2017-02-07 11:33:00
2017-02-07 11:34:00
2017-02-07 11:35:00
2017-02-07 11:36:00
2017-02-07 11:37:00
2017-02-07 11:38:00
2017-02-07 11:39:00
2017-02-07 11:40:00
2017-02-07 11:41:00
2017-02-07 11:42:00
2017-02-07 11:43:00
2017-02-07 11:44:00
2017-02-07 11:45:00
2017-02-07 11:46:00
2017-02-07 11:47:00
2017-02-07 11:48:00
2017-02-07 11:49:00
2017-02-07 11:50:00
2017-02-07 11:51:00
2017-02-07 11:52:00
2017-02-07 11:53:00
2017-02-07 11:54:00
2017-02-07 11:55:00
2017-02-07 11:56:00
2017-02-07 11:57:00
2017-02-07 11:58:00
2017-02-07 11:59:00
2017-02-07 12:00:00
2017-02-07 12:01:00
2017-02-07 12:02:00
2017-02-07 12:03:00
2017-02-07 12:04:00
2017-02-07 12:05:00
2017-02-07 12:06:00
2017-02-07 12:07:00
2017-02-07 12:08:00
2017-02-07 12:09:00
2017-02-07 12:10:00
2017-02-07 12:11:00
2017-02-07 12:12:00
2017-02-07 12:13:00
2017-02-07 12:14:00
2017-02-07 12:15:00
2017-02-07 12:16:00


2017-02-08 12:05:00
2017-02-08 12:06:00
2017-02-08 12:07:00
2017-02-08 12:08:00
2017-02-08 12:09:00
2017-02-08 12:10:00
2017-02-08 12:11:00
2017-02-08 12:12:00
2017-02-08 12:13:00
2017-02-08 12:14:00
2017-02-08 12:15:00
2017-02-08 12:16:00
2017-02-08 12:17:00
2017-02-08 12:18:00
2017-02-08 12:19:00
2017-02-08 12:20:00
2017-02-08 12:21:00
2017-02-08 12:22:00
2017-02-08 12:23:00
2017-02-08 12:24:00
2017-02-08 12:25:00
2017-02-08 12:26:00
2017-02-08 12:27:00
2017-02-08 12:28:00
2017-02-08 12:29:00
2017-02-08 12:30:00
2017-02-08 12:31:00
2017-02-08 12:32:00
2017-02-08 12:33:00
2017-02-08 12:34:00
2017-02-08 12:35:00
2017-02-08 12:36:00
2017-02-08 12:37:00
2017-02-08 12:38:00
2017-02-08 12:39:00
2017-02-08 12:40:00
2017-02-08 12:41:00
2017-02-08 12:42:00
2017-02-08 12:43:00
2017-02-08 12:44:00
2017-02-08 12:45:00
2017-02-08 12:46:00
2017-02-08 12:47:00
2017-02-08 12:48:00
2017-02-08 12:49:00
2017-02-08 12:50:00
2017-02-08 12:51:00
2017-02-08 12:52:00
2017-02-08 12:53:00
2017-02-08 12:54:00


In [11]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData3" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return ['AUZ',
 'DFZ',
 'DVV',
 #'EGV',
 #'FKI',
 'FUR',
 'GYJ',
 'GYV',
 #'HHK',
 'IFL',
 'JSG',
 'KFW',
 'KMV',
 'MAS',
 'OED',
 'PMS',
 'SVG',
 'TGI',
 'UWC',
 'UWD',
 'VKE',
 'VND',
 'VTN',
 #'ZEW'
               ]

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 1,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 2,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: AUZ
Processing data for stock: DFZ
Processing data for stock: DVV
Processing data for stock: FUR
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: IFL
Processing data for stock: JSG
Processing data for stock: KFW
Processing data for stock: KMV
Processing data for stock: MAS
Processing data for stock: OED
Processing data for stock: PMS
Processing data for stock: SVG
Processing data for stock: TGI
Processing data for stock: UWC
Processing data for stock: UWD
Processing data for stock: VKE
Processing data for stock: VND
Processing data for stock: VTN
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-06 09:17:00
2017-01-06 09:18:00
2017-01-06 09:19:00
2017-01-06 09:20:00
2017-01-06 09:21:00
2017-01-06 09:22:00
2017-01-06 09:23:00
2017-01-06 09:24:00
2017-01-06 09:25:00
2017-01-06 09:26:00
2017-01-06 09:27:00
2017-01-06 09:28:00
2017-01-06

2017-01-10 09:20:00
2017-01-10 09:21:00
2017-01-10 09:22:00
2017-01-10 09:23:00
2017-01-10 09:24:00
2017-01-10 09:25:00
2017-01-10 09:26:00
2017-01-10 09:27:00
2017-01-10 09:28:00
2017-01-10 09:29:00
2017-01-10 09:30:00
2017-01-10 09:31:00
2017-01-10 09:32:00
2017-01-10 09:33:00
2017-01-10 09:34:00
2017-01-10 09:35:00
2017-01-10 09:36:00
2017-01-10 09:37:00
2017-01-10 09:38:00
2017-01-10 09:39:00
2017-01-10 09:40:00
2017-01-10 09:41:00
2017-01-10 09:42:00
2017-01-10 09:43:00
2017-01-10 09:44:00
2017-01-10 09:45:00
2017-01-10 09:46:00
2017-01-10 09:47:00
2017-01-10 09:48:00
2017-01-10 09:49:00
2017-01-10 09:50:00
2017-01-10 09:51:00
2017-01-10 09:52:00
2017-01-10 09:53:00
2017-01-10 09:54:00
2017-01-10 09:55:00
2017-01-10 09:56:00
2017-01-10 09:57:00
2017-01-10 09:58:00
2017-01-10 09:59:00
2017-01-10 10:00:00
2017-01-10 10:01:00
2017-01-10 10:02:00
2017-01-10 10:03:00
2017-01-10 10:04:00
2017-01-10 10:05:00
2017-01-10 10:06:00
2017-01-10 10:07:00
2017-01-10 10:08:00
2017-01-10 10:09:00


2017-01-11 09:57:00
2017-01-11 09:58:00
2017-01-11 09:59:00
2017-01-11 10:00:00
2017-01-11 10:01:00
2017-01-11 10:02:00
2017-01-11 10:03:00
2017-01-11 10:04:00
2017-01-11 10:05:00
2017-01-11 10:06:00
2017-01-11 10:07:00
2017-01-11 10:08:00
2017-01-11 10:09:00
2017-01-11 10:10:00
2017-01-11 10:11:00
2017-01-11 10:12:00
2017-01-11 10:13:00
2017-01-11 10:14:00
2017-01-11 10:15:00
2017-01-11 10:16:00
2017-01-11 10:17:00
2017-01-11 10:18:00
2017-01-11 10:19:00
2017-01-11 10:20:00
2017-01-11 10:21:00
2017-01-11 10:22:00
2017-01-11 10:23:00
2017-01-11 10:24:00
2017-01-11 10:25:00
2017-01-11 10:26:00
2017-01-11 10:27:00
2017-01-11 10:28:00
2017-01-11 10:29:00
2017-01-11 10:30:00
2017-01-11 10:31:00
2017-01-11 10:32:00
2017-01-11 10:33:00
2017-01-11 10:34:00
2017-01-11 10:35:00
2017-01-11 10:36:00
2017-01-11 10:37:00
2017-01-11 10:38:00
2017-01-11 10:39:00
2017-01-11 10:40:00
2017-01-11 10:41:00
2017-01-11 10:42:00
2017-01-11 10:43:00
2017-01-11 10:44:00
2017-01-11 10:45:00
2017-01-11 10:46:00


2017-01-12 10:34:00
2017-01-12 10:35:00
2017-01-12 10:36:00
2017-01-12 10:37:00
2017-01-12 10:38:00
2017-01-12 10:39:00
2017-01-12 10:40:00
2017-01-12 10:41:00
2017-01-12 10:42:00
2017-01-12 10:43:00
2017-01-12 10:44:00
2017-01-12 10:45:00
2017-01-12 10:46:00
2017-01-12 10:47:00
2017-01-12 10:48:00
2017-01-12 10:49:00
2017-01-12 10:50:00
2017-01-12 10:51:00
2017-01-12 10:52:00
2017-01-12 10:53:00
2017-01-12 10:54:00
2017-01-12 10:55:00
2017-01-12 10:56:00
2017-01-12 10:57:00
2017-01-12 10:58:00
2017-01-12 10:59:00
2017-01-12 11:00:00
2017-01-12 11:01:00
2017-01-12 11:02:00
2017-01-12 11:03:00
2017-01-12 11:04:00
2017-01-12 11:05:00
2017-01-12 11:06:00
2017-01-12 11:07:00
2017-01-12 11:08:00
2017-01-12 11:09:00
2017-01-12 11:10:00
2017-01-12 11:11:00
2017-01-12 11:12:00
2017-01-12 11:13:00
2017-01-12 11:14:00
2017-01-12 11:15:00
2017-01-12 11:16:00
2017-01-12 11:17:00
2017-01-12 11:18:00
2017-01-12 11:19:00
2017-01-12 11:20:00
2017-01-12 11:21:00
2017-01-12 11:22:00
2017-01-12 11:23:00


2017-01-13 11:11:00
2017-01-13 11:12:00
2017-01-13 11:13:00
2017-01-13 11:14:00
2017-01-13 11:15:00
2017-01-13 11:16:00
2017-01-13 11:17:00
2017-01-13 11:18:00
2017-01-13 11:19:00
2017-01-13 11:20:00
2017-01-13 11:21:00
2017-01-13 11:22:00
2017-01-13 11:23:00
2017-01-13 11:24:00
2017-01-13 11:25:00
2017-01-13 11:26:00
2017-01-13 11:27:00
2017-01-13 11:28:00
2017-01-13 11:29:00
2017-01-13 11:30:00
2017-01-13 11:31:00
2017-01-13 11:32:00
2017-01-13 11:33:00
2017-01-13 11:34:00
2017-01-13 11:35:00
2017-01-13 11:36:00
2017-01-13 11:37:00
2017-01-13 11:38:00
2017-01-13 11:39:00
2017-01-13 11:40:00
2017-01-13 11:41:00
2017-01-13 11:42:00
2017-01-13 11:43:00
2017-01-13 11:44:00
2017-01-13 11:45:00
2017-01-13 11:46:00
2017-01-13 11:47:00
2017-01-13 11:48:00
2017-01-13 11:49:00
2017-01-13 11:50:00
2017-01-13 11:51:00
2017-01-13 11:52:00
2017-01-13 11:53:00
2017-01-13 11:54:00
2017-01-13 11:55:00
2017-01-13 11:56:00
2017-01-13 11:57:00
2017-01-13 11:58:00
2017-01-13 11:59:00
2017-01-13 12:00:00


...

2017-01-27 09:26:00
2017-01-27 09:27:00
2017-01-27 09:28:00
2017-01-27 09:29:00
2017-01-27 09:30:00
2017-01-27 09:31:00
2017-01-27 09:32:00
2017-01-27 09:33:00
2017-01-27 09:34:00
2017-01-27 09:35:00
2017-01-27 09:36:00
2017-01-27 09:37:00
2017-01-27 09:38:00
2017-01-27 09:39:00
2017-01-27 09:40:00
2017-01-27 09:41:00
2017-01-27 09:42:00
2017-01-27 09:43:00
2017-01-27 09:44:00
2017-01-27 09:45:00
2017-01-27 09:46:00
2017-01-27 09:47:00
2017-01-27 09:48:00
2017-01-27 09:49:00
2017-01-27 09:50:00
2017-01-27 09:51:00
2017-01-27 09:52:00
2017-01-27 09:53:00
2017-01-27 09:54:00
2017-01-27 09:55:00
2017-01-27 09:56:00
2017-01-27 09:57:00
2017-01-27 09:58:00
2017-01-27 09:59:00
2017-01-27 10:00:00
2017-01-27 10:01:00
2017-01-27 10:02:00
2017-01-27 10:03:00
2017-01-27 10:04:00
2017-01-27 10:05:00
2017-01-27 10:06:00
2017-01-27 10:07:00
2017-01-27 10:08:00
2017-01-27 10:09:00
2017-01-27 10:10:00
2017-01-27 10:11:00
2017-01-27 10:12:00
2017-01-27 10:13:00
2017-01-27 10:14:00
2017-01-27 10:15:00


2017-01-30 10:04:00
2017-01-30 10:05:00
2017-01-30 10:06:00
2017-01-30 10:07:00
2017-01-30 10:08:00
2017-01-30 10:09:00
2017-01-30 10:10:00
2017-01-30 10:11:00
2017-01-30 10:12:00
2017-01-30 10:13:00
2017-01-30 10:14:00
2017-01-30 10:15:00
2017-01-30 10:16:00
2017-01-30 10:17:00
2017-01-30 10:18:00
2017-01-30 10:19:00
2017-01-30 10:20:00
2017-01-30 10:21:00
2017-01-30 10:22:00
2017-01-30 10:23:00
2017-01-30 10:24:00
2017-01-30 10:25:00
2017-01-30 10:26:00
2017-01-30 10:27:00
2017-01-30 10:28:00
2017-01-30 10:29:00
2017-01-30 10:30:00
2017-01-30 10:31:00
2017-01-30 10:32:00
2017-01-30 10:33:00
2017-01-30 10:34:00
2017-01-30 10:35:00
2017-01-30 10:36:00
2017-01-30 10:37:00
2017-01-30 10:38:00
2017-01-30 10:39:00
2017-01-30 10:40:00
2017-01-30 10:41:00
2017-01-30 10:42:00
2017-01-30 10:43:00
2017-01-30 10:44:00
2017-01-30 10:45:00
2017-01-30 10:46:00
2017-01-30 10:47:00
2017-01-30 10:48:00
2017-01-30 10:49:00
2017-01-30 10:50:00
2017-01-30 10:51:00
2017-01-30 10:52:00
2017-01-30 10:53:00


2017-01-31 10:41:00
2017-01-31 10:42:00
2017-01-31 10:43:00
2017-01-31 10:44:00
2017-01-31 10:45:00
2017-01-31 10:46:00
2017-01-31 10:47:00
2017-01-31 10:48:00
2017-01-31 10:49:00
2017-01-31 10:50:00
2017-01-31 10:51:00
2017-01-31 10:52:00
2017-01-31 10:53:00
2017-01-31 10:54:00
2017-01-31 10:55:00
2017-01-31 10:56:00
2017-01-31 10:57:00
2017-01-31 10:58:00
2017-01-31 10:59:00
2017-01-31 11:00:00
2017-01-31 11:01:00
2017-01-31 11:02:00
2017-01-31 11:03:00
2017-01-31 11:04:00
2017-01-31 11:05:00
2017-01-31 11:06:00
2017-01-31 11:07:00
2017-01-31 11:08:00
2017-01-31 11:09:00
2017-01-31 11:10:00
2017-01-31 11:11:00
2017-01-31 11:12:00
2017-01-31 11:13:00
2017-01-31 11:14:00
2017-01-31 11:15:00
2017-01-31 11:16:00
2017-01-31 11:17:00
2017-01-31 11:18:00
2017-01-31 11:19:00
2017-01-31 11:20:00
2017-01-31 11:21:00
2017-01-31 11:22:00
2017-01-31 11:23:00
2017-01-31 11:24:00
2017-01-31 11:25:00
2017-01-31 11:26:00
2017-01-31 11:27:00
2017-01-31 11:28:00
2017-01-31 11:29:00
2017-01-31 11:30:00


2017-02-01 11:20:00
2017-02-01 11:21:00
2017-02-01 11:22:00
2017-02-01 11:23:00
2017-02-01 11:24:00
2017-02-01 11:25:00
2017-02-01 11:26:00
2017-02-01 11:27:00
2017-02-01 11:28:00
2017-02-01 11:29:00
2017-02-01 11:30:00
2017-02-01 11:31:00
2017-02-01 11:32:00
2017-02-01 11:33:00
2017-02-01 11:34:00
2017-02-01 11:35:00
2017-02-01 11:36:00
2017-02-01 11:37:00
2017-02-01 11:38:00
2017-02-01 11:39:00
2017-02-01 11:40:00
2017-02-01 11:41:00
2017-02-01 11:42:00
2017-02-01 11:43:00
2017-02-01 11:44:00
2017-02-01 11:45:00
2017-02-01 11:46:00
2017-02-01 11:47:00
2017-02-01 11:48:00
2017-02-01 11:49:00
2017-02-01 11:50:00
2017-02-01 11:51:00
2017-02-01 11:52:00
2017-02-01 11:53:00
2017-02-01 11:54:00
2017-02-01 11:55:00
2017-02-01 11:56:00
2017-02-01 11:57:00
2017-02-01 11:58:00
2017-02-01 11:59:00
2017-02-01 12:00:00
2017-02-01 12:01:00
2017-02-01 12:02:00
2017-02-01 12:03:00
2017-02-01 12:04:00
2017-02-01 12:05:00
2017-02-01 12:06:00
2017-02-01 12:07:00
2017-02-01 12:08:00
2017-02-01 12:09:00


Info: KFW:  Total Pnl: 44.28%  Profit/Loss Ratio: 2.23  Accuracy: 0.49  Score: 0.44  Normalized Score: 0.95 
Info: MAS:  Total Pnl: 15.38%  Profit/Loss Ratio: 1.67  Accuracy: 0.47  Score: 0.31  Normalized Score: 0.97 
Info: AUZ:  Total Pnl: 5.30%  Profit/Loss Ratio: 1.82  Accuracy: 0.47  Score: 0.19  Normalized Score: 0.93 
Info: FUR:  Total Pnl: 46.01%  Profit/Loss Ratio: 2.00  Accuracy: 0.48  Score: 0.52  Normalized Score: 0.97 
Info: DFZ:  Total Pnl: 16.37%  Profit/Loss Ratio: 1.75  Accuracy: 0.46  Score: 0.30  Normalized Score: 0.95 
Info: VND:  Total Pnl: 11.06%  Profit/Loss Ratio: 1.69  Accuracy: 0.47  Score: 0.26  Normalized Score: 0.98 
Info: SVG:  Total Pnl: 13.36%  Profit/Loss Ratio: 1.78  Accuracy: 0.47  Score: 0.26  Normalized Score: 0.96 
Info: PMS:  Total Pnl: 3.74%  Profit/Loss Ratio: 1.67  Accuracy: 0.49  Score: 0.15  Normalized Score: 0.98 
Info: KMV:  Total Pnl: 2.88%  Profit/Loss Ratio: 2.12  Accuracy: 0.49  Score: 0.12  Normalized Score: 0.94 
Info: GYJ:  Total Pnl:

In [7]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData1" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return ['DFZ',
 'EGV',
 'FKI',
 'FUR',
 'GYJ',
 'GYV',
 'HHK',
 'IFL',
 'JSG',
 'KFW',
 'KMV',
 'LDU',
 'MAS',
 'MQK',
 'OED',
 'SVG',
 'TGI',
 'UWC',
 'UWD',
 'VKE',
 'VND',
 'VTN']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 1,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 1,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: DFZ
Processing data for stock: EGV
Processing data for stock: FKI
Processing data for stock: FUR
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: HHK
Processing data for stock: IFL
Processing data for stock: JSG
Processing data for stock: KFW
Processing data for stock: KMV
Processing data for stock: LDU
Processing data for stock: MAS
Processing data for stock: MQK
Processing data for stock: OED
Processing data for stock: SVG
Processing data for stock: TGI
Processing data for stock: UWC
Processing data for stock: UWD
Processing data for stock: VKE
Processing data for stock: VND
Processing data for stock: VTN
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-06 09:17:00
2017-01-06 09:18:00
2017-01-06 09:19:00
2017-01-06 09:20:00
2017-01-06 09:21:00
2017-01-06 09:22:00
2017-01-06 09:23:00
2017-01-06 09:24:00
2017-01-06 09:25:00
2017-01-

2017-01-09 09:17:00
2017-01-09 09:18:00
2017-01-09 09:19:00
2017-01-09 09:20:00
2017-01-09 09:21:00
2017-01-09 09:22:00
2017-01-09 09:23:00
2017-01-09 09:24:00
2017-01-09 09:25:00
2017-01-09 09:26:00
2017-01-09 09:27:00
2017-01-09 09:28:00
2017-01-09 09:29:00
2017-01-09 09:30:00
2017-01-09 09:31:00
2017-01-09 09:32:00
2017-01-09 09:33:00
2017-01-09 09:34:00
2017-01-09 09:35:00
2017-01-09 09:36:00
2017-01-09 09:37:00
2017-01-09 09:38:00
2017-01-09 09:39:00
2017-01-09 09:40:00
2017-01-09 09:41:00
2017-01-09 09:42:00
2017-01-09 09:43:00
2017-01-09 09:44:00
2017-01-09 09:45:00
2017-01-09 09:46:00
2017-01-09 09:47:00
2017-01-09 09:48:00
2017-01-09 09:49:00
2017-01-09 09:50:00
2017-01-09 09:51:00
2017-01-09 09:52:00
2017-01-09 09:53:00
2017-01-09 09:54:00
2017-01-09 09:55:00
2017-01-09 09:56:00
2017-01-09 09:57:00
2017-01-09 09:58:00
2017-01-09 09:59:00
2017-01-09 10:00:00
2017-01-09 10:01:00
2017-01-09 10:02:00
2017-01-09 10:03:00
2017-01-09 10:04:00
2017-01-09 10:05:00
2017-01-09 10:06:00


2017-01-10 09:56:00
2017-01-10 09:57:00
2017-01-10 09:58:00
2017-01-10 09:59:00
2017-01-10 10:00:00
2017-01-10 10:01:00
2017-01-10 10:02:00
2017-01-10 10:03:00
2017-01-10 10:04:00
2017-01-10 10:05:00
2017-01-10 10:06:00
2017-01-10 10:07:00
2017-01-10 10:08:00
2017-01-10 10:09:00
2017-01-10 10:10:00
2017-01-10 10:11:00
2017-01-10 10:12:00
2017-01-10 10:13:00
2017-01-10 10:14:00
2017-01-10 10:15:00
2017-01-10 10:16:00
2017-01-10 10:17:00
2017-01-10 10:18:00
2017-01-10 10:19:00
2017-01-10 10:20:00
2017-01-10 10:21:00
2017-01-10 10:22:00
2017-01-10 10:23:00
2017-01-10 10:24:00
2017-01-10 10:25:00
2017-01-10 10:26:00
2017-01-10 10:27:00
2017-01-10 10:28:00
2017-01-10 10:29:00
2017-01-10 10:30:00
2017-01-10 10:31:00
2017-01-10 10:32:00
2017-01-10 10:33:00
2017-01-10 10:34:00
2017-01-10 10:35:00
2017-01-10 10:36:00
2017-01-10 10:37:00
2017-01-10 10:38:00
2017-01-10 10:39:00
2017-01-10 10:40:00
2017-01-10 10:41:00
2017-01-10 10:42:00
2017-01-10 10:43:00
2017-01-10 10:44:00
2017-01-10 10:45:00


2017-01-11 10:36:00
2017-01-11 10:37:00
2017-01-11 10:38:00
2017-01-11 10:39:00
2017-01-11 10:40:00
2017-01-11 10:41:00
2017-01-11 10:42:00
2017-01-11 10:43:00
2017-01-11 10:44:00
2017-01-11 10:45:00
2017-01-11 10:46:00
2017-01-11 10:47:00
2017-01-11 10:48:00
2017-01-11 10:49:00
2017-01-11 10:50:00
2017-01-11 10:51:00
2017-01-11 10:52:00
2017-01-11 10:53:00
2017-01-11 10:54:00
2017-01-11 10:55:00
2017-01-11 10:56:00
2017-01-11 10:57:00
2017-01-11 10:58:00
2017-01-11 10:59:00
2017-01-11 11:00:00
2017-01-11 11:01:00
2017-01-11 11:02:00
2017-01-11 11:03:00
2017-01-11 11:04:00
2017-01-11 11:05:00
2017-01-11 11:06:00
2017-01-11 11:07:00
2017-01-11 11:08:00
2017-01-11 11:09:00
2017-01-11 11:10:00
2017-01-11 11:11:00
2017-01-11 11:12:00
2017-01-11 11:13:00
2017-01-11 11:14:00
2017-01-11 11:15:00
2017-01-11 11:16:00
2017-01-11 11:17:00
2017-01-11 11:18:00
2017-01-11 11:19:00
2017-01-11 11:20:00
2017-01-11 11:21:00
2017-01-11 11:22:00
2017-01-11 11:23:00
2017-01-11 11:24:00
2017-01-11 11:25:00


2017-01-12 11:13:00
2017-01-12 11:14:00
2017-01-12 11:15:00
2017-01-12 11:16:00
2017-01-12 11:17:00
2017-01-12 11:18:00
2017-01-12 11:19:00
2017-01-12 11:20:00
2017-01-12 11:21:00
2017-01-12 11:22:00
2017-01-12 11:23:00
2017-01-12 11:24:00
2017-01-12 11:25:00
2017-01-12 11:26:00
2017-01-12 11:27:00
2017-01-12 11:28:00
2017-01-12 11:29:00
2017-01-12 11:30:00
2017-01-12 11:31:00
2017-01-12 11:32:00
2017-01-12 11:33:00
2017-01-12 11:34:00
2017-01-12 11:35:00
2017-01-12 11:36:00
2017-01-12 11:37:00
2017-01-12 11:38:00
2017-01-12 11:39:00
2017-01-12 11:40:00
2017-01-12 11:41:00
2017-01-12 11:42:00
2017-01-12 11:43:00
2017-01-12 11:44:00
2017-01-12 11:45:00
2017-01-12 11:46:00
2017-01-12 11:47:00
2017-01-12 11:48:00
2017-01-12 11:49:00
2017-01-12 11:50:00
2017-01-12 11:51:00
2017-01-12 11:52:00
2017-01-12 11:53:00
2017-01-12 11:54:00
2017-01-12 11:55:00
2017-01-12 11:56:00
2017-01-12 11:57:00
2017-01-12 11:58:00
2017-01-12 11:59:00
2017-01-12 12:00:00
2017-01-12 12:01:00
2017-01-12 12:02:00


...

2017-01-31 12:41:00
2017-01-31 12:42:00
2017-01-31 12:43:00
2017-01-31 12:44:00
2017-01-31 12:45:00
2017-01-31 12:46:00
2017-01-31 12:47:00
2017-01-31 12:48:00
2017-01-31 12:49:00
2017-01-31 12:50:00
2017-01-31 12:51:00
2017-01-31 12:52:00
2017-01-31 12:53:00
2017-01-31 12:54:00
2017-01-31 12:55:00
2017-01-31 12:56:00
2017-01-31 12:57:00
2017-01-31 12:58:00
2017-01-31 12:59:00
2017-01-31 13:00:00
2017-01-31 13:01:00
2017-01-31 13:02:00
2017-01-31 13:03:00
2017-01-31 13:04:00
2017-01-31 13:05:00
2017-01-31 13:06:00
2017-01-31 13:07:00
2017-01-31 13:08:00
2017-01-31 13:09:00
2017-01-31 13:10:00
2017-01-31 13:11:00
2017-01-31 13:12:00
2017-01-31 13:13:00
2017-01-31 13:14:00
2017-01-31 13:15:00
2017-01-31 13:16:00
2017-01-31 13:17:00
2017-01-31 13:18:00
2017-01-31 13:19:00
2017-01-31 13:20:00
2017-01-31 13:21:00
2017-01-31 13:22:00
2017-01-31 13:23:00
2017-01-31 13:24:00
2017-01-31 13:25:00
2017-01-31 13:26:00
2017-01-31 13:27:00
2017-01-31 13:28:00
2017-01-31 13:29:00
2017-01-31 13:30:00


2017-02-01 13:20:00
2017-02-01 13:21:00
2017-02-01 13:22:00
2017-02-01 13:23:00
2017-02-01 13:24:00
2017-02-01 13:25:00
2017-02-01 13:26:00
2017-02-01 13:27:00
2017-02-01 13:28:00
2017-02-01 13:29:00
2017-02-01 13:30:00
2017-02-01 13:31:00
2017-02-01 13:32:00
2017-02-01 13:33:00
2017-02-01 13:34:00
2017-02-01 13:35:00
2017-02-01 13:36:00
2017-02-01 13:37:00
2017-02-01 13:38:00
2017-02-01 13:39:00
2017-02-01 13:40:00
2017-02-01 13:41:00
2017-02-01 13:42:00
2017-02-01 13:43:00
2017-02-01 13:44:00
2017-02-01 13:45:00
2017-02-01 13:46:00
2017-02-01 13:47:00
2017-02-01 13:48:00
2017-02-01 13:49:00
2017-02-01 13:50:00
2017-02-01 13:51:00
2017-02-01 13:52:00
2017-02-01 13:53:00
2017-02-01 13:54:00
2017-02-01 13:55:00
2017-02-01 13:56:00
2017-02-01 13:57:00
2017-02-01 13:58:00
2017-02-01 13:59:00
2017-02-01 14:00:00
2017-02-01 14:01:00
2017-02-01 14:02:00
2017-02-01 14:03:00
2017-02-01 14:04:00
2017-02-01 14:05:00
2017-02-01 14:06:00
2017-02-01 14:07:00
2017-02-01 14:08:00
2017-02-01 14:09:00


2017-02-03 14:35:00
2017-02-03 14:36:00
2017-02-03 14:37:00
2017-02-03 14:38:00
2017-02-03 14:39:00
2017-02-03 14:40:00
2017-02-03 14:41:00
2017-02-03 14:42:00
2017-02-03 14:43:00
2017-02-03 14:44:00
2017-02-03 14:45:00
2017-02-03 14:46:00
2017-02-03 14:47:00
2017-02-03 14:48:00
2017-02-03 14:49:00
2017-02-03 14:50:00
2017-02-03 14:51:00
2017-02-03 14:52:00
2017-02-03 14:53:00
2017-02-03 14:54:00
2017-02-03 14:55:00
2017-02-03 14:56:00
2017-02-03 14:57:00
2017-02-03 14:58:00
2017-02-03 14:59:00
2017-02-03 15:00:00
2017-02-03 15:01:00
2017-02-03 15:02:00
2017-02-03 15:03:00
2017-02-03 15:04:00
2017-02-03 15:05:00
2017-02-03 15:06:00
2017-02-03 15:07:00
2017-02-03 15:08:00
2017-02-03 15:09:00
2017-02-03 15:10:00
2017-02-03 15:11:00
2017-02-03 15:12:00
2017-02-03 15:13:00
2017-02-03 15:14:00
2017-02-03 15:15:00
2017-02-03 15:16:00
2017-02-03 15:17:00
2017-02-03 15:18:00
2017-02-03 15:19:00
2017-02-03 15:20:00
2017-02-03 15:21:00
2017-02-03 15:22:00
2017-02-03 15:23:00
2017-02-03 15:24:00


2017-02-07 15:16:00
2017-02-07 15:17:00
2017-02-07 15:18:00
2017-02-07 15:19:00
2017-02-07 15:20:00
2017-02-07 15:21:00
2017-02-07 15:22:00
2017-02-07 15:23:00
2017-02-07 15:24:00
2017-02-07 15:25:00
2017-02-07 15:26:00
2017-02-07 15:27:00
2017-02-07 15:28:00
2017-02-07 15:29:00
2017-02-08 09:17:00
2017-02-08 09:18:00
2017-02-08 09:19:00
2017-02-08 09:20:00
2017-02-08 09:21:00
2017-02-08 09:22:00
2017-02-08 09:23:00
2017-02-08 09:24:00
2017-02-08 09:25:00
2017-02-08 09:26:00
2017-02-08 09:27:00
2017-02-08 09:28:00
2017-02-08 09:29:00
2017-02-08 09:30:00
2017-02-08 09:31:00
2017-02-08 09:32:00
2017-02-08 09:33:00
2017-02-08 09:34:00
2017-02-08 09:35:00
2017-02-08 09:36:00
2017-02-08 09:37:00
2017-02-08 09:38:00
2017-02-08 09:39:00
2017-02-08 09:40:00
2017-02-08 09:41:00
2017-02-08 09:42:00
2017-02-08 09:43:00
2017-02-08 09:44:00
2017-02-08 09:45:00
2017-02-08 09:46:00
2017-02-08 09:47:00
2017-02-08 09:48:00
2017-02-08 09:49:00
2017-02-08 09:50:00
2017-02-08 09:51:00
2017-02-08 09:52:00


2017-02-09 09:42:00
2017-02-09 09:43:00
2017-02-09 09:44:00
2017-02-09 09:45:00
2017-02-09 09:46:00
2017-02-09 09:47:00
2017-02-09 09:48:00
2017-02-09 09:49:00
2017-02-09 09:50:00
2017-02-09 09:51:00
2017-02-09 09:52:00
2017-02-09 09:53:00
2017-02-09 09:54:00
2017-02-09 09:55:00
2017-02-09 09:56:00
2017-02-09 09:57:00
2017-02-09 09:58:00
2017-02-09 09:59:00
2017-02-09 10:00:00
2017-02-09 10:01:00
2017-02-09 10:02:00
2017-02-09 10:03:00
2017-02-09 10:04:00
2017-02-09 10:05:00
2017-02-09 10:06:00
2017-02-09 10:07:00
2017-02-09 10:08:00
2017-02-09 10:09:00
2017-02-09 10:10:00
2017-02-09 10:11:00
2017-02-09 10:12:00
2017-02-09 10:13:00
2017-02-09 10:14:00
2017-02-09 10:15:00
2017-02-09 10:16:00
2017-02-09 10:17:00
2017-02-09 10:18:00
2017-02-09 10:19:00
2017-02-09 10:20:00
2017-02-09 10:21:00
2017-02-09 10:22:00
2017-02-09 10:23:00
2017-02-09 10:24:00
2017-02-09 10:25:00
2017-02-09 10:26:00
2017-02-09 10:27:00
2017-02-09 10:28:00
2017-02-09 10:29:00
2017-02-09 10:30:00
2017-02-09 10:31:00


In [1]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData2" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return ['DFZ',
 'EGV',
 'FKI',
 'FUR',
 'GYJ',
 'GYV',
 'HHK',
 'IFL',
 'JSG',
 'KFW',
 'KMV',
 'LDU',
 'MAS',
 'MQK',
 'OED',
 'SVG',
 'TGI',
 'UWC',
 'UWD',
 'VKE',
 'VND',
 'VTN']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 1,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 1,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: DFZ
Processing data for stock: EGV
Processing data for stock: FKI
Processing data for stock: FUR
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: HHK
Processing data for stock: IFL
Processing data for stock: JSG
Processing data for stock: KFW
Processing data for stock: KMV
Processing data for stock: LDU
Processing data for stock: MAS
Processing data for stock: MQK
Processing data for stock: OED
Processing data for stock: SVG
Processing data for stock: TGI
Processing data for stock: UWC
Processing data for stock: UWD
Processing data for stock: VKE
Processing data for stock: VND
Processing data for stock: VTN
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-13 09:17:00
2017-01-13 09:18:00
2017-01-13 09:19:00
2017-01-13 09:20:00
2017-01-13 09:21:00
2017-01-13 09:22:00
2017-01-13 09:23:00
2017-01-13 09:24:00
2017-01-13 09:25:00
2017-01-

2017-01-13 15:27:00
2017-01-13 15:28:00
2017-01-13 15:29:00
2017-01-16 09:17:00
2017-01-16 09:18:00
2017-01-16 09:19:00
2017-01-16 09:20:00
2017-01-16 09:21:00
2017-01-16 09:22:00
2017-01-16 09:23:00
2017-01-16 09:24:00
2017-01-16 09:25:00
2017-01-16 09:26:00
2017-01-16 09:27:00
2017-01-16 09:28:00
2017-01-16 09:29:00
2017-01-16 09:30:00
2017-01-16 09:31:00
2017-01-16 09:32:00
2017-01-16 09:33:00
2017-01-16 09:34:00
2017-01-16 09:35:00
2017-01-16 09:36:00
2017-01-16 09:37:00
2017-01-16 09:38:00
2017-01-16 09:39:00
2017-01-16 09:40:00
2017-01-16 09:41:00
2017-01-16 09:42:00
2017-01-16 09:43:00
2017-01-16 09:44:00
2017-01-16 09:45:00
2017-01-16 09:46:00
2017-01-16 09:47:00
2017-01-16 09:48:00
2017-01-16 09:49:00
2017-01-16 09:50:00
2017-01-16 09:51:00
2017-01-16 09:52:00
2017-01-16 09:53:00
2017-01-16 09:54:00
2017-01-16 09:55:00
2017-01-16 09:56:00
2017-01-16 09:57:00
2017-01-16 09:58:00
2017-01-16 09:59:00
2017-01-16 10:00:00
2017-01-16 10:01:00
2017-01-16 10:02:00
2017-01-16 10:03:00


2017-01-18 09:51:00
2017-01-18 09:52:00
2017-01-18 09:53:00
2017-01-18 09:54:00
2017-01-18 09:55:00
2017-01-18 09:56:00
2017-01-18 09:57:00
2017-01-18 09:58:00
2017-01-18 09:59:00
2017-01-18 10:00:00
2017-01-18 10:01:00
2017-01-18 10:02:00
2017-01-18 10:03:00
2017-01-18 10:04:00
2017-01-18 10:05:00
2017-01-18 10:06:00
2017-01-18 10:07:00
2017-01-18 10:08:00
2017-01-18 10:09:00
2017-01-18 10:10:00
2017-01-18 10:11:00
2017-01-18 10:12:00
2017-01-18 10:13:00
2017-01-18 10:14:00
2017-01-18 10:15:00
2017-01-18 10:16:00
2017-01-18 10:17:00
2017-01-18 10:18:00
2017-01-18 10:19:00
2017-01-18 10:20:00
2017-01-18 10:21:00
2017-01-18 10:22:00
2017-01-18 10:23:00
2017-01-18 10:24:00
2017-01-18 10:25:00
2017-01-18 10:26:00
2017-01-18 10:27:00
2017-01-18 10:28:00
2017-01-18 10:29:00
2017-01-18 10:30:00
2017-01-18 10:31:00
2017-01-18 10:32:00
2017-01-18 10:33:00
2017-01-18 10:34:00
2017-01-18 10:35:00
2017-01-18 10:36:00
2017-01-18 10:37:00
2017-01-18 10:38:00
2017-01-18 10:39:00
2017-01-18 10:40:00


2017-01-19 10:31:00
2017-01-19 10:32:00
2017-01-19 10:33:00
2017-01-19 10:34:00
2017-01-19 10:35:00
2017-01-19 10:36:00
2017-01-19 10:37:00
2017-01-19 10:38:00
2017-01-19 10:39:00
2017-01-19 10:40:00
2017-01-19 10:41:00
2017-01-19 10:42:00
2017-01-19 10:43:00
2017-01-19 10:44:00
2017-01-19 10:45:00
2017-01-19 10:46:00
2017-01-19 10:47:00
2017-01-19 10:48:00
2017-01-19 10:49:00
2017-01-19 10:50:00
2017-01-19 10:51:00
2017-01-19 10:52:00
2017-01-19 10:53:00
2017-01-19 10:54:00
2017-01-19 10:55:00
2017-01-19 10:56:00
2017-01-19 10:57:00
2017-01-19 10:58:00
2017-01-19 10:59:00
2017-01-19 11:00:00
2017-01-19 11:01:00
2017-01-19 11:02:00
2017-01-19 11:03:00
2017-01-19 11:04:00
2017-01-19 11:05:00
2017-01-19 11:06:00
2017-01-19 11:07:00
2017-01-19 11:08:00
2017-01-19 11:09:00
2017-01-19 11:10:00
2017-01-19 11:11:00
2017-01-19 11:12:00
2017-01-19 11:13:00
2017-01-19 11:14:00
2017-01-19 11:15:00
2017-01-19 11:16:00
2017-01-19 11:17:00
2017-01-19 11:18:00
2017-01-19 11:19:00
2017-01-19 11:20:00


2017-01-20 11:11:00
2017-01-20 11:12:00
2017-01-20 11:13:00
2017-01-20 11:14:00
2017-01-20 11:15:00
2017-01-20 11:16:00
2017-01-20 11:17:00
2017-01-20 11:18:00
2017-01-20 11:19:00
2017-01-20 11:20:00
2017-01-20 11:21:00
2017-01-20 11:22:00
2017-01-20 11:23:00
2017-01-20 11:24:00
2017-01-20 11:25:00
2017-01-20 11:26:00
2017-01-20 11:27:00
2017-01-20 11:28:00
2017-01-20 11:29:00
2017-01-20 11:30:00
2017-01-20 11:31:00
2017-01-20 11:32:00
2017-01-20 11:33:00
2017-01-20 11:34:00
2017-01-20 11:35:00
2017-01-20 11:36:00
2017-01-20 11:37:00
2017-01-20 11:38:00
2017-01-20 11:39:00
2017-01-20 11:40:00
2017-01-20 11:41:00
2017-01-20 11:42:00
2017-01-20 11:43:00
2017-01-20 11:44:00
2017-01-20 11:45:00
2017-01-20 11:46:00
2017-01-20 11:47:00
2017-01-20 11:48:00
2017-01-20 11:49:00
2017-01-20 11:50:00
2017-01-20 11:51:00
2017-01-20 11:52:00
2017-01-20 11:53:00
2017-01-20 11:54:00
2017-01-20 11:55:00
2017-01-20 11:56:00
2017-01-20 11:57:00
2017-01-20 11:58:00
2017-01-20 11:59:00
2017-01-20 12:00:00


...

2017-02-02 09:25:00
2017-02-02 09:26:00
2017-02-02 09:27:00
2017-02-02 09:28:00
2017-02-02 09:29:00
2017-02-02 09:30:00
2017-02-02 09:31:00
2017-02-02 09:32:00
2017-02-02 09:33:00
2017-02-02 09:34:00
2017-02-02 09:35:00
2017-02-02 09:36:00
2017-02-02 09:37:00
2017-02-02 09:38:00
2017-02-02 09:39:00
2017-02-02 09:40:00
2017-02-02 09:41:00
2017-02-02 09:42:00
2017-02-02 09:43:00
2017-02-02 09:44:00
2017-02-02 09:45:00
2017-02-02 09:46:00
2017-02-02 09:47:00
2017-02-02 09:48:00
2017-02-02 09:49:00
2017-02-02 09:50:00
2017-02-02 09:51:00
2017-02-02 09:52:00
2017-02-02 09:53:00
2017-02-02 09:54:00
2017-02-02 09:55:00
2017-02-02 09:56:00
2017-02-02 09:57:00
2017-02-02 09:58:00
2017-02-02 09:59:00
2017-02-02 10:00:00
2017-02-02 10:01:00
2017-02-02 10:02:00
2017-02-02 10:03:00
2017-02-02 10:04:00
2017-02-02 10:05:00
2017-02-02 10:06:00
2017-02-02 10:07:00
2017-02-02 10:08:00
2017-02-02 10:09:00
2017-02-02 10:10:00
2017-02-02 10:11:00
2017-02-02 10:12:00
2017-02-02 10:13:00
2017-02-02 10:14:00


2017-02-03 10:04:00
2017-02-03 10:05:00
2017-02-03 10:06:00
2017-02-03 10:07:00
2017-02-03 10:08:00
2017-02-03 10:09:00
2017-02-03 10:10:00
2017-02-03 10:11:00
2017-02-03 10:12:00
2017-02-03 10:13:00
2017-02-03 10:14:00
2017-02-03 10:15:00
2017-02-03 10:16:00
2017-02-03 10:17:00
2017-02-03 10:18:00
2017-02-03 10:19:00
2017-02-03 10:20:00
2017-02-03 10:21:00
2017-02-03 10:22:00
2017-02-03 10:23:00
2017-02-03 10:24:00
2017-02-03 10:25:00
2017-02-03 10:26:00
2017-02-03 10:27:00
2017-02-03 10:28:00
2017-02-03 10:29:00
2017-02-03 10:30:00
2017-02-03 10:31:00
2017-02-03 10:32:00
2017-02-03 10:33:00
2017-02-03 10:34:00
2017-02-03 10:35:00
2017-02-03 10:36:00
2017-02-03 10:37:00
2017-02-03 10:38:00
2017-02-03 10:39:00
2017-02-03 10:40:00
2017-02-03 10:41:00
2017-02-03 10:42:00
2017-02-03 10:43:00
2017-02-03 10:44:00
2017-02-03 10:45:00
2017-02-03 10:46:00
2017-02-03 10:47:00
2017-02-03 10:48:00
2017-02-03 10:49:00
2017-02-03 10:50:00
2017-02-03 10:51:00
2017-02-03 10:52:00
2017-02-03 10:53:00


2017-02-06 10:43:00
2017-02-06 10:44:00
2017-02-06 10:45:00
2017-02-06 10:46:00
2017-02-06 10:47:00
2017-02-06 10:48:00
2017-02-06 10:49:00
2017-02-06 10:50:00
2017-02-06 10:51:00
2017-02-06 10:52:00
2017-02-06 10:53:00
2017-02-06 10:54:00
2017-02-06 10:55:00
2017-02-06 10:56:00
2017-02-06 10:57:00
2017-02-06 10:58:00
2017-02-06 10:59:00
2017-02-06 11:00:00
2017-02-06 11:01:00
2017-02-06 11:02:00
2017-02-06 11:03:00
2017-02-06 11:04:00
2017-02-06 11:05:00
2017-02-06 11:06:00
2017-02-06 11:07:00
2017-02-06 11:08:00
2017-02-06 11:09:00
2017-02-06 11:10:00
2017-02-06 11:11:00
2017-02-06 11:12:00
2017-02-06 11:13:00
2017-02-06 11:14:00
2017-02-06 11:15:00
2017-02-06 11:16:00
2017-02-06 11:17:00
2017-02-06 11:18:00
2017-02-06 11:19:00
2017-02-06 11:20:00
2017-02-06 11:21:00
2017-02-06 11:22:00
2017-02-06 11:23:00
2017-02-06 11:24:00
2017-02-06 11:25:00
2017-02-06 11:26:00
2017-02-06 11:27:00
2017-02-06 11:28:00
2017-02-06 11:29:00
2017-02-06 11:30:00
2017-02-06 11:31:00
2017-02-06 11:32:00


2017-02-07 11:21:00
2017-02-07 11:22:00
2017-02-07 11:23:00
2017-02-07 11:24:00
2017-02-07 11:25:00
2017-02-07 11:26:00
2017-02-07 11:27:00
2017-02-07 11:28:00
2017-02-07 11:29:00
2017-02-07 11:30:00
2017-02-07 11:31:00
2017-02-07 11:32:00
2017-02-07 11:33:00
2017-02-07 11:34:00
2017-02-07 11:35:00
2017-02-07 11:36:00
2017-02-07 11:37:00
2017-02-07 11:38:00
2017-02-07 11:39:00
2017-02-07 11:40:00
2017-02-07 11:41:00
2017-02-07 11:42:00
2017-02-07 11:43:00
2017-02-07 11:44:00
2017-02-07 11:45:00
2017-02-07 11:46:00
2017-02-07 11:47:00
2017-02-07 11:48:00
2017-02-07 11:49:00
2017-02-07 11:50:00
2017-02-07 11:51:00
2017-02-07 11:52:00
2017-02-07 11:53:00
2017-02-07 11:54:00
2017-02-07 11:55:00
2017-02-07 11:56:00
2017-02-07 11:57:00
2017-02-07 11:58:00
2017-02-07 11:59:00
2017-02-07 12:00:00
2017-02-07 12:01:00
2017-02-07 12:02:00
2017-02-07 12:03:00
2017-02-07 12:04:00
2017-02-07 12:05:00
2017-02-07 12:06:00
2017-02-07 12:07:00
2017-02-07 12:08:00
2017-02-07 12:09:00
2017-02-07 12:10:00


2017-02-08 12:01:00
2017-02-08 12:02:00
2017-02-08 12:03:00
2017-02-08 12:04:00
2017-02-08 12:05:00
2017-02-08 12:06:00
2017-02-08 12:07:00
2017-02-08 12:08:00
2017-02-08 12:09:00
2017-02-08 12:10:00
2017-02-08 12:11:00
2017-02-08 12:12:00
2017-02-08 12:13:00
2017-02-08 12:14:00
2017-02-08 12:15:00
2017-02-08 12:16:00
2017-02-08 12:17:00
2017-02-08 12:18:00
2017-02-08 12:19:00
2017-02-08 12:20:00
2017-02-08 12:21:00
2017-02-08 12:22:00
2017-02-08 12:23:00
2017-02-08 12:24:00
2017-02-08 12:25:00
2017-02-08 12:26:00
2017-02-08 12:27:00
2017-02-08 12:28:00
2017-02-08 12:29:00
2017-02-08 12:30:00
2017-02-08 12:31:00
2017-02-08 12:32:00
2017-02-08 12:33:00
2017-02-08 12:34:00
2017-02-08 12:35:00
2017-02-08 12:36:00
2017-02-08 12:37:00
2017-02-08 12:38:00
2017-02-08 12:39:00
2017-02-08 12:40:00
2017-02-08 12:41:00
2017-02-08 12:42:00
2017-02-08 12:43:00
2017-02-08 12:44:00
2017-02-08 12:45:00
2017-02-08 12:46:00
2017-02-08 12:47:00
2017-02-08 12:48:00
2017-02-08 12:49:00
2017-02-08 12:50:00


In [2]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData3" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return ['DFZ',
 'EGV',
 'FKI',
 'FUR',
 'GYJ',
 'GYV',
 'HHK',
 'IFL',
 'JSG',
 'KFW',
 'KMV',
 'LDU',
 'MAS',
 'MQK',
 'OED',
 'SVG',
 'TGI',
 'UWC',
 'UWD',
 'VKE',
 'VND',
 'VTN']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 1,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 1,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: DFZ
Processing data for stock: EGV
Processing data for stock: FKI
Processing data for stock: FUR
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: HHK
Processing data for stock: IFL
Processing data for stock: JSG
Processing data for stock: KFW
Processing data for stock: KMV
Processing data for stock: LDU
Processing data for stock: MAS
Processing data for stock: MQK
Processing data for stock: OED
Processing data for stock: SVG
Processing data for stock: TGI
Processing data for stock: UWC
Processing data for stock: UWD
Processing data for stock: VKE
Processing data for stock: VND
Processing data for stock: VTN
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-06 09:17:00
2017-01-06 09:18:00
2017-01-06 09:19:00
2017-01-06 09:20:00
2017-01-06 09:21:00
2017-01-06 09:22:00
2017-01-06 09:23:00
2017-01-06 09:24:00
2017-01-06 09:25:00
2017-01-

2017-01-06 15:28:00
2017-01-06 15:29:00
2017-01-10 09:17:00
2017-01-10 09:18:00
2017-01-10 09:19:00
2017-01-10 09:20:00
2017-01-10 09:21:00
2017-01-10 09:22:00
2017-01-10 09:23:00
2017-01-10 09:24:00
2017-01-10 09:25:00
2017-01-10 09:26:00
2017-01-10 09:27:00
2017-01-10 09:28:00
2017-01-10 09:29:00
2017-01-10 09:30:00
2017-01-10 09:31:00
2017-01-10 09:32:00
2017-01-10 09:33:00
2017-01-10 09:34:00
2017-01-10 09:35:00
2017-01-10 09:36:00
2017-01-10 09:37:00
2017-01-10 09:38:00
2017-01-10 09:39:00
2017-01-10 09:40:00
2017-01-10 09:41:00
2017-01-10 09:42:00
2017-01-10 09:43:00
2017-01-10 09:44:00
2017-01-10 09:45:00
2017-01-10 09:46:00
2017-01-10 09:47:00
2017-01-10 09:48:00
2017-01-10 09:49:00
2017-01-10 09:50:00
2017-01-10 09:51:00
2017-01-10 09:52:00
2017-01-10 09:53:00
2017-01-10 09:54:00
2017-01-10 09:55:00
2017-01-10 09:56:00
2017-01-10 09:57:00
2017-01-10 09:58:00
2017-01-10 09:59:00
2017-01-10 10:00:00
2017-01-10 10:01:00
2017-01-10 10:02:00
2017-01-10 10:03:00
2017-01-10 10:04:00


2017-01-11 09:54:00
2017-01-11 09:55:00
2017-01-11 09:56:00
2017-01-11 09:57:00
2017-01-11 09:58:00
2017-01-11 09:59:00
2017-01-11 10:00:00
2017-01-11 10:01:00
2017-01-11 10:02:00
2017-01-11 10:03:00
2017-01-11 10:04:00
2017-01-11 10:05:00
2017-01-11 10:06:00
2017-01-11 10:07:00
2017-01-11 10:08:00
2017-01-11 10:09:00
2017-01-11 10:10:00
2017-01-11 10:11:00
2017-01-11 10:12:00
2017-01-11 10:13:00
2017-01-11 10:14:00
2017-01-11 10:15:00
2017-01-11 10:16:00
2017-01-11 10:17:00
2017-01-11 10:18:00
2017-01-11 10:19:00
2017-01-11 10:20:00
2017-01-11 10:21:00
2017-01-11 10:22:00
2017-01-11 10:23:00
2017-01-11 10:24:00
2017-01-11 10:25:00
2017-01-11 10:26:00
2017-01-11 10:27:00
2017-01-11 10:28:00
2017-01-11 10:29:00
2017-01-11 10:30:00
2017-01-11 10:31:00
2017-01-11 10:32:00
2017-01-11 10:33:00
2017-01-11 10:34:00
2017-01-11 10:35:00
2017-01-11 10:36:00
2017-01-11 10:37:00
2017-01-11 10:38:00
2017-01-11 10:39:00
2017-01-11 10:40:00
2017-01-11 10:41:00
2017-01-11 10:42:00
2017-01-11 10:43:00


2017-01-12 10:32:00
2017-01-12 10:33:00
2017-01-12 10:34:00
2017-01-12 10:35:00
2017-01-12 10:36:00
2017-01-12 10:37:00
2017-01-12 10:38:00
2017-01-12 10:39:00
2017-01-12 10:40:00
2017-01-12 10:41:00
2017-01-12 10:42:00
2017-01-12 10:43:00
2017-01-12 10:44:00
2017-01-12 10:45:00
2017-01-12 10:46:00
2017-01-12 10:47:00
2017-01-12 10:48:00
2017-01-12 10:49:00
2017-01-12 10:50:00
2017-01-12 10:51:00
2017-01-12 10:52:00
2017-01-12 10:53:00
2017-01-12 10:54:00
2017-01-12 10:55:00
2017-01-12 10:56:00
2017-01-12 10:57:00
2017-01-12 10:58:00
2017-01-12 10:59:00
2017-01-12 11:00:00
2017-01-12 11:01:00
2017-01-12 11:02:00
2017-01-12 11:03:00
2017-01-12 11:04:00
2017-01-12 11:05:00
2017-01-12 11:06:00
2017-01-12 11:07:00
2017-01-12 11:08:00
2017-01-12 11:09:00
2017-01-12 11:10:00
2017-01-12 11:11:00
2017-01-12 11:12:00
2017-01-12 11:13:00
2017-01-12 11:14:00
2017-01-12 11:15:00
2017-01-12 11:16:00
2017-01-12 11:17:00
2017-01-12 11:18:00
2017-01-12 11:19:00
2017-01-12 11:20:00
2017-01-12 11:21:00


2017-01-13 11:10:00
2017-01-13 11:11:00
2017-01-13 11:12:00
2017-01-13 11:13:00
2017-01-13 11:14:00
2017-01-13 11:15:00
2017-01-13 11:16:00
2017-01-13 11:17:00
2017-01-13 11:18:00
2017-01-13 11:19:00
2017-01-13 11:20:00
2017-01-13 11:21:00
2017-01-13 11:22:00
2017-01-13 11:23:00
2017-01-13 11:24:00
2017-01-13 11:25:00
2017-01-13 11:26:00
2017-01-13 11:27:00
2017-01-13 11:28:00
2017-01-13 11:29:00
2017-01-13 11:30:00
2017-01-13 11:31:00
2017-01-13 11:32:00
2017-01-13 11:33:00
2017-01-13 11:34:00
2017-01-13 11:35:00
2017-01-13 11:36:00
2017-01-13 11:37:00
2017-01-13 11:38:00
2017-01-13 11:39:00
2017-01-13 11:40:00
2017-01-13 11:41:00
2017-01-13 11:42:00
2017-01-13 11:43:00
2017-01-13 11:44:00
2017-01-13 11:45:00
2017-01-13 11:46:00
2017-01-13 11:47:00
2017-01-13 11:48:00
2017-01-13 11:49:00
2017-01-13 11:50:00
2017-01-13 11:51:00
2017-01-13 11:52:00
2017-01-13 11:53:00
2017-01-13 11:54:00
2017-01-13 11:55:00
2017-01-13 11:56:00
2017-01-13 11:57:00
2017-01-13 11:58:00
2017-01-13 11:59:00


...

2017-01-25 15:06:00
2017-01-25 15:07:00
2017-01-25 15:08:00
2017-01-25 15:09:00
2017-01-25 15:10:00
2017-01-25 15:11:00
2017-01-25 15:12:00
2017-01-25 15:13:00
2017-01-25 15:14:00
2017-01-25 15:15:00
2017-01-25 15:16:00
2017-01-25 15:17:00
2017-01-25 15:18:00
2017-01-25 15:19:00
2017-01-25 15:20:00
2017-01-25 15:21:00
2017-01-25 15:22:00
2017-01-25 15:23:00
2017-01-25 15:24:00
2017-01-25 15:25:00
2017-01-25 15:26:00
2017-01-25 15:27:00
2017-01-25 15:28:00
2017-01-25 15:29:00
2017-01-26 09:17:00
2017-01-26 09:18:00
2017-01-26 09:19:00
2017-01-26 09:20:00
2017-01-26 09:21:00
2017-01-26 09:22:00
2017-01-26 09:23:00
2017-01-26 09:24:00
2017-01-26 09:25:00
2017-01-26 09:26:00
2017-01-26 09:27:00
2017-01-26 09:28:00
2017-01-26 09:29:00
2017-01-26 09:30:00
2017-01-26 09:31:00
2017-01-26 09:32:00
2017-01-26 09:33:00
2017-01-26 09:34:00
2017-01-26 09:35:00
2017-01-26 09:36:00
2017-01-26 09:37:00
2017-01-26 09:38:00
2017-01-26 09:39:00
2017-01-26 09:40:00
2017-01-26 09:41:00
2017-01-26 09:42:00


2017-01-27 09:33:00
2017-01-27 09:34:00
2017-01-27 09:35:00
2017-01-27 09:36:00
2017-01-27 09:37:00
2017-01-27 09:38:00
2017-01-27 09:39:00
2017-01-27 09:40:00
2017-01-27 09:41:00
2017-01-27 09:42:00
2017-01-27 09:43:00
2017-01-27 09:44:00
2017-01-27 09:45:00
2017-01-27 09:46:00
2017-01-27 09:47:00
2017-01-27 09:48:00
2017-01-27 09:49:00
2017-01-27 09:50:00
2017-01-27 09:51:00
2017-01-27 09:52:00
2017-01-27 09:53:00
2017-01-27 09:54:00
2017-01-27 09:55:00
2017-01-27 09:56:00
2017-01-27 09:57:00
2017-01-27 09:58:00
2017-01-27 09:59:00
2017-01-27 10:00:00
2017-01-27 10:01:00
2017-01-27 10:02:00
2017-01-27 10:03:00
2017-01-27 10:04:00
2017-01-27 10:05:00
2017-01-27 10:06:00
2017-01-27 10:07:00
2017-01-27 10:08:00
2017-01-27 10:09:00
2017-01-27 10:10:00
2017-01-27 10:11:00
2017-01-27 10:12:00
2017-01-27 10:13:00
2017-01-27 10:14:00
2017-01-27 10:15:00
2017-01-27 10:16:00
2017-01-27 10:17:00
2017-01-27 10:18:00
2017-01-27 10:19:00
2017-01-27 10:20:00
2017-01-27 10:21:00
2017-01-27 10:22:00


2017-01-30 10:14:00
2017-01-30 10:15:00
2017-01-30 10:16:00
2017-01-30 10:17:00
2017-01-30 10:18:00
2017-01-30 10:19:00
2017-01-30 10:20:00
2017-01-30 10:21:00
2017-01-30 10:22:00
2017-01-30 10:23:00
2017-01-30 10:24:00
2017-01-30 10:25:00
2017-01-30 10:26:00
2017-01-30 10:27:00
2017-01-30 10:28:00
2017-01-30 10:29:00
2017-01-30 10:30:00
2017-01-30 10:31:00
2017-01-30 10:32:00
2017-01-30 10:33:00
2017-01-30 10:34:00
2017-01-30 10:35:00
2017-01-30 10:36:00
2017-01-30 10:37:00
2017-01-30 10:38:00
2017-01-30 10:39:00
2017-01-30 10:40:00
2017-01-30 10:41:00
2017-01-30 10:42:00
2017-01-30 10:43:00
2017-01-30 10:44:00
2017-01-30 10:45:00
2017-01-30 10:46:00
2017-01-30 10:47:00
2017-01-30 10:48:00
2017-01-30 10:49:00
2017-01-30 10:50:00
2017-01-30 10:51:00
2017-01-30 10:52:00
2017-01-30 10:53:00
2017-01-30 10:54:00
2017-01-30 10:55:00
2017-01-30 10:56:00
2017-01-30 10:57:00
2017-01-30 10:58:00
2017-01-30 10:59:00
2017-01-30 11:00:00
2017-01-30 11:01:00
2017-01-30 11:02:00
2017-01-30 11:03:00


2017-01-31 10:53:00
2017-01-31 10:54:00
2017-01-31 10:55:00
2017-01-31 10:56:00
2017-01-31 10:57:00
2017-01-31 10:58:00
2017-01-31 10:59:00
2017-01-31 11:00:00
2017-01-31 11:01:00
2017-01-31 11:02:00
2017-01-31 11:03:00
2017-01-31 11:04:00
2017-01-31 11:05:00
2017-01-31 11:06:00
2017-01-31 11:07:00
2017-01-31 11:08:00
2017-01-31 11:09:00
2017-01-31 11:10:00
2017-01-31 11:11:00
2017-01-31 11:12:00
2017-01-31 11:13:00
2017-01-31 11:14:00
2017-01-31 11:15:00
2017-01-31 11:16:00
2017-01-31 11:17:00
2017-01-31 11:18:00
2017-01-31 11:19:00
2017-01-31 11:20:00
2017-01-31 11:21:00
2017-01-31 11:22:00
2017-01-31 11:23:00
2017-01-31 11:24:00
2017-01-31 11:25:00
2017-01-31 11:26:00
2017-01-31 11:27:00
2017-01-31 11:28:00
2017-01-31 11:29:00
2017-01-31 11:30:00
2017-01-31 11:31:00
2017-01-31 11:32:00
2017-01-31 11:33:00
2017-01-31 11:34:00
2017-01-31 11:35:00
2017-01-31 11:36:00
2017-01-31 11:37:00
2017-01-31 11:38:00
2017-01-31 11:39:00
2017-01-31 11:40:00
2017-01-31 11:41:00
2017-01-31 11:42:00


2017-02-01 11:31:00
2017-02-01 11:32:00
2017-02-01 11:33:00
2017-02-01 11:34:00
2017-02-01 11:35:00
2017-02-01 11:36:00
2017-02-01 11:37:00
2017-02-01 11:38:00
2017-02-01 11:39:00
2017-02-01 11:40:00
2017-02-01 11:41:00
2017-02-01 11:42:00
2017-02-01 11:43:00
2017-02-01 11:44:00
2017-02-01 11:45:00
2017-02-01 11:46:00
2017-02-01 11:47:00
2017-02-01 11:48:00
2017-02-01 11:49:00
2017-02-01 11:50:00
2017-02-01 11:51:00
2017-02-01 11:52:00
2017-02-01 11:53:00
2017-02-01 11:54:00
2017-02-01 11:55:00
2017-02-01 11:56:00
2017-02-01 11:57:00
2017-02-01 11:58:00
2017-02-01 11:59:00
2017-02-01 12:00:00
2017-02-01 12:01:00
2017-02-01 12:02:00
2017-02-01 12:03:00
2017-02-01 12:04:00
2017-02-01 12:05:00
2017-02-01 12:06:00
2017-02-01 12:07:00
2017-02-01 12:08:00
2017-02-01 12:09:00
2017-02-01 12:10:00
2017-02-01 12:11:00
2017-02-01 12:12:00
2017-02-01 12:13:00
2017-02-01 12:14:00
2017-02-01 12:15:00
2017-02-01 12:16:00
2017-02-01 12:17:00
2017-02-01 12:18:00
2017-02-01 12:19:00
2017-02-01 12:20:00


In [3]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData1" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return ['DFZ',
 'EGV',
 'FKI',
 'FUR',
 'GYJ',
 'GYV',
 'HHK',
 'IFL',
 'JSG',
 'KFW',
 'KMV',
 'LDU',
 'MAS',
 #'MQK',
 'OED',
 'SVG',
 'TGI',
 'UWC',
 #'UWD',
 'VKE',
 'VND',
 'VTN']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 1,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 1,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: DFZ
Processing data for stock: EGV
Processing data for stock: FKI
Processing data for stock: FUR
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: HHK
Processing data for stock: IFL
Processing data for stock: JSG
Processing data for stock: KFW
Processing data for stock: KMV
Processing data for stock: LDU
Processing data for stock: MAS
Processing data for stock: OED
Processing data for stock: SVG
Processing data for stock: TGI
Processing data for stock: UWC
Processing data for stock: VKE
Processing data for stock: VND
Processing data for stock: VTN
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-06 09:17:00
2017-01-06 09:18:00
2017-01-06 09:19:00
2017-01-06 09:20:00
2017-01-06 09:21:00
2017-01-06 09:22:00
2017-01-06 09:23:00
2017-01-06 09:24:00
2017-01-06 09:25:00
2017-01-06 09:26:00
2017-01-06 09:27:00
2017-01-06 09:28:00
2017-01-06

2017-01-09 09:17:00
2017-01-09 09:18:00
2017-01-09 09:19:00
2017-01-09 09:20:00
2017-01-09 09:21:00
2017-01-09 09:22:00
2017-01-09 09:23:00
2017-01-09 09:24:00
2017-01-09 09:25:00
2017-01-09 09:26:00
2017-01-09 09:27:00
2017-01-09 09:28:00
2017-01-09 09:29:00
2017-01-09 09:30:00
2017-01-09 09:31:00
2017-01-09 09:32:00
2017-01-09 09:33:00
2017-01-09 09:34:00
2017-01-09 09:35:00
2017-01-09 09:36:00
2017-01-09 09:37:00
2017-01-09 09:38:00
2017-01-09 09:39:00
2017-01-09 09:40:00
2017-01-09 09:41:00
2017-01-09 09:42:00
2017-01-09 09:43:00
2017-01-09 09:44:00
2017-01-09 09:45:00
2017-01-09 09:46:00
2017-01-09 09:47:00
2017-01-09 09:48:00
2017-01-09 09:49:00
2017-01-09 09:50:00
2017-01-09 09:51:00
2017-01-09 09:52:00
2017-01-09 09:53:00
2017-01-09 09:54:00
2017-01-09 09:55:00
2017-01-09 09:56:00
2017-01-09 09:57:00
2017-01-09 09:58:00
2017-01-09 09:59:00
2017-01-09 10:00:00
2017-01-09 10:01:00
2017-01-09 10:02:00
2017-01-09 10:03:00
2017-01-09 10:04:00
2017-01-09 10:05:00
2017-01-09 10:06:00


2017-01-10 09:55:00
2017-01-10 09:56:00
2017-01-10 09:57:00
2017-01-10 09:58:00
2017-01-10 09:59:00
2017-01-10 10:00:00
2017-01-10 10:01:00
2017-01-10 10:02:00
2017-01-10 10:03:00
2017-01-10 10:04:00
2017-01-10 10:05:00
2017-01-10 10:06:00
2017-01-10 10:07:00
2017-01-10 10:08:00
2017-01-10 10:09:00
2017-01-10 10:10:00
2017-01-10 10:11:00
2017-01-10 10:12:00
2017-01-10 10:13:00
2017-01-10 10:14:00
2017-01-10 10:15:00
2017-01-10 10:16:00
2017-01-10 10:17:00
2017-01-10 10:18:00
2017-01-10 10:19:00
2017-01-10 10:20:00
2017-01-10 10:21:00
2017-01-10 10:22:00
2017-01-10 10:23:00
2017-01-10 10:24:00
2017-01-10 10:25:00
2017-01-10 10:26:00
2017-01-10 10:27:00
2017-01-10 10:28:00
2017-01-10 10:29:00
2017-01-10 10:30:00
2017-01-10 10:31:00
2017-01-10 10:32:00
2017-01-10 10:33:00
2017-01-10 10:34:00
2017-01-10 10:35:00
2017-01-10 10:36:00
2017-01-10 10:37:00
2017-01-10 10:38:00
2017-01-10 10:39:00
2017-01-10 10:40:00
2017-01-10 10:41:00
2017-01-10 10:42:00
2017-01-10 10:43:00
2017-01-10 10:44:00


2017-01-11 10:35:00
2017-01-11 10:36:00
2017-01-11 10:37:00
2017-01-11 10:38:00
2017-01-11 10:39:00
2017-01-11 10:40:00
2017-01-11 10:41:00
2017-01-11 10:42:00
2017-01-11 10:43:00
2017-01-11 10:44:00
2017-01-11 10:45:00
2017-01-11 10:46:00
2017-01-11 10:47:00
2017-01-11 10:48:00
2017-01-11 10:49:00
2017-01-11 10:50:00
2017-01-11 10:51:00
2017-01-11 10:52:00
2017-01-11 10:53:00
2017-01-11 10:54:00
2017-01-11 10:55:00
2017-01-11 10:56:00
2017-01-11 10:57:00
2017-01-11 10:58:00
2017-01-11 10:59:00
2017-01-11 11:00:00
2017-01-11 11:01:00
2017-01-11 11:02:00
2017-01-11 11:03:00
2017-01-11 11:04:00
2017-01-11 11:05:00
2017-01-11 11:06:00
2017-01-11 11:07:00
2017-01-11 11:08:00
2017-01-11 11:09:00
2017-01-11 11:10:00
2017-01-11 11:11:00
2017-01-11 11:12:00
2017-01-11 11:13:00
2017-01-11 11:14:00
2017-01-11 11:15:00
2017-01-11 11:16:00
2017-01-11 11:17:00
2017-01-11 11:18:00
2017-01-11 11:19:00
2017-01-11 11:20:00
2017-01-11 11:21:00
2017-01-11 11:22:00
2017-01-11 11:23:00
2017-01-11 11:24:00


2017-01-12 11:14:00
2017-01-12 11:15:00
2017-01-12 11:16:00
2017-01-12 11:17:00
2017-01-12 11:18:00
2017-01-12 11:19:00
2017-01-12 11:20:00
2017-01-12 11:21:00
2017-01-12 11:22:00
2017-01-12 11:23:00
2017-01-12 11:24:00
2017-01-12 11:25:00
2017-01-12 11:26:00
2017-01-12 11:27:00
2017-01-12 11:28:00
2017-01-12 11:29:00
2017-01-12 11:30:00
2017-01-12 11:31:00
2017-01-12 11:32:00
2017-01-12 11:33:00
2017-01-12 11:34:00
2017-01-12 11:35:00
2017-01-12 11:36:00
2017-01-12 11:37:00
2017-01-12 11:38:00
2017-01-12 11:39:00
2017-01-12 11:40:00
2017-01-12 11:41:00
2017-01-12 11:42:00
2017-01-12 11:43:00
2017-01-12 11:44:00
2017-01-12 11:45:00
2017-01-12 11:46:00
2017-01-12 11:47:00
2017-01-12 11:48:00
2017-01-12 11:49:00
2017-01-12 11:50:00
2017-01-12 11:51:00
2017-01-12 11:52:00
2017-01-12 11:53:00
2017-01-12 11:54:00
2017-01-12 11:55:00
2017-01-12 11:56:00
2017-01-12 11:57:00
2017-01-12 11:58:00
2017-01-12 11:59:00
2017-01-12 12:00:00
2017-01-12 12:01:00
2017-01-12 12:02:00
2017-01-12 12:03:00


...

2017-02-01 13:31:00
2017-02-01 13:32:00
2017-02-01 13:33:00
2017-02-01 13:34:00
2017-02-01 13:35:00
2017-02-01 13:36:00
2017-02-01 13:37:00
2017-02-01 13:38:00
2017-02-01 13:39:00
2017-02-01 13:40:00
2017-02-01 13:41:00
2017-02-01 13:42:00
2017-02-01 13:43:00
2017-02-01 13:44:00
2017-02-01 13:45:00
2017-02-01 13:46:00
2017-02-01 13:47:00
2017-02-01 13:48:00
2017-02-01 13:49:00
2017-02-01 13:50:00
2017-02-01 13:51:00
2017-02-01 13:52:00
2017-02-01 13:53:00
2017-02-01 13:54:00
2017-02-01 13:55:00
2017-02-01 13:56:00
2017-02-01 13:57:00
2017-02-01 13:58:00
2017-02-01 13:59:00
2017-02-01 14:00:00
2017-02-01 14:01:00
2017-02-01 14:02:00
2017-02-01 14:03:00
2017-02-01 14:04:00
2017-02-01 14:05:00
2017-02-01 14:06:00
2017-02-01 14:07:00
2017-02-01 14:08:00
2017-02-01 14:09:00
2017-02-01 14:10:00
2017-02-01 14:11:00
2017-02-01 14:12:00
2017-02-01 14:13:00
2017-02-01 14:14:00
2017-02-01 14:15:00
2017-02-01 14:16:00
2017-02-01 14:17:00
2017-02-01 14:18:00
2017-02-01 14:19:00
2017-02-01 14:20:00


2017-02-02 14:11:00
2017-02-02 14:12:00
2017-02-02 14:13:00
2017-02-02 14:14:00
2017-02-02 14:15:00
2017-02-02 14:16:00
2017-02-02 14:17:00
2017-02-02 14:18:00
2017-02-02 14:19:00
2017-02-02 14:20:00
2017-02-02 14:21:00
2017-02-02 14:22:00
2017-02-02 14:23:00
2017-02-02 14:24:00
2017-02-02 14:25:00
2017-02-02 14:26:00
2017-02-02 14:27:00
2017-02-02 14:28:00
2017-02-02 14:29:00
2017-02-02 14:30:00
2017-02-02 14:31:00
2017-02-02 14:32:00
2017-02-02 14:33:00
2017-02-02 14:34:00
2017-02-02 14:35:00
2017-02-02 14:36:00
2017-02-02 14:37:00
2017-02-02 14:38:00
2017-02-02 14:39:00
2017-02-02 14:40:00
2017-02-02 14:41:00
2017-02-02 14:42:00
2017-02-02 14:43:00
2017-02-02 14:44:00
2017-02-02 14:45:00
2017-02-02 14:46:00
2017-02-02 14:47:00
2017-02-02 14:48:00
2017-02-02 14:49:00
2017-02-02 14:50:00
2017-02-02 14:51:00
2017-02-02 14:52:00
2017-02-02 14:53:00
2017-02-02 14:54:00
2017-02-02 14:55:00
2017-02-02 14:56:00
2017-02-02 14:57:00
2017-02-02 14:58:00
2017-02-02 14:59:00
2017-02-02 15:00:00


2017-02-03 14:49:00
2017-02-03 14:50:00
2017-02-03 14:51:00
2017-02-03 14:52:00
2017-02-03 14:53:00
2017-02-03 14:54:00
2017-02-03 14:55:00
2017-02-03 14:56:00
2017-02-03 14:57:00
2017-02-03 14:58:00
2017-02-03 14:59:00
2017-02-03 15:00:00
2017-02-03 15:01:00
2017-02-03 15:02:00
2017-02-03 15:03:00
2017-02-03 15:04:00
2017-02-03 15:05:00
2017-02-03 15:06:00
2017-02-03 15:07:00
2017-02-03 15:08:00
2017-02-03 15:09:00
2017-02-03 15:10:00
2017-02-03 15:11:00
2017-02-03 15:12:00
2017-02-03 15:13:00
2017-02-03 15:14:00
2017-02-03 15:15:00
2017-02-03 15:16:00
2017-02-03 15:17:00
2017-02-03 15:18:00
2017-02-03 15:19:00
2017-02-03 15:20:00
2017-02-03 15:21:00
2017-02-03 15:22:00
2017-02-03 15:23:00
2017-02-03 15:24:00
2017-02-03 15:25:00
2017-02-03 15:26:00
2017-02-03 15:27:00
2017-02-03 15:28:00
2017-02-03 15:29:00
2017-02-07 09:17:00
2017-02-07 09:18:00
2017-02-07 09:19:00
2017-02-07 09:20:00
2017-02-07 09:21:00
2017-02-07 09:22:00
2017-02-07 09:23:00
2017-02-07 09:24:00
2017-02-07 09:25:00


2017-02-07 15:27:00
2017-02-07 15:28:00
2017-02-07 15:29:00
2017-02-08 09:17:00
2017-02-08 09:18:00
2017-02-08 09:19:00
2017-02-08 09:20:00
2017-02-08 09:21:00
2017-02-08 09:22:00
2017-02-08 09:23:00
2017-02-08 09:24:00
2017-02-08 09:25:00
2017-02-08 09:26:00
2017-02-08 09:27:00
2017-02-08 09:28:00
2017-02-08 09:29:00
2017-02-08 09:30:00
2017-02-08 09:31:00
2017-02-08 09:32:00
2017-02-08 09:33:00
2017-02-08 09:34:00
2017-02-08 09:35:00
2017-02-08 09:36:00
2017-02-08 09:37:00
2017-02-08 09:38:00
2017-02-08 09:39:00
2017-02-08 09:40:00
2017-02-08 09:41:00
2017-02-08 09:42:00
2017-02-08 09:43:00
2017-02-08 09:44:00
2017-02-08 09:45:00
2017-02-08 09:46:00
2017-02-08 09:47:00
2017-02-08 09:48:00
2017-02-08 09:49:00
2017-02-08 09:50:00
2017-02-08 09:51:00
2017-02-08 09:52:00
2017-02-08 09:53:00
2017-02-08 09:54:00
2017-02-08 09:55:00
2017-02-08 09:56:00
2017-02-08 09:57:00
2017-02-08 09:58:00
2017-02-08 09:59:00
2017-02-08 10:00:00
2017-02-08 10:01:00
2017-02-08 10:02:00
2017-02-08 10:03:00


2017-02-09 09:53:00
2017-02-09 09:54:00
2017-02-09 09:55:00
2017-02-09 09:56:00
2017-02-09 09:57:00
2017-02-09 09:58:00
2017-02-09 09:59:00
2017-02-09 10:00:00
2017-02-09 10:01:00
2017-02-09 10:02:00
2017-02-09 10:03:00
2017-02-09 10:04:00
2017-02-09 10:05:00
2017-02-09 10:06:00
2017-02-09 10:07:00
2017-02-09 10:08:00
2017-02-09 10:09:00
2017-02-09 10:10:00
2017-02-09 10:11:00
2017-02-09 10:12:00
2017-02-09 10:13:00
2017-02-09 10:14:00
2017-02-09 10:15:00
2017-02-09 10:16:00
2017-02-09 10:17:00
2017-02-09 10:18:00
2017-02-09 10:19:00
2017-02-09 10:20:00
2017-02-09 10:21:00
2017-02-09 10:22:00
2017-02-09 10:23:00
2017-02-09 10:24:00
2017-02-09 10:25:00
2017-02-09 10:26:00
2017-02-09 10:27:00
2017-02-09 10:28:00
2017-02-09 10:29:00
2017-02-09 10:30:00
2017-02-09 10:31:00
2017-02-09 10:32:00
2017-02-09 10:33:00
2017-02-09 10:34:00
2017-02-09 10:35:00
2017-02-09 10:36:00
2017-02-09 10:37:00
2017-02-09 10:38:00
2017-02-09 10:39:00
2017-02-09 10:40:00
2017-02-09 10:41:00
2017-02-09 10:42:00


In [4]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData2" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return ['DFZ',
 'EGV',
 'FKI',
 'FUR',
 'GYJ',
 'GYV',
 'HHK',
 'IFL',
 'JSG',
 'KFW',
 'KMV',
 'LDU',
 'MAS',
 #'MQK',
 'OED',
 'SVG',
 'TGI',
 'UWC',
 #'UWD',
 'VKE',
 'VND',
 'VTN']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 1,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 1,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: DFZ
Processing data for stock: EGV
Processing data for stock: FKI
Processing data for stock: FUR
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: HHK
Processing data for stock: IFL
Processing data for stock: JSG
Processing data for stock: KFW
Processing data for stock: KMV
Processing data for stock: LDU
Processing data for stock: MAS
Processing data for stock: OED
Processing data for stock: SVG
Processing data for stock: TGI
Processing data for stock: UWC
Processing data for stock: VKE
Processing data for stock: VND
Processing data for stock: VTN
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-13 09:17:00
2017-01-13 09:18:00
2017-01-13 09:19:00
2017-01-13 09:20:00
2017-01-13 09:21:00
2017-01-13 09:22:00
2017-01-13 09:23:00
2017-01-13 09:24:00
2017-01-13 09:25:00
2017-01-13 09:26:00
2017-01-13 09:27:00
2017-01-13 09:28:00
2017-01-13

2017-01-16 09:19:00
2017-01-16 09:20:00
2017-01-16 09:21:00
2017-01-16 09:22:00
2017-01-16 09:23:00
2017-01-16 09:24:00
2017-01-16 09:25:00
2017-01-16 09:26:00
2017-01-16 09:27:00
2017-01-16 09:28:00
2017-01-16 09:29:00
2017-01-16 09:30:00
2017-01-16 09:31:00
2017-01-16 09:32:00
2017-01-16 09:33:00
2017-01-16 09:34:00
2017-01-16 09:35:00
2017-01-16 09:36:00
2017-01-16 09:37:00
2017-01-16 09:38:00
2017-01-16 09:39:00
2017-01-16 09:40:00
2017-01-16 09:41:00
2017-01-16 09:42:00
2017-01-16 09:43:00
2017-01-16 09:44:00
2017-01-16 09:45:00
2017-01-16 09:46:00
2017-01-16 09:47:00
2017-01-16 09:48:00
2017-01-16 09:49:00
2017-01-16 09:50:00
2017-01-16 09:51:00
2017-01-16 09:52:00
2017-01-16 09:53:00
2017-01-16 09:54:00
2017-01-16 09:55:00
2017-01-16 09:56:00
2017-01-16 09:57:00
2017-01-16 09:58:00
2017-01-16 09:59:00
2017-01-16 10:00:00
2017-01-16 10:01:00
2017-01-16 10:02:00
2017-01-16 10:03:00
2017-01-16 10:04:00
2017-01-16 10:05:00
2017-01-16 10:06:00
2017-01-16 10:07:00
2017-01-16 10:08:00


2017-01-18 09:57:00
2017-01-18 09:58:00
2017-01-18 09:59:00
2017-01-18 10:00:00
2017-01-18 10:01:00
2017-01-18 10:02:00
2017-01-18 10:03:00
2017-01-18 10:04:00
2017-01-18 10:05:00
2017-01-18 10:06:00
2017-01-18 10:07:00
2017-01-18 10:08:00
2017-01-18 10:09:00
2017-01-18 10:10:00
2017-01-18 10:11:00
2017-01-18 10:12:00
2017-01-18 10:13:00
2017-01-18 10:14:00
2017-01-18 10:15:00
2017-01-18 10:16:00
2017-01-18 10:17:00
2017-01-18 10:18:00
2017-01-18 10:19:00
2017-01-18 10:20:00
2017-01-18 10:21:00
2017-01-18 10:22:00
2017-01-18 10:23:00
2017-01-18 10:24:00
2017-01-18 10:25:00
2017-01-18 10:26:00
2017-01-18 10:27:00
2017-01-18 10:28:00
2017-01-18 10:29:00
2017-01-18 10:30:00
2017-01-18 10:31:00
2017-01-18 10:32:00
2017-01-18 10:33:00
2017-01-18 10:34:00
2017-01-18 10:35:00
2017-01-18 10:36:00
2017-01-18 10:37:00
2017-01-18 10:38:00
2017-01-18 10:39:00
2017-01-18 10:40:00
2017-01-18 10:41:00
2017-01-18 10:42:00
2017-01-18 10:43:00
2017-01-18 10:44:00
2017-01-18 10:45:00
2017-01-18 10:46:00


2017-01-19 10:34:00
2017-01-19 10:35:00
2017-01-19 10:36:00
2017-01-19 10:37:00
2017-01-19 10:38:00
2017-01-19 10:39:00
2017-01-19 10:40:00
2017-01-19 10:41:00
2017-01-19 10:42:00
2017-01-19 10:43:00
2017-01-19 10:44:00
2017-01-19 10:45:00
2017-01-19 10:46:00
2017-01-19 10:47:00
2017-01-19 10:48:00
2017-01-19 10:49:00
2017-01-19 10:50:00
2017-01-19 10:51:00
2017-01-19 10:52:00
2017-01-19 10:53:00
2017-01-19 10:54:00
2017-01-19 10:55:00
2017-01-19 10:56:00
2017-01-19 10:57:00
2017-01-19 10:58:00
2017-01-19 10:59:00
2017-01-19 11:00:00
2017-01-19 11:01:00
2017-01-19 11:02:00
2017-01-19 11:03:00
2017-01-19 11:04:00
2017-01-19 11:05:00
2017-01-19 11:06:00
2017-01-19 11:07:00
2017-01-19 11:08:00
2017-01-19 11:09:00
2017-01-19 11:10:00
2017-01-19 11:11:00
2017-01-19 11:12:00
2017-01-19 11:13:00
2017-01-19 11:14:00
2017-01-19 11:15:00
2017-01-19 11:16:00
2017-01-19 11:17:00
2017-01-19 11:18:00
2017-01-19 11:19:00
2017-01-19 11:20:00
2017-01-19 11:21:00
2017-01-19 11:22:00
2017-01-19 11:23:00


2017-01-20 11:12:00
2017-01-20 11:13:00
2017-01-20 11:14:00
2017-01-20 11:15:00
2017-01-20 11:16:00
2017-01-20 11:17:00
2017-01-20 11:18:00
2017-01-20 11:19:00
2017-01-20 11:20:00
2017-01-20 11:21:00
2017-01-20 11:22:00
2017-01-20 11:23:00
2017-01-20 11:24:00
2017-01-20 11:25:00
2017-01-20 11:26:00
2017-01-20 11:27:00
2017-01-20 11:28:00
2017-01-20 11:29:00
2017-01-20 11:30:00
2017-01-20 11:31:00
2017-01-20 11:32:00
2017-01-20 11:33:00
2017-01-20 11:34:00
2017-01-20 11:35:00
2017-01-20 11:36:00
2017-01-20 11:37:00
2017-01-20 11:38:00
2017-01-20 11:39:00
2017-01-20 11:40:00
2017-01-20 11:41:00
2017-01-20 11:42:00
2017-01-20 11:43:00
2017-01-20 11:44:00
2017-01-20 11:45:00
2017-01-20 11:46:00
2017-01-20 11:47:00
2017-01-20 11:48:00
2017-01-20 11:49:00
2017-01-20 11:50:00
2017-01-20 11:51:00
2017-01-20 11:52:00
2017-01-20 11:53:00
2017-01-20 11:54:00
2017-01-20 11:55:00
2017-01-20 11:56:00
2017-01-20 11:57:00
2017-01-20 11:58:00
2017-01-20 11:59:00
2017-01-20 12:00:00
2017-01-20 12:01:00


...

2017-02-02 09:33:00
2017-02-02 09:34:00
2017-02-02 09:35:00
2017-02-02 09:36:00
2017-02-02 09:37:00
2017-02-02 09:38:00
2017-02-02 09:39:00
2017-02-02 09:40:00
2017-02-02 09:41:00
2017-02-02 09:42:00
2017-02-02 09:43:00
2017-02-02 09:44:00
2017-02-02 09:45:00
2017-02-02 09:46:00
2017-02-02 09:47:00
2017-02-02 09:48:00
2017-02-02 09:49:00
2017-02-02 09:50:00
2017-02-02 09:51:00
2017-02-02 09:52:00
2017-02-02 09:53:00
2017-02-02 09:54:00
2017-02-02 09:55:00
2017-02-02 09:56:00
2017-02-02 09:57:00
2017-02-02 09:58:00
2017-02-02 09:59:00
2017-02-02 10:00:00
2017-02-02 10:01:00
2017-02-02 10:02:00
2017-02-02 10:03:00
2017-02-02 10:04:00
2017-02-02 10:05:00
2017-02-02 10:06:00
2017-02-02 10:07:00
2017-02-02 10:08:00
2017-02-02 10:09:00
2017-02-02 10:10:00
2017-02-02 10:11:00
2017-02-02 10:12:00
2017-02-02 10:13:00
2017-02-02 10:14:00
2017-02-02 10:15:00
2017-02-02 10:16:00
2017-02-02 10:17:00
2017-02-02 10:18:00
2017-02-02 10:19:00
2017-02-02 10:20:00
2017-02-02 10:21:00
2017-02-02 10:22:00


2017-02-03 10:11:00
2017-02-03 10:12:00
2017-02-03 10:13:00
2017-02-03 10:14:00
2017-02-03 10:15:00
2017-02-03 10:16:00
2017-02-03 10:17:00
2017-02-03 10:18:00
2017-02-03 10:19:00
2017-02-03 10:20:00
2017-02-03 10:21:00
2017-02-03 10:22:00
2017-02-03 10:23:00
2017-02-03 10:24:00
2017-02-03 10:25:00
2017-02-03 10:26:00
2017-02-03 10:27:00
2017-02-03 10:28:00
2017-02-03 10:29:00
2017-02-03 10:30:00
2017-02-03 10:31:00
2017-02-03 10:32:00
2017-02-03 10:33:00
2017-02-03 10:34:00
2017-02-03 10:35:00
2017-02-03 10:36:00
2017-02-03 10:37:00
2017-02-03 10:38:00
2017-02-03 10:39:00
2017-02-03 10:40:00
2017-02-03 10:41:00
2017-02-03 10:42:00
2017-02-03 10:43:00
2017-02-03 10:44:00
2017-02-03 10:45:00
2017-02-03 10:46:00
2017-02-03 10:47:00
2017-02-03 10:48:00
2017-02-03 10:49:00
2017-02-03 10:50:00
2017-02-03 10:51:00
2017-02-03 10:52:00
2017-02-03 10:53:00
2017-02-03 10:54:00
2017-02-03 10:55:00
2017-02-03 10:56:00
2017-02-03 10:57:00
2017-02-03 10:58:00
2017-02-03 10:59:00
2017-02-03 11:00:00


2017-02-06 10:49:00
2017-02-06 10:50:00
2017-02-06 10:51:00
2017-02-06 10:52:00
2017-02-06 10:53:00
2017-02-06 10:54:00
2017-02-06 10:55:00
2017-02-06 10:56:00
2017-02-06 10:57:00
2017-02-06 10:58:00
2017-02-06 10:59:00
2017-02-06 11:00:00
2017-02-06 11:01:00
2017-02-06 11:02:00
2017-02-06 11:03:00
2017-02-06 11:04:00
2017-02-06 11:05:00
2017-02-06 11:06:00
2017-02-06 11:07:00
2017-02-06 11:08:00
2017-02-06 11:09:00
2017-02-06 11:10:00
2017-02-06 11:11:00
2017-02-06 11:12:00
2017-02-06 11:13:00
2017-02-06 11:14:00
2017-02-06 11:15:00
2017-02-06 11:16:00
2017-02-06 11:17:00
2017-02-06 11:18:00
2017-02-06 11:19:00
2017-02-06 11:20:00
2017-02-06 11:21:00
2017-02-06 11:22:00
2017-02-06 11:23:00
2017-02-06 11:24:00
2017-02-06 11:25:00
2017-02-06 11:26:00
2017-02-06 11:27:00
2017-02-06 11:28:00
2017-02-06 11:29:00
2017-02-06 11:30:00
2017-02-06 11:31:00
2017-02-06 11:32:00
2017-02-06 11:33:00
2017-02-06 11:34:00
2017-02-06 11:35:00
2017-02-06 11:36:00
2017-02-06 11:37:00
2017-02-06 11:38:00


2017-02-07 11:26:00
2017-02-07 11:27:00
2017-02-07 11:28:00
2017-02-07 11:29:00
2017-02-07 11:30:00
2017-02-07 11:31:00
2017-02-07 11:32:00
2017-02-07 11:33:00
2017-02-07 11:34:00
2017-02-07 11:35:00
2017-02-07 11:36:00
2017-02-07 11:37:00
2017-02-07 11:38:00
2017-02-07 11:39:00
2017-02-07 11:40:00
2017-02-07 11:41:00
2017-02-07 11:42:00
2017-02-07 11:43:00
2017-02-07 11:44:00
2017-02-07 11:45:00
2017-02-07 11:46:00
2017-02-07 11:47:00
2017-02-07 11:48:00
2017-02-07 11:49:00
2017-02-07 11:50:00
2017-02-07 11:51:00
2017-02-07 11:52:00
2017-02-07 11:53:00
2017-02-07 11:54:00
2017-02-07 11:55:00
2017-02-07 11:56:00
2017-02-07 11:57:00
2017-02-07 11:58:00
2017-02-07 11:59:00
2017-02-07 12:00:00
2017-02-07 12:01:00
2017-02-07 12:02:00
2017-02-07 12:03:00
2017-02-07 12:04:00
2017-02-07 12:05:00
2017-02-07 12:06:00
2017-02-07 12:07:00
2017-02-07 12:08:00
2017-02-07 12:09:00
2017-02-07 12:10:00
2017-02-07 12:11:00
2017-02-07 12:12:00
2017-02-07 12:13:00
2017-02-07 12:14:00
2017-02-07 12:15:00


2017-02-08 12:06:00
2017-02-08 12:07:00
2017-02-08 12:08:00
2017-02-08 12:09:00
2017-02-08 12:10:00
2017-02-08 12:11:00
2017-02-08 12:12:00
2017-02-08 12:13:00
2017-02-08 12:14:00
2017-02-08 12:15:00
2017-02-08 12:16:00
2017-02-08 12:17:00
2017-02-08 12:18:00
2017-02-08 12:19:00
2017-02-08 12:20:00
2017-02-08 12:21:00
2017-02-08 12:22:00
2017-02-08 12:23:00
2017-02-08 12:24:00
2017-02-08 12:25:00
2017-02-08 12:26:00
2017-02-08 12:27:00
2017-02-08 12:28:00
2017-02-08 12:29:00
2017-02-08 12:30:00
2017-02-08 12:31:00
2017-02-08 12:32:00
2017-02-08 12:33:00
2017-02-08 12:34:00
2017-02-08 12:35:00
2017-02-08 12:36:00
2017-02-08 12:37:00
2017-02-08 12:38:00
2017-02-08 12:39:00
2017-02-08 12:40:00
2017-02-08 12:41:00
2017-02-08 12:42:00
2017-02-08 12:43:00
2017-02-08 12:44:00
2017-02-08 12:45:00
2017-02-08 12:46:00
2017-02-08 12:47:00
2017-02-08 12:48:00
2017-02-08 12:49:00
2017-02-08 12:50:00
2017-02-08 12:51:00
2017-02-08 12:52:00
2017-02-08 12:53:00
2017-02-08 12:54:00
2017-02-08 12:55:00


In [5]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData3" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return ['DFZ',
 'EGV',
 'FKI',
 'FUR',
 'GYJ',
 'GYV',
 'HHK',
 'IFL',
 'JSG',
 'KFW',
 'KMV',
 'LDU',
 'MAS',
 #'MQK',
 'OED',
 'SVG',
 'TGI',
 'UWC',
 #'UWD',
 'VKE',
 'VND',
 'VTN']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 1,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 1,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: DFZ
Processing data for stock: EGV
Processing data for stock: FKI
Processing data for stock: FUR
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: HHK
Processing data for stock: IFL
Processing data for stock: JSG
Processing data for stock: KFW
Processing data for stock: KMV
Processing data for stock: LDU
Processing data for stock: MAS
Processing data for stock: OED
Processing data for stock: SVG
Processing data for stock: TGI
Processing data for stock: UWC
Processing data for stock: VKE
Processing data for stock: VND
Processing data for stock: VTN
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-06 09:17:00
2017-01-06 09:18:00
2017-01-06 09:19:00
2017-01-06 09:20:00
2017-01-06 09:21:00
2017-01-06 09:22:00
2017-01-06 09:23:00
2017-01-06 09:24:00
2017-01-06 09:25:00
2017-01-06 09:26:00
2017-01-06 09:27:00
2017-01-06 09:28:00
2017-01-06

2017-01-10 09:20:00
2017-01-10 09:21:00
2017-01-10 09:22:00
2017-01-10 09:23:00
2017-01-10 09:24:00
2017-01-10 09:25:00
2017-01-10 09:26:00
2017-01-10 09:27:00
2017-01-10 09:28:00
2017-01-10 09:29:00
2017-01-10 09:30:00
2017-01-10 09:31:00
2017-01-10 09:32:00
2017-01-10 09:33:00
2017-01-10 09:34:00
2017-01-10 09:35:00
2017-01-10 09:36:00
2017-01-10 09:37:00
2017-01-10 09:38:00
2017-01-10 09:39:00
2017-01-10 09:40:00
2017-01-10 09:41:00
2017-01-10 09:42:00
2017-01-10 09:43:00
2017-01-10 09:44:00
2017-01-10 09:45:00
2017-01-10 09:46:00
2017-01-10 09:47:00
2017-01-10 09:48:00
2017-01-10 09:49:00
2017-01-10 09:50:00
2017-01-10 09:51:00
2017-01-10 09:52:00
2017-01-10 09:53:00
2017-01-10 09:54:00
2017-01-10 09:55:00
2017-01-10 09:56:00
2017-01-10 09:57:00
2017-01-10 09:58:00
2017-01-10 09:59:00
2017-01-10 10:00:00
2017-01-10 10:01:00
2017-01-10 10:02:00
2017-01-10 10:03:00
2017-01-10 10:04:00
2017-01-10 10:05:00
2017-01-10 10:06:00
2017-01-10 10:07:00
2017-01-10 10:08:00
2017-01-10 10:09:00


2017-01-11 09:58:00
2017-01-11 09:59:00
2017-01-11 10:00:00
2017-01-11 10:01:00
2017-01-11 10:02:00
2017-01-11 10:03:00
2017-01-11 10:04:00
2017-01-11 10:05:00
2017-01-11 10:06:00
2017-01-11 10:07:00
2017-01-11 10:08:00
2017-01-11 10:09:00
2017-01-11 10:10:00
2017-01-11 10:11:00
2017-01-11 10:12:00
2017-01-11 10:13:00
2017-01-11 10:14:00
2017-01-11 10:15:00
2017-01-11 10:16:00
2017-01-11 10:17:00
2017-01-11 10:18:00
2017-01-11 10:19:00
2017-01-11 10:20:00
2017-01-11 10:21:00
2017-01-11 10:22:00
2017-01-11 10:23:00
2017-01-11 10:24:00
2017-01-11 10:25:00
2017-01-11 10:26:00
2017-01-11 10:27:00
2017-01-11 10:28:00
2017-01-11 10:29:00
2017-01-11 10:30:00
2017-01-11 10:31:00
2017-01-11 10:32:00
2017-01-11 10:33:00
2017-01-11 10:34:00
2017-01-11 10:35:00
2017-01-11 10:36:00
2017-01-11 10:37:00
2017-01-11 10:38:00
2017-01-11 10:39:00
2017-01-11 10:40:00
2017-01-11 10:41:00
2017-01-11 10:42:00
2017-01-11 10:43:00
2017-01-11 10:44:00
2017-01-11 10:45:00
2017-01-11 10:46:00
2017-01-11 10:47:00


2017-01-12 10:37:00
2017-01-12 10:38:00
2017-01-12 10:39:00
2017-01-12 10:40:00
2017-01-12 10:41:00
2017-01-12 10:42:00
2017-01-12 10:43:00
2017-01-12 10:44:00
2017-01-12 10:45:00
2017-01-12 10:46:00
2017-01-12 10:47:00
2017-01-12 10:48:00
2017-01-12 10:49:00
2017-01-12 10:50:00
2017-01-12 10:51:00
2017-01-12 10:52:00
2017-01-12 10:53:00
2017-01-12 10:54:00
2017-01-12 10:55:00
2017-01-12 10:56:00
2017-01-12 10:57:00
2017-01-12 10:58:00
2017-01-12 10:59:00
2017-01-12 11:00:00
2017-01-12 11:01:00
2017-01-12 11:02:00
2017-01-12 11:03:00
2017-01-12 11:04:00
2017-01-12 11:05:00
2017-01-12 11:06:00
2017-01-12 11:07:00
2017-01-12 11:08:00
2017-01-12 11:09:00
2017-01-12 11:10:00
2017-01-12 11:11:00
2017-01-12 11:12:00
2017-01-12 11:13:00
2017-01-12 11:14:00
2017-01-12 11:15:00
2017-01-12 11:16:00
2017-01-12 11:17:00
2017-01-12 11:18:00
2017-01-12 11:19:00
2017-01-12 11:20:00
2017-01-12 11:21:00
2017-01-12 11:22:00
2017-01-12 11:23:00
2017-01-12 11:24:00
2017-01-12 11:25:00
2017-01-12 11:26:00


2017-01-13 11:14:00
2017-01-13 11:15:00
2017-01-13 11:16:00
2017-01-13 11:17:00
2017-01-13 11:18:00
2017-01-13 11:19:00
2017-01-13 11:20:00
2017-01-13 11:21:00
2017-01-13 11:22:00
2017-01-13 11:23:00
2017-01-13 11:24:00
2017-01-13 11:25:00
2017-01-13 11:26:00
2017-01-13 11:27:00
2017-01-13 11:28:00
2017-01-13 11:29:00
2017-01-13 11:30:00
2017-01-13 11:31:00
2017-01-13 11:32:00
2017-01-13 11:33:00
2017-01-13 11:34:00
2017-01-13 11:35:00
2017-01-13 11:36:00
2017-01-13 11:37:00
2017-01-13 11:38:00
2017-01-13 11:39:00
2017-01-13 11:40:00
2017-01-13 11:41:00
2017-01-13 11:42:00
2017-01-13 11:43:00
2017-01-13 11:44:00
2017-01-13 11:45:00
2017-01-13 11:46:00
2017-01-13 11:47:00
2017-01-13 11:48:00
2017-01-13 11:49:00
2017-01-13 11:50:00
2017-01-13 11:51:00
2017-01-13 11:52:00
2017-01-13 11:53:00
2017-01-13 11:54:00
2017-01-13 11:55:00
2017-01-13 11:56:00
2017-01-13 11:57:00
2017-01-13 11:58:00
2017-01-13 11:59:00
2017-01-13 12:00:00
2017-01-13 12:01:00
2017-01-13 12:02:00
2017-01-13 12:03:00


...

2017-01-25 15:05:00
2017-01-25 15:06:00
2017-01-25 15:07:00
2017-01-25 15:08:00
2017-01-25 15:09:00
2017-01-25 15:10:00
2017-01-25 15:11:00
2017-01-25 15:12:00
2017-01-25 15:13:00
2017-01-25 15:14:00
2017-01-25 15:15:00
2017-01-25 15:16:00
2017-01-25 15:17:00
2017-01-25 15:18:00
2017-01-25 15:19:00
2017-01-25 15:20:00
2017-01-25 15:21:00
2017-01-25 15:22:00
2017-01-25 15:23:00
2017-01-25 15:24:00
2017-01-25 15:25:00
2017-01-25 15:26:00
2017-01-25 15:27:00
2017-01-25 15:28:00
2017-01-25 15:29:00
2017-01-26 09:17:00
2017-01-26 09:18:00
2017-01-26 09:19:00
2017-01-26 09:20:00
2017-01-26 09:21:00
2017-01-26 09:22:00
2017-01-26 09:23:00
2017-01-26 09:24:00
2017-01-26 09:25:00
2017-01-26 09:26:00
2017-01-26 09:27:00
2017-01-26 09:28:00
2017-01-26 09:29:00
2017-01-26 09:30:00
2017-01-26 09:31:00
2017-01-26 09:32:00
2017-01-26 09:33:00
2017-01-26 09:34:00
2017-01-26 09:35:00
2017-01-26 09:36:00
2017-01-26 09:37:00
2017-01-26 09:38:00
2017-01-26 09:39:00
2017-01-26 09:40:00
2017-01-26 09:41:00


2017-01-27 09:30:00
2017-01-27 09:31:00
2017-01-27 09:32:00
2017-01-27 09:33:00
2017-01-27 09:34:00
2017-01-27 09:35:00
2017-01-27 09:36:00
2017-01-27 09:37:00
2017-01-27 09:38:00
2017-01-27 09:39:00
2017-01-27 09:40:00
2017-01-27 09:41:00
2017-01-27 09:42:00
2017-01-27 09:43:00
2017-01-27 09:44:00
2017-01-27 09:45:00
2017-01-27 09:46:00
2017-01-27 09:47:00
2017-01-27 09:48:00
2017-01-27 09:49:00
2017-01-27 09:50:00
2017-01-27 09:51:00
2017-01-27 09:52:00
2017-01-27 09:53:00
2017-01-27 09:54:00
2017-01-27 09:55:00
2017-01-27 09:56:00
2017-01-27 09:57:00
2017-01-27 09:58:00
2017-01-27 09:59:00
2017-01-27 10:00:00
2017-01-27 10:01:00
2017-01-27 10:02:00
2017-01-27 10:03:00
2017-01-27 10:04:00
2017-01-27 10:05:00
2017-01-27 10:06:00
2017-01-27 10:07:00
2017-01-27 10:08:00
2017-01-27 10:09:00
2017-01-27 10:10:00
2017-01-27 10:11:00
2017-01-27 10:12:00
2017-01-27 10:13:00
2017-01-27 10:14:00
2017-01-27 10:15:00
2017-01-27 10:16:00
2017-01-27 10:17:00
2017-01-27 10:18:00
2017-01-27 10:19:00


2017-01-30 10:08:00
2017-01-30 10:09:00
2017-01-30 10:10:00
2017-01-30 10:11:00
2017-01-30 10:12:00
2017-01-30 10:13:00
2017-01-30 10:14:00
2017-01-30 10:15:00
2017-01-30 10:16:00
2017-01-30 10:17:00
2017-01-30 10:18:00
2017-01-30 10:19:00
2017-01-30 10:20:00
2017-01-30 10:21:00
2017-01-30 10:22:00
2017-01-30 10:23:00
2017-01-30 10:24:00
2017-01-30 10:25:00
2017-01-30 10:26:00
2017-01-30 10:27:00
2017-01-30 10:28:00
2017-01-30 10:29:00
2017-01-30 10:30:00
2017-01-30 10:31:00
2017-01-30 10:32:00
2017-01-30 10:33:00
2017-01-30 10:34:00
2017-01-30 10:35:00
2017-01-30 10:36:00
2017-01-30 10:37:00
2017-01-30 10:38:00
2017-01-30 10:39:00
2017-01-30 10:40:00
2017-01-30 10:41:00
2017-01-30 10:42:00
2017-01-30 10:43:00
2017-01-30 10:44:00
2017-01-30 10:45:00
2017-01-30 10:46:00
2017-01-30 10:47:00
2017-01-30 10:48:00
2017-01-30 10:49:00
2017-01-30 10:50:00
2017-01-30 10:51:00
2017-01-30 10:52:00
2017-01-30 10:53:00
2017-01-30 10:54:00
2017-01-30 10:55:00
2017-01-30 10:56:00
2017-01-30 10:57:00


2017-01-31 10:46:00
2017-01-31 10:47:00
2017-01-31 10:48:00
2017-01-31 10:49:00
2017-01-31 10:50:00
2017-01-31 10:51:00
2017-01-31 10:52:00
2017-01-31 10:53:00
2017-01-31 10:54:00
2017-01-31 10:55:00
2017-01-31 10:56:00
2017-01-31 10:57:00
2017-01-31 10:58:00
2017-01-31 10:59:00
2017-01-31 11:00:00
2017-01-31 11:01:00
2017-01-31 11:02:00
2017-01-31 11:03:00
2017-01-31 11:04:00
2017-01-31 11:05:00
2017-01-31 11:06:00
2017-01-31 11:07:00
2017-01-31 11:08:00
2017-01-31 11:09:00
2017-01-31 11:10:00
2017-01-31 11:11:00
2017-01-31 11:12:00
2017-01-31 11:13:00
2017-01-31 11:14:00
2017-01-31 11:15:00
2017-01-31 11:16:00
2017-01-31 11:17:00
2017-01-31 11:18:00
2017-01-31 11:19:00
2017-01-31 11:20:00
2017-01-31 11:21:00
2017-01-31 11:22:00
2017-01-31 11:23:00
2017-01-31 11:24:00
2017-01-31 11:25:00
2017-01-31 11:26:00
2017-01-31 11:27:00
2017-01-31 11:28:00
2017-01-31 11:29:00
2017-01-31 11:30:00
2017-01-31 11:31:00
2017-01-31 11:32:00
2017-01-31 11:33:00
2017-01-31 11:34:00
2017-01-31 11:35:00


2017-02-01 11:25:00
2017-02-01 11:26:00
2017-02-01 11:27:00
2017-02-01 11:28:00
2017-02-01 11:29:00
2017-02-01 11:30:00
2017-02-01 11:31:00
2017-02-01 11:32:00
2017-02-01 11:33:00
2017-02-01 11:34:00
2017-02-01 11:35:00
2017-02-01 11:36:00
2017-02-01 11:37:00
2017-02-01 11:38:00
2017-02-01 11:39:00
2017-02-01 11:40:00
2017-02-01 11:41:00
2017-02-01 11:42:00
2017-02-01 11:43:00
2017-02-01 11:44:00
2017-02-01 11:45:00
2017-02-01 11:46:00
2017-02-01 11:47:00
2017-02-01 11:48:00
2017-02-01 11:49:00
2017-02-01 11:50:00
2017-02-01 11:51:00
2017-02-01 11:52:00
2017-02-01 11:53:00
2017-02-01 11:54:00
2017-02-01 11:55:00
2017-02-01 11:56:00
2017-02-01 11:57:00
2017-02-01 11:58:00
2017-02-01 11:59:00
2017-02-01 12:00:00
2017-02-01 12:01:00
2017-02-01 12:02:00
2017-02-01 12:03:00
2017-02-01 12:04:00
2017-02-01 12:05:00
2017-02-01 12:06:00
2017-02-01 12:07:00
2017-02-01 12:08:00
2017-02-01 12:09:00
2017-02-01 12:10:00
2017-02-01 12:11:00
2017-02-01 12:12:00
2017-02-01 12:13:00
2017-02-01 12:14:00


In [6]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData1" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return ['FCY',
 'FRE',
 'ILW',
 'JSG',
 'KMV',
 'NSL',
 'PUO',
 'QRK',
 'SCN',
 'TWK',
 'UWD',
 'VTN',
 'XCS',
 'ZEW',
 'SVG',
 'DFZ',
 'GYJ',
 'GYV',
 'VKE',
 'AUZ']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 1,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 5,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: FCY
Processing data for stock: FRE
Processing data for stock: ILW
Processing data for stock: JSG
Processing data for stock: KMV
Processing data for stock: NSL
Processing data for stock: PUO
Processing data for stock: QRK
Processing data for stock: SCN
Processing data for stock: TWK
Processing data for stock: UWD
Processing data for stock: VTN
Processing data for stock: XCS
Processing data for stock: ZEW
Processing data for stock: SVG
Processing data for stock: DFZ
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: VKE
Processing data for stock: AUZ
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-06 09:17:00
2017-01-06 09:18:00
2017-01-06 09:19:00
2017-01-06 09:20:00
2017-01-06 09:21:00
2017-01-06 09:22:00
2017-01-06 09:23:00
2017-01-06 09:24:00
2017-01-06 09:25:00
2017-01-06 09:26:00
2017-01-06 09:27:00
2017-01-06 09:28:00
2017-01-06

2017-01-09 09:20:00
2017-01-09 09:21:00
2017-01-09 09:22:00
2017-01-09 09:23:00
2017-01-09 09:24:00
2017-01-09 09:25:00
2017-01-09 09:26:00
2017-01-09 09:27:00
2017-01-09 09:28:00
2017-01-09 09:29:00
2017-01-09 09:30:00
2017-01-09 09:31:00
2017-01-09 09:32:00
2017-01-09 09:33:00
2017-01-09 09:34:00
2017-01-09 09:35:00
2017-01-09 09:36:00
2017-01-09 09:37:00
2017-01-09 09:38:00
2017-01-09 09:39:00
2017-01-09 09:40:00
2017-01-09 09:41:00
2017-01-09 09:42:00
2017-01-09 09:43:00
2017-01-09 09:44:00
2017-01-09 09:45:00
2017-01-09 09:46:00
2017-01-09 09:47:00
2017-01-09 09:48:00
2017-01-09 09:49:00
2017-01-09 09:50:00
2017-01-09 09:51:00
2017-01-09 09:52:00
2017-01-09 09:53:00
2017-01-09 09:54:00
2017-01-09 09:55:00
2017-01-09 09:56:00
2017-01-09 09:57:00
2017-01-09 09:58:00
2017-01-09 09:59:00
2017-01-09 10:00:00
2017-01-09 10:01:00
2017-01-09 10:02:00
2017-01-09 10:03:00
2017-01-09 10:04:00
2017-01-09 10:05:00
2017-01-09 10:06:00
2017-01-09 10:07:00
2017-01-09 10:08:00
2017-01-09 10:09:00


2017-01-10 09:57:00
2017-01-10 09:58:00
2017-01-10 09:59:00
2017-01-10 10:00:00
2017-01-10 10:01:00
2017-01-10 10:02:00
2017-01-10 10:03:00
2017-01-10 10:04:00
2017-01-10 10:05:00
2017-01-10 10:06:00
2017-01-10 10:07:00
2017-01-10 10:08:00
2017-01-10 10:09:00
2017-01-10 10:10:00
2017-01-10 10:11:00
2017-01-10 10:12:00
2017-01-10 10:13:00
2017-01-10 10:14:00
2017-01-10 10:15:00
2017-01-10 10:16:00
2017-01-10 10:17:00
2017-01-10 10:18:00
2017-01-10 10:19:00
2017-01-10 10:20:00
2017-01-10 10:21:00
2017-01-10 10:22:00
2017-01-10 10:23:00
2017-01-10 10:24:00
2017-01-10 10:25:00
2017-01-10 10:26:00
2017-01-10 10:27:00
2017-01-10 10:28:00
2017-01-10 10:29:00
2017-01-10 10:30:00
2017-01-10 10:31:00
2017-01-10 10:32:00
2017-01-10 10:33:00
2017-01-10 10:34:00
2017-01-10 10:35:00
2017-01-10 10:36:00
2017-01-10 10:37:00
2017-01-10 10:38:00
2017-01-10 10:39:00
2017-01-10 10:40:00
2017-01-10 10:41:00
2017-01-10 10:42:00
2017-01-10 10:43:00
2017-01-10 10:44:00
2017-01-10 10:45:00
2017-01-10 10:46:00


2017-01-11 10:38:00
2017-01-11 10:39:00
2017-01-11 10:40:00
2017-01-11 10:41:00
2017-01-11 10:42:00
2017-01-11 10:43:00
2017-01-11 10:44:00
2017-01-11 10:45:00
2017-01-11 10:46:00
2017-01-11 10:47:00
2017-01-11 10:48:00
2017-01-11 10:49:00
2017-01-11 10:50:00
2017-01-11 10:51:00
2017-01-11 10:52:00
2017-01-11 10:53:00
2017-01-11 10:54:00
2017-01-11 10:55:00
2017-01-11 10:56:00
2017-01-11 10:57:00
2017-01-11 10:58:00
2017-01-11 10:59:00
2017-01-11 11:00:00
2017-01-11 11:01:00
2017-01-11 11:02:00
2017-01-11 11:03:00
2017-01-11 11:04:00
2017-01-11 11:05:00
2017-01-11 11:06:00
2017-01-11 11:07:00
2017-01-11 11:08:00
2017-01-11 11:09:00
2017-01-11 11:10:00
2017-01-11 11:11:00
2017-01-11 11:12:00
2017-01-11 11:13:00
2017-01-11 11:14:00
2017-01-11 11:15:00
2017-01-11 11:16:00
2017-01-11 11:17:00
2017-01-11 11:18:00
2017-01-11 11:19:00
2017-01-11 11:20:00
2017-01-11 11:21:00
2017-01-11 11:22:00
2017-01-11 11:23:00
2017-01-11 11:24:00
2017-01-11 11:25:00
2017-01-11 11:26:00
2017-01-11 11:27:00


2017-01-12 11:19:00
2017-01-12 11:20:00
2017-01-12 11:21:00
2017-01-12 11:22:00
2017-01-12 11:23:00
2017-01-12 11:24:00
2017-01-12 11:25:00
2017-01-12 11:26:00
2017-01-12 11:27:00
2017-01-12 11:28:00
2017-01-12 11:29:00
2017-01-12 11:30:00
2017-01-12 11:31:00
2017-01-12 11:32:00
2017-01-12 11:33:00
2017-01-12 11:34:00
2017-01-12 11:35:00
2017-01-12 11:36:00
2017-01-12 11:37:00
2017-01-12 11:38:00
2017-01-12 11:39:00
2017-01-12 11:40:00
2017-01-12 11:41:00
2017-01-12 11:42:00
2017-01-12 11:43:00
2017-01-12 11:44:00
2017-01-12 11:45:00
2017-01-12 11:46:00
2017-01-12 11:47:00
2017-01-12 11:48:00
2017-01-12 11:49:00
2017-01-12 11:50:00
2017-01-12 11:51:00
2017-01-12 11:52:00
2017-01-12 11:53:00
2017-01-12 11:54:00
2017-01-12 11:55:00
2017-01-12 11:56:00
2017-01-12 11:57:00
2017-01-12 11:58:00
2017-01-12 11:59:00
2017-01-12 12:00:00
2017-01-12 12:01:00
2017-01-12 12:02:00
2017-01-12 12:03:00
2017-01-12 12:04:00
2017-01-12 12:05:00
2017-01-12 12:06:00
2017-01-12 12:07:00
2017-01-12 12:08:00


...

2017-02-01 13:27:00
2017-02-01 13:28:00
2017-02-01 13:29:00
2017-02-01 13:30:00
2017-02-01 13:31:00
2017-02-01 13:32:00
2017-02-01 13:33:00
2017-02-01 13:34:00
2017-02-01 13:35:00
2017-02-01 13:36:00
2017-02-01 13:37:00
2017-02-01 13:38:00
2017-02-01 13:39:00
2017-02-01 13:40:00
2017-02-01 13:41:00
2017-02-01 13:42:00
2017-02-01 13:43:00
2017-02-01 13:44:00
2017-02-01 13:45:00
2017-02-01 13:46:00
2017-02-01 13:47:00
2017-02-01 13:48:00
2017-02-01 13:49:00
2017-02-01 13:50:00
2017-02-01 13:51:00
2017-02-01 13:52:00
2017-02-01 13:53:00
2017-02-01 13:54:00
2017-02-01 13:55:00
2017-02-01 13:56:00
2017-02-01 13:57:00
2017-02-01 13:58:00
2017-02-01 13:59:00
2017-02-01 14:00:00
2017-02-01 14:01:00
2017-02-01 14:02:00
2017-02-01 14:03:00
2017-02-01 14:04:00
2017-02-01 14:05:00
2017-02-01 14:06:00
2017-02-01 14:07:00
2017-02-01 14:08:00
2017-02-01 14:09:00
2017-02-01 14:10:00
2017-02-01 14:11:00
2017-02-01 14:12:00
2017-02-01 14:13:00
2017-02-01 14:14:00
2017-02-01 14:15:00
2017-02-01 14:16:00


2017-02-02 14:06:00
2017-02-02 14:07:00
2017-02-02 14:08:00
2017-02-02 14:09:00
2017-02-02 14:10:00
2017-02-02 14:11:00
2017-02-02 14:12:00
2017-02-02 14:13:00
2017-02-02 14:14:00
2017-02-02 14:15:00
2017-02-02 14:16:00
2017-02-02 14:17:00
2017-02-02 14:18:00
2017-02-02 14:19:00
2017-02-02 14:20:00
2017-02-02 14:21:00
2017-02-02 14:22:00
2017-02-02 14:23:00
2017-02-02 14:24:00
2017-02-02 14:25:00
2017-02-02 14:26:00
2017-02-02 14:27:00
2017-02-02 14:28:00
2017-02-02 14:29:00
2017-02-02 14:30:00
2017-02-02 14:31:00
2017-02-02 14:32:00
2017-02-02 14:33:00
2017-02-02 14:34:00
2017-02-02 14:35:00
2017-02-02 14:36:00
2017-02-02 14:37:00
2017-02-02 14:38:00
2017-02-02 14:39:00
2017-02-02 14:40:00
2017-02-02 14:41:00
2017-02-02 14:42:00
2017-02-02 14:43:00
2017-02-02 14:44:00
2017-02-02 14:45:00
2017-02-02 14:46:00
2017-02-02 14:47:00
2017-02-02 14:48:00
2017-02-02 14:49:00
2017-02-02 14:50:00
2017-02-02 14:51:00
2017-02-02 14:52:00
2017-02-02 14:53:00
2017-02-02 14:54:00
2017-02-02 14:55:00


2017-02-03 14:46:00
2017-02-03 14:47:00
2017-02-03 14:48:00
2017-02-03 14:49:00
2017-02-03 14:50:00
2017-02-03 14:51:00
2017-02-03 14:52:00
2017-02-03 14:53:00
2017-02-03 14:54:00
2017-02-03 14:55:00
2017-02-03 14:56:00
2017-02-03 14:57:00
2017-02-03 14:58:00
2017-02-03 14:59:00
2017-02-03 15:00:00
2017-02-03 15:01:00
2017-02-03 15:02:00
2017-02-03 15:03:00
2017-02-03 15:04:00
2017-02-03 15:05:00
2017-02-03 15:06:00
2017-02-03 15:07:00
2017-02-03 15:08:00
2017-02-03 15:09:00
2017-02-03 15:10:00
2017-02-03 15:11:00
2017-02-03 15:12:00
2017-02-03 15:13:00
2017-02-03 15:14:00
2017-02-03 15:15:00
2017-02-03 15:16:00
2017-02-03 15:17:00
2017-02-03 15:18:00
2017-02-03 15:19:00
2017-02-03 15:20:00
2017-02-03 15:21:00
2017-02-03 15:22:00
2017-02-03 15:23:00
2017-02-03 15:24:00
2017-02-03 15:25:00
2017-02-03 15:26:00
2017-02-03 15:27:00
2017-02-03 15:28:00
2017-02-03 15:29:00
2017-02-07 09:17:00
2017-02-07 09:18:00
2017-02-07 09:19:00
2017-02-07 09:20:00
2017-02-07 09:21:00
2017-02-07 09:22:00


2017-02-07 15:27:00
2017-02-07 15:28:00
2017-02-07 15:29:00
2017-02-08 09:17:00
2017-02-08 09:18:00
2017-02-08 09:19:00
2017-02-08 09:20:00
2017-02-08 09:21:00
2017-02-08 09:22:00
2017-02-08 09:23:00
2017-02-08 09:24:00
2017-02-08 09:25:00
2017-02-08 09:26:00
2017-02-08 09:27:00
2017-02-08 09:28:00
2017-02-08 09:29:00
2017-02-08 09:30:00
2017-02-08 09:31:00
2017-02-08 09:32:00
2017-02-08 09:33:00
2017-02-08 09:34:00
2017-02-08 09:35:00
2017-02-08 09:36:00
2017-02-08 09:37:00
2017-02-08 09:38:00
2017-02-08 09:39:00
2017-02-08 09:40:00
2017-02-08 09:41:00
2017-02-08 09:42:00
2017-02-08 09:43:00
2017-02-08 09:44:00
2017-02-08 09:45:00
2017-02-08 09:46:00
2017-02-08 09:47:00
2017-02-08 09:48:00
2017-02-08 09:49:00
2017-02-08 09:50:00
2017-02-08 09:51:00
2017-02-08 09:52:00
2017-02-08 09:53:00
2017-02-08 09:54:00
2017-02-08 09:55:00
2017-02-08 09:56:00
2017-02-08 09:57:00
2017-02-08 09:58:00
2017-02-08 09:59:00
2017-02-08 10:00:00
2017-02-08 10:01:00
2017-02-08 10:02:00
2017-02-08 10:03:00


2017-02-09 09:54:00
2017-02-09 09:55:00
2017-02-09 09:56:00
2017-02-09 09:57:00
2017-02-09 09:58:00
2017-02-09 09:59:00
2017-02-09 10:00:00
2017-02-09 10:01:00
2017-02-09 10:02:00
2017-02-09 10:03:00
2017-02-09 10:04:00
2017-02-09 10:05:00
2017-02-09 10:06:00
2017-02-09 10:07:00
2017-02-09 10:08:00
2017-02-09 10:09:00
2017-02-09 10:10:00
2017-02-09 10:11:00
2017-02-09 10:12:00
2017-02-09 10:13:00
2017-02-09 10:14:00
2017-02-09 10:15:00
2017-02-09 10:16:00
2017-02-09 10:17:00
2017-02-09 10:18:00
2017-02-09 10:19:00
2017-02-09 10:20:00
2017-02-09 10:21:00
2017-02-09 10:22:00
2017-02-09 10:23:00
2017-02-09 10:24:00
2017-02-09 10:25:00
2017-02-09 10:26:00
2017-02-09 10:27:00
2017-02-09 10:28:00
2017-02-09 10:29:00
2017-02-09 10:30:00
2017-02-09 10:31:00
2017-02-09 10:32:00
2017-02-09 10:33:00
2017-02-09 10:34:00
2017-02-09 10:35:00
2017-02-09 10:36:00
2017-02-09 10:37:00
2017-02-09 10:38:00
2017-02-09 10:39:00
2017-02-09 10:40:00
2017-02-09 10:41:00
2017-02-09 10:42:00
2017-02-09 10:43:00


In [7]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData2" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return ['FCY',
 'FRE',
 'ILW',
 'JSG',
 'KMV',
 'NSL',
 'PUO',
 'QRK',
 'SCN',
 'TWK',
 'UWD',
 'VTN',
 'XCS',
 'ZEW',
 'SVG',
 'DFZ',
 'GYJ',
 'GYV',
 'VKE',
 'AUZ']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 1,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 5,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: FCY
Processing data for stock: FRE
Processing data for stock: ILW
Processing data for stock: JSG
Processing data for stock: KMV
Processing data for stock: NSL
Processing data for stock: PUO
Processing data for stock: QRK
Processing data for stock: SCN
Processing data for stock: TWK
Processing data for stock: UWD
Processing data for stock: VTN
Processing data for stock: XCS
Processing data for stock: ZEW
Processing data for stock: SVG
Processing data for stock: DFZ
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: VKE
Processing data for stock: AUZ
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-13 09:17:00
2017-01-13 09:18:00
2017-01-13 09:19:00
2017-01-13 09:20:00
2017-01-13 09:21:00
2017-01-13 09:22:00
2017-01-13 09:23:00
2017-01-13 09:24:00
2017-01-13 09:25:00
2017-01-13 09:26:00
2017-01-13 09:27:00
2017-01-13 09:28:00
2017-01-13

2017-01-16 09:19:00
2017-01-16 09:20:00
2017-01-16 09:21:00
2017-01-16 09:22:00
2017-01-16 09:23:00
2017-01-16 09:24:00
2017-01-16 09:25:00
2017-01-16 09:26:00
2017-01-16 09:27:00
2017-01-16 09:28:00
2017-01-16 09:29:00
2017-01-16 09:30:00
2017-01-16 09:31:00
2017-01-16 09:32:00
2017-01-16 09:33:00
2017-01-16 09:34:00
2017-01-16 09:35:00
2017-01-16 09:36:00
2017-01-16 09:37:00
2017-01-16 09:38:00
2017-01-16 09:39:00
2017-01-16 09:40:00
2017-01-16 09:41:00
2017-01-16 09:42:00
2017-01-16 09:43:00
2017-01-16 09:44:00
2017-01-16 09:45:00
2017-01-16 09:46:00
2017-01-16 09:47:00
2017-01-16 09:48:00
2017-01-16 09:49:00
2017-01-16 09:50:00
2017-01-16 09:51:00
2017-01-16 09:52:00
2017-01-16 09:53:00
2017-01-16 09:54:00
2017-01-16 09:55:00
2017-01-16 09:56:00
2017-01-16 09:57:00
2017-01-16 09:58:00
2017-01-16 09:59:00
2017-01-16 10:00:00
2017-01-16 10:01:00
2017-01-16 10:02:00
2017-01-16 10:03:00
2017-01-16 10:04:00
2017-01-16 10:05:00
2017-01-16 10:06:00
2017-01-16 10:07:00
2017-01-16 10:08:00


2017-01-18 09:57:00
2017-01-18 09:58:00
2017-01-18 09:59:00
2017-01-18 10:00:00
2017-01-18 10:01:00
2017-01-18 10:02:00
2017-01-18 10:03:00
2017-01-18 10:04:00
2017-01-18 10:05:00
2017-01-18 10:06:00
2017-01-18 10:07:00
2017-01-18 10:08:00
2017-01-18 10:09:00
2017-01-18 10:10:00
2017-01-18 10:11:00
2017-01-18 10:12:00
2017-01-18 10:13:00
2017-01-18 10:14:00
2017-01-18 10:15:00
2017-01-18 10:16:00
2017-01-18 10:17:00
2017-01-18 10:18:00
2017-01-18 10:19:00
2017-01-18 10:20:00
2017-01-18 10:21:00
2017-01-18 10:22:00
2017-01-18 10:23:00
2017-01-18 10:24:00
2017-01-18 10:25:00
2017-01-18 10:26:00
2017-01-18 10:27:00
2017-01-18 10:28:00
2017-01-18 10:29:00
2017-01-18 10:30:00
2017-01-18 10:31:00
2017-01-18 10:32:00
2017-01-18 10:33:00
2017-01-18 10:34:00
2017-01-18 10:35:00
2017-01-18 10:36:00
2017-01-18 10:37:00
2017-01-18 10:38:00
2017-01-18 10:39:00
2017-01-18 10:40:00
2017-01-18 10:41:00
2017-01-18 10:42:00
2017-01-18 10:43:00
2017-01-18 10:44:00
2017-01-18 10:45:00
2017-01-18 10:46:00


2017-01-19 10:34:00
2017-01-19 10:35:00
2017-01-19 10:36:00
2017-01-19 10:37:00
2017-01-19 10:38:00
2017-01-19 10:39:00
2017-01-19 10:40:00
2017-01-19 10:41:00
2017-01-19 10:42:00
2017-01-19 10:43:00
2017-01-19 10:44:00
2017-01-19 10:45:00
2017-01-19 10:46:00
2017-01-19 10:47:00
2017-01-19 10:48:00
2017-01-19 10:49:00
2017-01-19 10:50:00
2017-01-19 10:51:00
2017-01-19 10:52:00
2017-01-19 10:53:00
2017-01-19 10:54:00
2017-01-19 10:55:00
2017-01-19 10:56:00
2017-01-19 10:57:00
2017-01-19 10:58:00
2017-01-19 10:59:00
2017-01-19 11:00:00
2017-01-19 11:01:00
2017-01-19 11:02:00
2017-01-19 11:03:00
2017-01-19 11:04:00
2017-01-19 11:05:00
2017-01-19 11:06:00
2017-01-19 11:07:00
2017-01-19 11:08:00
2017-01-19 11:09:00
2017-01-19 11:10:00
2017-01-19 11:11:00
2017-01-19 11:12:00
2017-01-19 11:13:00
2017-01-19 11:14:00
2017-01-19 11:15:00
2017-01-19 11:16:00
2017-01-19 11:17:00
2017-01-19 11:18:00
2017-01-19 11:19:00
2017-01-19 11:20:00
2017-01-19 11:21:00
2017-01-19 11:22:00
2017-01-19 11:23:00


2017-01-20 11:14:00
2017-01-20 11:15:00
2017-01-20 11:16:00
2017-01-20 11:17:00
2017-01-20 11:18:00
2017-01-20 11:19:00
2017-01-20 11:20:00
2017-01-20 11:21:00
2017-01-20 11:22:00
2017-01-20 11:23:00
2017-01-20 11:24:00
2017-01-20 11:25:00
2017-01-20 11:26:00
2017-01-20 11:27:00
2017-01-20 11:28:00
2017-01-20 11:29:00
2017-01-20 11:30:00
2017-01-20 11:31:00
2017-01-20 11:32:00
2017-01-20 11:33:00
2017-01-20 11:34:00
2017-01-20 11:35:00
2017-01-20 11:36:00
2017-01-20 11:37:00
2017-01-20 11:38:00
2017-01-20 11:39:00
2017-01-20 11:40:00
2017-01-20 11:41:00
2017-01-20 11:42:00
2017-01-20 11:43:00
2017-01-20 11:44:00
2017-01-20 11:45:00
2017-01-20 11:46:00
2017-01-20 11:47:00
2017-01-20 11:48:00
2017-01-20 11:49:00
2017-01-20 11:50:00
2017-01-20 11:51:00
2017-01-20 11:52:00
2017-01-20 11:53:00
2017-01-20 11:54:00
2017-01-20 11:55:00
2017-01-20 11:56:00
2017-01-20 11:57:00
2017-01-20 11:58:00
2017-01-20 11:59:00
2017-01-20 12:00:00
2017-01-20 12:01:00
2017-01-20 12:02:00
2017-01-20 12:03:00


...

2017-02-02 09:31:00
2017-02-02 09:32:00
2017-02-02 09:33:00
2017-02-02 09:34:00
2017-02-02 09:35:00
2017-02-02 09:36:00
2017-02-02 09:37:00
2017-02-02 09:38:00
2017-02-02 09:39:00
2017-02-02 09:40:00
2017-02-02 09:41:00
2017-02-02 09:42:00
2017-02-02 09:43:00
2017-02-02 09:44:00
2017-02-02 09:45:00
2017-02-02 09:46:00
2017-02-02 09:47:00
2017-02-02 09:48:00
2017-02-02 09:49:00
2017-02-02 09:50:00
2017-02-02 09:51:00
2017-02-02 09:52:00
2017-02-02 09:53:00
2017-02-02 09:54:00
2017-02-02 09:55:00
2017-02-02 09:56:00
2017-02-02 09:57:00
2017-02-02 09:58:00
2017-02-02 09:59:00
2017-02-02 10:00:00
2017-02-02 10:01:00
2017-02-02 10:02:00
2017-02-02 10:03:00
2017-02-02 10:04:00
2017-02-02 10:05:00
2017-02-02 10:06:00
2017-02-02 10:07:00
2017-02-02 10:08:00
2017-02-02 10:09:00
2017-02-02 10:10:00
2017-02-02 10:11:00
2017-02-02 10:12:00
2017-02-02 10:13:00
2017-02-02 10:14:00
2017-02-02 10:15:00
2017-02-02 10:16:00
2017-02-02 10:17:00
2017-02-02 10:18:00
2017-02-02 10:19:00
2017-02-02 10:20:00


2017-02-03 10:11:00
2017-02-03 10:12:00
2017-02-03 10:13:00
2017-02-03 10:14:00
2017-02-03 10:15:00
2017-02-03 10:16:00
2017-02-03 10:17:00
2017-02-03 10:18:00
2017-02-03 10:19:00
2017-02-03 10:20:00
2017-02-03 10:21:00
2017-02-03 10:22:00
2017-02-03 10:23:00
2017-02-03 10:24:00
2017-02-03 10:25:00
2017-02-03 10:26:00
2017-02-03 10:27:00
2017-02-03 10:28:00
2017-02-03 10:29:00
2017-02-03 10:30:00
2017-02-03 10:31:00
2017-02-03 10:32:00
2017-02-03 10:33:00
2017-02-03 10:34:00
2017-02-03 10:35:00
2017-02-03 10:36:00
2017-02-03 10:37:00
2017-02-03 10:38:00
2017-02-03 10:39:00
2017-02-03 10:40:00
2017-02-03 10:41:00
2017-02-03 10:42:00
2017-02-03 10:43:00
2017-02-03 10:44:00
2017-02-03 10:45:00
2017-02-03 10:46:00
2017-02-03 10:47:00
2017-02-03 10:48:00
2017-02-03 10:49:00
2017-02-03 10:50:00
2017-02-03 10:51:00
2017-02-03 10:52:00
2017-02-03 10:53:00
2017-02-03 10:54:00
2017-02-03 10:55:00
2017-02-03 10:56:00
2017-02-03 10:57:00
2017-02-03 10:58:00
2017-02-03 10:59:00
2017-02-03 11:00:00


2017-02-06 10:48:00
2017-02-06 10:49:00
2017-02-06 10:50:00
2017-02-06 10:51:00
2017-02-06 10:52:00
2017-02-06 10:53:00
2017-02-06 10:54:00
2017-02-06 10:55:00
2017-02-06 10:56:00
2017-02-06 10:57:00
2017-02-06 10:58:00
2017-02-06 10:59:00
2017-02-06 11:00:00
2017-02-06 11:01:00
2017-02-06 11:02:00
2017-02-06 11:03:00
2017-02-06 11:04:00
2017-02-06 11:05:00
2017-02-06 11:06:00
2017-02-06 11:07:00
2017-02-06 11:08:00
2017-02-06 11:09:00
2017-02-06 11:10:00
2017-02-06 11:11:00
2017-02-06 11:12:00
2017-02-06 11:13:00
2017-02-06 11:14:00
2017-02-06 11:15:00
2017-02-06 11:16:00
2017-02-06 11:17:00
2017-02-06 11:18:00
2017-02-06 11:19:00
2017-02-06 11:20:00
2017-02-06 11:21:00
2017-02-06 11:22:00
2017-02-06 11:23:00
2017-02-06 11:24:00
2017-02-06 11:25:00
2017-02-06 11:26:00
2017-02-06 11:27:00
2017-02-06 11:28:00
2017-02-06 11:29:00
2017-02-06 11:30:00
2017-02-06 11:31:00
2017-02-06 11:32:00
2017-02-06 11:33:00
2017-02-06 11:34:00
2017-02-06 11:35:00
2017-02-06 11:36:00
2017-02-06 11:37:00


2017-02-07 11:26:00
2017-02-07 11:27:00
2017-02-07 11:28:00
2017-02-07 11:29:00
2017-02-07 11:30:00
2017-02-07 11:31:00
2017-02-07 11:32:00
2017-02-07 11:33:00
2017-02-07 11:34:00
2017-02-07 11:35:00
2017-02-07 11:36:00
2017-02-07 11:37:00
2017-02-07 11:38:00
2017-02-07 11:39:00
2017-02-07 11:40:00
2017-02-07 11:41:00
2017-02-07 11:42:00
2017-02-07 11:43:00
2017-02-07 11:44:00
2017-02-07 11:45:00
2017-02-07 11:46:00
2017-02-07 11:47:00
2017-02-07 11:48:00
2017-02-07 11:49:00
2017-02-07 11:50:00
2017-02-07 11:51:00
2017-02-07 11:52:00
2017-02-07 11:53:00
2017-02-07 11:54:00
2017-02-07 11:55:00
2017-02-07 11:56:00
2017-02-07 11:57:00
2017-02-07 11:58:00
2017-02-07 11:59:00
2017-02-07 12:00:00
2017-02-07 12:01:00
2017-02-07 12:02:00
2017-02-07 12:03:00
2017-02-07 12:04:00
2017-02-07 12:05:00
2017-02-07 12:06:00
2017-02-07 12:07:00
2017-02-07 12:08:00
2017-02-07 12:09:00
2017-02-07 12:10:00
2017-02-07 12:11:00
2017-02-07 12:12:00
2017-02-07 12:13:00
2017-02-07 12:14:00
2017-02-07 12:15:00


2017-02-08 12:05:00
2017-02-08 12:06:00
2017-02-08 12:07:00
2017-02-08 12:08:00
2017-02-08 12:09:00
2017-02-08 12:10:00
2017-02-08 12:11:00
2017-02-08 12:12:00
2017-02-08 12:13:00
2017-02-08 12:14:00
2017-02-08 12:15:00
2017-02-08 12:16:00
2017-02-08 12:17:00
2017-02-08 12:18:00
2017-02-08 12:19:00
2017-02-08 12:20:00
2017-02-08 12:21:00
2017-02-08 12:22:00
2017-02-08 12:23:00
2017-02-08 12:24:00
2017-02-08 12:25:00
2017-02-08 12:26:00
2017-02-08 12:27:00
2017-02-08 12:28:00
2017-02-08 12:29:00
2017-02-08 12:30:00
2017-02-08 12:31:00
2017-02-08 12:32:00
2017-02-08 12:33:00
2017-02-08 12:34:00
2017-02-08 12:35:00
2017-02-08 12:36:00
2017-02-08 12:37:00
2017-02-08 12:38:00
2017-02-08 12:39:00
2017-02-08 12:40:00
2017-02-08 12:41:00
2017-02-08 12:42:00
2017-02-08 12:43:00
2017-02-08 12:44:00
2017-02-08 12:45:00
2017-02-08 12:46:00
2017-02-08 12:47:00
2017-02-08 12:48:00
2017-02-08 12:49:00
2017-02-08 12:50:00
2017-02-08 12:51:00
2017-02-08 12:52:00
2017-02-08 12:53:00
2017-02-08 12:54:00


In [8]:
from backtester.features.feature import Feature
from backtester.trading_system import TradingSystem
from backtester.sample_scripts.fair_value_params import FairValueTradingParams
from backtester.version import updateCheck


class Problem1Solver():

    '''
    Specifies which training data set to use. Right now support
    trainingData1, trainingData2, trainingData3.
    '''

    def getTrainingDataSet(self):
        return "trainingData3" # Changed the data

    '''
    Returns the stocks to trade.
    If empty, uses all the stocks.
    '''

    def getSymbolsToTrade(self):
        return ['FCY',
 'FRE',
 'ILW',
 'JSG',
 'KMV',
 'NSL',
 'PUO',
 'QRK',
 'SCN',
 'TWK',
 'UWD',
 'VTN',
 'XCS',
 'ZEW',
 'SVG',
 'DFZ',
 'GYJ',
 'GYV',
 'VKE',
 'AUZ']

    '''
    [Optional] This is a way to use any custom features you might have made.
    Returns a dictionary where
    key: featureId to access this feature (Make sure this doesnt conflict with any of the pre defined feature Ids)
    value: Your custom Class which computes this feature. The class should be an instance of Feature
    Eg. if your custom class is MyCustomFeature, and you want to access this via featureId='my_custom_feature',
    you will import that class, and return this function as {'my_custom_feature': MyCustomFeature}
    '''

    def getCustomFeatures(self):
        return {'my_custom_feature': MyCustomFeature}

    '''
    Returns a dictionary with:
    value: Array of instrument feature config dictionaries
        feature config Dictionary has the following keys:
        featureId: a string representing the type of feature you want to use
        featureKey: {optional} a string representing the key you will use to access the value of this feature.
                    If not present, will just use featureId
        params: {optional} A dictionary with which contains other optional params if needed by the feature
    Example:
    ma1Dict = {'featureKey': 'ma_5',
               'featureId': 'moving_average',
               'params': {'period': 5,
                          'featureName': 'stockVWAP'}}
    sdevDict = {'featureKey': 'sdev_5',
                'featureId': 'moving_sdev',
                'params': {'period': 5,
                           'featureName': 'stockVWAP'}}
    customFeatureDict = {'featureKey': 'custom_inst_feature',
                         'featureId': 'my_custom_feature',
                          'params': {'param1': 'value1'}}
    return [ma1Dict, sdevDict, customFeatureDict]
    For  instrument, you will have features keyed by ma_5, sdev_5, custom_inst_feature
    '''

    def getFeatureConfigDicts(self):
        ma2Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 5,
                              'featureName': 'stockTopAskPrice'}}
        ma1Dict = {'featureKey': 'ma_5',
                   'featureId': 'moving_average',
                   'params': {'period': 1,
                              'featureName': 'basis'}}
        expma = {'featureKey': 'exponential_moving_average',
                 'featureId': 'exponential_moving_average',
                 'params': {'period': 5,
                              'featureName': 'basis'}}
        sdevDict = {'featureKey': 'sdev_5',
                    'featureId': 'moving_sdev',
                    'params': {'period': 30,
                               'featureName': 'basis'}}
        customFeatureDict = {'featureKey': 'custom_inst_feature',
                             'featureId': 'my_custom_feature',
                             'params': {'param1': 'value1'}}
        return [ma1Dict, sdevDict, expma]

    '''
    Using all the features you have calculated in getFeatureConfigDicts, combine them in a meaningful way
    to compute the fair value as specified in the question
    Params:
    time: time at which this is being calculated
    instrumentManager: Holder for all the instruments
    Returns:
    A Pandas DataSeries with instrumentIds as the index, and the corresponding data your estimation of the fair value
    for that stock/instrumentId
    '''

    def getFairValue(self, updateNum, time, instrumentManager):
        # holder for all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (ma_5 in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stock symbols/instrumentIds.
        ma5Data = lookbackInstrumentFeatures.getFeatureDf('exponential_moving_average')

        # Returns a series with index as all the instrumentIds. This returns the value of the feature at the last
        # time update.
        ma5 = ma5Data.iloc[-1]

        return ma5

'''
We have already provided a bunch of commonly used features. But if you wish to make your own, define your own class like this.
Write a class that inherits from Feature and implement the one method provided.
'''


class MyCustomFeature(Feature):
    ''''
    Custom Feature to implement for instrument. This function would return the value of the feature you want to implement.
    This function would be called at every update cycle for every instrument. To use this feature you MUST do the following things:
    1. Define it in getCustomFeatures, where you specify the identifier with which you want to access this feature.
    2. To finally use it in a meaningful way, specify this feature in getFeatureConfigDicts with appropirate feature params.
    Example for this is provided below.
    Params:
    updateNum: current iteration of update. For first iteration, it will be 1.
    time: time in datetime format when this update for feature will be run
    featureParams: A dictionary of parameter and parameter values your features computation might depend on.
                   You define the structure for this. just have to make sure these parameters are provided when
                   you wanted to actually use this feature in getFeatureConfigDicts
    featureKey: Name of the key this will feature will be mapped against.
    instrumentManager: A holder for all the instruments
    Returns:
    A Pandas series with stocks/instrumentIds as the index and the corresponding data the value of your custom feature
    for that stock/instrumentId
    '''
    @classmethod
    def computeForInstrument(cls, updateNum, time, featureParams, featureKey, instrumentManager):
        # Custom parameter which can be used as input to computation of this feature
        param1Value = featureParams['param1']

        # A holder for the all the instrument features
        lookbackInstrumentFeatures = instrumentManager.getLookbackInstrumentFeatures()

        # dataframe for a historical instrument feature (basis in this case). The index is the timestamps
        # atmost upto lookback data points. The columns of this dataframe are the stocks/instrumentIds.
        lookbackInstrumentBasis = lookbackInstrumentFeatures.getFeatureDf('basis')

        # The last row of the previous dataframe gives the last calculated value for that feature (basis in this case)
        # This returns a series with stocks/instrumentIds as the index.
        currentBasisValue = lookbackInstrumentBasis.iloc[-1]

        if param1Value == 'value1':
            return currentBasisValue * 0.1
        else:
            return currentBasisValue * 0.5


if __name__ == "__main__":
    if updateCheck():
        print('Your version of the auquan toolbox package is old. Please update by running the following command:')
        print('pip install -U auquan_toolbox')
    else:
        problem1Solver = Problem1Solver()
        tsParams = FairValueTradingParams(problem1Solver)
        tradingSystem = TradingSystem(tsParams)
        # Set shouldPlot to True to quickly generate csv files with all the features
        # Set onlyAnalyze to False to run a full backtest
        # Set makeInstrumentCsvs to True to make instrument specific csvs in runLogs. This degrades the performance of the backtesting system
        tradingSystem.startTrading(onlyAnalyze=False, shouldPlot=True, makeInstrumentCsvs=False)


Processing data for stock: FCY
Processing data for stock: FRE
Processing data for stock: ILW
Processing data for stock: JSG
Processing data for stock: KMV
Processing data for stock: NSL
Processing data for stock: PUO
Processing data for stock: QRK
Processing data for stock: SCN
Processing data for stock: TWK
Processing data for stock: UWD
Processing data for stock: VTN
Processing data for stock: XCS
Processing data for stock: ZEW
Processing data for stock: SVG
Processing data for stock: DFZ
Processing data for stock: GYJ
Processing data for stock: GYV
Processing data for stock: VKE
Processing data for stock: AUZ
Processing instruments before beginning backtesting. This could take some time...
20% done...
40% done...
60% done...
80% done...
2017-01-06 09:17:00
2017-01-06 09:18:00
2017-01-06 09:19:00
2017-01-06 09:20:00
2017-01-06 09:21:00
2017-01-06 09:22:00
2017-01-06 09:23:00
2017-01-06 09:24:00
2017-01-06 09:25:00
2017-01-06 09:26:00
2017-01-06 09:27:00
2017-01-06 09:28:00
2017-01-06

2017-01-10 09:17:00
2017-01-10 09:18:00
2017-01-10 09:19:00
2017-01-10 09:20:00
2017-01-10 09:21:00
2017-01-10 09:22:00
2017-01-10 09:23:00
2017-01-10 09:24:00
2017-01-10 09:25:00
2017-01-10 09:26:00
2017-01-10 09:27:00
2017-01-10 09:28:00
2017-01-10 09:29:00
2017-01-10 09:30:00
2017-01-10 09:31:00
2017-01-10 09:32:00
2017-01-10 09:33:00
2017-01-10 09:34:00
2017-01-10 09:35:00
2017-01-10 09:36:00
2017-01-10 09:37:00
2017-01-10 09:38:00
2017-01-10 09:39:00
2017-01-10 09:40:00
2017-01-10 09:41:00
2017-01-10 09:42:00
2017-01-10 09:43:00
2017-01-10 09:44:00
2017-01-10 09:45:00
2017-01-10 09:46:00
2017-01-10 09:47:00
2017-01-10 09:48:00
2017-01-10 09:49:00
2017-01-10 09:50:00
2017-01-10 09:51:00
2017-01-10 09:52:00
2017-01-10 09:53:00
2017-01-10 09:54:00
2017-01-10 09:55:00
2017-01-10 09:56:00
2017-01-10 09:57:00
2017-01-10 09:58:00
2017-01-10 09:59:00
2017-01-10 10:00:00
2017-01-10 10:01:00
2017-01-10 10:02:00
2017-01-10 10:03:00
2017-01-10 10:04:00
2017-01-10 10:05:00
2017-01-10 10:06:00


2017-01-11 09:55:00
2017-01-11 09:56:00
2017-01-11 09:57:00
2017-01-11 09:58:00
2017-01-11 09:59:00
2017-01-11 10:00:00
2017-01-11 10:01:00
2017-01-11 10:02:00
2017-01-11 10:03:00
2017-01-11 10:04:00
2017-01-11 10:05:00
2017-01-11 10:06:00
2017-01-11 10:07:00
2017-01-11 10:08:00
2017-01-11 10:09:00
2017-01-11 10:10:00
2017-01-11 10:11:00
2017-01-11 10:12:00
2017-01-11 10:13:00
2017-01-11 10:14:00
2017-01-11 10:15:00
2017-01-11 10:16:00
2017-01-11 10:17:00
2017-01-11 10:18:00
2017-01-11 10:19:00
2017-01-11 10:20:00
2017-01-11 10:21:00
2017-01-11 10:22:00
2017-01-11 10:23:00
2017-01-11 10:24:00
2017-01-11 10:25:00
2017-01-11 10:26:00
2017-01-11 10:27:00
2017-01-11 10:28:00
2017-01-11 10:29:00
2017-01-11 10:30:00
2017-01-11 10:31:00
2017-01-11 10:32:00
2017-01-11 10:33:00
2017-01-11 10:34:00
2017-01-11 10:35:00
2017-01-11 10:36:00
2017-01-11 10:37:00
2017-01-11 10:38:00
2017-01-11 10:39:00
2017-01-11 10:40:00
2017-01-11 10:41:00
2017-01-11 10:42:00
2017-01-11 10:43:00
2017-01-11 10:44:00


2017-01-12 10:36:00
2017-01-12 10:37:00
2017-01-12 10:38:00
2017-01-12 10:39:00
2017-01-12 10:40:00
2017-01-12 10:41:00
2017-01-12 10:42:00
2017-01-12 10:43:00
2017-01-12 10:44:00
2017-01-12 10:45:00
2017-01-12 10:46:00
2017-01-12 10:47:00
2017-01-12 10:48:00
2017-01-12 10:49:00
2017-01-12 10:50:00
2017-01-12 10:51:00
2017-01-12 10:52:00
2017-01-12 10:53:00
2017-01-12 10:54:00
2017-01-12 10:55:00
2017-01-12 10:56:00
2017-01-12 10:57:00
2017-01-12 10:58:00
2017-01-12 10:59:00
2017-01-12 11:00:00
2017-01-12 11:01:00
2017-01-12 11:02:00
2017-01-12 11:03:00
2017-01-12 11:04:00
2017-01-12 11:05:00
2017-01-12 11:06:00
2017-01-12 11:07:00
2017-01-12 11:08:00
2017-01-12 11:09:00
2017-01-12 11:10:00
2017-01-12 11:11:00
2017-01-12 11:12:00
2017-01-12 11:13:00
2017-01-12 11:14:00
2017-01-12 11:15:00
2017-01-12 11:16:00
2017-01-12 11:17:00
2017-01-12 11:18:00
2017-01-12 11:19:00
2017-01-12 11:20:00
2017-01-12 11:21:00
2017-01-12 11:22:00
2017-01-12 11:23:00
2017-01-12 11:24:00
2017-01-12 11:25:00


2017-01-13 11:13:00
2017-01-13 11:14:00
2017-01-13 11:15:00
2017-01-13 11:16:00
2017-01-13 11:17:00
2017-01-13 11:18:00
2017-01-13 11:19:00
2017-01-13 11:20:00
2017-01-13 11:21:00
2017-01-13 11:22:00
2017-01-13 11:23:00
2017-01-13 11:24:00
2017-01-13 11:25:00
2017-01-13 11:26:00
2017-01-13 11:27:00
2017-01-13 11:28:00
2017-01-13 11:29:00
2017-01-13 11:30:00
2017-01-13 11:31:00
2017-01-13 11:32:00
2017-01-13 11:33:00
2017-01-13 11:34:00
2017-01-13 11:35:00
2017-01-13 11:36:00
2017-01-13 11:37:00
2017-01-13 11:38:00
2017-01-13 11:39:00
2017-01-13 11:40:00
2017-01-13 11:41:00
2017-01-13 11:42:00
2017-01-13 11:43:00
2017-01-13 11:44:00
2017-01-13 11:45:00
2017-01-13 11:46:00
2017-01-13 11:47:00
2017-01-13 11:48:00
2017-01-13 11:49:00
2017-01-13 11:50:00
2017-01-13 11:51:00
2017-01-13 11:52:00
2017-01-13 11:53:00
2017-01-13 11:54:00
2017-01-13 11:55:00
2017-01-13 11:56:00
2017-01-13 11:57:00
2017-01-13 11:58:00
2017-01-13 11:59:00
2017-01-13 12:00:00
2017-01-13 12:01:00
2017-01-13 12:02:00


...

2017-01-25 15:02:00
2017-01-25 15:03:00
2017-01-25 15:04:00
2017-01-25 15:05:00
2017-01-25 15:06:00
2017-01-25 15:07:00
2017-01-25 15:08:00
2017-01-25 15:09:00
2017-01-25 15:10:00
2017-01-25 15:11:00
2017-01-25 15:12:00
2017-01-25 15:13:00
2017-01-25 15:14:00
2017-01-25 15:15:00
2017-01-25 15:16:00
2017-01-25 15:17:00
2017-01-25 15:18:00
2017-01-25 15:19:00
2017-01-25 15:20:00
2017-01-25 15:21:00
2017-01-25 15:22:00
2017-01-25 15:23:00
2017-01-25 15:24:00
2017-01-25 15:25:00
2017-01-25 15:26:00
2017-01-25 15:27:00
2017-01-25 15:28:00
2017-01-25 15:29:00
2017-01-26 09:17:00
2017-01-26 09:18:00
2017-01-26 09:19:00
2017-01-26 09:20:00
2017-01-26 09:21:00
2017-01-26 09:22:00
2017-01-26 09:23:00
2017-01-26 09:24:00
2017-01-26 09:25:00
2017-01-26 09:26:00
2017-01-26 09:27:00
2017-01-26 09:28:00
2017-01-26 09:29:00
2017-01-26 09:30:00
2017-01-26 09:31:00
2017-01-26 09:32:00
2017-01-26 09:33:00
2017-01-26 09:34:00
2017-01-26 09:35:00
2017-01-26 09:36:00
2017-01-26 09:37:00
2017-01-26 09:38:00


2017-01-27 09:29:00
2017-01-27 09:30:00
2017-01-27 09:31:00
2017-01-27 09:32:00
2017-01-27 09:33:00
2017-01-27 09:34:00
2017-01-27 09:35:00
2017-01-27 09:36:00
2017-01-27 09:37:00
2017-01-27 09:38:00
2017-01-27 09:39:00
2017-01-27 09:40:00
2017-01-27 09:41:00
2017-01-27 09:42:00
2017-01-27 09:43:00
2017-01-27 09:44:00
2017-01-27 09:45:00
2017-01-27 09:46:00
2017-01-27 09:47:00
2017-01-27 09:48:00
2017-01-27 09:49:00
2017-01-27 09:50:00
2017-01-27 09:51:00
2017-01-27 09:52:00
2017-01-27 09:53:00
2017-01-27 09:54:00
2017-01-27 09:55:00
2017-01-27 09:56:00
2017-01-27 09:57:00
2017-01-27 09:58:00
2017-01-27 09:59:00
2017-01-27 10:00:00
2017-01-27 10:01:00
2017-01-27 10:02:00
2017-01-27 10:03:00
2017-01-27 10:04:00
2017-01-27 10:05:00
2017-01-27 10:06:00
2017-01-27 10:07:00
2017-01-27 10:08:00
2017-01-27 10:09:00
2017-01-27 10:10:00
2017-01-27 10:11:00
2017-01-27 10:12:00
2017-01-27 10:13:00
2017-01-27 10:14:00
2017-01-27 10:15:00
2017-01-27 10:16:00
2017-01-27 10:17:00
2017-01-27 10:18:00


2017-01-30 10:09:00
2017-01-30 10:10:00
2017-01-30 10:11:00
2017-01-30 10:12:00
2017-01-30 10:13:00
2017-01-30 10:14:00
2017-01-30 10:15:00
2017-01-30 10:16:00
2017-01-30 10:17:00
2017-01-30 10:18:00
2017-01-30 10:19:00
2017-01-30 10:20:00
2017-01-30 10:21:00
2017-01-30 10:22:00
2017-01-30 10:23:00
2017-01-30 10:24:00
2017-01-30 10:25:00
2017-01-30 10:26:00
2017-01-30 10:27:00
2017-01-30 10:28:00
2017-01-30 10:29:00
2017-01-30 10:30:00
2017-01-30 10:31:00
2017-01-30 10:32:00
2017-01-30 10:33:00
2017-01-30 10:34:00
2017-01-30 10:35:00
2017-01-30 10:36:00
2017-01-30 10:37:00
2017-01-30 10:38:00
2017-01-30 10:39:00
2017-01-30 10:40:00
2017-01-30 10:41:00
2017-01-30 10:42:00
2017-01-30 10:43:00
2017-01-30 10:44:00
2017-01-30 10:45:00
2017-01-30 10:46:00
2017-01-30 10:47:00
2017-01-30 10:48:00
2017-01-30 10:49:00
2017-01-30 10:50:00
2017-01-30 10:51:00
2017-01-30 10:52:00
2017-01-30 10:53:00
2017-01-30 10:54:00
2017-01-30 10:55:00
2017-01-30 10:56:00
2017-01-30 10:57:00
2017-01-30 10:58:00


2017-01-31 10:49:00
2017-01-31 10:50:00
2017-01-31 10:51:00
2017-01-31 10:52:00
2017-01-31 10:53:00
2017-01-31 10:54:00
2017-01-31 10:55:00
2017-01-31 10:56:00
2017-01-31 10:57:00
2017-01-31 10:58:00
2017-01-31 10:59:00
2017-01-31 11:00:00
2017-01-31 11:01:00
2017-01-31 11:02:00
2017-01-31 11:03:00
2017-01-31 11:04:00
2017-01-31 11:05:00
2017-01-31 11:06:00
2017-01-31 11:07:00
2017-01-31 11:08:00
2017-01-31 11:09:00
2017-01-31 11:10:00
2017-01-31 11:11:00
2017-01-31 11:12:00
2017-01-31 11:13:00
2017-01-31 11:14:00
2017-01-31 11:15:00
2017-01-31 11:16:00
2017-01-31 11:17:00
2017-01-31 11:18:00
2017-01-31 11:19:00
2017-01-31 11:20:00
2017-01-31 11:21:00
2017-01-31 11:22:00
2017-01-31 11:23:00
2017-01-31 11:24:00
2017-01-31 11:25:00
2017-01-31 11:26:00
2017-01-31 11:27:00
2017-01-31 11:28:00
2017-01-31 11:29:00
2017-01-31 11:30:00
2017-01-31 11:31:00
2017-01-31 11:32:00
2017-01-31 11:33:00
2017-01-31 11:34:00
2017-01-31 11:35:00
2017-01-31 11:36:00
2017-01-31 11:37:00
2017-01-31 11:38:00


2017-02-01 11:28:00
2017-02-01 11:29:00
2017-02-01 11:30:00
2017-02-01 11:31:00
2017-02-01 11:32:00
2017-02-01 11:33:00
2017-02-01 11:34:00
2017-02-01 11:35:00
2017-02-01 11:36:00
2017-02-01 11:37:00
2017-02-01 11:38:00
2017-02-01 11:39:00
2017-02-01 11:40:00
2017-02-01 11:41:00
2017-02-01 11:42:00
2017-02-01 11:43:00
2017-02-01 11:44:00
2017-02-01 11:45:00
2017-02-01 11:46:00
2017-02-01 11:47:00
2017-02-01 11:48:00
2017-02-01 11:49:00
2017-02-01 11:50:00
2017-02-01 11:51:00
2017-02-01 11:52:00
2017-02-01 11:53:00
2017-02-01 11:54:00
2017-02-01 11:55:00
2017-02-01 11:56:00
2017-02-01 11:57:00
2017-02-01 11:58:00
2017-02-01 11:59:00
2017-02-01 12:00:00
2017-02-01 12:01:00
2017-02-01 12:02:00
2017-02-01 12:03:00
2017-02-01 12:04:00
2017-02-01 12:05:00
2017-02-01 12:06:00
2017-02-01 12:07:00
2017-02-01 12:08:00
2017-02-01 12:09:00
2017-02-01 12:10:00
2017-02-01 12:11:00
2017-02-01 12:12:00
2017-02-01 12:13:00
2017-02-01 12:14:00
2017-02-01 12:15:00
2017-02-01 12:16:00
2017-02-01 12:17:00
